In [1]:
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import Dataset, DataLoader
from sklearn.model_selection import train_test_split
from pytorch_tabnet.tab_model import TabNetClassifier
#from pytorch_tabnet.tab_model import TabNetModel
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import xgboost as xgb
import lightgbm as lgb
import statsmodels.api as sm
import warnings
import shap
import optuna
import torch
from sklearn import svm
import tensorflow as tf
from tensorflow import feature_column
from tensorflow.keras import layers
from tqdm.auto import tqdm
from pytorch_tabnet.tab_model import TabNetRegressor
from sklearn.model_selection import KFold
from sklearn.model_selection import cross_validate
from sklearn.ensemble import VotingClassifier
from sklearn.ensemble import VotingRegressor
from sklearn.preprocessing import StandardScaler
from sklearn.preprocessing import RobustScaler
from sklearn.preprocessing import MinMaxScaler
from sklearn.model_selection import StratifiedKFold
from pycaret.regression import *
from xgboost import XGBRegressor
from xgboost import XGBClassifier
from sklearn.tree import ExtraTreeClassifier
from sklearn.tree import ExtraTreeRegressor
from sklearn.experimental import enable_iterative_imputer 
from sklearn.impute import KNNImputer
from sklearn.impute import IterativeImputer
from sklearn.ensemble import GradientBoostingClassifier
from sklearn.ensemble import GradientBoostingRegressor
from sklearn.tree import DecisionTreeClassifier
from sklearn.svm import SVC
from sklearn.preprocessing import MinMaxScaler
from sklearn.preprocessing import OneHotEncoder
from sklearn.preprocessing import LabelEncoder
from sklearn.model_selection import train_test_split
from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import RandomizedSearchCV
from sklearn.ensemble import RandomForestClassifier
from sklearn.ensemble import RandomForestRegressor
from catboost import CatBoostClassifier, Pool
from sklearn.ensemble import AdaBoostClassifier
from sklearn.ensemble import AdaBoostRegressor
from catboost import CatBoostRegressor
from catboost import CatBoostClassifier
from sklearn.metrics import mean_squared_error
from sklearn.impute import KNNImputer
from sklearn.decomposition import PCA

In [2]:
warnings.simplefilter(action='ignore')
pd.set_option('display.max_columns', None)

In [3]:
train_data = pd.read_csv("./train.csv")

In [4]:
train_data['YEAR'] =  pd.to_datetime(train_data['TIMESTAMP']).dt.year
train_data['MONTH'] =  pd.to_datetime(train_data['TIMESTAMP']).dt.month
train_data['DAY'] =  pd.to_datetime(train_data['TIMESTAMP']).dt.day
train_data['HOUR'] =  pd.to_datetime(train_data['TIMESTAMP']).dt.hour
train_data['MINUTE'] =  pd.to_datetime(train_data['TIMESTAMP']).dt.minute
train_data['DAY_OF_WEEK'] =  pd.to_datetime(train_data['TIMESTAMP']).dt.day_name()

train_data = train_data.drop(['MONTH', 'DAY', 'YEAR', 'MINUTE', 'HOUR', 'DAY_OF_WEEK'], axis = 1)

In [5]:
colls = []
for coll in train_data :
    if 'X' in coll and train_data[coll].isna().sum() == 598 :
        colls.append(coll)
print(len(colls))

train_data.drop(colls, inplace = True, axis = 1)

82


In [6]:
train_data.loc[train_data.PRODUCT_CODE == 'A_31','PRODUCT_CODE'] = 1
train_data.loc[train_data.PRODUCT_CODE == 'T_31','PRODUCT_CODE'] = 2
train_data.loc[train_data.PRODUCT_CODE == 'O_31','PRODUCT_CODE'] = 3

#train_data.loc[train_data.DAY_OF_WEEK == 'Monday','DAY_OF_WEEK'] = 1
#train_data.loc[train_data.DAY_OF_WEEK == 'Tuesday','DAY_OF_WEEK'] = 2
#train_data.loc[train_data.DAY_OF_WEEK == 'Wednesday','DAY_OF_WEEK'] = 3
#train_data.loc[train_data.DAY_OF_WEEK == 'Thursday','DAY_OF_WEEK'] = 4
#train_data.loc[train_data.DAY_OF_WEEK == 'Friday','DAY_OF_WEEK'] = 5
#train_data.loc[train_data.DAY_OF_WEEK == 'Saturday','DAY_OF_WEEK'] = 6
#train_data.loc[train_data.DAY_OF_WEEK == 'Sunday','DAY_OF_WEEK'] = 7

train_data.drop(['PRODUCT_ID', 'TIMESTAMP'], axis = 1, inplace = True)
train_data

Y_Class  Y_Quality     LINE PRODUCT_CODE   X_1   X_2  X_3   X_4   X_5  \
0          1   0.533433  T050304            1   NaN   NaN  NaN   NaN   NaN   
1          2   0.541819  T050307            1   NaN   NaN  NaN   NaN   NaN   
2          1   0.531267  T050304            1   NaN   NaN  NaN   NaN   NaN   
3          2   0.537325  T050307            1   NaN   NaN  NaN   NaN   NaN   
4          1   0.531590  T050304            1   NaN   NaN  NaN   NaN   NaN   
..       ...        ...      ...          ...   ...   ...  ...   ...   ...   
593        1   0.526546  T100306            2   2.0  95.0  0.0  45.0  10.0   
594        0   0.524022  T050304            1   NaN   NaN  NaN   NaN   NaN   
595        0   0.521289  T050304            1   NaN   NaN  NaN   NaN   NaN   
596        1   0.531375  T100304            3  40.0  94.0  0.0  45.0  11.0   
597        1   0.533702  T100306            3  21.0  87.0  0.0  45.0  10.0   

     X_6   X_7   X_8   X_9  X_10   X_11   X_12   X_13  X_14  X_15   X_16  \
0    NaN   NaN   NaN   NaN   NaN    NaN    NaN    NaN   NaN   NaN    NaN   
1    NaN   NaN   NaN   NaN   NaN    NaN    NaN    NaN   NaN   NaN    NaN   
2    NaN   NaN   NaN   NaN   NaN    NaN    NaN    NaN   NaN   NaN    NaN   
3    NaN   NaN   NaN   NaN   NaN    NaN    NaN    NaN   NaN   NaN    NaN   
4    NaN   NaN   NaN   NaN   NaN    NaN    NaN    NaN   NaN   NaN    NaN   
..   ...   ...   ...   ...   ...    ...    ...    ...   ...   ...    ...   
593  0.0  50.0  10.0  52.0   2.0  468.9  473.9  459.2   0.0   0.0  247.5   
594  NaN   NaN   NaN   NaN   NaN    NaN    NaN    NaN   NaN   NaN    NaN   
595  NaN   NaN   NaN   NaN   NaN    NaN    NaN    NaN   NaN   NaN    NaN   
596  0.0  45.0  10.0  31.0   2.0  505.8  510.9  497.1   0.0   0.0  247.5   
597  0.0  61.0  10.0  52.0   2.0  470.6  474.9  462.9   0.0   0.0  247.5   

      X_17   X_18   X_19   X_20   X_21   X_22  X_23  X_24  X_25   X_26   X_27  \
0      NaN    NaN    NaN    NaN    NaN    NaN   NaN   NaN   NaN    NaN    NaN   
1      NaN    NaN    NaN    NaN    NaN    NaN   NaN   NaN   NaN    NaN    NaN   
2      NaN    NaN    NaN    NaN    NaN    NaN   NaN   NaN   NaN    NaN    NaN   
3      NaN    NaN    NaN    NaN    NaN    NaN   NaN   NaN   NaN    NaN    NaN   
4      NaN    NaN    NaN    NaN    NaN    NaN   NaN   NaN   NaN    NaN    NaN   
..     ...    ...    ...    ...    ...    ...   ...   ...   ...    ...    ...   
593  248.0  247.3  250.0  527.0  538.0  522.0  0.19  0.19  0.19  155.0  155.0   
594    NaN    NaN    NaN    NaN    NaN    NaN   NaN   NaN   NaN    NaN    NaN   
595    NaN    NaN    NaN    NaN    NaN    NaN   NaN   NaN   NaN    NaN    NaN   
596  248.1  247.3  250.0  489.0  498.0  485.0  0.19  0.19  0.19  155.0  155.0   
597  248.0  247.3  250.0  525.0  534.0  520.0  0.19  0.20  0.19  155.0  155.0   

      X_28   X_29   X_30   X_31   X_32   X_33   X_34   X_35   X_36   X_37  \
0      NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
1      NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
2      NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
3      NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
4      NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
593  155.0  155.0  185.0  185.0  185.0  185.0  155.0  155.0  155.0  155.0   
594    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
595    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
596  155.0  155.0  185.0  185.0  185.0  185.0  155.0  155.0  155.0  155.0   
597  155.0  155.0  185.0  185.0  185.0  185.0  155.0  155.0  155.0  155.0   

      X_38  X_39  X_40  X_41  X_42  X_43  X_44  X_45  X_46  X_47  X_48  X_49  \
0      NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
1      NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
2      NaN   NaN 

In [7]:
T0503041 = train_data[(train_data['LINE'] == 'T050304') & (train_data['PRODUCT_CODE'] == 1)]
T0503042 = train_data[(train_data['LINE'] == 'T050304') & (train_data['PRODUCT_CODE'] == 2)]
T0503043 = train_data[(train_data['LINE'] == 'T050304') & (train_data['PRODUCT_CODE'] == 3)]

T0503071 = train_data[(train_data['LINE'] == 'T050307') & (train_data['PRODUCT_CODE'] == 1)]
T0503072 = train_data[(train_data['LINE'] == 'T050307') & (train_data['PRODUCT_CODE'] == 2)]
T0503073 = train_data[(train_data['LINE'] == 'T050307') & (train_data['PRODUCT_CODE'] == 3)]

T0103051 = train_data[(train_data['LINE'] == 'T010305') & (train_data['PRODUCT_CODE'] == 1)]
T0103052 = train_data[(train_data['LINE'] == 'T010305') & (train_data['PRODUCT_CODE'] == 2)]
T0103053 = train_data[(train_data['LINE'] == 'T010305') & (train_data['PRODUCT_CODE'] == 3)]

T0103061 = train_data[(train_data['LINE'] == 'T010306') & (train_data['PRODUCT_CODE'] == 1)]
T0103062 = train_data[(train_data['LINE'] == 'T010306') & (train_data['PRODUCT_CODE'] == 2)]
T0103063 = train_data[(train_data['LINE'] == 'T010306') & (train_data['PRODUCT_CODE'] == 3)]

T1003041 = train_data[(train_data['LINE'] == 'T100304') & (train_data['PRODUCT_CODE'] == 1)]
T1003042 = train_data[(train_data['LINE'] == 'T100304') & (train_data['PRODUCT_CODE'] == 2)]
T1003043 = train_data[(train_data['LINE'] == 'T100304') & (train_data['PRODUCT_CODE'] == 3)]

T1003061 = train_data[(train_data['LINE'] == 'T100306') & (train_data['PRODUCT_CODE'] == 1)]
T1003062 = train_data[(train_data['LINE'] == 'T100306') & (train_data['PRODUCT_CODE'] == 2)]
T1003063 = train_data[(train_data['LINE'] == 'T100306') & (train_data['PRODUCT_CODE'] == 3)]

In [8]:
T0503041_col = []
for col in T0503041 :
    if 'X' in col and T0503041[col].isna().sum() == len(T0503041) :
        T0503041_col.append(col)
print(len(T0503041_col))

T0503041.drop(T0503041_col, inplace = True, axis = 1)

825


In [9]:
T0503071_col = []
for col in T0503071 :
    if 'X' in col and T0503071[col].isna().sum() == len(T0503071) :
        T0503071_col.append(col)
print(len(T0503071_col))

T0503071.drop(T0503071_col, inplace = True, axis = 1)

818


In [10]:
T0103051_col = []
for col in T0103051 :
    if 'X' in col and T0103051[col].isna().sum() == len(T0103051) :
        T0103051_col.append(col)
print(len(T0103051_col))

T0103051.drop(T0103051_col, inplace = True, axis = 1)

1907


In [11]:
T0103061_col = []
for col in T0103061 :
    if 'X' in col and T0103061[col].isna().sum() == len(T0103061) :
        T0103061_col.append(col)
print(len(T0103061_col))

T0103061.drop(T0103061_col, inplace = True, axis = 1)

1907


In [12]:
T1003042_col = []
for col in T1003042 :
    if 'X' in col and T1003042[col].isna().sum() == len(T1003042) :
        T1003042_col.append(col)
print(len(T1003042_col))

T1003042.drop(T1003042_col, inplace = True, axis = 1)

2122


In [13]:
T1003043_col = []
for col in T1003043 :
    if 'X' in col and T1003043[col].isna().sum() == len(T1003043) :
        T1003043_col.append(col)
print(len(T1003043_col))

T1003043.drop(T1003043_col, inplace = True, axis = 1)

2132


In [14]:
T1003062_col = []
for col in T1003062 :
    if 'X' in col and T1003062[col].isna().sum() == len(T1003062) :
        T1003062_col.append(col)
print(len(T1003062_col))

T1003062.drop(T1003062_col, inplace = True, axis = 1)

2122


In [15]:
T1003063_col = []
for col in T1003063 :
    if 'X' in col and T1003063[col].isna().sum() == len(T1003063) :
        T1003063_col.append(col)
print(len(T1003063_col))

T1003063.drop(T1003063_col, inplace = True, axis = 1)

2132


In [16]:
# 여기
T0503041x_col = []
for col in T0503041 :
    if 'X' in col and T0503041[col].std() == 0 :
        T0503041x_col.append(col)
print(len(T0503041x_col))
T0503041.drop(T0503041x_col, inplace = True, axis = 1)

T0503071x_col = []
for col in T0503071 :
    if 'X' in col and T0503071[col].std() == 0 :
        T0503071x_col.append(col)
print(len(T0503071x_col))
T0503071.drop(T0503071x_col, inplace = True, axis = 1)

T0103051x_col = []
for col in T0103051 :
    if 'X' in col and T0103051[col].std() == 0 :
        T0103051x_col.append(col)
print(len(T0103051x_col))
T0103051.drop(T0103051x_col, inplace = True, axis = 1)

T0103061x_col = []
for col in T0103061 :
    if 'X' in col and T0103061[col].std() == 0 :
        T0103061x_col.append(col)
print(len(T0103061x_col))
T0103061.drop(T0103061x_col, inplace = True, axis = 1)

T1003042x_col = []
for col in T1003042 :
    if 'X' in col and T1003042[col].std() == 0 :
        T1003042x_col.append(col)
print(len(T1003042x_col))
T1003042.drop(T1003042x_col, inplace = True, axis = 1)

T1003043x_col = []
for col in T1003043 :
    if 'X' in col and T1003043[col].std() == 0 :
        T1003043x_col.append(col)
print(len(T1003043x_col))
T1003043.drop(T1003043x_col, inplace = True, axis = 1)

T1003062x_col = []
for col in T1003062 :
    if 'X' in col and T1003062[col].std() == 0 :
        T1003062x_col.append(col)
print(len(T1003062x_col))
T1003062.drop(T1003062x_col, inplace = True, axis = 1)

T1003063x_col = []
for col in T1003063 :
    if 'X' in col and T1003063[col].std() == 0 :
        T1003063x_col.append(col)
print(len(T1003063x_col))
T1003063.drop(T1003063x_col, inplace = True, axis = 1)

269
233
152
150
124
209
124
217


In [17]:
#T0503041 = T0503041.fillna(0)
#T0503071 = T0503071.fillna(0)
#T0103051 = T0103051.fillna(0)
#T0103061 = T0103061.fillna(0)
#T1003042 = T1003042.fillna(0)
#T1003043 = T1003043.fillna(0)
#T1003062 = T1003062.fillna(0)
#T1003063 = T1003063.fillna(0)

T0503041 = T0503041.fillna(T0503041.mean())
T0503071 = T0503071.fillna(T0503071.mean())
T0103051 = T0103051.fillna(T0103051.mean())
T0103061 = T0103061.fillna(T0103061.mean())
T1003042 = T1003042.fillna(T1003042.mean())
T1003043 = T1003043.fillna(T1003043.mean())
T1003062 = T1003062.fillna(T1003062.mean())
T1003063 = T1003063.fillna(T1003063.mean())

In [ ]:
# 여기2
T0503041x_col = []
for col in T0503041 :
    if 'X' in col and T0503041[col].std() == 0 :
        T0503041x_col.append(col)
print(len(T0503041x_col))
T0503041.drop(T0503041x_col, inplace = True, axis = 1)

T0503071x_col = []
for col in T0503071 :
    if 'X' in col and T0503071[col].std() == 0 :
        T0503071x_col.append(col)
print(len(T0503071x_col))
T0503071.drop(T0503071x_col, inplace = True, axis = 1)

T0103051x_col = []
for col in T0103051 :
    if 'X' in col and T0103051[col].std() == 0 :
        T0103051x_col.append(col)
print(len(T0103051x_col))
T0103051.drop(T0103051x_col, inplace = True, axis = 1)

T0103061x_col = []
for col in T0103061 :
    if 'X' in col and T0103061[col].std() == 0 :
        T0103061x_col.append(col)
print(len(T0103061x_col))
T0103061.drop(T0103061x_col, inplace = True, axis = 1)

T1003042x_col = []
for col in T1003042 :
    if 'X' in col and T1003042[col].std() == 0 :
        T1003042x_col.append(col)
print(len(T1003042x_col))
T1003042.drop(T1003042x_col, inplace = True, axis = 1)

T1003043x_col = []
for col in T1003043 :
    if 'X' in col and T1003043[col].std() == 0 :
        T1003043x_col.append(col)
print(len(T1003043x_col))
T1003043.drop(T1003043x_col, inplace = True, axis = 1)

T1003062x_col = []
for col in T1003062 :
    if 'X' in col and T1003062[col].std() == 0 :
        T1003062x_col.append(col)
print(len(T1003062x_col))
T1003062.drop(T1003062x_col, inplace = True, axis = 1)

T1003063x_col = []
for col in T1003063 :
    if 'X' in col and T1003063[col].std() == 0 :
        T1003063x_col.append(col)
print(len(T1003063x_col))
T1003063.drop(T1003063x_col, inplace = True, axis = 1)

In [18]:
T0503041.drop(['LINE'], axis = 1, inplace = True)
T0503071.drop(['LINE'], axis = 1, inplace = True)
T0103051.drop(['LINE'], axis = 1, inplace = True)
T0103061.drop(['LINE'], axis = 1, inplace = True)
T1003042.drop(['LINE'], axis = 1, inplace = True)
T1003043.drop(['LINE'], axis = 1, inplace = True) # *4
T1003062.drop(['LINE'], axis = 1, inplace = True)
T1003063.drop(['LINE'], axis = 1, inplace = True) # *4

In [19]:
T1003043 = pd.concat([T1003043, T1003043, T1003043, T1003043, T1003043]).reset_index()
T1003063 = pd.concat([T1003063, T1003063, T1003063, T1003063, T1003063]).reset_index()

# 1

In [20]:
T0503041_class = T0503041['Y_Class']
T0503041_target = T0503041['Y_Quality']
T0503041_data = T0503041.drop(['Y_Class', 'Y_Quality'], axis = 1)

In [21]:
T0503041c = T0503041_data.columns
T0503041scaler = RobustScaler()
T0503041scaled = T0503041scaler.fit_transform(T0503041_data)
T0503041_data = pd.DataFrame(T0503041scaled, columns = T0503041c)

T0503041_y_class = pd.DataFrame(T0503041_target, columns = ['Y_Quality'])
T0503041_idx = T0503041_y_class.index
T0503041_y_class = T0503041_y_class.reset_index()
T0503041_data = pd.concat([T0503041_data, T0503041_y_class], axis = 1)
T0503041_data = T0503041_data.set_index('index')
T0503041_data.drop(['Y_Quality'], axis = 1, inplace = True)
T0503041_data

PRODUCT_CODE     X_128     X_129  X_132  X_133  X_134  X_135     X_136  \
index                                                                           
0               0.0 -0.364170 -0.364234   -1.0   -1.0    0.0    0.0 -0.259277   
2               0.0 -0.364041 -0.364106   -1.0   -1.0    0.0    0.0 -0.259277   
4               0.0 -0.363913 -0.363977   -1.0   -1.0   -1.0    0.0 -0.259277   
6               0.0 -0.363721 -0.363785   -1.0   -1.0    0.0    0.0 -0.259277   
8               0.0 -0.363593 -0.363657   -1.0   -1.0    0.0    0.0 -0.259277   
...             ...       ...       ...    ...    ...    ...    ...       ...   
581             0.0 -0.104465 -0.104484   -1.0   -1.0    0.0    0.0 -0.255422   
582             0.0 -0.102285 -0.102304   -2.0   -1.0   -1.0    0.0 -0.255422   
583             0.0 -0.100875 -0.100893   -1.0   -1.0    0.0    0.0 -0.255422   
594             0.0  0.084399  0.084414   -1.0   -1.0    0.0    0.0 -0.112771   
595             0.0  0.084591  0.084606   -1.0   -1.0    0.0    0.0 -0.112771   

          X_137     X_138     X_139     X_140     X_141  X_143  X_144  X_145  \
index                                                                          
0     -0.259277 -0.264678 -0.075041 -0.091691 -0.213256    0.0   -1.0    0.0   
2     -0.259277 -0.264678 -0.016313 -0.063037  0.109510    0.0    0.0    0.0   
4     -0.259277 -0.264678 -0.055465 -0.080229 -0.293948    0.0   -1.0    0.0   
6     -0.259277 -0.264678 -0.042414 -0.080229 -1.561960    0.0   -2.0    0.0   
8     -0.259277 -0.264678 -0.048940 -0.085960  0.051873    0.0    0.0    0.0   
...         ...       ...       ...       ...       ...    ...    ...    ...   
581   -0.255422 -0.255053 -0.003263  0.000000 -0.737752    0.0   -1.0    0.0   
582   -0.255422 -0.255053 -0.048940 -0.017192 -0.051873    0.0   -1.0    0.0   
583   -0.255422 -0.255053 -0.035889 -0.022923 -0.870317    0.0    0.0    0.0   
594   -0.112771 -0.112608  0.316476  0.338109  0.219020    0.0    0.0    0.0   
595   -0.112771 -0.112608  0.309951  0.338109 -0.011527    0.0   -1.0    0.0   

          X_146     X_148     X_149  X_150  X_151  X_152  X_153  X_155  X_156  \
index                                                                           
0      0.000000  0.093023  0.090909   0.16   -1.0    0.0    0.0    0.0    0.0   
2      0.522293  0.000000  0.000000   0.08   -1.0    0.0   -0.1    0.0    0.0   
4     -0.318471  0.093023  0.000000   0.16    0.0    0.0   -0.1    0.0    0.1   
6     -3.789809  0.093023  0.000000   0.08    0.0    0.1    0.0   -1.0    0.0   
8      0.477707  0.093023  0.000000   0.16    0.0    0.0    0.0    0.0    0.0   
...         ...       ...       ...    ...    ...    ...    ...    ...    ...   
581   -1.987261  0.000000  0.000000   0.00    0.0    0.0    0.0   -1.0    0.0   
582    0.207006  0.093023  0.272727   0.08    0.0    0.0    0.0   -1.0    0.0   
583   -2.149682  0.093023  0.090909   0.08    0.0    0.0    0.0   -1.0    0.0   
594    0.105096 -0.279070 -0.272727  -0.32   -1.0    0.0    0.0    0.0    0.0   
595   -0.589172 -0.279070 -0.272727  -0.32    0.0    0.0    0.0    0.0    0.1   

       X_157  X_159  X_160  X_161  X_163  X_164  X_165  X_167  X_168  X_169  \
index                                                                         
0        0.0    0.0    0.0    0.0   -0.1    0.0    0.0   -1.0    0.0    0.0   
2        0.0    1.0    0.0    0.0   -0.1    0.0    0.0   -1.0    0.0    0.0   
4        0.1    0.0    0.0    0.0    0.0    1.0    1.0   -1.0    0.0    0.0   
6        0.0    1.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
8        0.0    1.0    0.0    0.0    0.0    1.0    1.0    0.0    0.0    0.0   
...      ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
581      0.0    1.0    0.0    0.0    0.0    1.0    1.0    0.0    0.0    0.0   
582      0.0    1.0    0.0    0.0    0.0    1.0    1.0    0.0    0.1    0.0   
583      0.0    0.0    0.0    0.0    0.0    1.0    1.0   -1.0    0.0

In [22]:
#13
setup_rgs = setup(data = T0503041_data, target = T0503041_target, session_id = 4)
top5 = compare_models(sort='MSE', n_select=5)

Processing:   0%|          | 0/89 [00:00<?, ?it/s]

In [23]:
T05_total_models = []

T05_model_lightgbm = create_model('lightgbm', fold = 5)
T05_total_models.append(T05_model_lightgbm)

T05_model_rf = create_model('rf', fold = 5)
T05_total_models.append(T05_model_rf)

T05_model_gbr = create_model('gbr', fold = 5)
T05_total_models.append(T05_model_gbr)

T05_model_et = create_model('et', fold = 5)
T05_total_models.append(T05_model_et)

T05_model_catboost = create_model('catboost', fold = 5)
T05_total_models.append(T05_model_catboost)

T05_model_xgb = create_model('xgboost', fold = 5)
T05_total_models.append(T05_model_xgb)

T05_model_ada = create_model('ada', fold = 5)

T05_total_models.append(T05_model_ada)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [24]:
T05_model_lightgbm = tune_model(T05_model_lightgbm, fold=5, choose_better = True)

T05_model_rf = tune_model(T05_model_rf, fold=5, choose_better = True)

T05_model_gbr = tune_model(T05_model_gbr, fold=5, choose_better = True)

T05_model_et = tune_model(T05_model_et, fold=5, choose_better = True)

T05_model_catboost = tune_model(T05_model_catboost, fold=5, choose_better = True)

T05_model_xgb = tune_model(T05_model_xgb, fold=5, choose_better = True)

T05_model_ada = tune_model(T05_model_ada, fold=5, choose_better = True)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

...

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


In [25]:
T05_tuned_models = [T05_model_lightgbm, T05_model_rf, T05_model_gbr, T05_model_et, T05_model_catboost, T05_model_xgb, T05_model_ada]

for model in T05_tuned_models:
    display(predict_model(model))

PRODUCT_CODE     X_128     X_129  X_132  X_133  X_134  X_135     X_136  \
54           0.0  0.729846  0.729975    0.0    0.0    0.0    0.0  0.887711   
55           0.0 -0.262365 -0.262411   -1.0   -1.0    0.0    0.0 -0.330602   
56           0.0 -0.509953 -0.510043   -1.0   -1.0    0.0    0.0 -0.386506   
57           0.0  0.729653  0.729782    0.0    0.0    1.0    0.0  0.887711   
58           0.0  0.358015  0.358078    0.0    0.0    0.0    0.0  0.317108   
59           0.0  0.007982  0.007983    0.0    0.0    1.0    0.0  0.197590   
60           0.0 -0.102285 -0.102304   -2.0   -1.0   -1.0    0.0 -0.255422   
61           0.0 -0.112222 -0.112242    0.0    0.0    0.0    0.0  0.112771   
62           0.0  0.253069  0.253114    0.0    0.0    1.0    0.0  0.401928   
63           0.0 -0.363593 -0.363657   -1.0   -1.0    0.0    0.0 -0.259277   
64           0.0 -0.677084 -0.677204    0.0    0.0    1.0    0.0 -0.461687   
65           0.0 -0.258134 -0.258179   -1.0   -1.0    0.0    0.0 -0.328675   
66           0.0  0.642337  0.642451    0.0    0.0    1.0    0.0  0.787470   
67           0.0 -0.363400 -0.363464   -1.0   -1.0    0.0    0.0 -0.259277   
68           0.0  0.578293  0.578395    0.0    0.0    1.0    0.0  0.698795   
69           0.0  0.720230  0.720357    0.0   -1.0    1.0    0.0  0.878072   
70           0.0  0.639453  0.639565    0.0    0.0    1.0    0.0  0.787470   
71           0.0 -0.676123 -0.676242    0.0    0.0    0.0    0.0 -0.461687   
72           0.0 -0.362631 -0.362695   -1.0   -1.0    0.0    0.0 -0.259277   
73           0.0  0.356605  0.356668    0.0    0.0    1.0    0.0  0.317108   
74           0.0 -0.363080 -0.363144   -1.0   -1.0    0.0    0.0 -0.259277   
75           0.0 -0.363272 -0.363336   -1.0   -1.0    0.0    0.0 -0.259277   
76           0.0 -0.338911 -0.338971   -1.0   -1.0    0.0    0.0 -0.367229   
77           0.0 -0.341667 -0.341728   -1.0   -1.0    0.0    0.0 -0.367229   

       X_137     X_138  ...  X_2863    X_2864  X_2865    X_2866    X_2867  \
54  0.887711  0.886429  ...     0.0 -1.579615    -9.0  0.392068  0.980269   
55 -0.330602 -0.330125  ...    -1.0  1.449588     0.0 -0.179037  0.687892   
56 -0.386506 -0.385948  ...     0.0 -0.423635     2.0  0.276487 -0.121076   
57  0.887711  0.886429  ...   -11.0 -5.594505   -10.0  0.274221  1.301345   
58  0.317108  0.312801  ...     0.0  0.000000     0.0  0.729745  0.964126   
59  0.197590  0.197305  ...     0.0 -0.079274     1.0 -0.426671 -0.158718   
60 -0.255422 -0.255053  ...     0.0 -0.645939     0.0 -0.580170 -0.338117   
61  0.112771  0.112608  ...     1.0 -0.568133     0.0 -0.426671 -0.158718   
62  0.401928  0.401347  ...     0.0  0.249148     0.0  1.541077  0.187444   
63 -0.259277 -0.264678  ...     9.0  3.233262     1.0 -2.535977 -2.142601   
64 -0.461687 -0.461020  ...     0.0 -0.271798     1.0  0.775071 -0.834978   
65 -0.328675 -0.328200  ...    -1.0 -5.192051   -10.0  0.521246  0.268161   
66  0.787470  0.786333  ...     0.0 -0.668170     0.0  0.464589  0.293274   
67 -0.259277 -0.264678  ...    10.0  3.839144     0.0 -4.831728 -3.654709   
68  0.698795  0.697786  ...     0.0  0.407697     0.0  0.577904 -0.544395   
69  0.878072  0.876805  ...     0.0  0.951292     1.0 -1.142210  1.003587   
70  0.787470  0.786333  ...     0.0 -0.158549     0.0 -0.625496  0.377578   
71 -0.461687 -0.461020  ...     0.0 -0.237823     0.0 -1.169405 -0.693274   
72 -0.259277 -0.264678  ...     0.0 -0.156871     0.0 -0.426671 -0.158718   
73  0.317108  0.310876  ...     0.0  0.328422     0.0  0.976771  1.859193   
74 -0.259277 -0.264678  ...    10.0  2.831227     0.0 -2.950708 -3.010762   
75 -0.259277 -0.264678  ...     8.0  3.622293     0.0 -3.827762 -4.088789   
76 -0.367229 -0.366699  ...    -2.0 -3.602580    -9.0  1.019830  0.130045   
77 -0.367229 -0.366699  ...    -1.0  0.328422     1.0  0.666289  0.356054   

      X_2868    X_2869    X_2870  Y_Quality  prediction_label  
54 -0.709447  0.573454 -0.306043   0.515229          0.519390  

PRODUCT_CODE     X_128     X_129  X_132  X_133  X_134  X_135     X_136  \
54           0.0  0.729846  0.729975    0.0    0.0    0.0    0.0  0.887711   
55           0.0 -0.262365 -0.262411   -1.0   -1.0    0.0    0.0 -0.330602   
56           0.0 -0.509953 -0.510043   -1.0   -1.0    0.0    0.0 -0.386506   
57           0.0  0.729653  0.729782    0.0    0.0    1.0    0.0  0.887711   
58           0.0  0.358015  0.358078    0.0    0.0    0.0    0.0  0.317108   
59           0.0  0.007982  0.007983    0.0    0.0    1.0    0.0  0.197590   
60           0.0 -0.102285 -0.102304   -2.0   -1.0   -1.0    0.0 -0.255422   
61           0.0 -0.112222 -0.112242    0.0    0.0    0.0    0.0  0.112771   
62           0.0  0.253069  0.253114    0.0    0.0    1.0    0.0  0.401928   
63           0.0 -0.363593 -0.363657   -1.0   -1.0    0.0    0.0 -0.259277   
64           0.0 -0.677084 -0.677204    0.0    0.0    1.0    0.0 -0.461687   
65           0.0 -0.258134 -0.258179   -1.0   -1.0    0.0    0.0 -0.328675   
66           0.0  0.642337  0.642451    0.0    0.0    1.0    0.0  0.787470   
67           0.0 -0.363400 -0.363464   -1.0   -1.0    0.0    0.0 -0.259277   
68           0.0  0.578293  0.578395    0.0    0.0    1.0    0.0  0.698795   
69           0.0  0.720230  0.720357    0.0   -1.0    1.0    0.0  0.878072   
70           0.0  0.639453  0.639565    0.0    0.0    1.0    0.0  0.787470   
71           0.0 -0.676123 -0.676242    0.0    0.0    0.0    0.0 -0.461687   
72           0.0 -0.362631 -0.362695   -1.0   -1.0    0.0    0.0 -0.259277   
73           0.0  0.356605  0.356668    0.0    0.0    1.0    0.0  0.317108   
74           0.0 -0.363080 -0.363144   -1.0   -1.0    0.0    0.0 -0.259277   
75           0.0 -0.363272 -0.363336   -1.0   -1.0    0.0    0.0 -0.259277   
76           0.0 -0.338911 -0.338971   -1.0   -1.0    0.0    0.0 -0.367229   
77           0.0 -0.341667 -0.341728   -1.0   -1.0    0.0    0.0 -0.367229   

       X_137     X_138  ...  X_2863    X_2864  X_2865    X_2866    X_2867  \
54  0.887711  0.886429  ...     0.0 -1.579615    -9.0  0.392068  0.980269   
55 -0.330602 -0.330125  ...    -1.0  1.449588     0.0 -0.179037  0.687892   
56 -0.386506 -0.385948  ...     0.0 -0.423635     2.0  0.276487 -0.121076   
57  0.887711  0.886429  ...   -11.0 -5.594505   -10.0  0.274221  1.301345   
58  0.317108  0.312801  ...     0.0  0.000000     0.0  0.729745  0.964126   
59  0.197590  0.197305  ...     0.0 -0.079274     1.0 -0.426671 -0.158718   
60 -0.255422 -0.255053  ...     0.0 -0.645939     0.0 -0.580170 -0.338117   
61  0.112771  0.112608  ...     1.0 -0.568133     0.0 -0.426671 -0.158718   
62  0.401928  0.401347  ...     0.0  0.249148     0.0  1.541077  0.187444   
63 -0.259277 -0.264678  ...     9.0  3.233262     1.0 -2.535977 -2.142601   
64 -0.461687 -0.461020  ...     0.0 -0.271798     1.0  0.775071 -0.834978   
65 -0.328675 -0.328200  ...    -1.0 -5.192051   -10.0  0.521246  0.268161   
66  0.787470  0.786333  ...     0.0 -0.668170     0.0  0.464589  0.293274   
67 -0.259277 -0.264678  ...    10.0  3.839144     0.0 -4.831728 -3.654709   
68  0.698795  0.697786  ...     0.0  0.407697     0.0  0.577904 -0.544395   
69  0.878072  0.876805  ...     0.0  0.951292     1.0 -1.142210  1.003587   
70  0.787470  0.786333  ...     0.0 -0.158549     0.0 -0.625496  0.377578   
71 -0.461687 -0.461020  ...     0.0 -0.237823     0.0 -1.169405 -0.693274   
72 -0.259277 -0.264678  ...     0.0 -0.156871     0.0 -0.426671 -0.158718   
73  0.317108  0.310876  ...     0.0  0.328422     0.0  0.976771  1.859193   
74 -0.259277 -0.264678  ...    10.0  2.831227     0.0 -2.950708 -3.010762   
75 -0.259277 -0.264678  ...     8.0  3.622293     0.0 -3.827762 -4.088789   
76 -0.367229 -0.366699  ...    -2.0 -3.602580    -9.0  1.019830  0.130045   
77 -0.367229 -0.366699  ...    -1.0  0.328422     1.0  0.666289  0.356054   

      X_2868    X_2869    X_2870  Y_Quality  prediction_label  
54 -0.709447  0.573454 -0.306043   0.515229          0.521635  

PRODUCT_CODE     X_128     X_129  X_132  X_133  X_134  X_135     X_136  \
54           0.0  0.729846  0.729975    0.0    0.0    0.0    0.0  0.887711   
55           0.0 -0.262365 -0.262411   -1.0   -1.0    0.0    0.0 -0.330602   
56           0.0 -0.509953 -0.510043   -1.0   -1.0    0.0    0.0 -0.386506   
57           0.0  0.729653  0.729782    0.0    0.0    1.0    0.0  0.887711   
58           0.0  0.358015  0.358078    0.0    0.0    0.0    0.0  0.317108   
59           0.0  0.007982  0.007983    0.0    0.0    1.0    0.0  0.197590   
60           0.0 -0.102285 -0.102304   -2.0   -1.0   -1.0    0.0 -0.255422   
61           0.0 -0.112222 -0.112242    0.0    0.0    0.0    0.0  0.112771   
62           0.0  0.253069  0.253114    0.0    0.0    1.0    0.0  0.401928   
63           0.0 -0.363593 -0.363657   -1.0   -1.0    0.0    0.0 -0.259277   
64           0.0 -0.677084 -0.677204    0.0    0.0    1.0    0.0 -0.461687   
65           0.0 -0.258134 -0.258179   -1.0   -1.0    0.0    0.0 -0.328675   
66           0.0  0.642337  0.642451    0.0    0.0    1.0    0.0  0.787470   
67           0.0 -0.363400 -0.363464   -1.0   -1.0    0.0    0.0 -0.259277   
68           0.0  0.578293  0.578395    0.0    0.0    1.0    0.0  0.698795   
69           0.0  0.720230  0.720357    0.0   -1.0    1.0    0.0  0.878072   
70           0.0  0.639453  0.639565    0.0    0.0    1.0    0.0  0.787470   
71           0.0 -0.676123 -0.676242    0.0    0.0    0.0    0.0 -0.461687   
72           0.0 -0.362631 -0.362695   -1.0   -1.0    0.0    0.0 -0.259277   
73           0.0  0.356605  0.356668    0.0    0.0    1.0    0.0  0.317108   
74           0.0 -0.363080 -0.363144   -1.0   -1.0    0.0    0.0 -0.259277   
75           0.0 -0.363272 -0.363336   -1.0   -1.0    0.0    0.0 -0.259277   
76           0.0 -0.338911 -0.338971   -1.0   -1.0    0.0    0.0 -0.367229   
77           0.0 -0.341667 -0.341728   -1.0   -1.0    0.0    0.0 -0.367229   

       X_137     X_138  ...  X_2863    X_2864  X_2865    X_2866    X_2867  \
54  0.887711  0.886429  ...     0.0 -1.579615    -9.0  0.392068  0.980269   
55 -0.330602 -0.330125  ...    -1.0  1.449588     0.0 -0.179037  0.687892   
56 -0.386506 -0.385948  ...     0.0 -0.423635     2.0  0.276487 -0.121076   
57  0.887711  0.886429  ...   -11.0 -5.594505   -10.0  0.274221  1.301345   
58  0.317108  0.312801  ...     0.0  0.000000     0.0  0.729745  0.964126   
59  0.197590  0.197305  ...     0.0 -0.079274     1.0 -0.426671 -0.158718   
60 -0.255422 -0.255053  ...     0.0 -0.645939     0.0 -0.580170 -0.338117   
61  0.112771  0.112608  ...     1.0 -0.568133     0.0 -0.426671 -0.158718   
62  0.401928  0.401347  ...     0.0  0.249148     0.0  1.541077  0.187444   
63 -0.259277 -0.264678  ...     9.0  3.233262     1.0 -2.535977 -2.142601   
64 -0.461687 -0.461020  ...     0.0 -0.271798     1.0  0.775071 -0.834978   
65 -0.328675 -0.328200  ...    -1.0 -5.192051   -10.0  0.521246  0.268161   
66  0.787470  0.786333  ...     0.0 -0.668170     0.0  0.464589  0.293274   
67 -0.259277 -0.264678  ...    10.0  3.839144     0.0 -4.831728 -3.654709   
68  0.698795  0.697786  ...     0.0  0.407697     0.0  0.577904 -0.544395   
69  0.878072  0.876805  ...     0.0  0.951292     1.0 -1.142210  1.003587   
70  0.787470  0.786333  ...     0.0 -0.158549     0.0 -0.625496  0.377578   
71 -0.461687 -0.461020  ...     0.0 -0.237823     0.0 -1.169405 -0.693274   
72 -0.259277 -0.264678  ...     0.0 -0.156871     0.0 -0.426671 -0.158718   
73  0.317108  0.310876  ...     0.0  0.328422     0.0  0.976771  1.859193   
74 -0.259277 -0.264678  ...    10.0  2.831227     0.0 -2.950708 -3.010762   
75 -0.259277 -0.264678  ...     8.0  3.622293     0.0 -3.827762 -4.088789   
76 -0.367229 -0.366699  ...    -2.0 -3.602580    -9.0  1.019830  0.130045   
77 -0.367229 -0.366699  ...    -1.0  0.328422     1.0  0.666289  0.356054   

      X_2868    X_2869    X_2870  Y_Quality  prediction_label  
54 -0.709447  0.573454 -0.306043   0.515229          0.519227  

PRODUCT_CODE     X_128     X_129  X_132  X_133  X_134  X_135     X_136  \
54           0.0  0.729846  0.729975    0.0    0.0    0.0    0.0  0.887711   
55           0.0 -0.262365 -0.262411   -1.0   -1.0    0.0    0.0 -0.330602   
56           0.0 -0.509953 -0.510043   -1.0   -1.0    0.0    0.0 -0.386506   
57           0.0  0.729653  0.729782    0.0    0.0    1.0    0.0  0.887711   
58           0.0  0.358015  0.358078    0.0    0.0    0.0    0.0  0.317108   
59           0.0  0.007982  0.007983    0.0    0.0    1.0    0.0  0.197590   
60           0.0 -0.102285 -0.102304   -2.0   -1.0   -1.0    0.0 -0.255422   
61           0.0 -0.112222 -0.112242    0.0    0.0    0.0    0.0  0.112771   
62           0.0  0.253069  0.253114    0.0    0.0    1.0    0.0  0.401928   
63           0.0 -0.363593 -0.363657   -1.0   -1.0    0.0    0.0 -0.259277   
64           0.0 -0.677084 -0.677204    0.0    0.0    1.0    0.0 -0.461687   
65           0.0 -0.258134 -0.258179   -1.0   -1.0    0.0    0.0 -0.328675   
66           0.0  0.642337  0.642451    0.0    0.0    1.0    0.0  0.787470   
67           0.0 -0.363400 -0.363464   -1.0   -1.0    0.0    0.0 -0.259277   
68           0.0  0.578293  0.578395    0.0    0.0    1.0    0.0  0.698795   
69           0.0  0.720230  0.720357    0.0   -1.0    1.0    0.0  0.878072   
70           0.0  0.639453  0.639565    0.0    0.0    1.0    0.0  0.787470   
71           0.0 -0.676123 -0.676242    0.0    0.0    0.0    0.0 -0.461687   
72           0.0 -0.362631 -0.362695   -1.0   -1.0    0.0    0.0 -0.259277   
73           0.0  0.356605  0.356668    0.0    0.0    1.0    0.0  0.317108   
74           0.0 -0.363080 -0.363144   -1.0   -1.0    0.0    0.0 -0.259277   
75           0.0 -0.363272 -0.363336   -1.0   -1.0    0.0    0.0 -0.259277   
76           0.0 -0.338911 -0.338971   -1.0   -1.0    0.0    0.0 -0.367229   
77           0.0 -0.341667 -0.341728   -1.0   -1.0    0.0    0.0 -0.367229   

       X_137     X_138  ...  X_2863    X_2864  X_2865    X_2866    X_2867  \
54  0.887711  0.886429  ...     0.0 -1.579615    -9.0  0.392068  0.980269   
55 -0.330602 -0.330125  ...    -1.0  1.449588     0.0 -0.179037  0.687892   
56 -0.386506 -0.385948  ...     0.0 -0.423635     2.0  0.276487 -0.121076   
57  0.887711  0.886429  ...   -11.0 -5.594505   -10.0  0.274221  1.301345   
58  0.317108  0.312801  ...     0.0  0.000000     0.0  0.729745  0.964126   
59  0.197590  0.197305  ...     0.0 -0.079274     1.0 -0.426671 -0.158718   
60 -0.255422 -0.255053  ...     0.0 -0.645939     0.0 -0.580170 -0.338117   
61  0.112771  0.112608  ...     1.0 -0.568133     0.0 -0.426671 -0.158718   
62  0.401928  0.401347  ...     0.0  0.249148     0.0  1.541077  0.187444   
63 -0.259277 -0.264678  ...     9.0  3.233262     1.0 -2.535977 -2.142601   
64 -0.461687 -0.461020  ...     0.0 -0.271798     1.0  0.775071 -0.834978   
65 -0.328675 -0.328200  ...    -1.0 -5.192051   -10.0  0.521246  0.268161   
66  0.787470  0.786333  ...     0.0 -0.668170     0.0  0.464589  0.293274   
67 -0.259277 -0.264678  ...    10.0  3.839144     0.0 -4.831728 -3.654709   
68  0.698795  0.697786  ...     0.0  0.407697     0.0  0.577904 -0.544395   
69  0.878072  0.876805  ...     0.0  0.951292     1.0 -1.142210  1.003587   
70  0.787470  0.786333  ...     0.0 -0.158549     0.0 -0.625496  0.377578   
71 -0.461687 -0.461020  ...     0.0 -0.237823     0.0 -1.169405 -0.693274   
72 -0.259277 -0.264678  ...     0.0 -0.156871     0.0 -0.426671 -0.158718   
73  0.317108  0.310876  ...     0.0  0.328422     0.0  0.976771  1.859193   
74 -0.259277 -0.264678  ...    10.0  2.831227     0.0 -2.950708 -3.010762   
75 -0.259277 -0.264678  ...     8.0  3.622293     0.0 -3.827762 -4.088789   
76 -0.367229 -0.366699  ...    -2.0 -3.602580    -9.0  1.019830  0.130045   
77 -0.367229 -0.366699  ...    -1.0  0.328422     1.0  0.666289  0.356054   

      X_2868    X_2869    X_2870  Y_Quality  prediction_label  
54 -0.709447  0.573454 -0.306043   0.515229          0.520169  

PRODUCT_CODE     X_128     X_129  X_132  X_133  X_134  X_135     X_136  \
54           0.0  0.729846  0.729975    0.0    0.0    0.0    0.0  0.887711   
55           0.0 -0.262365 -0.262411   -1.0   -1.0    0.0    0.0 -0.330602   
56           0.0 -0.509953 -0.510043   -1.0   -1.0    0.0    0.0 -0.386506   
57           0.0  0.729653  0.729782    0.0    0.0    1.0    0.0  0.887711   
58           0.0  0.358015  0.358078    0.0    0.0    0.0    0.0  0.317108   
59           0.0  0.007982  0.007983    0.0    0.0    1.0    0.0  0.197590   
60           0.0 -0.102285 -0.102304   -2.0   -1.0   -1.0    0.0 -0.255422   
61           0.0 -0.112222 -0.112242    0.0    0.0    0.0    0.0  0.112771   
62           0.0  0.253069  0.253114    0.0    0.0    1.0    0.0  0.401928   
63           0.0 -0.363593 -0.363657   -1.0   -1.0    0.0    0.0 -0.259277   
64           0.0 -0.677084 -0.677204    0.0    0.0    1.0    0.0 -0.461687   
65           0.0 -0.258134 -0.258179   -1.0   -1.0    0.0    0.0 -0.328675   
66           0.0  0.642337  0.642451    0.0    0.0    1.0    0.0  0.787470   
67           0.0 -0.363400 -0.363464   -1.0   -1.0    0.0    0.0 -0.259277   
68           0.0  0.578293  0.578395    0.0    0.0    1.0    0.0  0.698795   
69           0.0  0.720230  0.720357    0.0   -1.0    1.0    0.0  0.878072   
70           0.0  0.639453  0.639565    0.0    0.0    1.0    0.0  0.787470   
71           0.0 -0.676123 -0.676242    0.0    0.0    0.0    0.0 -0.461687   
72           0.0 -0.362631 -0.362695   -1.0   -1.0    0.0    0.0 -0.259277   
73           0.0  0.356605  0.356668    0.0    0.0    1.0    0.0  0.317108   
74           0.0 -0.363080 -0.363144   -1.0   -1.0    0.0    0.0 -0.259277   
75           0.0 -0.363272 -0.363336   -1.0   -1.0    0.0    0.0 -0.259277   
76           0.0 -0.338911 -0.338971   -1.0   -1.0    0.0    0.0 -0.367229   
77           0.0 -0.341667 -0.341728   -1.0   -1.0    0.0    0.0 -0.367229   

       X_137     X_138  ...  X_2863    X_2864  X_2865    X_2866    X_2867  \
54  0.887711  0.886429  ...     0.0 -1.579615    -9.0  0.392068  0.980269   
55 -0.330602 -0.330125  ...    -1.0  1.449588     0.0 -0.179037  0.687892   
56 -0.386506 -0.385948  ...     0.0 -0.423635     2.0  0.276487 -0.121076   
57  0.887711  0.886429  ...   -11.0 -5.594505   -10.0  0.274221  1.301345   
58  0.317108  0.312801  ...     0.0  0.000000     0.0  0.729745  0.964126   
59  0.197590  0.197305  ...     0.0 -0.079274     1.0 -0.426671 -0.158718   
60 -0.255422 -0.255053  ...     0.0 -0.645939     0.0 -0.580170 -0.338117   
61  0.112771  0.112608  ...     1.0 -0.568133     0.0 -0.426671 -0.158718   
62  0.401928  0.401347  ...     0.0  0.249148     0.0  1.541077  0.187444   
63 -0.259277 -0.264678  ...     9.0  3.233262     1.0 -2.535977 -2.142601   
64 -0.461687 -0.461020  ...     0.0 -0.271798     1.0  0.775071 -0.834978   
65 -0.328675 -0.328200  ...    -1.0 -5.192051   -10.0  0.521246  0.268161   
66  0.787470  0.786333  ...     0.0 -0.668170     0.0  0.464589  0.293274   
67 -0.259277 -0.264678  ...    10.0  3.839144     0.0 -4.831728 -3.654709   
68  0.698795  0.697786  ...     0.0  0.407697     0.0  0.577904 -0.544395   
69  0.878072  0.876805  ...     0.0  0.951292     1.0 -1.142210  1.003587   
70  0.787470  0.786333  ...     0.0 -0.158549     0.0 -0.625496  0.377578   
71 -0.461687 -0.461020  ...     0.0 -0.237823     0.0 -1.169405 -0.693274   
72 -0.259277 -0.264678  ...     0.0 -0.156871     0.0 -0.426671 -0.158718   
73  0.317108  0.310876  ...     0.0  0.328422     0.0  0.976771  1.859193   
74 -0.259277 -0.264678  ...    10.0  2.831227     0.0 -2.950708 -3.010762   
75 -0.259277 -0.264678  ...     8.0  3.622293     0.0 -3.827762 -4.088789   
76 -0.367229 -0.366699  ...    -2.0 -3.602580    -9.0  1.019830  0.130045   
77 -0.367229 -0.366699  ...    -1.0  0.328422     1.0  0.666289  0.356054   

      X_2868    X_2869    X_2870  Y_Quality  prediction_label  
54 -0.709447  0.573454 -0.306043   0.515229          0.518323  

PRODUCT_CODE     X_128     X_129  X_132  X_133  X_134  X_135     X_136  \
54           0.0  0.729846  0.729975    0.0    0.0    0.0    0.0  0.887711   
55           0.0 -0.262365 -0.262411   -1.0   -1.0    0.0    0.0 -0.330602   
56           0.0 -0.509953 -0.510043   -1.0   -1.0    0.0    0.0 -0.386506   
57           0.0  0.729653  0.729782    0.0    0.0    1.0    0.0  0.887711   
58           0.0  0.358015  0.358078    0.0    0.0    0.0    0.0  0.317108   
59           0.0  0.007982  0.007983    0.0    0.0    1.0    0.0  0.197590   
60           0.0 -0.102285 -0.102304   -2.0   -1.0   -1.0    0.0 -0.255422   
61           0.0 -0.112222 -0.112242    0.0    0.0    0.0    0.0  0.112771   
62           0.0  0.253069  0.253114    0.0    0.0    1.0    0.0  0.401928   
63           0.0 -0.363593 -0.363657   -1.0   -1.0    0.0    0.0 -0.259277   
64           0.0 -0.677084 -0.677204    0.0    0.0    1.0    0.0 -0.461687   
65           0.0 -0.258134 -0.258179   -1.0   -1.0    0.0    0.0 -0.328675   
66           0.0  0.642337  0.642451    0.0    0.0    1.0    0.0  0.787470   
67           0.0 -0.363400 -0.363464   -1.0   -1.0    0.0    0.0 -0.259277   
68           0.0  0.578293  0.578395    0.0    0.0    1.0    0.0  0.698795   
69           0.0  0.720230  0.720357    0.0   -1.0    1.0    0.0  0.878072   
70           0.0  0.639453  0.639565    0.0    0.0    1.0    0.0  0.787470   
71           0.0 -0.676123 -0.676242    0.0    0.0    0.0    0.0 -0.461687   
72           0.0 -0.362631 -0.362695   -1.0   -1.0    0.0    0.0 -0.259277   
73           0.0  0.356605  0.356668    0.0    0.0    1.0    0.0  0.317108   
74           0.0 -0.363080 -0.363144   -1.0   -1.0    0.0    0.0 -0.259277   
75           0.0 -0.363272 -0.363336   -1.0   -1.0    0.0    0.0 -0.259277   
76           0.0 -0.338911 -0.338971   -1.0   -1.0    0.0    0.0 -0.367229   
77           0.0 -0.341667 -0.341728   -1.0   -1.0    0.0    0.0 -0.367229   

       X_137     X_138  ...  X_2863    X_2864  X_2865    X_2866    X_2867  \
54  0.887711  0.886429  ...     0.0 -1.579615    -9.0  0.392068  0.980269   
55 -0.330602 -0.330125  ...    -1.0  1.449588     0.0 -0.179037  0.687892   
56 -0.386506 -0.385948  ...     0.0 -0.423635     2.0  0.276487 -0.121076   
57  0.887711  0.886429  ...   -11.0 -5.594505   -10.0  0.274221  1.301345   
58  0.317108  0.312801  ...     0.0  0.000000     0.0  0.729745  0.964126   
59  0.197590  0.197305  ...     0.0 -0.079274     1.0 -0.426671 -0.158718   
60 -0.255422 -0.255053  ...     0.0 -0.645939     0.0 -0.580170 -0.338117   
61  0.112771  0.112608  ...     1.0 -0.568133     0.0 -0.426671 -0.158718   
62  0.401928  0.401347  ...     0.0  0.249148     0.0  1.541077  0.187444   
63 -0.259277 -0.264678  ...     9.0  3.233262     1.0 -2.535977 -2.142601   
64 -0.461687 -0.461020  ...     0.0 -0.271798     1.0  0.775071 -0.834978   
65 -0.328675 -0.328200  ...    -1.0 -5.192051   -10.0  0.521246  0.268161   
66  0.787470  0.786333  ...     0.0 -0.668170     0.0  0.464589  0.293274   
67 -0.259277 -0.264678  ...    10.0  3.839144     0.0 -4.831728 -3.654709   
68  0.698795  0.697786  ...     0.0  0.407697     0.0  0.577904 -0.544395   
69  0.878072  0.876805  ...     0.0  0.951292     1.0 -1.142210  1.003587   
70  0.787470  0.786333  ...     0.0 -0.158549     0.0 -0.625496  0.377578   
71 -0.461687 -0.461020  ...     0.0 -0.237823     0.0 -1.169405 -0.693274   
72 -0.259277 -0.264678  ...     0.0 -0.156871     0.0 -0.426671 -0.158718   
73  0.317108  0.310876  ...     0.0  0.328422     0.0  0.976771  1.859193   
74 -0.259277 -0.264678  ...    10.0  2.831227     0.0 -2.950708 -3.010762   
75 -0.259277 -0.264678  ...     8.0  3.622293     0.0 -3.827762 -4.088789   
76 -0.367229 -0.366699  ...    -2.0 -3.602580    -9.0  1.019830  0.130045   
77 -0.367229 -0.366699  ...    -1.0  0.328422     1.0  0.666289  0.356054   

      X_2868    X_2869    X_2870  Y_Quality  prediction_label  
54 -0.709447  0.573454 -0.306043   0.515229          0.518723  

PRODUCT_CODE     X_128     X_129  X_132  X_133  X_134  X_135     X_136  \
54           0.0  0.729846  0.729975    0.0    0.0    0.0    0.0  0.887711   
55           0.0 -0.262365 -0.262411   -1.0   -1.0    0.0    0.0 -0.330602   
56           0.0 -0.509953 -0.510043   -1.0   -1.0    0.0    0.0 -0.386506   
57           0.0  0.729653  0.729782    0.0    0.0    1.0    0.0  0.887711   
58           0.0  0.358015  0.358078    0.0    0.0    0.0    0.0  0.317108   
59           0.0  0.007982  0.007983    0.0    0.0    1.0    0.0  0.197590   
60           0.0 -0.102285 -0.102304   -2.0   -1.0   -1.0    0.0 -0.255422   
61           0.0 -0.112222 -0.112242    0.0    0.0    0.0    0.0  0.112771   
62           0.0  0.253069  0.253114    0.0    0.0    1.0    0.0  0.401928   
63           0.0 -0.363593 -0.363657   -1.0   -1.0    0.0    0.0 -0.259277   
64           0.0 -0.677084 -0.677204    0.0    0.0    1.0    0.0 -0.461687   
65           0.0 -0.258134 -0.258179   -1.0   -1.0    0.0    0.0 -0.328675   
66           0.0  0.642337  0.642451    0.0    0.0    1.0    0.0  0.787470   
67           0.0 -0.363400 -0.363464   -1.0   -1.0    0.0    0.0 -0.259277   
68           0.0  0.578293  0.578395    0.0    0.0    1.0    0.0  0.698795   
69           0.0  0.720230  0.720357    0.0   -1.0    1.0    0.0  0.878072   
70           0.0  0.639453  0.639565    0.0    0.0    1.0    0.0  0.787470   
71           0.0 -0.676123 -0.676242    0.0    0.0    0.0    0.0 -0.461687   
72           0.0 -0.362631 -0.362695   -1.0   -1.0    0.0    0.0 -0.259277   
73           0.0  0.356605  0.356668    0.0    0.0    1.0    0.0  0.317108   
74           0.0 -0.363080 -0.363144   -1.0   -1.0    0.0    0.0 -0.259277   
75           0.0 -0.363272 -0.363336   -1.0   -1.0    0.0    0.0 -0.259277   
76           0.0 -0.338911 -0.338971   -1.0   -1.0    0.0    0.0 -0.367229   
77           0.0 -0.341667 -0.341728   -1.0   -1.0    0.0    0.0 -0.367229   

       X_137     X_138  ...  X_2863    X_2864  X_2865    X_2866    X_2867  \
54  0.887711  0.886429  ...     0.0 -1.579615    -9.0  0.392068  0.980269   
55 -0.330602 -0.330125  ...    -1.0  1.449588     0.0 -0.179037  0.687892   
56 -0.386506 -0.385948  ...     0.0 -0.423635     2.0  0.276487 -0.121076   
57  0.887711  0.886429  ...   -11.0 -5.594505   -10.0  0.274221  1.301345   
58  0.317108  0.312801  ...     0.0  0.000000     0.0  0.729745  0.964126   
59  0.197590  0.197305  ...     0.0 -0.079274     1.0 -0.426671 -0.158718   
60 -0.255422 -0.255053  ...     0.0 -0.645939     0.0 -0.580170 -0.338117   
61  0.112771  0.112608  ...     1.0 -0.568133     0.0 -0.426671 -0.158718   
62  0.401928  0.401347  ...     0.0  0.249148     0.0  1.541077  0.187444   
63 -0.259277 -0.264678  ...     9.0  3.233262     1.0 -2.535977 -2.142601   
64 -0.461687 -0.461020  ...     0.0 -0.271798     1.0  0.775071 -0.834978   
65 -0.328675 -0.328200  ...    -1.0 -5.192051   -10.0  0.521246  0.268161   
66  0.787470  0.786333  ...     0.0 -0.668170     0.0  0.464589  0.293274   
67 -0.259277 -0.264678  ...    10.0  3.839144     0.0 -4.831728 -3.654709   
68  0.698795  0.697786  ...     0.0  0.407697     0.0  0.577904 -0.544395   
69  0.878072  0.876805  ...     0.0  0.951292     1.0 -1.142210  1.003587   
70  0.787470  0.786333  ...     0.0 -0.158549     0.0 -0.625496  0.377578   
71 -0.461687 -0.461020  ...     0.0 -0.237823     0.0 -1.169405 -0.693274   
72 -0.259277 -0.264678  ...     0.0 -0.156871     0.0 -0.426671 -0.158718   
73  0.317108  0.310876  ...     0.0  0.328422     0.0  0.976771  1.859193   
74 -0.259277 -0.264678  ...    10.0  2.831227     0.0 -2.950708 -3.010762   
75 -0.259277 -0.264678  ...     8.0  3.622293     0.0 -3.827762 -4.088789   
76 -0.367229 -0.366699  ...    -2.0 -3.602580    -9.0  1.019830  0.130045   
77 -0.367229 -0.366699  ...    -1.0  0.328422     1.0  0.666289  0.356054   

      X_2868    X_2869    X_2870  Y_Quality  prediction_label  
54 -0.709447  0.573454 -0.306043   0.515229          0.520631  

In [26]:
T0503041_final_regression_model = finalize_model(T05_model_et)

T0503041_prediction = predict_model(T0503041_final_regression_model, data=T0503041_data)
T0503041_prediction

T0503041_datas = T0503041_prediction['prediction_label']
T0503041_datas = pd.DataFrame(T0503041_datas.values, columns = ['Y_Quality'])

T0503041y_idx= T0503041_class.index
T0503041y_idx = pd.DataFrame(T0503041y_idx, columns = ['index'])
T0503041_datas = pd.concat([T0503041y_idx, T0503041_datas], axis = 1)
T0503041_datas = T0503041_datas.set_index('index')
T0503041_datas

Y_Quality
index           
0       0.533433
2       0.531267
4       0.531590
6       0.533665
8       0.531821
...          ...
581     0.523465
582     0.522233
583     0.522340
594     0.524022
595     0.521289

[78 rows x 1 columns]

In [27]:
from pycaret.classification import *
# 분류 패키지의 모든 모듈을 임포트한다.
exp_clf101 = setup(data=T0503041_datas, 
                   target=T0503041_class, 
                   fold=5,
                   session_id=4)
top5 = compare_models(sort='Accuracy', n_select=5)

Processing:   0%|          | 0/73 [00:00<?, ?it/s]

In [28]:
T05_total_models = []

T05_model_lightgbm = create_model('lightgbm', fold = 5)
T05_total_models.append(T05_model_lightgbm)

T05_model_rf = create_model('rf', fold = 5)
T05_total_models.append(T05_model_rf)

T05_model_gbc = create_model('gbc', fold = 5)
T05_total_models.append(T05_model_gbc)

T05_model_et = create_model('et', fold = 5)
T05_total_models.append(T05_model_et)

T05_model_catboost = create_model('catboost', fold = 5)
T05_total_models.append(T05_model_catboost)

T05_model_xgb = create_model('xgboost', fold = 5)
T05_total_models.append(T05_model_xgb)

T05_model_ada = create_model('ada', fold = 5)

T05_total_models.append(T05_model_ada)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [29]:
T05_model_lightgbm = tune_model(T05_model_lightgbm, fold=5, choose_better = True)

T05_model_rf = tune_model(T05_model_rf, fold=5, choose_better = True)

T05_model_gbc = tune_model(T05_model_gbc, fold=5, choose_better = True)

T05_model_et = tune_model(T05_model_et, fold=5, choose_better = True)

T05_model_catboost = tune_model(T05_model_catboost, fold=5, choose_better = True)

T05_model_xgb = tune_model(T05_model_xgb, fold=5, choose_better = True)

T05_model_ada = tune_model(T05_model_ada, fold=5, choose_better = True)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

...

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


In [30]:
T05_tuned_models = [T05_model_lightgbm, T05_model_rf, T05_model_gbc, T05_model_et, T05_model_catboost, T05_model_xgb, T05_model_ada]

for model in T05_tuned_models:
    display(predict_model(model))

Y_Quality  Y_Class  prediction_label  prediction_score
54   0.527332        1                 1            0.9647
55   0.531267        1                 1            0.9647
56   0.531179        1                 1            0.9647
57   0.559464        2                 2            0.8737
58   0.530167        1                 1            0.9647
59   0.522460        0                 0            0.9494
60   0.522233        0                 0            0.9494
61   0.521259        0                 0            0.9494
62   0.519332        0                 0            0.9494
63   0.529035        1                 1            0.9647
64   0.516711        0                 0            0.9494
65   0.531590        1                 1            0.9647
66   0.529130        1                 1            0.9647
67   0.521987        0                 0            0.9494
68   0.535405        2                 2            0.8070
69   0.522340        0                 0            0.9494
70   0.535965        2                 2            0.8070
71   0.522300        0                 0            0.9494
72   0.528552        1                 1            0.9647
73   0.526033        1                 1            0.9647
74   0.532929        1                 1            0.8824
75   0.515892        0                 0            0.9494
76   0.533433        1                 1            0.8824
77   0.534054        1                 2            0.8070

Y_Quality  Y_Class  prediction_label  prediction_score
54   0.527332        1                 1              1.00
55   0.531267        1                 1              1.00
56   0.531179        1                 1              1.00
57   0.559464        2                 2              1.00
58   0.530167        1                 1              1.00
59   0.522460        0                 0              1.00
60   0.522233        0                 0              1.00
61   0.521259        0                 0              1.00
62   0.519332        0                 0              1.00
63   0.529035        1                 1              1.00
64   0.516711        0                 0              1.00
65   0.531590        1                 1              1.00
66   0.529130        1                 1              1.00
67   0.521987        0                 0              1.00
68   0.535405        2                 2              0.67
69   0.522340        0                 0              1.00
70   0.535965        2                 2              0.93
71   0.522300        0                 0              1.00
72   0.528552        1                 1              1.00
73   0.526033        1                 1              1.00
74   0.532929        1                 1              1.00
75   0.515892        0                 0              1.00
76   0.533433        1                 1              1.00
77   0.534054        1                 1              1.00

Y_Quality  Y_Class  prediction_label  prediction_score
54   0.527332        1                 1            0.9994
55   0.531267        1                 1            0.9969
56   0.531179        1                 1            0.9978
57   0.559464        2                 2            0.9606
58   0.530167        1                 1            0.9993
59   0.522460        0                 0            0.9998
60   0.522233        0                 0            0.9998
61   0.521259        0                 0            0.9998
62   0.519332        0                 0            0.9998
63   0.529035        1                 1            0.9993
64   0.516711        0                 0            0.9998
65   0.531590        1                 1            0.9902
66   0.529130        1                 1            0.9994
67   0.521987        0                 0            0.9998
68   0.535405        2                 2            0.8077
69   0.522340        0                 0            0.9998
70   0.535965        2                 2            0.9606
71   0.522300        0                 0            0.9998
72   0.528552        1                 1            0.9994
73   0.526033        1                 1            0.9988
74   0.532929        1                 1            0.9499
75   0.515892        0                 0            0.9998
76   0.533433        1                 1            0.8947
77   0.534054        1                 1            0.8346

Y_Quality  Y_Class  prediction_label  prediction_score
54   0.527332        1                 1              1.00
55   0.531267        1                 1              1.00
56   0.531179        1                 1              1.00
57   0.559464        2                 2              1.00
58   0.530167        1                 1              1.00
59   0.522460        0                 0              1.00
60   0.522233        0                 0              1.00
61   0.521259        0                 0              1.00
62   0.519332        0                 0              1.00
63   0.529035        1                 1              1.00
64   0.516711        0                 0              1.00
65   0.531590        1                 1              1.00
66   0.529130        1                 1              1.00
67   0.521987        0                 0              1.00
68   0.535405        2                 1              0.50
69   0.522340        0                 0              1.00
70   0.535965        2                 2              0.67
71   0.522300        0                 0              1.00
72   0.528552        1                 1              1.00
73   0.526033        1                 1              1.00
74   0.532929        1                 1              1.00
75   0.515892        0                 0              1.00
76   0.533433        1                 1              1.00
77   0.534054        1                 1              0.89

Y_Quality  Y_Class  prediction_label  prediction_score
54   0.527332        1                 1            0.9987
55   0.531267        1                 1            0.9986
56   0.531179        1                 1            0.9986
57   0.559464        2                 2            0.9952
58   0.530167        1                 1            0.9988
59   0.522460        0                 0            0.9982
60   0.522233        0                 0            0.9982
61   0.521259        0                 0            0.9985
62   0.519332        0                 0            0.9984
63   0.529035        1                 1            0.9988
64   0.516711        0                 0            0.9981
65   0.531590        1                 1            0.9983
66   0.529130        1                 1            0.9988
67   0.521987        0                 0            0.9982
68   0.535405        2                 2            0.9858
69   0.522340        0                 0            0.9982
70   0.535965        2                 2            0.9858
71   0.522300        0                 0            0.9982
72   0.528552        1                 1            0.9987
73   0.526033        1                 1            0.9974
74   0.532929        1                 1            0.9915
75   0.515892        0                 0            0.9979
76   0.533433        1                 1            0.9915
77   0.534054        1                 1            0.9816

Y_Quality  Y_Class  prediction_label  prediction_score
54   0.527332        1                 1            0.9773
55   0.531267        1                 1            0.9899
56   0.531179        1                 1            0.9899
57   0.559464        2                 2            0.9453
58   0.530167        1                 1            0.9899
59   0.522460        0                 0            0.9785
60   0.522233        0                 0            0.9785
61   0.521259        0                 0            0.9785
62   0.519332        0                 0            0.9785
63   0.529035        1                 1            0.9899
64   0.516711        0                 0            0.9785
65   0.531590        1                 1            0.9729
66   0.529130        1                 1            0.9899
67   0.521987        0                 0            0.9785
68   0.535405        2                 2            0.9453
69   0.522340        0                 0            0.9785
70   0.535965        2                 2            0.9453
71   0.522300        0                 0            0.9785
72   0.528552        1                 1            0.9899
73   0.526033        1                 1            0.9740
74   0.532929        1                 1            0.9477
75   0.515892        0                 0            0.9785
76   0.533433        1                 1            0.9477
77   0.534054        1                 1            0.9431

Y_Quality  Y_Class  prediction_label  prediction_score
54   0.527332        1                 1               1.0
55   0.531267        1                 1               1.0
56   0.531179        1                 1               1.0
57   0.559464        2                 2               1.0
58   0.530167        1                 1               1.0
59   0.522460        0                 0               1.0
60   0.522233        0                 0               1.0
61   0.521259        0                 0               1.0
62   0.519332        0                 0               1.0
63   0.529035        1                 1               1.0
64   0.516711        0                 0               1.0
65   0.531590        1                 1               1.0
66   0.529130        1                 1               1.0
67   0.521987        0                 0               1.0
68   0.535405        2                 2               1.0
69   0.522340        0                 0               1.0
70   0.535965        2                 2               1.0
71   0.522300        0                 0               1.0
72   0.528552        1                 1               1.0
73   0.526033        1                 1               1.0
74   0.532929        1                 1               1.0
75   0.515892        0                 0               1.0
76   0.533433        1                 1               1.0
77   0.534054        1                 1               1.0

In [31]:
T0503041_final_classification_model = finalize_model(T05_model_ada)

T0503041_prediction = predict_model(T0503041_final_classification_model, data=T0503041_datas)

T0503041_y_class = pd.DataFrame(T0503041_class, columns = ['Y_Class'])
T0503041_idx = T0503041_y_class.index
T0503041_y_class = T0503041_y_class.reset_index()
T0503041_prediction = pd.concat([T0503041_prediction, T0503041_y_class], axis = 1)
T0503041_prediction = T0503041_prediction.set_index('index')
T0503041_prediction.drop(['Y_Class'], axis = 1, inplace = True)

# 2

In [32]:
T0503071_class = T0503071['Y_Class']
T0503071_target = T0503071['Y_Quality']
T0503071_data = T0503071.drop(['Y_Class', 'Y_Quality'], axis = 1)

In [33]:
T0503071c = T0503071_data.columns
T0503071scaler = RobustScaler()
T0503071scaled = T0503071scaler.fit_transform(T0503071_data)
T0503071_data = pd.DataFrame(T0503071scaled, columns = T0503071c)

T0503071_y_class = pd.DataFrame(T0503071_target, columns = ['Y_Quality'])
T0503071_idx = T0503071_y_class.index
T0503071_y_class = T0503071_y_class.reset_index()
T0503071_data = pd.concat([T0503071_data, T0503071_y_class], axis = 1)
T0503071_data = T0503071_data.set_index('index')
T0503071_data.drop(['Y_Quality'], axis = 1, inplace = True)
T0503071_data

PRODUCT_CODE     X_130     X_131  X_132  X_133  X_134  X_135     X_136  \
index                                                                           
1               0.0  0.643981  0.643981    0.0   0.00    0.0    0.0  0.449286   
3               0.0  0.644094  0.644094    0.0   0.00    0.0    0.0  0.452292   
5               0.0  0.644265  0.644265    0.0   0.00    0.0    0.0  0.452292   
7               0.0  0.644378  0.644378    0.0   0.00    0.0    0.0  0.452292   
9               0.0  0.644549  0.644549    0.0   0.00    0.0    0.0  0.452292   
11              0.0  0.644662  0.644662    0.0   0.00    0.0    0.0  0.452292   
13              0.0  0.644832  0.644832    0.0   0.00    0.0    0.0  0.452292   
15              0.0  0.644946  0.644946    0.0   0.00    0.0    0.0  0.452292   
17              0.0  0.645116  0.645116    0.0   0.00    0.0    0.0  0.452292   
19              0.0  0.645230  0.645230    0.0   0.00    0.0    0.0  0.452292   
24              0.0  0.799290  0.799290    0.0   0.00    0.0    0.0  0.722765   
35              0.0  1.001789  1.001789    0.0   0.00    0.0    0.0  1.065364   
81              0.0 -0.115872 -0.115872    0.0   0.00    0.0    0.0 -0.277986   
82              0.0 -0.115361 -0.115361    0.0   0.00    0.0    0.0 -0.274981   
187             0.0  0.631317  0.631317    0.0   0.00   -1.0    0.0  1.038317   
195             0.0  0.686002  0.686002    0.0   0.00    0.0    0.0  1.110443   
198             0.0  0.725468  0.725468    0.0   0.00   -1.0    0.0  1.149512   
256             0.0  0.958631  0.958631    0.0   0.00    0.0    0.0  1.492111   
261             0.0  1.000142  1.000142   -1.0   0.00   -1.0    0.0  1.549211   
296             0.0 -0.423538 -0.423538    0.0   0.00    0.0    0.0 -0.641623   
298             0.0 -0.420869 -0.420869   -1.0   0.00   -1.0    0.0 -0.641623   
307             0.0 -0.413487 -0.413487    0.0   0.00    0.0    0.0 -0.617581   
316             0.0 -0.394804 -0.394804    0.0   0.00    0.0    0.0 -0.590533   
336             0.0 -0.329841 -0.329841    0.0   0.00    0.0    0.0 -0.434260   
355             0.0 -0.273396 -0.273396    0.0   0.00    0.0    0.0 -0.320060   
356             0.0 -0.273112 -0.273112    0.0   0.00    0.0    0.0 -0.320060   
369             0.0 -0.230977 -0.230977    0.0   0.00    0.0    0.0 -0.256950   
432             0.0  0.115361  0.115361    0.0   0.00    0.0    0.0  0.256950   
444             0.0  0.171749  0.171749    0.0   0.00    0.0    0.0  0.338092   
454             0.0  0.194691  0.194691    0.0   0.00    0.0    0.0  0.392186   
477             0.0  0.310136  0.310136    0.0   0.00    0.0    0.0  0.557476   
541             0.0 -0.437677 -0.437677   -1.0   0.00   -1.0    0.0 -0.617581   
542             0.0 -0.436371 -0.436371   -1.0  -0.01   -1.0    0.0 -0.617581   
543             0.0 -0.435122 -0.435122   -1.0   0.00   -1.0    0.0 -0.614576   
544             0.0 -0.433816 -0.433816   -1.0   0.00   -1.0    0.0 -0.614576   
545             0.0 -0.432567 -0.432567   -1.0   0.00   -1.0    0.0 -0.614576   
546             0.0 -0.431261 -0.431261   -1.0   0.00   -1.0    0.0 -0.614576   
549             0.0 -0.355792 -0.355792   -1.0  -0.01   -1.0    0.0 -0.548460   
550             0.0 -0.354089 -0.354089   -1.0  -0.01   -1.0    0.0 -0.545455   
551             0.0 -0.346763 -0.346763   -1.0  -0.01   -1.0    0.0 -0.539444   
552             0.0 -0.344549 -0.344549   -1.0  -0.01   -1.0    0.0 -0.539444   
555             0.0 -0.339211 -0.339211   -1.0  -0.01   -1.0    0.0 -0.530428   

          X_137     X_138  ...    X_2861    X_2862  X_2863    X_2864  X_2865  \
index                      ...                                                 
1      0.446281  0.446281  ...  1.890203  2.326870    -1.0 -0.409259     1.0   
3      0.446281  0.446281  ...  0.802965  0.132964     0.0  0.496623     1.0   
5      0.446281  0.446281  ...  1.604799  2.227147     0.0  0.143682     0.0   
7      0.446281  0.446281  ...  1.070902  

In [34]:
#13
from pycaret.regression import *
setup_rgs = setup(data = T0503071_data, target = T0503071_target, session_id = 4)
top5 = compare_models(sort='MSE', n_select=5)

Processing:   0%|          | 0/89 [00:00<?, ?it/s]

In [35]:
T05_total_models = []

T05_model_lightgbm = create_model('lightgbm', fold = 5)
T05_total_models.append(T05_model_lightgbm)

T05_model_rf = create_model('rf', fold = 5)
T05_total_models.append(T05_model_rf)

T05_model_gbr = create_model('gbr', fold = 5)
T05_total_models.append(T05_model_gbr)

T05_model_et = create_model('et', fold = 5)
T05_total_models.append(T05_model_et)

T05_model_catboost = create_model('catboost', fold = 5)
T05_total_models.append(T05_model_catboost)

T05_model_xgb = create_model('xgboost', fold = 5)
T05_total_models.append(T05_model_xgb)

T05_model_ada = create_model('ada', fold = 5)

T05_total_models.append(T05_model_ada)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [36]:
T05_model_lightgbm = tune_model(T05_model_lightgbm, fold=5, choose_better = True)

T05_model_rf = tune_model(T05_model_rf, fold=5, choose_better = True)

T05_model_gbr = tune_model(T05_model_gbr, fold=5, choose_better = True)

T05_model_et = tune_model(T05_model_et, fold=5, choose_better = True)

T05_model_catboost = tune_model(T05_model_catboost, fold=5, choose_better = True)

T05_model_xgb = tune_model(T05_model_xgb, fold=5, choose_better = True)

T05_model_ada = tune_model(T05_model_ada, fold=5, choose_better = True)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

...

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


In [37]:
T05_tuned_models = [T05_model_lightgbm, T05_model_rf, T05_model_gbr, T05_model_et, T05_model_catboost, T05_model_xgb, T05_model_ada]

for model in T05_tuned_models:
    display(predict_model(model))

PRODUCT_CODE     X_130     X_131  X_132  X_133  X_134  X_135     X_136  \
29           0.0 -0.437677 -0.437677   -1.0   0.00   -1.0    0.0 -0.617581   
30           0.0 -0.339211 -0.339211   -1.0  -0.01   -1.0    0.0 -0.530428   
31           0.0  0.644549  0.644549    0.0   0.00    0.0    0.0  0.452292   
32           0.0  0.686002  0.686002    0.0   0.00    0.0    0.0  1.110443   
33           0.0  0.171749  0.171749    0.0   0.00    0.0    0.0  0.338092   
34           0.0 -0.423538 -0.423538    0.0   0.00    0.0    0.0 -0.641623   
35           0.0  0.725468  0.725468    0.0   0.00   -1.0    0.0  1.149512   
36           0.0  0.644946  0.644946    0.0   0.00    0.0    0.0  0.452292   
37           0.0  1.000142  1.000142   -1.0   0.00   -1.0    0.0  1.549211   
38           0.0  1.001789  1.001789    0.0   0.00    0.0    0.0  1.065364   
39           0.0  0.115361  0.115361    0.0   0.00    0.0    0.0  0.256950   
40           0.0 -0.432567 -0.432567   -1.0   0.00   -1.0    0.0 -0.614576   
41           0.0 -0.115872 -0.115872    0.0   0.00    0.0    0.0 -0.277986   

       X_137     X_138  ...  X_2863    X_2864  X_2865    X_2866    X_2867  \
29 -0.623591 -0.623591  ...     0.0  0.061329     1.0  0.404531  1.105487   
30 -0.536439 -0.536439  ...    -2.0 -0.832789     1.0 -0.579215 -0.151689   
31  0.446281  0.446281  ...     9.0  2.792266     1.0 -4.163301 -3.615185   
32  1.104433  1.104433  ...     0.0 -0.279194     1.0 -0.579215 -0.151689   
33  0.338092  0.338092  ...     0.0 -0.021024     0.0  0.840366  0.099925   
34 -0.641623 -0.641623  ...     0.0  0.355447     0.0  0.370820  2.111049   
35  1.143501  1.143501  ...     0.0  0.436710     1.0  0.380452  0.619536   
36  0.446281  0.446281  ...     3.0  0.543682     1.0 -3.289225 -1.795496   
37  1.543201  1.543201  ...     0.0 -0.515142     0.0 -1.842062  1.509395   
38  1.041322  1.059354  ...     0.0  0.073094     1.0 -0.579215 -0.151689   
39  0.256950  0.256950  ...    -1.0  0.517538     0.0  0.893340  1.368448   
40 -0.620586 -0.620586  ...     0.0  0.320153     0.0  0.857221 -0.423893   
41 -0.283997 -0.283997  ...     0.0  0.602505     1.0  1.851694  0.855148   

      X_2868    X_2869    X_2870  Y_Quality  prediction_label  
29 -0.391998  0.217453 -1.228283   0.515884          0.537299  
30  0.000000 -0.222752  0.087721   0.521406          0.537299  
31 -0.187618 -1.962956  1.644006   0.538049          0.537299  
32  0.000000 -0.222752  0.087721   0.547592          0.537299  
33 -0.638551  0.277694 -1.398564   0.527944          0.537299  
34  1.442552  1.047596 -0.434709   0.522368          0.537299  
35  1.290078  1.040249 -0.331897   0.542848          0.537299  
36 -1.618275 -2.146616  1.978143   0.539254          0.537299  
37  1.317653  0.812511 -0.142339   0.537560          0.537299  
38  0.000000 -0.222752  0.087721   0.527976          0.537299  
39 -1.449581  0.847774 -0.450773   0.532386          0.537299  
40 -0.273587  1.025557 -0.977680   0.521494          0.537299  
41 -0.221682  0.787533 -0.736717   0.544584          0.537299  

[13 rows x 1745 columns]

PRODUCT_CODE     X_130     X_131  X_132  X_133  X_134  X_135     X_136  \
29           0.0 -0.437677 -0.437677   -1.0   0.00   -1.0    0.0 -0.617581   
30           0.0 -0.339211 -0.339211   -1.0  -0.01   -1.0    0.0 -0.530428   
31           0.0  0.644549  0.644549    0.0   0.00    0.0    0.0  0.452292   
32           0.0  0.686002  0.686002    0.0   0.00    0.0    0.0  1.110443   
33           0.0  0.171749  0.171749    0.0   0.00    0.0    0.0  0.338092   
34           0.0 -0.423538 -0.423538    0.0   0.00    0.0    0.0 -0.641623   
35           0.0  0.725468  0.725468    0.0   0.00   -1.0    0.0  1.149512   
36           0.0  0.644946  0.644946    0.0   0.00    0.0    0.0  0.452292   
37           0.0  1.000142  1.000142   -1.0   0.00   -1.0    0.0  1.549211   
38           0.0  1.001789  1.001789    0.0   0.00    0.0    0.0  1.065364   
39           0.0  0.115361  0.115361    0.0   0.00    0.0    0.0  0.256950   
40           0.0 -0.432567 -0.432567   -1.0   0.00   -1.0    0.0 -0.614576   
41           0.0 -0.115872 -0.115872    0.0   0.00    0.0    0.0 -0.277986   

       X_137     X_138  ...  X_2863    X_2864  X_2865    X_2866    X_2867  \
29 -0.623591 -0.623591  ...     0.0  0.061329     1.0  0.404531  1.105487   
30 -0.536439 -0.536439  ...    -2.0 -0.832789     1.0 -0.579215 -0.151689   
31  0.446281  0.446281  ...     9.0  2.792266     1.0 -4.163301 -3.615185   
32  1.104433  1.104433  ...     0.0 -0.279194     1.0 -0.579215 -0.151689   
33  0.338092  0.338092  ...     0.0 -0.021024     0.0  0.840366  0.099925   
34 -0.641623 -0.641623  ...     0.0  0.355447     0.0  0.370820  2.111049   
35  1.143501  1.143501  ...     0.0  0.436710     1.0  0.380452  0.619536   
36  0.446281  0.446281  ...     3.0  0.543682     1.0 -3.289225 -1.795496   
37  1.543201  1.543201  ...     0.0 -0.515142     0.0 -1.842062  1.509395   
38  1.041322  1.059354  ...     0.0  0.073094     1.0 -0.579215 -0.151689   
39  0.256950  0.256950  ...    -1.0  0.517538     0.0  0.893340  1.368448   
40 -0.620586 -0.620586  ...     0.0  0.320153     0.0  0.857221 -0.423893   
41 -0.283997 -0.283997  ...     0.0  0.602505     1.0  1.851694  0.855148   

      X_2868    X_2869    X_2870  Y_Quality  prediction_label  
29 -0.391998  0.217453 -1.228283   0.515884          0.527233  
30  0.000000 -0.222752  0.087721   0.521406          0.534566  
31 -0.187618 -1.962956  1.644006   0.538049          0.539258  
32  0.000000 -0.222752  0.087721   0.547592          0.543821  
33 -0.638551  0.277694 -1.398564   0.527944          0.535323  
34  1.442552  1.047596 -0.434709   0.522368          0.534603  
35  1.290078  1.040249 -0.331897   0.542848          0.541250  
36 -1.618275 -2.146616  1.978143   0.539254          0.538784  
37  1.317653  0.812511 -0.142339   0.537560          0.543208  
38  0.000000 -0.222752  0.087721   0.527976          0.541894  
39 -1.449581  0.847774 -0.450773   0.532386          0.537532  
40 -0.273587  1.025557 -0.977680   0.521494          0.525913  
41 -0.221682  0.787533 -0.736717   0.544584          0.540324  

[13 rows x 1745 columns]

PRODUCT_CODE     X_130     X_131  X_132  X_133  X_134  X_135     X_136  \
29           0.0 -0.437677 -0.437677   -1.0   0.00   -1.0    0.0 -0.617581   
30           0.0 -0.339211 -0.339211   -1.0  -0.01   -1.0    0.0 -0.530428   
31           0.0  0.644549  0.644549    0.0   0.00    0.0    0.0  0.452292   
32           0.0  0.686002  0.686002    0.0   0.00    0.0    0.0  1.110443   
33           0.0  0.171749  0.171749    0.0   0.00    0.0    0.0  0.338092   
34           0.0 -0.423538 -0.423538    0.0   0.00    0.0    0.0 -0.641623   
35           0.0  0.725468  0.725468    0.0   0.00   -1.0    0.0  1.149512   
36           0.0  0.644946  0.644946    0.0   0.00    0.0    0.0  0.452292   
37           0.0  1.000142  1.000142   -1.0   0.00   -1.0    0.0  1.549211   
38           0.0  1.001789  1.001789    0.0   0.00    0.0    0.0  1.065364   
39           0.0  0.115361  0.115361    0.0   0.00    0.0    0.0  0.256950   
40           0.0 -0.432567 -0.432567   -1.0   0.00   -1.0    0.0 -0.614576   
41           0.0 -0.115872 -0.115872    0.0   0.00    0.0    0.0 -0.277986   

       X_137     X_138  ...  X_2863    X_2864  X_2865    X_2866    X_2867  \
29 -0.623591 -0.623591  ...     0.0  0.061329     1.0  0.404531  1.105487   
30 -0.536439 -0.536439  ...    -2.0 -0.832789     1.0 -0.579215 -0.151689   
31  0.446281  0.446281  ...     9.0  2.792266     1.0 -4.163301 -3.615185   
32  1.104433  1.104433  ...     0.0 -0.279194     1.0 -0.579215 -0.151689   
33  0.338092  0.338092  ...     0.0 -0.021024     0.0  0.840366  0.099925   
34 -0.641623 -0.641623  ...     0.0  0.355447     0.0  0.370820  2.111049   
35  1.143501  1.143501  ...     0.0  0.436710     1.0  0.380452  0.619536   
36  0.446281  0.446281  ...     3.0  0.543682     1.0 -3.289225 -1.795496   
37  1.543201  1.543201  ...     0.0 -0.515142     0.0 -1.842062  1.509395   
38  1.041322  1.059354  ...     0.0  0.073094     1.0 -0.579215 -0.151689   
39  0.256950  0.256950  ...    -1.0  0.517538     0.0  0.893340  1.368448   
40 -0.620586 -0.620586  ...     0.0  0.320153     0.0  0.857221 -0.423893   
41 -0.283997 -0.283997  ...     0.0  0.602505     1.0  1.851694  0.855148   

      X_2868    X_2869    X_2870  Y_Quality  prediction_label  
29 -0.391998  0.217453 -1.228283   0.515884          0.536561  
30  0.000000 -0.222752  0.087721   0.521406          0.536640  
31 -0.187618 -1.962956  1.644006   0.538049          0.537307  
32  0.000000 -0.222752  0.087721   0.547592          0.537456  
33 -0.638551  0.277694 -1.398564   0.527944          0.535870  
34  1.442552  1.047596 -0.434709   0.522368          0.536964  
35  1.290078  1.040249 -0.331897   0.542848          0.538698  
36 -1.618275 -2.146616  1.978143   0.539254          0.537058  
37  1.317653  0.812511 -0.142339   0.537560          0.538565  
38  0.000000 -0.222752  0.087721   0.527976          0.538607  
39 -1.449581  0.847774 -0.450773   0.532386          0.535712  
40 -0.273587  1.025557 -0.977680   0.521494          0.535139  
41 -0.221682  0.787533 -0.736717   0.544584          0.537554  

[13 rows x 1745 columns]

PRODUCT_CODE     X_130     X_131  X_132  X_133  X_134  X_135     X_136  \
29           0.0 -0.437677 -0.437677   -1.0   0.00   -1.0    0.0 -0.617581   
30           0.0 -0.339211 -0.339211   -1.0  -0.01   -1.0    0.0 -0.530428   
31           0.0  0.644549  0.644549    0.0   0.00    0.0    0.0  0.452292   
32           0.0  0.686002  0.686002    0.0   0.00    0.0    0.0  1.110443   
33           0.0  0.171749  0.171749    0.0   0.00    0.0    0.0  0.338092   
34           0.0 -0.423538 -0.423538    0.0   0.00    0.0    0.0 -0.641623   
35           0.0  0.725468  0.725468    0.0   0.00   -1.0    0.0  1.149512   
36           0.0  0.644946  0.644946    0.0   0.00    0.0    0.0  0.452292   
37           0.0  1.000142  1.000142   -1.0   0.00   -1.0    0.0  1.549211   
38           0.0  1.001789  1.001789    0.0   0.00    0.0    0.0  1.065364   
39           0.0  0.115361  0.115361    0.0   0.00    0.0    0.0  0.256950   
40           0.0 -0.432567 -0.432567   -1.0   0.00   -1.0    0.0 -0.614576   
41           0.0 -0.115872 -0.115872    0.0   0.00    0.0    0.0 -0.277986   

       X_137     X_138  ...  X_2863    X_2864  X_2865    X_2866    X_2867  \
29 -0.623591 -0.623591  ...     0.0  0.061329     1.0  0.404531  1.105487   
30 -0.536439 -0.536439  ...    -2.0 -0.832789     1.0 -0.579215 -0.151689   
31  0.446281  0.446281  ...     9.0  2.792266     1.0 -4.163301 -3.615185   
32  1.104433  1.104433  ...     0.0 -0.279194     1.0 -0.579215 -0.151689   
33  0.338092  0.338092  ...     0.0 -0.021024     0.0  0.840366  0.099925   
34 -0.641623 -0.641623  ...     0.0  0.355447     0.0  0.370820  2.111049   
35  1.143501  1.143501  ...     0.0  0.436710     1.0  0.380452  0.619536   
36  0.446281  0.446281  ...     3.0  0.543682     1.0 -3.289225 -1.795496   
37  1.543201  1.543201  ...     0.0 -0.515142     0.0 -1.842062  1.509395   
38  1.041322  1.059354  ...     0.0  0.073094     1.0 -0.579215 -0.151689   
39  0.256950  0.256950  ...    -1.0  0.517538     0.0  0.893340  1.368448   
40 -0.620586 -0.620586  ...     0.0  0.320153     0.0  0.857221 -0.423893   
41 -0.283997 -0.283997  ...     0.0  0.602505     1.0  1.851694  0.855148   

      X_2868    X_2869    X_2870  Y_Quality  prediction_label  
29 -0.391998  0.217453 -1.228283   0.515884          0.537299  
30  0.000000 -0.222752  0.087721   0.521406          0.537299  
31 -0.187618 -1.962956  1.644006   0.538049          0.537299  
32  0.000000 -0.222752  0.087721   0.547592          0.537299  
33 -0.638551  0.277694 -1.398564   0.527944          0.537299  
34  1.442552  1.047596 -0.434709   0.522368          0.537299  
35  1.290078  1.040249 -0.331897   0.542848          0.537299  
36 -1.618275 -2.146616  1.978143   0.539254          0.537299  
37  1.317653  0.812511 -0.142339   0.537560          0.537299  
38  0.000000 -0.222752  0.087721   0.527976          0.537299  
39 -1.449581  0.847774 -0.450773   0.532386          0.537299  
40 -0.273587  1.025557 -0.977680   0.521494          0.537299  
41 -0.221682  0.787533 -0.736717   0.544584          0.537299  

[13 rows x 1745 columns]

PRODUCT_CODE     X_130     X_131  X_132  X_133  X_134  X_135     X_136  \
29           0.0 -0.437677 -0.437677   -1.0   0.00   -1.0    0.0 -0.617581   
30           0.0 -0.339211 -0.339211   -1.0  -0.01   -1.0    0.0 -0.530428   
31           0.0  0.644549  0.644549    0.0   0.00    0.0    0.0  0.452292   
32           0.0  0.686002  0.686002    0.0   0.00    0.0    0.0  1.110443   
33           0.0  0.171749  0.171749    0.0   0.00    0.0    0.0  0.338092   
34           0.0 -0.423538 -0.423538    0.0   0.00    0.0    0.0 -0.641623   
35           0.0  0.725468  0.725468    0.0   0.00   -1.0    0.0  1.149512   
36           0.0  0.644946  0.644946    0.0   0.00    0.0    0.0  0.452292   
37           0.0  1.000142  1.000142   -1.0   0.00   -1.0    0.0  1.549211   
38           0.0  1.001789  1.001789    0.0   0.00    0.0    0.0  1.065364   
39           0.0  0.115361  0.115361    0.0   0.00    0.0    0.0  0.256950   
40           0.0 -0.432567 -0.432567   -1.0   0.00   -1.0    0.0 -0.614576   
41           0.0 -0.115872 -0.115872    0.0   0.00    0.0    0.0 -0.277986   

       X_137     X_138  ...  X_2863    X_2864  X_2865    X_2866    X_2867  \
29 -0.623591 -0.623591  ...     0.0  0.061329     1.0  0.404531  1.105487   
30 -0.536439 -0.536439  ...    -2.0 -0.832789     1.0 -0.579215 -0.151689   
31  0.446281  0.446281  ...     9.0  2.792266     1.0 -4.163301 -3.615185   
32  1.104433  1.104433  ...     0.0 -0.279194     1.0 -0.579215 -0.151689   
33  0.338092  0.338092  ...     0.0 -0.021024     0.0  0.840366  0.099925   
34 -0.641623 -0.641623  ...     0.0  0.355447     0.0  0.370820  2.111049   
35  1.143501  1.143501  ...     0.0  0.436710     1.0  0.380452  0.619536   
36  0.446281  0.446281  ...     3.0  0.543682     1.0 -3.289225 -1.795496   
37  1.543201  1.543201  ...     0.0 -0.515142     0.0 -1.842062  1.509395   
38  1.041322  1.059354  ...     0.0  0.073094     1.0 -0.579215 -0.151689   
39  0.256950  0.256950  ...    -1.0  0.517538     0.0  0.893340  1.368448   
40 -0.620586 -0.620586  ...     0.0  0.320153     0.0  0.857221 -0.423893   
41 -0.283997 -0.283997  ...     0.0  0.602505     1.0  1.851694  0.855148   

      X_2868    X_2869    X_2870  Y_Quality  prediction_label  
29 -0.391998  0.217453 -1.228283   0.515884          0.529552  
30  0.000000 -0.222752  0.087721   0.521406          0.533044  
31 -0.187618 -1.962956  1.644006   0.538049          0.539045  
32  0.000000 -0.222752  0.087721   0.547592          0.547865  
33 -0.638551  0.277694 -1.398564   0.527944          0.531992  
34  1.442552  1.047596 -0.434709   0.522368          0.532791  
35  1.290078  1.040249 -0.331897   0.542848          0.546258  
36 -1.618275 -2.146616  1.978143   0.539254          0.538620  
37  1.317653  0.812511 -0.142339   0.537560          0.545416  
38  0.000000 -0.222752  0.087721   0.527976          0.548347  
39 -1.449581  0.847774 -0.450773   0.532386          0.530699  
40 -0.273587  1.025557 -0.977680   0.521494          0.525967  
41 -0.221682  0.787533 -0.736717   0.544584          0.538895  

[13 rows x 1745 columns]

PRODUCT_CODE     X_130     X_131  X_132  X_133  X_134  X_135     X_136  \
29           0.0 -0.437677 -0.437677   -1.0   0.00   -1.0    0.0 -0.617581   
30           0.0 -0.339211 -0.339211   -1.0  -0.01   -1.0    0.0 -0.530428   
31           0.0  0.644549  0.644549    0.0   0.00    0.0    0.0  0.452292   
32           0.0  0.686002  0.686002    0.0   0.00    0.0    0.0  1.110443   
33           0.0  0.171749  0.171749    0.0   0.00    0.0    0.0  0.338092   
34           0.0 -0.423538 -0.423538    0.0   0.00    0.0    0.0 -0.641623   
35           0.0  0.725468  0.725468    0.0   0.00   -1.0    0.0  1.149512   
36           0.0  0.644946  0.644946    0.0   0.00    0.0    0.0  0.452292   
37           0.0  1.000142  1.000142   -1.0   0.00   -1.0    0.0  1.549211   
38           0.0  1.001789  1.001789    0.0   0.00    0.0    0.0  1.065364   
39           0.0  0.115361  0.115361    0.0   0.00    0.0    0.0  0.256950   
40           0.0 -0.432567 -0.432567   -1.0   0.00   -1.0    0.0 -0.614576   
41           0.0 -0.115872 -0.115872    0.0   0.00    0.0    0.0 -0.277986   

       X_137     X_138  ...  X_2863    X_2864  X_2865    X_2866    X_2867  \
29 -0.623591 -0.623591  ...     0.0  0.061329     1.0  0.404531  1.105487   
30 -0.536439 -0.536439  ...    -2.0 -0.832789     1.0 -0.579215 -0.151689   
31  0.446281  0.446281  ...     9.0  2.792266     1.0 -4.163301 -3.615185   
32  1.104433  1.104433  ...     0.0 -0.279194     1.0 -0.579215 -0.151689   
33  0.338092  0.338092  ...     0.0 -0.021024     0.0  0.840366  0.099925   
34 -0.641623 -0.641623  ...     0.0  0.355447     0.0  0.370820  2.111049   
35  1.143501  1.143501  ...     0.0  0.436710     1.0  0.380452  0.619536   
36  0.446281  0.446281  ...     3.0  0.543682     1.0 -3.289225 -1.795496   
37  1.543201  1.543201  ...     0.0 -0.515142     0.0 -1.842062  1.509395   
38  1.041322  1.059354  ...     0.0  0.073094     1.0 -0.579215 -0.151689   
39  0.256950  0.256950  ...    -1.0  0.517538     0.0  0.893340  1.368448   
40 -0.620586 -0.620586  ...     0.0  0.320153     0.0  0.857221 -0.423893   
41 -0.283997 -0.283997  ...     0.0  0.602505     1.0  1.851694  0.855148   

      X_2868    X_2869    X_2870  Y_Quality  prediction_label  
29 -0.391998  0.217453 -1.228283   0.515884          0.523569  
30  0.000000 -0.222752  0.087721   0.521406          0.531975  
31 -0.187618 -1.962956  1.644006   0.538049          0.539388  
32  0.000000 -0.222752  0.087721   0.547592          0.540083  
33 -0.638551  0.277694 -1.398564   0.527944          0.531970  
34  1.442552  1.047596 -0.434709   0.522368          0.534574  
35  1.290078  1.040249 -0.331897   0.542848          0.542857  
36 -1.618275 -2.146616  1.978143   0.539254          0.537514  
37  1.317653  0.812511 -0.142339   0.537560          0.538474  
38  0.000000 -0.222752  0.087721   0.527976          0.538319  
39 -1.449581  0.847774 -0.450773   0.532386          0.532659  
40 -0.273587  1.025557 -0.977680   0.521494          0.524863  
41 -0.221682  0.787533 -0.736717   0.544584          0.537903  

[13 rows x 1745 columns]

PRODUCT_CODE     X_130     X_131  X_132  X_133  X_134  X_135     X_136  \
29           0.0 -0.437677 -0.437677   -1.0   0.00   -1.0    0.0 -0.617581   
30           0.0 -0.339211 -0.339211   -1.0  -0.01   -1.0    0.0 -0.530428   
31           0.0  0.644549  0.644549    0.0   0.00    0.0    0.0  0.452292   
32           0.0  0.686002  0.686002    0.0   0.00    0.0    0.0  1.110443   
33           0.0  0.171749  0.171749    0.0   0.00    0.0    0.0  0.338092   
34           0.0 -0.423538 -0.423538    0.0   0.00    0.0    0.0 -0.641623   
35           0.0  0.725468  0.725468    0.0   0.00   -1.0    0.0  1.149512   
36           0.0  0.644946  0.644946    0.0   0.00    0.0    0.0  0.452292   
37           0.0  1.000142  1.000142   -1.0   0.00   -1.0    0.0  1.549211   
38           0.0  1.001789  1.001789    0.0   0.00    0.0    0.0  1.065364   
39           0.0  0.115361  0.115361    0.0   0.00    0.0    0.0  0.256950   
40           0.0 -0.432567 -0.432567   -1.0   0.00   -1.0    0.0 -0.614576   
41           0.0 -0.115872 -0.115872    0.0   0.00    0.0    0.0 -0.277986   

       X_137     X_138  ...  X_2863    X_2864  X_2865    X_2866    X_2867  \
29 -0.623591 -0.623591  ...     0.0  0.061329     1.0  0.404531  1.105487   
30 -0.536439 -0.536439  ...    -2.0 -0.832789     1.0 -0.579215 -0.151689   
31  0.446281  0.446281  ...     9.0  2.792266     1.0 -4.163301 -3.615185   
32  1.104433  1.104433  ...     0.0 -0.279194     1.0 -0.579215 -0.151689   
33  0.338092  0.338092  ...     0.0 -0.021024     0.0  0.840366  0.099925   
34 -0.641623 -0.641623  ...     0.0  0.355447     0.0  0.370820  2.111049   
35  1.143501  1.143501  ...     0.0  0.436710     1.0  0.380452  0.619536   
36  0.446281  0.446281  ...     3.0  0.543682     1.0 -3.289225 -1.795496   
37  1.543201  1.543201  ...     0.0 -0.515142     0.0 -1.842062  1.509395   
38  1.041322  1.059354  ...     0.0  0.073094     1.0 -0.579215 -0.151689   
39  0.256950  0.256950  ...    -1.0  0.517538     0.0  0.893340  1.368448   
40 -0.620586 -0.620586  ...     0.0  0.320153     0.0  0.857221 -0.423893   
41 -0.283997 -0.283997  ...     0.0  0.602505     1.0  1.851694  0.855148   

      X_2868    X_2869    X_2870  Y_Quality  prediction_label  
29 -0.391998  0.217453 -1.228283   0.515884          0.524378  
30  0.000000 -0.222752  0.087721   0.521406          0.529806  
31 -0.187618 -1.962956  1.644006   0.538049          0.539346  
32  0.000000 -0.222752  0.087721   0.547592          0.538963  
33 -0.638551  0.277694 -1.398564   0.527944          0.525102  
34  1.442552  1.047596 -0.434709   0.522368          0.536106  
35  1.290078  1.040249 -0.331897   0.542848          0.549518  
36 -1.618275 -2.146616  1.978143   0.539254          0.539346  
37  1.317653  0.812511 -0.142339   0.537560          0.550803  
38  0.000000 -0.222752  0.087721   0.527976          0.540130  
39 -1.449581  0.847774 -0.450773   0.532386          0.524639  
40 -0.273587  1.025557 -0.977680   0.521494          0.523865  
41 -0.221682  0.787533 -0.736717   0.544584          0.540187  

[13 rows x 1745 columns]

In [39]:
T0503071_final_regression_model = finalize_model(T05_model_xgb)

T0503071_prediction = predict_model(T0503071_final_regression_model, data=T0503071_data)
T0503071_prediction

T0503071_datas = T0503071_prediction['prediction_label']
T0503071_datas = pd.DataFrame(T0503071_datas.values, columns = ['Y_Quality'])

T0503071y_idx= T0503071_class.index
T0503071y_idx = pd.DataFrame(T0503071y_idx, columns = ['index'])
T0503071_datas = pd.concat([T0503071y_idx, T0503071_datas], axis = 1)
T0503071_datas = T0503071_datas.set_index('index')
T0503071_datas

Y_Quality
index           
1       0.541575
3       0.537909
5       0.537806
7       0.539156
9       0.538689
11      0.539457
13      0.538492
15      0.539092
17      0.539066
19      0.539185
24      0.549873
35      0.529839
81      0.543820
82      0.546161
187     0.546038
195     0.545249
198     0.543630
256     0.548650
261     0.537594
296     0.522602
298     0.523417
307     0.525595
316     0.541825
336     0.534985
355     0.547031
356     0.549460
369     0.540290
432     0.532880
444     0.528292
454     0.529072
477     0.524877
541     0.516552
542     0.523678
543     0.520310
544     0.518691
545     0.521212
546     0.519688
549     0.533884
550     0.533809
551     0.526673
552     0.530877
555     0.524168

In [40]:
from pycaret.classification import *
# 분류 패키지의 모든 모듈을 임포트한다.
exp_clf101 = setup(data=T0503071_datas, 
                   target=T0503071_class, 
                   fold=5,
                   session_id=4)
top5 = compare_models(sort='Accuracy', n_select=5)

Processing:   0%|          | 0/73 [00:00<?, ?it/s]

In [41]:
T05_total_models = []

T05_model_lightgbm = create_model('lightgbm', fold = 5)
T05_total_models.append(T05_model_lightgbm)

T05_model_rf = create_model('rf', fold = 5)
T05_total_models.append(T05_model_rf)

T05_model_gbc = create_model('gbc', fold = 5)
T05_total_models.append(T05_model_gbc)

T05_model_et = create_model('et', fold = 5)
T05_total_models.append(T05_model_et)

T05_model_catboost = create_model('catboost', fold = 5)
T05_total_models.append(T05_model_catboost)

T05_model_xgb = create_model('xgboost', fold = 5)
T05_total_models.append(T05_model_xgb)

T05_model_ada = create_model('ada', fold = 5)

T05_total_models.append(T05_model_ada)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [42]:
T05_model_lightgbm = tune_model(T05_model_lightgbm, fold=5, choose_better = True)

T05_model_rf = tune_model(T05_model_rf, fold=5, choose_better = True)

T05_model_gbc = tune_model(T05_model_gbc, fold=5, choose_better = True)

T05_model_et = tune_model(T05_model_et, fold=5, choose_better = True)

T05_model_catboost = tune_model(T05_model_catboost, fold=5, choose_better = True)

T05_model_xgb = tune_model(T05_model_xgb, fold=5, choose_better = True)

T05_model_ada = tune_model(T05_model_ada, fold=5, choose_better = True)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

...

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


In [43]:
T05_tuned_models = [T05_model_lightgbm, T05_model_rf, T05_model_gbc, T05_model_et, T05_model_catboost, T05_model_xgb, T05_model_ada]

for model in T05_tuned_models:
    display(predict_model(model))

Y_Quality  Y_Class  prediction_label  prediction_score
29   0.539156        2                 2            0.9162
30   0.546038        2                 2            0.9162
31   0.540290        2                 2            0.9162
32   0.524168        0                 0            0.7934
33   0.541575        2                 2            0.9162
34   0.538492        2                 2            0.9162
35   0.549873        2                 2            0.9162
36   0.518691        0                 0            0.8355
37   0.539185        2                 2            0.9162
38   0.533809        1                 1            0.5243
39   0.533884        1                 1            0.5243
40   0.526673        1                 0            0.7934
41   0.523678        0                 0            0.8355

Y_Quality  Y_Class  prediction_label  prediction_score
29   0.539156        2                 2              1.00
30   0.546038        2                 2              1.00
31   0.540290        2                 2              1.00
32   0.524168        0                 0              1.00
33   0.541575        2                 2              1.00
34   0.538492        2                 2              1.00
35   0.549873        2                 2              1.00
36   0.518691        0                 0              1.00
37   0.539185        2                 2              1.00
38   0.533809        1                 1              0.98
39   0.533884        1                 1              0.96
40   0.526673        1                 0              0.73
41   0.523678        0                 0              1.00

Y_Quality  Y_Class  prediction_label  prediction_score
29   0.539156        2                 2               1.0
30   0.546038        2                 2               1.0
31   0.540290        2                 2               1.0
32   0.524168        0                 0               1.0
33   0.541575        2                 2               1.0
34   0.538492        2                 2               1.0
35   0.549873        2                 2               1.0
36   0.518691        0                 0               1.0
37   0.539185        2                 2               1.0
38   0.533809        1                 1               1.0
39   0.533884        1                 1               1.0
40   0.526673        1                 0               1.0
41   0.523678        0                 0               1.0

Y_Quality  Y_Class  prediction_label  prediction_score
29   0.539156        2                 2              1.00
30   0.546038        2                 2              1.00
31   0.540290        2                 2              1.00
32   0.524168        0                 0              1.00
33   0.541575        2                 2              1.00
34   0.538492        2                 2              1.00
35   0.549873        2                 2              1.00
36   0.518691        0                 0              1.00
37   0.539185        2                 2              1.00
38   0.533809        1                 1              1.00
39   0.533884        1                 1              1.00
40   0.526673        1                 0              0.63
41   0.523678        0                 0              1.00

Y_Quality  Y_Class  prediction_label  prediction_score
29   0.539156        2                 2            0.9959
30   0.546038        2                 2            0.9954
31   0.540290        2                 2            0.9959
32   0.524168        0                 0            0.9936
33   0.541575        2                 2            0.9958
34   0.538492        2                 2            0.9956
35   0.549873        2                 2            0.9887
36   0.518691        0                 0            0.9945
37   0.539185        2                 2            0.9959
38   0.533809        1                 1            0.9940
39   0.533884        1                 1            0.9940
40   0.526673        1                 0            0.9836
41   0.523678        0                 0            0.9955

Y_Quality  Y_Class  prediction_label  prediction_score
29   0.539156        2                 2            0.9667
30   0.546038        2                 2            0.9667
31   0.540290        2                 2            0.9667
32   0.524168        0                 0            0.9378
33   0.541575        2                 2            0.9667
34   0.538492        2                 2            0.9667
35   0.549873        2                 2            0.9667
36   0.518691        0                 0            0.9378
37   0.539185        2                 2            0.9667
38   0.533809        1                 1            0.9114
39   0.533884        1                 1            0.9114
40   0.526673        1                 0            0.9378
41   0.523678        0                 0            0.9378

Y_Quality  Y_Class  prediction_label  prediction_score
29   0.539156        2                 2               1.0
30   0.546038        2                 2               1.0
31   0.540290        2                 2               1.0
32   0.524168        0                 0               1.0
33   0.541575        2                 2               1.0
34   0.538492        2                 2               1.0
35   0.549873        2                 2               1.0
36   0.518691        0                 0               1.0
37   0.539185        2                 2               1.0
38   0.533809        1                 1               1.0
39   0.533884        1                 1               1.0
40   0.526673        1                 0               1.0
41   0.523678        0                 0               1.0

In [44]:
T0503071_final_classification_model = finalize_model(T05_model_gbc)

T0503071_prediction = predict_model(T0503071_final_classification_model, data=T0503071_datas)

T0503071_y_class = pd.DataFrame(T0503071_class, columns = ['Y_Class'])
T0503071_idx = T0503071_y_class.index
T0503071_y_class = T0503071_y_class.reset_index()
T0503071_prediction = pd.concat([T0503071_prediction, T0503071_y_class], axis = 1)
T0503071_prediction = T0503071_prediction.set_index('index')
T0503071_prediction.drop(['Y_Class'], axis = 1, inplace = True)

# 3

In [45]:
T0103051_class = T0103051['Y_Class']
T0103051_target = T0103051['Y_Quality']
T0103051_data = T0103051.drop(['Y_Class', 'Y_Quality'], axis = 1)

In [46]:
T0103051c = T0103051_data.columns
T0103051scaler = RobustScaler()
T0103051scaled = T0103051scaler.fit_transform(T0103051_data)
T0103051_data = pd.DataFrame(T0103051scaled, columns = T0103051c)

T0103051_y_class = pd.DataFrame(T0103051_target, columns = ['Y_Quality'])
T0103051_idx = T0103051_y_class.index
T0103051_y_class = T0103051_y_class.reset_index()
T0103051_data = pd.concat([T0103051_data, T0103051_y_class], axis = 1)
T0103051_data = T0103051_data.set_index('index')
T0103051_data.drop(['Y_Quality'], axis = 1, inplace = True)
T0103051_data

PRODUCT_CODE  X_246     X_247     X_251  X_253     X_256     X_257  \
index                                                                       
28              0.0    0.0  0.000000  0.000000    0.0 -0.221574 -0.247475   
33              0.0    0.0  2.000000  0.105960    0.0 -0.204082 -0.171717   
39              0.0    0.0  2.000000  0.158940    1.0 -0.128280 -0.121212   
40              0.0    0.0  2.000000  0.198675    0.0  0.005831  0.000000   
41              0.0    0.0 -0.666667  0.198675    0.0  0.000000  0.000000   
48              0.0    0.0  0.666667  0.278146    0.0 -0.034985  0.015152   
52              0.0    1.0 -0.666667  0.317881    0.0  0.017493  0.101010   
57              0.0    1.0 -0.666667  0.384106    0.0  0.093294  0.171717   
58              0.0    0.0 -0.333333  0.384106    0.0  0.134111  0.186869   
59              0.0    1.0 -0.333333  0.397351    0.0  0.099125  0.126263   
64              0.0    0.0  0.333333  0.463576    0.0  0.221574  0.247475   
65              0.0    1.0 -0.666667  0.476821    0.0  0.192420  0.222222   
66              0.0    1.0 -0.333333  0.490066    0.0  0.309038  0.308081   
69              0.0    1.0  0.666667  0.516556    0.0  0.314869  0.308081   
71              0.0    0.0  0.000000  0.516556    0.0  0.303207  0.323232   
75              0.0    1.0  0.000000  0.596026    0.0  0.536443  0.560606   
77              0.0    0.0  2.000000  0.768212    0.0  0.740525  0.732323   
84              0.0    0.0  2.000000  0.860927    0.0  0.927114  0.909091   
90              0.0    1.0  0.000000  0.966887    0.0  0.810496  0.782828   
94              0.0    0.0 -0.333333  1.019868    0.0  0.880466  0.858586   
95              0.0    1.0  0.333333  1.033113    0.0  0.874636  0.858586   
116             0.0    0.0  2.000000 -1.165563    0.0 -2.699708 -2.343434   
118             0.0    0.0  0.666667 -1.165563    1.0 -2.717201 -2.429293   
123             0.0    1.0  1.333333 -1.086093    0.0 -1.597668 -1.479798   
129             0.0    0.0  0.000000 -1.019868    1.0 -1.265306 -1.181818   
179             0.0    0.0 -0.666667 -1.046358    0.0 -0.606414 -0.626263   
190             0.0    0.0  2.000000 -0.900662    0.0 -0.542274 -0.626263   
208             0.0    0.0  2.000000 -0.821192    0.0 -0.379009 -0.383838   
220             0.0    1.0  1.333333 -0.741722    0.0 -0.454810 -0.494949   
230             0.0    1.0  0.666667 -0.688742    0.0 -0.396501 -0.444444   
235             0.0    1.0 -0.333333 -0.635762    0.0 -0.314869 -0.393939   
239             0.0    1.0 -0.333333 -0.609272    0.0 -0.285714 -0.333333   
244             0.0    0.0  0.333333 -0.582781    0.0 -0.268222 -0.333333   
281             0.0    1.0 -0.333333 -0.066225    0.0  0.542274  0.489899   
283             0.0    0.0  0.000000 -0.066225    1.0  0.536443  0.489899   
287             0.0    0.0  0.333333 -0.039735    0.0  0.542274  0.500000   
291             0.0    0.0  0.333333 -0.013245    0.0  0.641399  0.611111   
292             0.0    0.0  0.000000 -0.013245    0.0  0.676385  0.621212   
295             0.0    0.0  0.000000  0.013245    0.0  0.653061  0.636364   
299             0.0    0.0  2.333333  0.039735    0.0  0.769679  0.696970   
300             0.0    0.0 -0.666667  0.039735    0.0  0.705539  0.661616   
312             0.0    0.0 -0.333333  0.079470    0.0  0.827988  0.797980   
332             0.0    0.0  0.333333  0.278146    0.0  1.102041  1.055556   
334             0.0    1.0 -0.333333  0.278146    0.0  1.102041  1.055556   
404             0.0    0.0  0.333333 -1.006623    0.0 -1.335277 -1.232323   
410             0.0    0.0 -0.333333 -0.940397    0.0 -1.311953 -1.232323   
436             0.0    0.0  0.333333 -0.728477    0.0 -1.014577 -0.984848   
449             0.0   10.0  0.333333 -0.622517    0.0 -0.798834 -0.762626   
455             0.0    0.0  0.000000 -0.596026    0.0 -0.868805 -0.813131   
456             0.0    0.0  0.666667 -0.596026    0.0 -0.903790 -0.914141   
480

In [47]:
from pycaret.regression import *
setup_rgs = setup(data = T0103051_data, target = T0103051_target, session_id = 4)
top5 = compare_models(sort='MSE', n_select=5)

Processing:   0%|          | 0/89 [00:00<?, ?it/s]

In [48]:
T01_total_models = []

T01_model_lightgbm = create_model('lightgbm', fold = 5)
T01_total_models.append(T01_model_lightgbm)

T01_model_rf = create_model('rf', fold = 5)
T01_total_models.append(T01_model_rf)

T01_model_gbr = create_model('gbr', fold = 5)
T01_total_models.append(T01_model_gbr)

T01_model_et = create_model('et', fold = 5)
T01_total_models.append(T01_model_et)

T01_model_catboost = create_model('catboost', fold = 5)
T01_total_models.append(T01_model_catboost)

T01_model_xgb = create_model('xgboost', fold = 5)
T01_total_models.append(T01_model_xgb)

T01_model_ada = create_model('ada', fold = 5)
T01_total_models.append(T01_model_ada)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [49]:
T01_model_lightgbm = tune_model(T01_model_lightgbm, fold=5, choose_better = True)

T01_model_rf = tune_model(T01_model_rf, fold=5, choose_better = True)

T01_model_gbr = tune_model(T01_model_gbr, fold=5, choose_better = True)

T01_model_et = tune_model(T01_model_et, fold=5, choose_better = True)

T01_model_catboost = tune_model(T01_model_catboost, fold=5, choose_better = True)

T01_model_xgb = tune_model(T01_model_xgb, fold=5, choose_better = True)

T01_model_ada = tune_model(T01_model_ada, fold=5, choose_better = True)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

...

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


In [50]:
T01_tuned_models = [T01_model_lightgbm, T01_model_rf, T01_model_gbr, T01_model_et, T01_model_catboost, T01_model_xgb, T01_model_ada]

for model in T01_tuned_models:
    display(predict_model(model))

PRODUCT_CODE  X_246     X_247     X_251  X_253     X_256     X_257  \
41           0.0    0.0 -0.666667  0.198675    0.0  0.000000  0.000000   
42           0.0    1.0  0.333333  1.033113    0.0  0.874636  0.858586   
43           0.0    1.0  0.333333  0.423841    0.0  0.215743  0.222222   
44           0.0    0.0  0.000000 -1.019868    1.0 -1.265306 -1.181818   
45           0.0    1.0 -0.333333  0.490066    0.0  0.309038  0.308081   
46           0.0    1.0  1.333333 -0.741722    0.0 -0.454811 -0.494949   
47           0.0    0.0  0.333333 -0.039735    0.0  0.542274  0.500000   
48           0.0    0.0  0.333333 -0.582781    0.0 -0.268222 -0.333333   
49           0.0    1.0 -0.666667  0.317881    0.0  0.017493  0.101010   
50           0.0    1.0 -0.333333  0.278146    0.0  1.102041  1.055556   
51           0.0    1.0 -0.666667  0.384106    0.0  0.093294  0.171717   
52           0.0    0.0 -0.666667 -1.046358    0.0 -0.606414 -0.626263   
53           0.0    1.0 -0.666667  0.476821    0.0  0.192420  0.222222   
54           0.0    0.0  0.000000  0.516556    0.0  0.303207  0.323232   
55           0.0    0.0  0.000000 -0.013245    0.0  0.676385  0.621212   
56           0.0    0.0  2.000000 -0.900662    0.0 -0.542274 -0.626263   
57           0.0    0.0  2.000000  0.768212    0.0  0.740525  0.732323   
58           0.0    0.0  2.000000  0.860927    0.0  0.927114  0.909091   

       X_258  X_261     X_262  ...    X_2858    X_2859    X_2860    X_2861  \
41  0.091954    1.0  0.333333  ... -1.185290 -1.515790  0.027149 -0.018761   
42  0.873563    0.0  0.333333  ... -0.874603 -0.463158  0.371041 -0.046244   
43  0.222222    0.0  0.000000  ...  1.253015  1.052632  1.728507  2.012444   
44 -1.609195    0.5  0.333333  ... -1.674824 -1.089474 -1.746606 -1.170464   
45  0.444444    0.5  0.666667  ...  0.354302  0.747368  0.751131  1.374572   
46 -0.375479   -0.5 -0.666667  ... -0.211231 -0.547368 -1.285068 -1.503554   
47  0.574713    0.5  0.333333  ... -0.172034 -0.352632 -0.923077 -0.738041   
48 -0.168582    0.0 -0.333333  ... -0.073931  0.000000 -0.407240 -0.188160   
49 -0.022989   -0.5 -1.000000  ... -0.436182 -1.000000  0.171946  0.162148   
50  1.402299    0.0  0.333333  ...  0.182059  0.131579  0.235294  0.254242   
51  0.000000   -0.5 -0.666667  ...  0.800936  0.394737  1.393665  1.810429   
52 -0.505747    0.0  0.666667  ... -0.649287 -0.242105 -0.950226 -0.276640   
53  0.168582   -1.0 -1.000000  ...  1.130196  0.863158  0.895928  1.532030   
54  0.275862    0.5  0.000000  ... -0.626733 -0.331579  0.171946  0.671313   
55  0.835249    1.0  0.333333  ... -0.204519  0.089474 -0.932127 -0.707937   
56 -0.467433    0.0  0.000000  ... -0.650640 -0.768421  0.271493 -0.343607   
57  0.781609   -1.0 -1.000000  ... -1.238425 -0.347368  1.520362  1.743090   
58  1.042146    0.0  0.666667  ... -1.499353 -0.873684 -0.986425 -1.592393   

      X_2862  X_2863    X_2864  X_2865  Y_Quality  prediction_label  
41  0.153846    -1.9 -1.455824    -8.5   0.528270          0.528743  
42 -0.529231     0.1  0.854574     0.0   0.536041          0.535054  
43  1.310769     0.1  0.343306     0.5   0.524686          0.531437  
44 -0.646154     0.1  0.828347     4.5   0.528856          0.519974  
45  1.206154     0.1  0.915854     5.5   0.524408          0.531996  
46 -0.972308     0.1  0.514856     0.0   0.529254          0.524945  
47 -0.400000     0.1  0.360461    -0.5   0.531036          0.530924  
48  0.018462     0.0  0.435514     0.0   0.527486          0.525037  
49  0.264615    -2.0 -1.503000    -5.0   0.555514          0.527057  
50 -0.061538    -0.9 -0.299429     0.0   0.529070          0.535712  
51  1.316923    -2.8 -2.641663   -13.5   0.535741          0.537042  
52  0.289231     0.1  0.684097     5.0   0.526741          0.523805  
53  0.904615    -0.2 -0.117734     0.0   0.527910          0.536674  
54  0.596923     0.1  0.688468     4.5   0.534486          0.530986  
55 -0.621538     0.1  0.852389     4.5   0.558770          0.533

PRODUCT_CODE  X_246     X_247     X_251  X_253     X_256     X_257  \
41           0.0    0.0 -0.666667  0.198675    0.0  0.000000  0.000000   
42           0.0    1.0  0.333333  1.033113    0.0  0.874636  0.858586   
43           0.0    1.0  0.333333  0.423841    0.0  0.215743  0.222222   
44           0.0    0.0  0.000000 -1.019868    1.0 -1.265306 -1.181818   
45           0.0    1.0 -0.333333  0.490066    0.0  0.309038  0.308081   
46           0.0    1.0  1.333333 -0.741722    0.0 -0.454811 -0.494949   
47           0.0    0.0  0.333333 -0.039735    0.0  0.542274  0.500000   
48           0.0    0.0  0.333333 -0.582781    0.0 -0.268222 -0.333333   
49           0.0    1.0 -0.666667  0.317881    0.0  0.017493  0.101010   
50           0.0    1.0 -0.333333  0.278146    0.0  1.102041  1.055556   
51           0.0    1.0 -0.666667  0.384106    0.0  0.093294  0.171717   
52           0.0    0.0 -0.666667 -1.046358    0.0 -0.606414 -0.626263   
53           0.0    1.0 -0.666667  0.476821    0.0  0.192420  0.222222   
54           0.0    0.0  0.000000  0.516556    0.0  0.303207  0.323232   
55           0.0    0.0  0.000000 -0.013245    0.0  0.676385  0.621212   
56           0.0    0.0  2.000000 -0.900662    0.0 -0.542274 -0.626263   
57           0.0    0.0  2.000000  0.768212    0.0  0.740525  0.732323   
58           0.0    0.0  2.000000  0.860927    0.0  0.927114  0.909091   

       X_258  X_261     X_262  ...    X_2858    X_2859    X_2860    X_2861  \
41  0.091954    1.0  0.333333  ... -1.185290 -1.515790  0.027149 -0.018761   
42  0.873563    0.0  0.333333  ... -0.874603 -0.463158  0.371041 -0.046244   
43  0.222222    0.0  0.000000  ...  1.253015  1.052632  1.728507  2.012444   
44 -1.609195    0.5  0.333333  ... -1.674824 -1.089474 -1.746606 -1.170464   
45  0.444444    0.5  0.666667  ...  0.354302  0.747368  0.751131  1.374572   
46 -0.375479   -0.5 -0.666667  ... -0.211231 -0.547368 -1.285068 -1.503554   
47  0.574713    0.5  0.333333  ... -0.172034 -0.352632 -0.923077 -0.738041   
48 -0.168582    0.0 -0.333333  ... -0.073931  0.000000 -0.407240 -0.188160   
49 -0.022989   -0.5 -1.000000  ... -0.436182 -1.000000  0.171946  0.162148   
50  1.402299    0.0  0.333333  ...  0.182059  0.131579  0.235294  0.254242   
51  0.000000   -0.5 -0.666667  ...  0.800936  0.394737  1.393665  1.810429   
52 -0.505747    0.0  0.666667  ... -0.649287 -0.242105 -0.950226 -0.276640   
53  0.168582   -1.0 -1.000000  ...  1.130196  0.863158  0.895928  1.532030   
54  0.275862    0.5  0.000000  ... -0.626733 -0.331579  0.171946  0.671313   
55  0.835249    1.0  0.333333  ... -0.204519  0.089474 -0.932127 -0.707937   
56 -0.467433    0.0  0.000000  ... -0.650640 -0.768421  0.271493 -0.343607   
57  0.781609   -1.0 -1.000000  ... -1.238425 -0.347368  1.520362  1.743090   
58  1.042146    0.0  0.666667  ... -1.499353 -0.873684 -0.986425 -1.592393   

      X_2862  X_2863    X_2864  X_2865  Y_Quality  prediction_label  
41  0.153846    -1.9 -1.455824    -8.5   0.528270          0.530508  
42 -0.529231     0.1  0.854574     0.0   0.536041          0.532193  
43  1.310769     0.1  0.343306     0.5   0.524686          0.528799  
44 -0.646154     0.1  0.828347     4.5   0.528856          0.524606  
45  1.206154     0.1  0.915854     5.5   0.524408          0.532646  
46 -0.972308     0.1  0.514856     0.0   0.529254          0.527535  
47 -0.400000     0.1  0.360461    -0.5   0.531036          0.530997  
48  0.018462     0.0  0.435514     0.0   0.527486          0.528546  
49  0.264615    -2.0 -1.503000    -5.0   0.555514          0.532088  
50 -0.061538    -0.9 -0.299429     0.0   0.529070          0.533160  
51  1.316923    -2.8 -2.641663   -13.5   0.535741          0.534212  
52  0.289231     0.1  0.684097     5.0   0.526741          0.527672  
53  0.904615    -0.2 -0.117734     0.0   0.527910          0.534202  
54  0.596923     0.1  0.688468     4.5   0.534486          0.532049  
55 -0.621538     0.1  0.852389     4.5   0.558770          0.531

PRODUCT_CODE  X_246     X_247     X_251  X_253     X_256     X_257  \
41           0.0    0.0 -0.666667  0.198675    0.0  0.000000  0.000000   
42           0.0    1.0  0.333333  1.033113    0.0  0.874636  0.858586   
43           0.0    1.0  0.333333  0.423841    0.0  0.215743  0.222222   
44           0.0    0.0  0.000000 -1.019868    1.0 -1.265306 -1.181818   
45           0.0    1.0 -0.333333  0.490066    0.0  0.309038  0.308081   
46           0.0    1.0  1.333333 -0.741722    0.0 -0.454811 -0.494949   
47           0.0    0.0  0.333333 -0.039735    0.0  0.542274  0.500000   
48           0.0    0.0  0.333333 -0.582781    0.0 -0.268222 -0.333333   
49           0.0    1.0 -0.666667  0.317881    0.0  0.017493  0.101010   
50           0.0    1.0 -0.333333  0.278146    0.0  1.102041  1.055556   
51           0.0    1.0 -0.666667  0.384106    0.0  0.093294  0.171717   
52           0.0    0.0 -0.666667 -1.046358    0.0 -0.606414 -0.626263   
53           0.0    1.0 -0.666667  0.476821    0.0  0.192420  0.222222   
54           0.0    0.0  0.000000  0.516556    0.0  0.303207  0.323232   
55           0.0    0.0  0.000000 -0.013245    0.0  0.676385  0.621212   
56           0.0    0.0  2.000000 -0.900662    0.0 -0.542274 -0.626263   
57           0.0    0.0  2.000000  0.768212    0.0  0.740525  0.732323   
58           0.0    0.0  2.000000  0.860927    0.0  0.927114  0.909091   

       X_258  X_261     X_262  ...    X_2858    X_2859    X_2860    X_2861  \
41  0.091954    1.0  0.333333  ... -1.185290 -1.515790  0.027149 -0.018761   
42  0.873563    0.0  0.333333  ... -0.874603 -0.463158  0.371041 -0.046244   
43  0.222222    0.0  0.000000  ...  1.253015  1.052632  1.728507  2.012444   
44 -1.609195    0.5  0.333333  ... -1.674824 -1.089474 -1.746606 -1.170464   
45  0.444444    0.5  0.666667  ...  0.354302  0.747368  0.751131  1.374572   
46 -0.375479   -0.5 -0.666667  ... -0.211231 -0.547368 -1.285068 -1.503554   
47  0.574713    0.5  0.333333  ... -0.172034 -0.352632 -0.923077 -0.738041   
48 -0.168582    0.0 -0.333333  ... -0.073931  0.000000 -0.407240 -0.188160   
49 -0.022989   -0.5 -1.000000  ... -0.436182 -1.000000  0.171946  0.162148   
50  1.402299    0.0  0.333333  ...  0.182059  0.131579  0.235294  0.254242   
51  0.000000   -0.5 -0.666667  ...  0.800936  0.394737  1.393665  1.810429   
52 -0.505747    0.0  0.666667  ... -0.649287 -0.242105 -0.950226 -0.276640   
53  0.168582   -1.0 -1.000000  ...  1.130196  0.863158  0.895928  1.532030   
54  0.275862    0.5  0.000000  ... -0.626733 -0.331579  0.171946  0.671313   
55  0.835249    1.0  0.333333  ... -0.204519  0.089474 -0.932127 -0.707937   
56 -0.467433    0.0  0.000000  ... -0.650640 -0.768421  0.271493 -0.343607   
57  0.781609   -1.0 -1.000000  ... -1.238425 -0.347368  1.520362  1.743090   
58  1.042146    0.0  0.666667  ... -1.499353 -0.873684 -0.986425 -1.592393   

      X_2862  X_2863    X_2864  X_2865  Y_Quality  prediction_label  
41  0.153846    -1.9 -1.455824    -8.5   0.528270          0.531142  
42 -0.529231     0.1  0.854574     0.0   0.536041          0.533826  
43  1.310769     0.1  0.343306     0.5   0.524686          0.528644  
44 -0.646154     0.1  0.828347     4.5   0.528856          0.525519  
45  1.206154     0.1  0.915854     5.5   0.524408          0.532474  
46 -0.972308     0.1  0.514856     0.0   0.529254          0.526641  
47 -0.400000     0.1  0.360461    -0.5   0.531036          0.537091  
48  0.018462     0.0  0.435514     0.0   0.527486          0.532327  
49  0.264615    -2.0 -1.503000    -5.0   0.555514          0.535206  
50 -0.061538    -0.9 -0.299429     0.0   0.529070          0.533199  
51  1.316923    -2.8 -2.641663   -13.5   0.535741          0.534796  
52  0.289231     0.1  0.684097     5.0   0.526741          0.528577  
53  0.904615    -0.2 -0.117734     0.0   0.527910          0.532076  
54  0.596923     0.1  0.688468     4.5   0.534486          0.531254  
55 -0.621538     0.1  0.852389     4.5   0.558770          0.533

PRODUCT_CODE  X_246     X_247     X_251  X_253     X_256     X_257  \
41           0.0    0.0 -0.666667  0.198675    0.0  0.000000  0.000000   
42           0.0    1.0  0.333333  1.033113    0.0  0.874636  0.858586   
43           0.0    1.0  0.333333  0.423841    0.0  0.215743  0.222222   
44           0.0    0.0  0.000000 -1.019868    1.0 -1.265306 -1.181818   
45           0.0    1.0 -0.333333  0.490066    0.0  0.309038  0.308081   
46           0.0    1.0  1.333333 -0.741722    0.0 -0.454811 -0.494949   
47           0.0    0.0  0.333333 -0.039735    0.0  0.542274  0.500000   
48           0.0    0.0  0.333333 -0.582781    0.0 -0.268222 -0.333333   
49           0.0    1.0 -0.666667  0.317881    0.0  0.017493  0.101010   
50           0.0    1.0 -0.333333  0.278146    0.0  1.102041  1.055556   
51           0.0    1.0 -0.666667  0.384106    0.0  0.093294  0.171717   
52           0.0    0.0 -0.666667 -1.046358    0.0 -0.606414 -0.626263   
53           0.0    1.0 -0.666667  0.476821    0.0  0.192420  0.222222   
54           0.0    0.0  0.000000  0.516556    0.0  0.303207  0.323232   
55           0.0    0.0  0.000000 -0.013245    0.0  0.676385  0.621212   
56           0.0    0.0  2.000000 -0.900662    0.0 -0.542274 -0.626263   
57           0.0    0.0  2.000000  0.768212    0.0  0.740525  0.732323   
58           0.0    0.0  2.000000  0.860927    0.0  0.927114  0.909091   

       X_258  X_261     X_262  ...    X_2858    X_2859    X_2860    X_2861  \
41  0.091954    1.0  0.333333  ... -1.185290 -1.515790  0.027149 -0.018761   
42  0.873563    0.0  0.333333  ... -0.874603 -0.463158  0.371041 -0.046244   
43  0.222222    0.0  0.000000  ...  1.253015  1.052632  1.728507  2.012444   
44 -1.609195    0.5  0.333333  ... -1.674824 -1.089474 -1.746606 -1.170464   
45  0.444444    0.5  0.666667  ...  0.354302  0.747368  0.751131  1.374572   
46 -0.375479   -0.5 -0.666667  ... -0.211231 -0.547368 -1.285068 -1.503554   
47  0.574713    0.5  0.333333  ... -0.172034 -0.352632 -0.923077 -0.738041   
48 -0.168582    0.0 -0.333333  ... -0.073931  0.000000 -0.407240 -0.188160   
49 -0.022989   -0.5 -1.000000  ... -0.436182 -1.000000  0.171946  0.162148   
50  1.402299    0.0  0.333333  ...  0.182059  0.131579  0.235294  0.254242   
51  0.000000   -0.5 -0.666667  ...  0.800936  0.394737  1.393665  1.810429   
52 -0.505747    0.0  0.666667  ... -0.649287 -0.242105 -0.950226 -0.276640   
53  0.168582   -1.0 -1.000000  ...  1.130196  0.863158  0.895928  1.532030   
54  0.275862    0.5  0.000000  ... -0.626733 -0.331579  0.171946  0.671313   
55  0.835249    1.0  0.333333  ... -0.204519  0.089474 -0.932127 -0.707937   
56 -0.467433    0.0  0.000000  ... -0.650640 -0.768421  0.271493 -0.343607   
57  0.781609   -1.0 -1.000000  ... -1.238425 -0.347368  1.520362  1.743090   
58  1.042146    0.0  0.666667  ... -1.499353 -0.873684 -0.986425 -1.592393   

      X_2862  X_2863    X_2864  X_2865  Y_Quality  prediction_label  
41  0.153846    -1.9 -1.455824    -8.5   0.528270          0.530917  
42 -0.529231     0.1  0.854574     0.0   0.536041          0.535448  
43  1.310769     0.1  0.343306     0.5   0.524686          0.529737  
44 -0.646154     0.1  0.828347     4.5   0.528856          0.519883  
45  1.206154     0.1  0.915854     5.5   0.524408          0.533464  
46 -0.972308     0.1  0.514856     0.0   0.529254          0.528933  
47 -0.400000     0.1  0.360461    -0.5   0.531036          0.533688  
48  0.018462     0.0  0.435514     0.0   0.527486          0.528668  
49  0.264615    -2.0 -1.503000    -5.0   0.555514          0.538410  
50 -0.061538    -0.9 -0.299429     0.0   0.529070          0.532723  
51  1.316923    -2.8 -2.641663   -13.5   0.535741          0.535733  
52  0.289231     0.1  0.684097     5.0   0.526741          0.525682  
53  0.904615    -0.2 -0.117734     0.0   0.527910          0.535278  
54  0.596923     0.1  0.688468     4.5   0.534486          0.533974  
55 -0.621538     0.1  0.852389     4.5   0.558770          0.546

PRODUCT_CODE  X_246     X_247     X_251  X_253     X_256     X_257  \
41           0.0    0.0 -0.666667  0.198675    0.0  0.000000  0.000000   
42           0.0    1.0  0.333333  1.033113    0.0  0.874636  0.858586   
43           0.0    1.0  0.333333  0.423841    0.0  0.215743  0.222222   
44           0.0    0.0  0.000000 -1.019868    1.0 -1.265306 -1.181818   
45           0.0    1.0 -0.333333  0.490066    0.0  0.309038  0.308081   
46           0.0    1.0  1.333333 -0.741722    0.0 -0.454811 -0.494949   
47           0.0    0.0  0.333333 -0.039735    0.0  0.542274  0.500000   
48           0.0    0.0  0.333333 -0.582781    0.0 -0.268222 -0.333333   
49           0.0    1.0 -0.666667  0.317881    0.0  0.017493  0.101010   
50           0.0    1.0 -0.333333  0.278146    0.0  1.102041  1.055556   
51           0.0    1.0 -0.666667  0.384106    0.0  0.093294  0.171717   
52           0.0    0.0 -0.666667 -1.046358    0.0 -0.606414 -0.626263   
53           0.0    1.0 -0.666667  0.476821    0.0  0.192420  0.222222   
54           0.0    0.0  0.000000  0.516556    0.0  0.303207  0.323232   
55           0.0    0.0  0.000000 -0.013245    0.0  0.676385  0.621212   
56           0.0    0.0  2.000000 -0.900662    0.0 -0.542274 -0.626263   
57           0.0    0.0  2.000000  0.768212    0.0  0.740525  0.732323   
58           0.0    0.0  2.000000  0.860927    0.0  0.927114  0.909091   

       X_258  X_261     X_262  ...    X_2858    X_2859    X_2860    X_2861  \
41  0.091954    1.0  0.333333  ... -1.185290 -1.515790  0.027149 -0.018761   
42  0.873563    0.0  0.333333  ... -0.874603 -0.463158  0.371041 -0.046244   
43  0.222222    0.0  0.000000  ...  1.253015  1.052632  1.728507  2.012444   
44 -1.609195    0.5  0.333333  ... -1.674824 -1.089474 -1.746606 -1.170464   
45  0.444444    0.5  0.666667  ...  0.354302  0.747368  0.751131  1.374572   
46 -0.375479   -0.5 -0.666667  ... -0.211231 -0.547368 -1.285068 -1.503554   
47  0.574713    0.5  0.333333  ... -0.172034 -0.352632 -0.923077 -0.738041   
48 -0.168582    0.0 -0.333333  ... -0.073931  0.000000 -0.407240 -0.188160   
49 -0.022989   -0.5 -1.000000  ... -0.436182 -1.000000  0.171946  0.162148   
50  1.402299    0.0  0.333333  ...  0.182059  0.131579  0.235294  0.254242   
51  0.000000   -0.5 -0.666667  ...  0.800936  0.394737  1.393665  1.810429   
52 -0.505747    0.0  0.666667  ... -0.649287 -0.242105 -0.950226 -0.276640   
53  0.168582   -1.0 -1.000000  ...  1.130196  0.863158  0.895928  1.532030   
54  0.275862    0.5  0.000000  ... -0.626733 -0.331579  0.171946  0.671313   
55  0.835249    1.0  0.333333  ... -0.204519  0.089474 -0.932127 -0.707937   
56 -0.467433    0.0  0.000000  ... -0.650640 -0.768421  0.271493 -0.343607   
57  0.781609   -1.0 -1.000000  ... -1.238425 -0.347368  1.520362  1.743090   
58  1.042146    0.0  0.666667  ... -1.499353 -0.873684 -0.986425 -1.592393   

      X_2862  X_2863    X_2864  X_2865  Y_Quality  prediction_label  
41  0.153846    -1.9 -1.455824    -8.5   0.528270          0.530565  
42 -0.529231     0.1  0.854574     0.0   0.536041          0.533386  
43  1.310769     0.1  0.343306     0.5   0.524686          0.530748  
44 -0.646154     0.1  0.828347     4.5   0.528856          0.524197  
45  1.206154     0.1  0.915854     5.5   0.524408          0.534002  
46 -0.972308     0.1  0.514856     0.0   0.529254          0.529074  
47 -0.400000     0.1  0.360461    -0.5   0.531036          0.533538  
48  0.018462     0.0  0.435514     0.0   0.527486          0.529706  
49  0.264615    -2.0 -1.503000    -5.0   0.555514          0.532326  
50 -0.061538    -0.9 -0.299429     0.0   0.529070          0.533447  
51  1.316923    -2.8 -2.641663   -13.5   0.535741          0.534220  
52  0.289231     0.1  0.684097     5.0   0.526741          0.525862  
53  0.904615    -0.2 -0.117734     0.0   0.527910          0.533383  
54  0.596923     0.1  0.688468     4.5   0.534486          0.532673  
55 -0.621538     0.1  0.852389     4.5   0.558770          0.534

PRODUCT_CODE  X_246     X_247     X_251  X_253     X_256     X_257  \
41           0.0    0.0 -0.666667  0.198675    0.0  0.000000  0.000000   
42           0.0    1.0  0.333333  1.033113    0.0  0.874636  0.858586   
43           0.0    1.0  0.333333  0.423841    0.0  0.215743  0.222222   
44           0.0    0.0  0.000000 -1.019868    1.0 -1.265306 -1.181818   
45           0.0    1.0 -0.333333  0.490066    0.0  0.309038  0.308081   
46           0.0    1.0  1.333333 -0.741722    0.0 -0.454811 -0.494949   
47           0.0    0.0  0.333333 -0.039735    0.0  0.542274  0.500000   
48           0.0    0.0  0.333333 -0.582781    0.0 -0.268222 -0.333333   
49           0.0    1.0 -0.666667  0.317881    0.0  0.017493  0.101010   
50           0.0    1.0 -0.333333  0.278146    0.0  1.102041  1.055556   
51           0.0    1.0 -0.666667  0.384106    0.0  0.093294  0.171717   
52           0.0    0.0 -0.666667 -1.046358    0.0 -0.606414 -0.626263   
53           0.0    1.0 -0.666667  0.476821    0.0  0.192420  0.222222   
54           0.0    0.0  0.000000  0.516556    0.0  0.303207  0.323232   
55           0.0    0.0  0.000000 -0.013245    0.0  0.676385  0.621212   
56           0.0    0.0  2.000000 -0.900662    0.0 -0.542274 -0.626263   
57           0.0    0.0  2.000000  0.768212    0.0  0.740525  0.732323   
58           0.0    0.0  2.000000  0.860927    0.0  0.927114  0.909091   

       X_258  X_261     X_262  ...    X_2858    X_2859    X_2860    X_2861  \
41  0.091954    1.0  0.333333  ... -1.185290 -1.515790  0.027149 -0.018761   
42  0.873563    0.0  0.333333  ... -0.874603 -0.463158  0.371041 -0.046244   
43  0.222222    0.0  0.000000  ...  1.253015  1.052632  1.728507  2.012444   
44 -1.609195    0.5  0.333333  ... -1.674824 -1.089474 -1.746606 -1.170464   
45  0.444444    0.5  0.666667  ...  0.354302  0.747368  0.751131  1.374572   
46 -0.375479   -0.5 -0.666667  ... -0.211231 -0.547368 -1.285068 -1.503554   
47  0.574713    0.5  0.333333  ... -0.172034 -0.352632 -0.923077 -0.738041   
48 -0.168582    0.0 -0.333333  ... -0.073931  0.000000 -0.407240 -0.188160   
49 -0.022989   -0.5 -1.000000  ... -0.436182 -1.000000  0.171946  0.162148   
50  1.402299    0.0  0.333333  ...  0.182059  0.131579  0.235294  0.254242   
51  0.000000   -0.5 -0.666667  ...  0.800936  0.394737  1.393665  1.810429   
52 -0.505747    0.0  0.666667  ... -0.649287 -0.242105 -0.950226 -0.276640   
53  0.168582   -1.0 -1.000000  ...  1.130196  0.863158  0.895928  1.532030   
54  0.275862    0.5  0.000000  ... -0.626733 -0.331579  0.171946  0.671313   
55  0.835249    1.0  0.333333  ... -0.204519  0.089474 -0.932127 -0.707937   
56 -0.467433    0.0  0.000000  ... -0.650640 -0.768421  0.271493 -0.343607   
57  0.781609   -1.0 -1.000000  ... -1.238425 -0.347368  1.520362  1.743090   
58  1.042146    0.0  0.666667  ... -1.499353 -0.873684 -0.986425 -1.592393   

      X_2862  X_2863    X_2864  X_2865  Y_Quality  prediction_label  
41  0.153846    -1.9 -1.455824    -8.5   0.528270          0.531284  
42 -0.529231     0.1  0.854574     0.0   0.536041          0.534042  
43  1.310769     0.1  0.343306     0.5   0.524686          0.531482  
44 -0.646154     0.1  0.828347     4.5   0.528856          0.522924  
45  1.206154     0.1  0.915854     5.5   0.524408          0.535809  
46 -0.972308     0.1  0.514856     0.0   0.529254          0.530735  
47 -0.400000     0.1  0.360461    -0.5   0.531036          0.534894  
48  0.018462     0.0  0.435514     0.0   0.527486          0.530014  
49  0.264615    -2.0 -1.503000    -5.0   0.555514          0.554812  
50 -0.061538    -0.9 -0.299429     0.0   0.529070          0.534364  
51  1.316923    -2.8 -2.641663   -13.5   0.535741          0.528981  
52  0.289231     0.1  0.684097     5.0   0.526741          0.526085  
53  0.904615    -0.2 -0.117734     0.0   0.527910          0.533472  
54  0.596923     0.1  0.688468     4.5   0.534486          0.531657  
55 -0.621538     0.1  0.852389     4.5   0.558770          0.553

PRODUCT_CODE  X_246     X_247     X_251  X_253     X_256     X_257  \
41           0.0    0.0 -0.666667  0.198675    0.0  0.000000  0.000000   
42           0.0    1.0  0.333333  1.033113    0.0  0.874636  0.858586   
43           0.0    1.0  0.333333  0.423841    0.0  0.215743  0.222222   
44           0.0    0.0  0.000000 -1.019868    1.0 -1.265306 -1.181818   
45           0.0    1.0 -0.333333  0.490066    0.0  0.309038  0.308081   
46           0.0    1.0  1.333333 -0.741722    0.0 -0.454811 -0.494949   
47           0.0    0.0  0.333333 -0.039735    0.0  0.542274  0.500000   
48           0.0    0.0  0.333333 -0.582781    0.0 -0.268222 -0.333333   
49           0.0    1.0 -0.666667  0.317881    0.0  0.017493  0.101010   
50           0.0    1.0 -0.333333  0.278146    0.0  1.102041  1.055556   
51           0.0    1.0 -0.666667  0.384106    0.0  0.093294  0.171717   
52           0.0    0.0 -0.666667 -1.046358    0.0 -0.606414 -0.626263   
53           0.0    1.0 -0.666667  0.476821    0.0  0.192420  0.222222   
54           0.0    0.0  0.000000  0.516556    0.0  0.303207  0.323232   
55           0.0    0.0  0.000000 -0.013245    0.0  0.676385  0.621212   
56           0.0    0.0  2.000000 -0.900662    0.0 -0.542274 -0.626263   
57           0.0    0.0  2.000000  0.768212    0.0  0.740525  0.732323   
58           0.0    0.0  2.000000  0.860927    0.0  0.927114  0.909091   

       X_258  X_261     X_262  ...    X_2858    X_2859    X_2860    X_2861  \
41  0.091954    1.0  0.333333  ... -1.185290 -1.515790  0.027149 -0.018761   
42  0.873563    0.0  0.333333  ... -0.874603 -0.463158  0.371041 -0.046244   
43  0.222222    0.0  0.000000  ...  1.253015  1.052632  1.728507  2.012444   
44 -1.609195    0.5  0.333333  ... -1.674824 -1.089474 -1.746606 -1.170464   
45  0.444444    0.5  0.666667  ...  0.354302  0.747368  0.751131  1.374572   
46 -0.375479   -0.5 -0.666667  ... -0.211231 -0.547368 -1.285068 -1.503554   
47  0.574713    0.5  0.333333  ... -0.172034 -0.352632 -0.923077 -0.738041   
48 -0.168582    0.0 -0.333333  ... -0.073931  0.000000 -0.407240 -0.188160   
49 -0.022989   -0.5 -1.000000  ... -0.436182 -1.000000  0.171946  0.162148   
50  1.402299    0.0  0.333333  ...  0.182059  0.131579  0.235294  0.254242   
51  0.000000   -0.5 -0.666667  ...  0.800936  0.394737  1.393665  1.810429   
52 -0.505747    0.0  0.666667  ... -0.649287 -0.242105 -0.950226 -0.276640   
53  0.168582   -1.0 -1.000000  ...  1.130196  0.863158  0.895928  1.532030   
54  0.275862    0.5  0.000000  ... -0.626733 -0.331579  0.171946  0.671313   
55  0.835249    1.0  0.333333  ... -0.204519  0.089474 -0.932127 -0.707937   
56 -0.467433    0.0  0.000000  ... -0.650640 -0.768421  0.271493 -0.343607   
57  0.781609   -1.0 -1.000000  ... -1.238425 -0.347368  1.520362  1.743090   
58  1.042146    0.0  0.666667  ... -1.499353 -0.873684 -0.986425 -1.592393   

      X_2862  X_2863    X_2864  X_2865  Y_Quality  prediction_label  
41  0.153846    -1.9 -1.455824    -8.5   0.528270          0.532787  
42 -0.529231     0.1  0.854574     0.0   0.536041          0.533500  
43  1.310769     0.1  0.343306     0.5   0.524686          0.532766  
44 -0.646154     0.1  0.828347     4.5   0.528856          0.522180  
45  1.206154     0.1  0.915854     5.5   0.524408          0.533918  
46 -0.972308     0.1  0.514856     0.0   0.529254          0.528990  
47 -0.400000     0.1  0.360461    -0.5   0.531036          0.533500  
48  0.018462     0.0  0.435514     0.0   0.527486          0.529093  
49  0.264615    -2.0 -1.503000    -5.0   0.555514          0.533354  
50 -0.061538    -0.9 -0.299429     0.0   0.529070          0.533678  
51  1.316923    -2.8 -2.641663   -13.5   0.535741          0.533619  
52  0.289231     0.1  0.684097     5.0   0.526741          0.528157  
53  0.904615    -0.2 -0.117734     0.0   0.527910          0.533850  
54  0.596923     0.1  0.688468     4.5   0.534486          0.533441  
55 -0.621538     0.1  0.852389     4.5   0.558770          0.533

In [51]:
T0103051_final_regression_model = finalize_model(T01_model_xgb)

T0103051_prediction = predict_model(T0103051_final_regression_model, data=T0103051_data)

T0103051_datas = T0103051_prediction['prediction_label']
T0103051_datas = pd.DataFrame(T0103051_datas.values, columns = ['Y_Quality'])

T0103051y_idx= T0103051_class.index
T0103051y_idx = pd.DataFrame(T0103051y_idx, columns = ['index'])
T0103051_datas = pd.concat([T0103051y_idx, T0103051_datas], axis = 1)
T0103051_datas = T0103051_datas.set_index('index')
T0103051_datas

Y_Quality
index           
28      0.521615
33      0.527009
39      0.531752
40      0.530792
41      0.528421
48      0.533311
52      0.555471
57      0.535684
58      0.536467
59      0.536467
64      0.532977
65      0.528140
66      0.524784
69      0.531891
71      0.534007
75      0.534238
77      0.534478
84      0.530048
90      0.534558
94      0.535811
95      0.535857
116     0.523542
118     0.521428
123     0.518370
129     0.528666
179     0.527114
190     0.528564
208     0.529835
220     0.529341
230     0.530216
235     0.530003
239     0.524119
244     0.527566
281     0.534242
283     0.538012
287     0.531423
291     0.557766
292     0.557948
295     0.532852
299     0.536319
300     0.536945
312     0.523900
332     0.534101
334     0.529262
404     0.501683
410     0.520812
436     0.526281
449     0.529705
455     0.530369
456     0.527366
480     0.530600
490     0.523277
491     0.524898
500     0.531679
521     0.529237
530     0.532758
553     0.524876
554     0.531407
584     0.519552

In [52]:
from pycaret.classification import *
# 분류 패키지의 모든 모듈을 임포트한다.
exp_clf101 = setup(data=T0103051_datas, 
                   target=T0103051_class, 
                   fold=5,
                   session_id=4)
top5 = compare_models(sort='Accuracy', n_select=5)

Processing:   0%|          | 0/73 [00:00<?, ?it/s]

In [53]:
T01_total_models = []

T01_model_lightgbm = create_model('lightgbm', fold = 5)
T01_total_models.append(T01_model_lightgbm)

T01_model_rf = create_model('rf', fold = 5)
T01_total_models.append(T01_model_rf)

T01_model_gbc = create_model('gbc', fold = 5)
T01_total_models.append(T01_model_gbc)

T01_model_et = create_model('et', fold = 5)
T01_total_models.append(T01_model_et)

T01_model_catboost = create_model('catboost', fold = 5)
T01_total_models.append(T01_model_catboost)

T01_model_xgb = create_model('xgboost', fold = 5)
T01_total_models.append(T01_model_xgb)

T01_model_ada = create_model('ada', fold = 5)
T01_total_models.append(T01_model_ada)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [54]:
T01_model_lightgbm = tune_model(T01_model_lightgbm, fold=5, choose_better = True)

T01_model_rf = tune_model(T01_model_rf, fold=5, choose_better = True)

T01_model_gbc = tune_model(T01_model_gbc, fold=5, choose_better = True)

T01_model_et = tune_model(T01_model_et, fold=5, choose_better = True)

T01_model_catboost = tune_model(T01_model_catboost, fold=5, choose_better = True)

T01_model_xgb = tune_model(T01_model_xgb, fold=5, choose_better = True)

T01_model_ada = tune_model(T01_model_ada, fold=5, choose_better = True)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

...

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


In [55]:
T01_tuned_models = [T01_model_lightgbm, T01_model_rf, T01_model_gbc, T01_model_et, T01_model_catboost, T01_model_xgb, T01_model_ada]

for model in T01_tuned_models:
    display(predict_model(model))

Y_Quality  Y_Class  prediction_label  prediction_score
41   0.528421        1                 1            0.9414
42   0.501683        0                 0            0.8873
43   0.530792        1                 1            0.9739
44   0.555471        2                 2            0.8728
45   0.524898        0                 0            0.8873
46   0.531407        1                 1            0.9739
47   0.534101        1                 1            0.8301
48   0.528140        1                 1            0.9414
49   0.534238        1                 1            0.8301
50   0.524784        0                 0            0.8873
51   0.529705        1                 1            0.9739
52   0.530600        1                 1            0.9739
53   0.536319        2                 2            0.8728
54   0.557766        2                 2            0.8728
55   0.532852        1                 1            0.9418
56   0.524119        0                 0            0.8873
57   0.534242        1                 1            0.8301
58   0.527009        1                 1            0.8822

Y_Quality  Y_Class  prediction_label  prediction_score
41   0.528421        1                 1              1.00
42   0.501683        0                 0              1.00
43   0.530792        1                 1              1.00
44   0.555471        2                 2              1.00
45   0.524898        0                 0              0.97
46   0.531407        1                 1              1.00
47   0.534101        1                 1              1.00
48   0.528140        1                 1              1.00
49   0.534238        1                 1              0.99
50   0.524784        0                 0              0.97
51   0.529705        1                 1              1.00
52   0.530600        1                 1              1.00
53   0.536319        2                 2              1.00
54   0.557766        2                 2              1.00
55   0.532852        1                 1              1.00
56   0.524119        0                 0              1.00
57   0.534242        1                 1              0.99
58   0.527009        1                 1              1.00

Y_Quality  Y_Class  prediction_label  prediction_score
41   0.528421        1                 1               1.0
42   0.501683        0                 0               1.0
43   0.530792        1                 1               1.0
44   0.555471        2                 2               1.0
45   0.524898        0                 0               1.0
46   0.531407        1                 1               1.0
47   0.534101        1                 1               1.0
48   0.528140        1                 1               1.0
49   0.534238        1                 1               1.0
50   0.524784        0                 0               1.0
51   0.529705        1                 1               1.0
52   0.530600        1                 1               1.0
53   0.536319        2                 2               1.0
54   0.557766        2                 2               1.0
55   0.532852        1                 1               1.0
56   0.524119        0                 0               1.0
57   0.534242        1                 1               1.0
58   0.527009        1                 1               1.0

Y_Quality  Y_Class  prediction_label  prediction_score
41   0.528421        1                 1              1.00
42   0.501683        0                 0              1.00
43   0.530792        1                 1              1.00
44   0.555471        2                 2              1.00
45   0.524898        0                 0              0.99
46   0.531407        1                 1              1.00
47   0.534101        1                 1              1.00
48   0.528140        1                 1              1.00
49   0.534238        1                 1              1.00
50   0.524784        0                 0              1.00
51   0.529705        1                 1              1.00
52   0.530600        1                 1              1.00
53   0.536319        2                 2              1.00
54   0.557766        2                 2              1.00
55   0.532852        1                 1              1.00
56   0.524119        0                 0              1.00
57   0.534242        1                 1              1.00
58   0.527009        1                 1              1.00

Y_Quality  Y_Class  prediction_label  prediction_score
41   0.528421        1                 1            0.9980
42   0.501683        0                 0            0.9943
43   0.530792        1                 1            0.9983
44   0.555471        2                 2            0.9942
45   0.524898        0                 0            0.9840
46   0.531407        1                 1            0.9980
47   0.534101        1                 1            0.9953
48   0.528140        1                 1            0.9980
49   0.534238        1                 1            0.9953
50   0.524784        0                 0            0.9840
51   0.529705        1                 1            0.9983
52   0.530600        1                 1            0.9983
53   0.536319        2                 2            0.9966
54   0.557766        2                 2            0.9942
55   0.532852        1                 1            0.9976
56   0.524119        0                 0            0.9918
57   0.534242        1                 1            0.9953
58   0.527009        1                 1            0.9925

Y_Quality  Y_Class  prediction_label  prediction_score
41   0.528421        1                 1            0.9701
42   0.501683        0                 0            0.9504
43   0.530792        1                 1            0.9903
44   0.555471        2                 2            0.9435
45   0.524898        0                 0            0.9504
46   0.531407        1                 1            0.9903
47   0.534101        1                 1            0.9559
48   0.528140        1                 1            0.9701
49   0.534238        1                 1            0.9559
50   0.524784        0                 0            0.9504
51   0.529705        1                 1            0.9903
52   0.530600        1                 1            0.9903
53   0.536319        2                 2            0.9435
54   0.557766        2                 2            0.9435
55   0.532852        1                 1            0.9722
56   0.524119        0                 0            0.9504
57   0.534242        1                 1            0.9559
58   0.527009        1                 1            0.9535

Y_Quality  Y_Class  prediction_label  prediction_score
41   0.528421        1                 1               1.0
42   0.501683        0                 0               1.0
43   0.530792        1                 1               1.0
44   0.555471        2                 2               1.0
45   0.524898        0                 0               1.0
46   0.531407        1                 1               1.0
47   0.534101        1                 1               1.0
48   0.528140        1                 1               1.0
49   0.534238        1                 1               1.0
50   0.524784        0                 0               1.0
51   0.529705        1                 1               1.0
52   0.530600        1                 1               1.0
53   0.536319        2                 2               1.0
54   0.557766        2                 2               1.0
55   0.532852        1                 1               1.0
56   0.524119        0                 0               1.0
57   0.534242        1                 1               1.0
58   0.527009        1                 1               1.0

In [56]:
T0103051_final_classification_model = finalize_model(T01_model_gbc)

T0103051_prediction = predict_model(T0103051_final_classification_model, data=T0103051_datas)

T0103051_prediction = pd.DataFrame(T0103051_prediction, columns = ['prediction_label'])

T0103051_y_class = pd.DataFrame(T0103051_class, columns = ['Y_Class'])
T0103051_idx = T0103051_y_class.index
T0103051_y_class = T0103051_y_class.reset_index()
T0103051_prediction = pd.concat([T0103051_prediction, T0103051_y_class], axis = 1)
T0103051_prediction = T0103051_prediction.set_index('index')
T0103051_prediction.drop(['Y_Class'], axis = 1, inplace = True)

# 4

In [57]:
T0103061_class = T0103061['Y_Class']
T0103061_target = T0103061['Y_Quality']
T0103061_data = T0103061.drop(['Y_Class', 'Y_Quality'], axis = 1)

In [58]:
T0103061c = T0103061_data.columns
T0103061scaler = RobustScaler()
T0103061scaled = T0103061scaler.fit_transform(T0103061_data)
T0103061_data = pd.DataFrame(T0103061scaled, columns = T0103061c)

T0103061_y_class = pd.DataFrame(T0103061_target, columns = ['Y_Quality'])
T0103061_idx = T0103061_y_class.index
T0103061_y_class = T0103061_y_class.reset_index()
T0103061_data = pd.concat([T0103061_data, T0103061_y_class], axis = 1)
T0103061_data = T0103061_data.set_index('index')
T0103061_data.drop(['Y_Quality'], axis = 1, inplace = True)
T0103061_data

PRODUCT_CODE  X_246  X_247     X_248  X_250     X_256     X_257  \
index                                                                    
27              0.0    0.0   -0.9  0.683616    0.0  0.697479  0.704673   
31              0.0    3.0    0.3  0.751412    0.0  0.609244  0.641121   
32              0.0    0.0   -0.5  0.774011    0.0  0.567227  0.577570   
38              0.0    1.0   -0.1  0.841808   -1.0  0.693277  0.685981   
47              0.0    0.0    0.7  0.932203   -1.0  0.714286  0.723364   
...             ...    ...    ...       ...    ...       ...       ...   
479             0.0    0.0    0.3  0.265537   -1.0  0.067227  0.095327   
501             0.0    1.0    0.7  0.457627   -1.0  0.277311  0.278505   
523             0.0    0.0   -0.5  0.593220    0.0  0.428571  0.439252   
531             0.0    0.0   -0.3  0.661017   -1.0  0.529412  0.495327   
585             0.0    0.0    0.3 -0.231638    0.0 -0.155462 -0.166355   

          X_258  X_261  X_262  ...    X_2856    X_2857    X_2858    X_2859  \
index                          ...                                           
27     0.795337    1.0    2.0  ... -0.423963 -0.795148 -1.190999 -1.066482   
31     0.505181    0.0    0.0  ... -0.656221  0.369272  0.268104 -0.540166   
32     0.546632   -0.8   -4.0  ... -0.519816 -0.552561 -0.405088 -0.168975   
38     0.733161    0.8    0.0  ... -0.763134 -0.035040 -0.027909  0.240997   
47     0.619171    0.2    0.0  ... -0.571429  0.148248  0.045164 -0.578947   
...         ...    ...    ...  ...       ...       ...       ...       ...   
479    0.038860   -0.4   -0.5  ...  0.409217  1.167116  0.368366  0.096953   
501    0.318653   -0.4   -1.5  ...  0.276498  0.547170  0.642876 -0.146814   
523    0.494819   -0.4   -0.5  ...  0.538249  0.223720  0.473929  0.451524   
531    0.531088    0.2    0.5  ...  0.014747  0.018868  0.176782  0.296399   
585   -0.101036   -1.0   -2.0  ...  0.571429  0.811321  1.155724  1.127424   

         X_2860    X_2861    X_2862  X_2863    X_2864    X_2865  
index                                                            
27     0.377863  0.271284  0.014260   -1.95 -1.524832 -3.636364  
31     0.889313  1.315793  1.568627   -1.95 -1.667990 -3.636364  
32    -0.263359 -0.228745 -0.399287   -1.95 -1.579987 -2.909091  
38     0.064885  0.449890  0.491979   -1.95 -2.026210 -6.909091  
47     0.187023  0.145024 -0.178253   -1.85 -1.589013 -3.636364  
...         ...       ...       ...     ...       ...       ...  
479   -0.011450 -0.168446 -0.392157   -0.95 -0.605177 -3.636364  
501    0.316794  0.807656  1.098039    0.05  0.252989  0.727273  
523    0.438931  0.773319  0.926916    0.05  0.170192  0.000000  
531    0.698473  1.045244  0.962567    0.05  0.340385  1.454545  
585    0.667939  1.214998  1.212121    0.65  0.854781  3.272727  

[70 rows x 737 columns]

In [59]:
from pycaret.regression import *
setup_rgs = setup(data = T0103061_data, target = T0103061_target, session_id = 4)
top5 = compare_models(sort='MSE', n_select=5)

Processing:   0%|          | 0/89 [00:00<?, ?it/s]

In [60]:
T01_total_models = []

T01_model_lightgbm = create_model('lightgbm', fold = 5)
T01_total_models.append(T01_model_lightgbm)

T01_model_rf = create_model('rf', fold = 5)
T01_total_models.append(T01_model_rf)

T01_model_gbr = create_model('gbr', fold = 5)
T01_total_models.append(T01_model_gbr)

T01_model_et = create_model('et', fold = 5)
T01_total_models.append(T01_model_et)

T01_model_catboost = create_model('catboost', fold = 5)
T01_total_models.append(T01_model_catboost)

T01_model_xgb = create_model('xgboost', fold = 5)
T01_total_models.append(T01_model_xgb)

T01_model_ada = create_model('ada', fold = 5)
T01_total_models.append(T01_model_ada)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [61]:
T01_model_lightgbm = tune_model(T01_model_lightgbm, fold=5, choose_better = True)

T01_model_rf = tune_model(T01_model_rf, fold=5, choose_better = True)

T01_model_gbr = tune_model(T01_model_gbr, fold=5, choose_better = True)

T01_model_et = tune_model(T01_model_et, fold=5, choose_better = True)

T01_model_catboost = tune_model(T01_model_catboost, fold=5, choose_better = True)

T01_model_xgb = tune_model(T01_model_xgb, fold=5, choose_better = True)

T01_model_ada = tune_model(T01_model_ada, fold=5, choose_better = True)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

...

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


In [62]:
T01_tuned_models = [T01_model_lightgbm, T01_model_rf, T01_model_gbr, T01_model_et, T01_model_catboost, T01_model_xgb, T01_model_ada]

for model in T01_tuned_models:
    display(predict_model(model))

PRODUCT_CODE  X_246  X_247     X_248  X_250     X_256     X_257     X_258  \
49           0.0    0.0   -0.7  0.096045    0.0 -0.046218 -0.057944  0.049223   
50           0.0    0.0   -0.5  0.593220    0.0  0.428571  0.439252  0.494819   
51           0.0    0.0    0.7  0.694915   -1.0  0.647059  0.659813  0.634715   
52           0.0    1.0   -0.9 -0.141243    0.0 -0.247899 -0.222430 -0.225389   
53           0.0    0.0   -0.3 -0.005650    0.0  0.100840  0.125234  0.049223   
54           0.0    0.0    0.7  0.932203   -1.0  0.714286  0.723364  0.619171   
55           0.0    0.0    0.7 -0.197740   -1.0 -0.285714 -0.315888 -0.240933   
56           0.0    1.0    0.9  0.661017    0.0  0.739496  0.659813  0.847150   
57           0.0    0.0   -0.7 -0.807910    0.0 -1.004202 -0.936449 -1.303109   
58           0.0    0.0    0.5 -0.887006    0.0 -1.117647 -1.033645 -1.417098   
59           0.0    1.0   -0.1  0.977401   -1.0  0.823529  0.775701  0.950777   
60           0.0    0.0    0.9 -0.638418    0.0 -0.550420 -0.532710 -0.556995   
61           0.0    1.0   -0.5 -0.186441   -1.0 -0.315126 -0.304673 -0.329016   
62           0.0    1.0    0.3  0.016949    0.0 -0.092437 -0.076636 -0.152850   
63           0.0    0.0    0.9  0.129944    0.0  0.142857  0.158879  0.163212   
64           0.0    0.0   -0.1 -0.932203    0.0 -1.760504 -1.564486 -2.137306   
65           0.0    0.0    0.3 -0.717514    0.0 -0.647059 -0.659813 -0.681347   
66           0.0    1.0    0.3  0.977401   -1.0  0.768908  0.775701  0.748705   
67           0.0    1.0    0.7  0.977401    0.0  0.735294  0.749533  0.784974   
68           0.0    0.0   -0.1 -0.028249    0.0  0.004202  0.013084 -0.038860   
69           0.0    0.0    0.9 -0.920904    0.0 -1.705882 -1.557009 -2.012953   

    X_261  X_262  ...    X_2858    X_2859    X_2860    X_2861    X_2862  \
49   -0.6   -3.5  ...  0.600789  0.700831  0.370229  0.438317  0.491979   
50   -0.4   -0.5  ...  0.473929  0.451524  0.438931  0.773319  0.926916   
51    0.0    1.0  ...  0.795143  0.573407 -0.171756 -0.316869 -0.121212   
52   -0.6   -0.5  ... -1.182502 -0.983379 -0.904580 -0.420175 -0.313726   
53    0.2    0.5  ... -0.780106 -0.894737 -0.049618 -0.104958  0.171123   
54    0.2    0.0  ...  0.045164 -0.578947  0.187023  0.145024 -0.178253   
55    0.0   -1.5  ... -0.702188 -0.285319 -0.400763 -0.030454 -0.385027   
56    0.8    2.5  ...  0.698397  0.634349  1.011450  0.837285  0.627451   
57    0.4    1.0  ...  0.007892 -0.207756 -0.072519  0.044764 -0.028520   
58   -0.2    0.5  ...  0.631676  0.351801 -0.805344 -0.331268  0.000000   
59    1.0    0.5  ... -0.007892 -0.844875  0.812977  0.656187  0.413547   
60   -0.6   -1.5  ... -0.182082  0.290859  0.438931  0.948049  1.411765   
61    0.0    0.5  ...  0.530174  0.806094 -0.538168 -0.214239 -0.192513   
62    1.2    0.0  ... -0.648652 -0.429363  1.293893  1.208619  1.254902   
63    0.6    0.5  ... -0.856440 -0.340720  0.110687  0.473981  0.677362   
64   -1.0   -2.5  ... -0.201145 -0.335180 -0.393130 -0.234351  0.327986   
65    0.6   -0.5  ... -1.042388 -0.983379  0.759542  0.857003  0.812834   
66   -0.2   -1.5  ... -0.046635 -0.002770 -0.309160 -0.110038 -0.392157   
67   -1.2   -5.5  ... -0.269296  0.163435  0.484733  0.471766  0.000000   
68    0.8    0.0  ... -1.492911 -0.811634 -1.019084 -0.631714 -0.591800   
69    0.2    0.5  ... -0.179847 -0.390582  0.522901  0.690973  0.855615   

    X_2863    X_2864    X_2865  Y_Quality  prediction_label  
49   -0.95 -0.453991 -2.909091   0.528087          0.536588  
50    0.05  0.170192  0.000000   0.534640          0.536197  
51   -0.95 -0.386383 -0.363636   0.534737          0.531938  
52    0.05  0.543383  3.272727   0.533489          0.530898  
53    0.05  0.696826  1.818182   0.527689          0.529389  
54   -1.85 -1.589013 -3.636364   0.533230          0.535640  
55   -0.95 -0.241489 -0.363636   0.531043          0.524825  
56    0.05 -0.250906 -0.363636   0.529189          0.532713  
57    0.05  

PRODUCT_CODE  X_246  X_247     X_248  X_250     X_256     X_257     X_258  \
49           0.0    0.0   -0.7  0.096045    0.0 -0.046218 -0.057944  0.049223   
50           0.0    0.0   -0.5  0.593220    0.0  0.428571  0.439252  0.494819   
51           0.0    0.0    0.7  0.694915   -1.0  0.647059  0.659813  0.634715   
52           0.0    1.0   -0.9 -0.141243    0.0 -0.247899 -0.222430 -0.225389   
53           0.0    0.0   -0.3 -0.005650    0.0  0.100840  0.125234  0.049223   
54           0.0    0.0    0.7  0.932203   -1.0  0.714286  0.723364  0.619171   
55           0.0    0.0    0.7 -0.197740   -1.0 -0.285714 -0.315888 -0.240933   
56           0.0    1.0    0.9  0.661017    0.0  0.739496  0.659813  0.847150   
57           0.0    0.0   -0.7 -0.807910    0.0 -1.004202 -0.936449 -1.303109   
58           0.0    0.0    0.5 -0.887006    0.0 -1.117647 -1.033645 -1.417098   
59           0.0    1.0   -0.1  0.977401   -1.0  0.823529  0.775701  0.950777   
60           0.0    0.0    0.9 -0.638418    0.0 -0.550420 -0.532710 -0.556995   
61           0.0    1.0   -0.5 -0.186441   -1.0 -0.315126 -0.304673 -0.329016   
62           0.0    1.0    0.3  0.016949    0.0 -0.092437 -0.076636 -0.152850   
63           0.0    0.0    0.9  0.129944    0.0  0.142857  0.158879  0.163212   
64           0.0    0.0   -0.1 -0.932203    0.0 -1.760504 -1.564486 -2.137306   
65           0.0    0.0    0.3 -0.717514    0.0 -0.647059 -0.659813 -0.681347   
66           0.0    1.0    0.3  0.977401   -1.0  0.768908  0.775701  0.748705   
67           0.0    1.0    0.7  0.977401    0.0  0.735294  0.749533  0.784974   
68           0.0    0.0   -0.1 -0.028249    0.0  0.004202  0.013084 -0.038860   
69           0.0    0.0    0.9 -0.920904    0.0 -1.705882 -1.557009 -2.012953   

    X_261  X_262  ...    X_2858    X_2859    X_2860    X_2861    X_2862  \
49   -0.6   -3.5  ...  0.600789  0.700831  0.370229  0.438317  0.491979   
50   -0.4   -0.5  ...  0.473929  0.451524  0.438931  0.773319  0.926916   
51    0.0    1.0  ...  0.795143  0.573407 -0.171756 -0.316869 -0.121212   
52   -0.6   -0.5  ... -1.182502 -0.983379 -0.904580 -0.420175 -0.313726   
53    0.2    0.5  ... -0.780106 -0.894737 -0.049618 -0.104958  0.171123   
54    0.2    0.0  ...  0.045164 -0.578947  0.187023  0.145024 -0.178253   
55    0.0   -1.5  ... -0.702188 -0.285319 -0.400763 -0.030454 -0.385027   
56    0.8    2.5  ...  0.698397  0.634349  1.011450  0.837285  0.627451   
57    0.4    1.0  ...  0.007892 -0.207756 -0.072519  0.044764 -0.028520   
58   -0.2    0.5  ...  0.631676  0.351801 -0.805344 -0.331268  0.000000   
59    1.0    0.5  ... -0.007892 -0.844875  0.812977  0.656187  0.413547   
60   -0.6   -1.5  ... -0.182082  0.290859  0.438931  0.948049  1.411765   
61    0.0    0.5  ...  0.530174  0.806094 -0.538168 -0.214239 -0.192513   
62    1.2    0.0  ... -0.648652 -0.429363  1.293893  1.208619  1.254902   
63    0.6    0.5  ... -0.856440 -0.340720  0.110687  0.473981  0.677362   
64   -1.0   -2.5  ... -0.201145 -0.335180 -0.393130 -0.234351  0.327986   
65    0.6   -0.5  ... -1.042388 -0.983379  0.759542  0.857003  0.812834   
66   -0.2   -1.5  ... -0.046635 -0.002770 -0.309160 -0.110038 -0.392157   
67   -1.2   -5.5  ... -0.269296  0.163435  0.484733  0.471766  0.000000   
68    0.8    0.0  ... -1.492911 -0.811634 -1.019084 -0.631714 -0.591800   
69    0.2    0.5  ... -0.179847 -0.390582  0.522901  0.690973  0.855615   

    X_2863    X_2864    X_2865  Y_Quality  prediction_label  
49   -0.95 -0.453991 -2.909091   0.528087          0.533517  
50    0.05  0.170192  0.000000   0.534640          0.534659  
51   -0.95 -0.386383 -0.363636   0.534737          0.536134  
52    0.05  0.543383  3.272727   0.533489          0.531540  
53    0.05  0.696826  1.818182   0.527689          0.530260  
54   -1.85 -1.589013 -3.636364   0.533230          0.536957  
55   -0.95 -0.241489 -0.363636   0.531043          0.530634  
56    0.05 -0.250906 -0.363636   0.529189          0.535024  
57    0.05  

PRODUCT_CODE  X_246  X_247     X_248  X_250     X_256     X_257     X_258  \
49           0.0    0.0   -0.7  0.096045    0.0 -0.046218 -0.057944  0.049223   
50           0.0    0.0   -0.5  0.593220    0.0  0.428571  0.439252  0.494819   
51           0.0    0.0    0.7  0.694915   -1.0  0.647059  0.659813  0.634715   
52           0.0    1.0   -0.9 -0.141243    0.0 -0.247899 -0.222430 -0.225389   
53           0.0    0.0   -0.3 -0.005650    0.0  0.100840  0.125234  0.049223   
54           0.0    0.0    0.7  0.932203   -1.0  0.714286  0.723364  0.619171   
55           0.0    0.0    0.7 -0.197740   -1.0 -0.285714 -0.315888 -0.240933   
56           0.0    1.0    0.9  0.661017    0.0  0.739496  0.659813  0.847150   
57           0.0    0.0   -0.7 -0.807910    0.0 -1.004202 -0.936449 -1.303109   
58           0.0    0.0    0.5 -0.887006    0.0 -1.117647 -1.033645 -1.417098   
59           0.0    1.0   -0.1  0.977401   -1.0  0.823529  0.775701  0.950777   
60           0.0    0.0    0.9 -0.638418    0.0 -0.550420 -0.532710 -0.556995   
61           0.0    1.0   -0.5 -0.186441   -1.0 -0.315126 -0.304673 -0.329016   
62           0.0    1.0    0.3  0.016949    0.0 -0.092437 -0.076636 -0.152850   
63           0.0    0.0    0.9  0.129944    0.0  0.142857  0.158879  0.163212   
64           0.0    0.0   -0.1 -0.932203    0.0 -1.760504 -1.564486 -2.137306   
65           0.0    0.0    0.3 -0.717514    0.0 -0.647059 -0.659813 -0.681347   
66           0.0    1.0    0.3  0.977401   -1.0  0.768908  0.775701  0.748705   
67           0.0    1.0    0.7  0.977401    0.0  0.735294  0.749533  0.784974   
68           0.0    0.0   -0.1 -0.028249    0.0  0.004202  0.013084 -0.038860   
69           0.0    0.0    0.9 -0.920904    0.0 -1.705882 -1.557009 -2.012953   

    X_261  X_262  ...    X_2858    X_2859    X_2860    X_2861    X_2862  \
49   -0.6   -3.5  ...  0.600789  0.700831  0.370229  0.438317  0.491979   
50   -0.4   -0.5  ...  0.473929  0.451524  0.438931  0.773319  0.926916   
51    0.0    1.0  ...  0.795143  0.573407 -0.171756 -0.316869 -0.121212   
52   -0.6   -0.5  ... -1.182502 -0.983379 -0.904580 -0.420175 -0.313726   
53    0.2    0.5  ... -0.780106 -0.894737 -0.049618 -0.104958  0.171123   
54    0.2    0.0  ...  0.045164 -0.578947  0.187023  0.145024 -0.178253   
55    0.0   -1.5  ... -0.702188 -0.285319 -0.400763 -0.030454 -0.385027   
56    0.8    2.5  ...  0.698397  0.634349  1.011450  0.837285  0.627451   
57    0.4    1.0  ...  0.007892 -0.207756 -0.072519  0.044764 -0.028520   
58   -0.2    0.5  ...  0.631676  0.351801 -0.805344 -0.331268  0.000000   
59    1.0    0.5  ... -0.007892 -0.844875  0.812977  0.656187  0.413547   
60   -0.6   -1.5  ... -0.182082  0.290859  0.438931  0.948049  1.411765   
61    0.0    0.5  ...  0.530174  0.806094 -0.538168 -0.214239 -0.192513   
62    1.2    0.0  ... -0.648652 -0.429363  1.293893  1.208619  1.254902   
63    0.6    0.5  ... -0.856440 -0.340720  0.110687  0.473981  0.677362   
64   -1.0   -2.5  ... -0.201145 -0.335180 -0.393130 -0.234351  0.327986   
65    0.6   -0.5  ... -1.042388 -0.983379  0.759542  0.857003  0.812834   
66   -0.2   -1.5  ... -0.046635 -0.002770 -0.309160 -0.110038 -0.392157   
67   -1.2   -5.5  ... -0.269296  0.163435  0.484733  0.471766  0.000000   
68    0.8    0.0  ... -1.492911 -0.811634 -1.019084 -0.631714 -0.591800   
69    0.2    0.5  ... -0.179847 -0.390582  0.522901  0.690973  0.855615   

    X_2863    X_2864    X_2865  Y_Quality  prediction_label  
49   -0.95 -0.453991 -2.909091   0.528087          0.531204  
50    0.05  0.170192  0.000000   0.534640          0.531983  
51   -0.95 -0.386383 -0.363636   0.534737          0.535179  
52    0.05  0.543383  3.272727   0.533489          0.529899  
53    0.05  0.696826  1.818182   0.527689          0.527972  
54   -1.85 -1.589013 -3.636364   0.533230          0.537143  
55   -0.95 -0.241489 -0.363636   0.531043          0.529841  
56    0.05 -0.250906 -0.363636   0.529189          0.534579  
57    0.05  

PRODUCT_CODE  X_246  X_247     X_248  X_250     X_256     X_257     X_258  \
49           0.0    0.0   -0.7  0.096045    0.0 -0.046218 -0.057944  0.049223   
50           0.0    0.0   -0.5  0.593220    0.0  0.428571  0.439252  0.494819   
51           0.0    0.0    0.7  0.694915   -1.0  0.647059  0.659813  0.634715   
52           0.0    1.0   -0.9 -0.141243    0.0 -0.247899 -0.222430 -0.225389   
53           0.0    0.0   -0.3 -0.005650    0.0  0.100840  0.125234  0.049223   
54           0.0    0.0    0.7  0.932203   -1.0  0.714286  0.723364  0.619171   
55           0.0    0.0    0.7 -0.197740   -1.0 -0.285714 -0.315888 -0.240933   
56           0.0    1.0    0.9  0.661017    0.0  0.739496  0.659813  0.847150   
57           0.0    0.0   -0.7 -0.807910    0.0 -1.004202 -0.936449 -1.303109   
58           0.0    0.0    0.5 -0.887006    0.0 -1.117647 -1.033645 -1.417098   
59           0.0    1.0   -0.1  0.977401   -1.0  0.823529  0.775701  0.950777   
60           0.0    0.0    0.9 -0.638418    0.0 -0.550420 -0.532710 -0.556995   
61           0.0    1.0   -0.5 -0.186441   -1.0 -0.315126 -0.304673 -0.329016   
62           0.0    1.0    0.3  0.016949    0.0 -0.092437 -0.076636 -0.152850   
63           0.0    0.0    0.9  0.129944    0.0  0.142857  0.158879  0.163212   
64           0.0    0.0   -0.1 -0.932203    0.0 -1.760504 -1.564486 -2.137306   
65           0.0    0.0    0.3 -0.717514    0.0 -0.647059 -0.659813 -0.681347   
66           0.0    1.0    0.3  0.977401   -1.0  0.768908  0.775701  0.748705   
67           0.0    1.0    0.7  0.977401    0.0  0.735294  0.749533  0.784974   
68           0.0    0.0   -0.1 -0.028249    0.0  0.004202  0.013084 -0.038860   
69           0.0    0.0    0.9 -0.920904    0.0 -1.705882 -1.557009 -2.012953   

    X_261  X_262  ...    X_2858    X_2859    X_2860    X_2861    X_2862  \
49   -0.6   -3.5  ...  0.600789  0.700831  0.370229  0.438317  0.491979   
50   -0.4   -0.5  ...  0.473929  0.451524  0.438931  0.773319  0.926916   
51    0.0    1.0  ...  0.795143  0.573407 -0.171756 -0.316869 -0.121212   
52   -0.6   -0.5  ... -1.182502 -0.983379 -0.904580 -0.420175 -0.313726   
53    0.2    0.5  ... -0.780106 -0.894737 -0.049618 -0.104958  0.171123   
54    0.2    0.0  ...  0.045164 -0.578947  0.187023  0.145024 -0.178253   
55    0.0   -1.5  ... -0.702188 -0.285319 -0.400763 -0.030454 -0.385027   
56    0.8    2.5  ...  0.698397  0.634349  1.011450  0.837285  0.627451   
57    0.4    1.0  ...  0.007892 -0.207756 -0.072519  0.044764 -0.028520   
58   -0.2    0.5  ...  0.631676  0.351801 -0.805344 -0.331268  0.000000   
59    1.0    0.5  ... -0.007892 -0.844875  0.812977  0.656187  0.413547   
60   -0.6   -1.5  ... -0.182082  0.290859  0.438931  0.948049  1.411765   
61    0.0    0.5  ...  0.530174  0.806094 -0.538168 -0.214239 -0.192513   
62    1.2    0.0  ... -0.648652 -0.429363  1.293893  1.208619  1.254902   
63    0.6    0.5  ... -0.856440 -0.340720  0.110687  0.473981  0.677362   
64   -1.0   -2.5  ... -0.201145 -0.335180 -0.393130 -0.234351  0.327986   
65    0.6   -0.5  ... -1.042388 -0.983379  0.759542  0.857003  0.812834   
66   -0.2   -1.5  ... -0.046635 -0.002770 -0.309160 -0.110038 -0.392157   
67   -1.2   -5.5  ... -0.269296  0.163435  0.484733  0.471766  0.000000   
68    0.8    0.0  ... -1.492911 -0.811634 -1.019084 -0.631714 -0.591800   
69    0.2    0.5  ... -0.179847 -0.390582  0.522901  0.690973  0.855615   

    X_2863    X_2864    X_2865  Y_Quality  prediction_label  
49   -0.95 -0.453991 -2.909091   0.528087          0.532204  
50    0.05  0.170192  0.000000   0.534640          0.534659  
51   -0.95 -0.386383 -0.363636   0.534737          0.535827  
52    0.05  0.543383  3.272727   0.533489          0.530834  
53    0.05  0.696826  1.818182   0.527689          0.530291  
54   -1.85 -1.589013 -3.636364   0.533230          0.538298  
55   -0.95 -0.241489 -0.363636   0.531043          0.528676  
56    0.05 -0.250906 -0.363636   0.529189          0.534851  
57    0.05  

PRODUCT_CODE  X_246  X_247     X_248  X_250     X_256     X_257     X_258  \
49           0.0    0.0   -0.7  0.096045    0.0 -0.046218 -0.057944  0.049223   
50           0.0    0.0   -0.5  0.593220    0.0  0.428571  0.439252  0.494819   
51           0.0    0.0    0.7  0.694915   -1.0  0.647059  0.659813  0.634715   
52           0.0    1.0   -0.9 -0.141243    0.0 -0.247899 -0.222430 -0.225389   
53           0.0    0.0   -0.3 -0.005650    0.0  0.100840  0.125234  0.049223   
54           0.0    0.0    0.7  0.932203   -1.0  0.714286  0.723364  0.619171   
55           0.0    0.0    0.7 -0.197740   -1.0 -0.285714 -0.315888 -0.240933   
56           0.0    1.0    0.9  0.661017    0.0  0.739496  0.659813  0.847150   
57           0.0    0.0   -0.7 -0.807910    0.0 -1.004202 -0.936449 -1.303109   
58           0.0    0.0    0.5 -0.887006    0.0 -1.117647 -1.033645 -1.417098   
59           0.0    1.0   -0.1  0.977401   -1.0  0.823529  0.775701  0.950777   
60           0.0    0.0    0.9 -0.638418    0.0 -0.550420 -0.532710 -0.556995   
61           0.0    1.0   -0.5 -0.186441   -1.0 -0.315126 -0.304673 -0.329016   
62           0.0    1.0    0.3  0.016949    0.0 -0.092437 -0.076636 -0.152850   
63           0.0    0.0    0.9  0.129944    0.0  0.142857  0.158879  0.163212   
64           0.0    0.0   -0.1 -0.932203    0.0 -1.760504 -1.564486 -2.137306   
65           0.0    0.0    0.3 -0.717514    0.0 -0.647059 -0.659813 -0.681347   
66           0.0    1.0    0.3  0.977401   -1.0  0.768908  0.775701  0.748705   
67           0.0    1.0    0.7  0.977401    0.0  0.735294  0.749533  0.784974   
68           0.0    0.0   -0.1 -0.028249    0.0  0.004202  0.013084 -0.038860   
69           0.0    0.0    0.9 -0.920904    0.0 -1.705882 -1.557009 -2.012953   

    X_261  X_262  ...    X_2858    X_2859    X_2860    X_2861    X_2862  \
49   -0.6   -3.5  ...  0.600789  0.700831  0.370229  0.438317  0.491979   
50   -0.4   -0.5  ...  0.473929  0.451524  0.438931  0.773319  0.926916   
51    0.0    1.0  ...  0.795143  0.573407 -0.171756 -0.316869 -0.121212   
52   -0.6   -0.5  ... -1.182502 -0.983379 -0.904580 -0.420175 -0.313726   
53    0.2    0.5  ... -0.780106 -0.894737 -0.049618 -0.104958  0.171123   
54    0.2    0.0  ...  0.045164 -0.578947  0.187023  0.145024 -0.178253   
55    0.0   -1.5  ... -0.702188 -0.285319 -0.400763 -0.030454 -0.385027   
56    0.8    2.5  ...  0.698397  0.634349  1.011450  0.837285  0.627451   
57    0.4    1.0  ...  0.007892 -0.207756 -0.072519  0.044764 -0.028520   
58   -0.2    0.5  ...  0.631676  0.351801 -0.805344 -0.331268  0.000000   
59    1.0    0.5  ... -0.007892 -0.844875  0.812977  0.656187  0.413547   
60   -0.6   -1.5  ... -0.182082  0.290859  0.438931  0.948049  1.411765   
61    0.0    0.5  ...  0.530174  0.806094 -0.538168 -0.214239 -0.192513   
62    1.2    0.0  ... -0.648652 -0.429363  1.293893  1.208619  1.254902   
63    0.6    0.5  ... -0.856440 -0.340720  0.110687  0.473981  0.677362   
64   -1.0   -2.5  ... -0.201145 -0.335180 -0.393130 -0.234351  0.327986   
65    0.6   -0.5  ... -1.042388 -0.983379  0.759542  0.857003  0.812834   
66   -0.2   -1.5  ... -0.046635 -0.002770 -0.309160 -0.110038 -0.392157   
67   -1.2   -5.5  ... -0.269296  0.163435  0.484733  0.471766  0.000000   
68    0.8    0.0  ... -1.492911 -0.811634 -1.019084 -0.631714 -0.591800   
69    0.2    0.5  ... -0.179847 -0.390582  0.522901  0.690973  0.855615   

    X_2863    X_2864    X_2865  Y_Quality  prediction_label  
49   -0.95 -0.453991 -2.909091   0.528087          0.539654  
50    0.05  0.170192  0.000000   0.534640          0.533871  
51   -0.95 -0.386383 -0.363636   0.534737          0.533763  
52    0.05  0.543383  3.272727   0.533489          0.529793  
53    0.05  0.696826  1.818182   0.527689          0.529271  
54   -1.85 -1.589013 -3.636364   0.533230          0.537571  
55   -0.95 -0.241489 -0.363636   0.531043          0.527493  
56    0.05 -0.250906 -0.363636   0.529189          0.532505  
57    0.05  

PRODUCT_CODE  X_246  X_247     X_248  X_250     X_256     X_257     X_258  \
49           0.0    0.0   -0.7  0.096045    0.0 -0.046218 -0.057944  0.049223   
50           0.0    0.0   -0.5  0.593220    0.0  0.428571  0.439252  0.494819   
51           0.0    0.0    0.7  0.694915   -1.0  0.647059  0.659813  0.634715   
52           0.0    1.0   -0.9 -0.141243    0.0 -0.247899 -0.222430 -0.225389   
53           0.0    0.0   -0.3 -0.005650    0.0  0.100840  0.125234  0.049223   
54           0.0    0.0    0.7  0.932203   -1.0  0.714286  0.723364  0.619171   
55           0.0    0.0    0.7 -0.197740   -1.0 -0.285714 -0.315888 -0.240933   
56           0.0    1.0    0.9  0.661017    0.0  0.739496  0.659813  0.847150   
57           0.0    0.0   -0.7 -0.807910    0.0 -1.004202 -0.936449 -1.303109   
58           0.0    0.0    0.5 -0.887006    0.0 -1.117647 -1.033645 -1.417098   
59           0.0    1.0   -0.1  0.977401   -1.0  0.823529  0.775701  0.950777   
60           0.0    0.0    0.9 -0.638418    0.0 -0.550420 -0.532710 -0.556995   
61           0.0    1.0   -0.5 -0.186441   -1.0 -0.315126 -0.304673 -0.329016   
62           0.0    1.0    0.3  0.016949    0.0 -0.092437 -0.076636 -0.152850   
63           0.0    0.0    0.9  0.129944    0.0  0.142857  0.158879  0.163212   
64           0.0    0.0   -0.1 -0.932203    0.0 -1.760504 -1.564486 -2.137306   
65           0.0    0.0    0.3 -0.717514    0.0 -0.647059 -0.659813 -0.681347   
66           0.0    1.0    0.3  0.977401   -1.0  0.768908  0.775701  0.748705   
67           0.0    1.0    0.7  0.977401    0.0  0.735294  0.749533  0.784974   
68           0.0    0.0   -0.1 -0.028249    0.0  0.004202  0.013084 -0.038860   
69           0.0    0.0    0.9 -0.920904    0.0 -1.705882 -1.557009 -2.012953   

    X_261  X_262  ...    X_2858    X_2859    X_2860    X_2861    X_2862  \
49   -0.6   -3.5  ...  0.600789  0.700831  0.370229  0.438317  0.491979   
50   -0.4   -0.5  ...  0.473929  0.451524  0.438931  0.773319  0.926916   
51    0.0    1.0  ...  0.795143  0.573407 -0.171756 -0.316869 -0.121212   
52   -0.6   -0.5  ... -1.182502 -0.983379 -0.904580 -0.420175 -0.313726   
53    0.2    0.5  ... -0.780106 -0.894737 -0.049618 -0.104958  0.171123   
54    0.2    0.0  ...  0.045164 -0.578947  0.187023  0.145024 -0.178253   
55    0.0   -1.5  ... -0.702188 -0.285319 -0.400763 -0.030454 -0.385027   
56    0.8    2.5  ...  0.698397  0.634349  1.011450  0.837285  0.627451   
57    0.4    1.0  ...  0.007892 -0.207756 -0.072519  0.044764 -0.028520   
58   -0.2    0.5  ...  0.631676  0.351801 -0.805344 -0.331268  0.000000   
59    1.0    0.5  ... -0.007892 -0.844875  0.812977  0.656187  0.413547   
60   -0.6   -1.5  ... -0.182082  0.290859  0.438931  0.948049  1.411765   
61    0.0    0.5  ...  0.530174  0.806094 -0.538168 -0.214239 -0.192513   
62    1.2    0.0  ... -0.648652 -0.429363  1.293893  1.208619  1.254902   
63    0.6    0.5  ... -0.856440 -0.340720  0.110687  0.473981  0.677362   
64   -1.0   -2.5  ... -0.201145 -0.335180 -0.393130 -0.234351  0.327986   
65    0.6   -0.5  ... -1.042388 -0.983379  0.759542  0.857003  0.812834   
66   -0.2   -1.5  ... -0.046635 -0.002770 -0.309160 -0.110038 -0.392157   
67   -1.2   -5.5  ... -0.269296  0.163435  0.484733  0.471766  0.000000   
68    0.8    0.0  ... -1.492911 -0.811634 -1.019084 -0.631714 -0.591800   
69    0.2    0.5  ... -0.179847 -0.390582  0.522901  0.690973  0.855615   

    X_2863    X_2864    X_2865  Y_Quality  prediction_label  
49   -0.95 -0.453991 -2.909091   0.528087          0.533629  
50    0.05  0.170192  0.000000   0.534640          0.530747  
51   -0.95 -0.386383 -0.363636   0.534737          0.538590  
52    0.05  0.543383  3.272727   0.533489          0.530352  
53    0.05  0.696826  1.818182   0.527689          0.529571  
54   -1.85 -1.589013 -3.636364   0.533230          0.536253  
55   -0.95 -0.241489 -0.363636   0.531043          0.528073  
56    0.05 -0.250906 -0.363636   0.529189          0.533512  
57    0.05  

PRODUCT_CODE  X_246  X_247     X_248  X_250     X_256     X_257     X_258  \
49           0.0    0.0   -0.7  0.096045    0.0 -0.046218 -0.057944  0.049223   
50           0.0    0.0   -0.5  0.593220    0.0  0.428571  0.439252  0.494819   
51           0.0    0.0    0.7  0.694915   -1.0  0.647059  0.659813  0.634715   
52           0.0    1.0   -0.9 -0.141243    0.0 -0.247899 -0.222430 -0.225389   
53           0.0    0.0   -0.3 -0.005650    0.0  0.100840  0.125234  0.049223   
54           0.0    0.0    0.7  0.932203   -1.0  0.714286  0.723364  0.619171   
55           0.0    0.0    0.7 -0.197740   -1.0 -0.285714 -0.315888 -0.240933   
56           0.0    1.0    0.9  0.661017    0.0  0.739496  0.659813  0.847150   
57           0.0    0.0   -0.7 -0.807910    0.0 -1.004202 -0.936449 -1.303109   
58           0.0    0.0    0.5 -0.887006    0.0 -1.117647 -1.033645 -1.417098   
59           0.0    1.0   -0.1  0.977401   -1.0  0.823529  0.775701  0.950777   
60           0.0    0.0    0.9 -0.638418    0.0 -0.550420 -0.532710 -0.556995   
61           0.0    1.0   -0.5 -0.186441   -1.0 -0.315126 -0.304673 -0.329016   
62           0.0    1.0    0.3  0.016949    0.0 -0.092437 -0.076636 -0.152850   
63           0.0    0.0    0.9  0.129944    0.0  0.142857  0.158879  0.163212   
64           0.0    0.0   -0.1 -0.932203    0.0 -1.760504 -1.564486 -2.137306   
65           0.0    0.0    0.3 -0.717514    0.0 -0.647059 -0.659813 -0.681347   
66           0.0    1.0    0.3  0.977401   -1.0  0.768908  0.775701  0.748705   
67           0.0    1.0    0.7  0.977401    0.0  0.735294  0.749533  0.784974   
68           0.0    0.0   -0.1 -0.028249    0.0  0.004202  0.013084 -0.038860   
69           0.0    0.0    0.9 -0.920904    0.0 -1.705882 -1.557009 -2.012953   

    X_261  X_262  ...    X_2858    X_2859    X_2860    X_2861    X_2862  \
49   -0.6   -3.5  ...  0.600789  0.700831  0.370229  0.438317  0.491979   
50   -0.4   -0.5  ...  0.473929  0.451524  0.438931  0.773319  0.926916   
51    0.0    1.0  ...  0.795143  0.573407 -0.171756 -0.316869 -0.121212   
52   -0.6   -0.5  ... -1.182502 -0.983379 -0.904580 -0.420175 -0.313726   
53    0.2    0.5  ... -0.780106 -0.894737 -0.049618 -0.104958  0.171123   
54    0.2    0.0  ...  0.045164 -0.578947  0.187023  0.145024 -0.178253   
55    0.0   -1.5  ... -0.702188 -0.285319 -0.400763 -0.030454 -0.385027   
56    0.8    2.5  ...  0.698397  0.634349  1.011450  0.837285  0.627451   
57    0.4    1.0  ...  0.007892 -0.207756 -0.072519  0.044764 -0.028520   
58   -0.2    0.5  ...  0.631676  0.351801 -0.805344 -0.331268  0.000000   
59    1.0    0.5  ... -0.007892 -0.844875  0.812977  0.656187  0.413547   
60   -0.6   -1.5  ... -0.182082  0.290859  0.438931  0.948049  1.411765   
61    0.0    0.5  ...  0.530174  0.806094 -0.538168 -0.214239 -0.192513   
62    1.2    0.0  ... -0.648652 -0.429363  1.293893  1.208619  1.254902   
63    0.6    0.5  ... -0.856440 -0.340720  0.110687  0.473981  0.677362   
64   -1.0   -2.5  ... -0.201145 -0.335180 -0.393130 -0.234351  0.327986   
65    0.6   -0.5  ... -1.042388 -0.983379  0.759542  0.857003  0.812834   
66   -0.2   -1.5  ... -0.046635 -0.002770 -0.309160 -0.110038 -0.392157   
67   -1.2   -5.5  ... -0.269296  0.163435  0.484733  0.471766  0.000000   
68    0.8    0.0  ... -1.492911 -0.811634 -1.019084 -0.631714 -0.591800   
69    0.2    0.5  ... -0.179847 -0.390582  0.522901  0.690973  0.855615   

    X_2863    X_2864    X_2865  Y_Quality  prediction_label  
49   -0.95 -0.453991 -2.909091   0.528087          0.532573  
50    0.05  0.170192  0.000000   0.534640          0.533965  
51   -0.95 -0.386383 -0.363636   0.534737          0.536463  
52    0.05  0.543383  3.272727   0.533489          0.531842  
53    0.05  0.696826  1.818182   0.527689          0.530101  
54   -1.85 -1.589013 -3.636364   0.533230          0.536154  
55   -0.95 -0.241489 -0.363636   0.531043          0.530923  
56    0.05 -0.250906 -0.363636   0.529189          0.535274  
57    0.05  

In [63]:
T0103061_final_regression_model = finalize_model(T01_model_gbr)

T0103061_prediction = predict_model(T0103061_final_regression_model, data=T0103061_data)

T0103061_datas = T0103061_prediction['prediction_label']
T0103061_datas = pd.DataFrame(T0103061_datas.values, columns = ['Y_Quality'])

T0103061y_idx= T0103061_class.index
T0103061y_idx = pd.DataFrame(T0103061y_idx, columns = ['index'])
T0103061_datas = pd.concat([T0103061y_idx, T0103061_datas], axis = 1)
T0103061_datas = T0103061_datas.set_index('index')
T0103061_datas

Y_Quality
index           
27      0.539948
31      0.536202
32      0.548583
38      0.536693
47      0.533262
...          ...
479     0.534723
501     0.533100
523     0.534621
531     0.560275
585     0.515279

[70 rows x 1 columns]

In [64]:
from pycaret.classification import *
# 분류 패키지의 모든 모듈을 임포트한다.
exp_clf101 = setup(data=T0103061_datas, 
                   target=T0103061_class, 
                   fold=5,
                   session_id=4)
top5 = compare_models(sort='Accuracy', n_select=5)

Processing:   0%|          | 0/73 [00:00<?, ?it/s]

In [65]:
T01_total_models = []

T01_model_lightgbm = create_model('lightgbm', fold = 5)
T01_total_models.append(T01_model_lightgbm)

T01_model_rf = create_model('rf', fold = 5)
T01_total_models.append(T01_model_rf)

T01_model_gbc = create_model('gbc', fold = 5)
T01_total_models.append(T01_model_gbc)

T01_model_et = create_model('et', fold = 5)
T01_total_models.append(T01_model_et)

T01_model_catboost = create_model('catboost', fold = 5)
T01_total_models.append(T01_model_catboost)

T01_model_xgb = create_model('xgboost', fold = 5)
T01_total_models.append(T01_model_xgb)

T01_model_ada = create_model('ada', fold = 5)
T01_total_models.append(T01_model_ada)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [66]:
T01_model_lightgbm = tune_model(T01_model_lightgbm, fold=5, choose_better = True)

T01_model_rf = tune_model(T01_model_rf, fold=5, choose_better = True)

T01_model_gbc = tune_model(T01_model_gbc, fold=5, choose_better = True)

T01_model_et = tune_model(T01_model_et, fold=5, choose_better = True)

T01_model_catboost = tune_model(T01_model_catboost, fold=5, choose_better = True)

T01_model_xgb = tune_model(T01_model_xgb, fold=5, choose_better = True)

T01_model_ada = tune_model(T01_model_ada, fold=5, choose_better = True)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

...

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


In [67]:
T01_tuned_models = [T01_model_lightgbm, T01_model_rf, T01_model_gbc, T01_model_et, T01_model_catboost, T01_model_xgb, T01_model_ada]

for model in T01_tuned_models:
    display(predict_model(model))

Y_Quality  Y_Class  prediction_label  prediction_score
49   0.531993        1                 1            0.9657
50   0.531070        1                 1            0.9657
51   0.530372        1                 1            0.9657
52   0.517953        0                 0            0.6678
53   0.530613        1                 1            0.9657
54   0.547466        2                 2            0.9443
55   0.533509        1                 1            0.9637
56   0.527725        1                 1            0.9347
57   0.549343        2                 2            0.9443
58   0.535250        2                 2            0.9443
59   0.534621        1                 1            0.9637
60   0.533262        1                 1            0.9637
61   0.536693        2                 2            0.9443
62   0.535556        2                 2            0.9443
63   0.538483        2                 2            0.9443
64   0.526977        1                 1            0.9192
65   0.539025        2                 2            0.9443
66   0.525277        1                 1            0.4858
67   0.536660        2                 2            0.9443
68   0.515279        0                 0            0.6678
69   0.531645        1                 1            0.9657

Y_Quality  Y_Class  prediction_label  prediction_score
49   0.531993        1                 1              1.00
50   0.531070        1                 1              1.00
51   0.530372        1                 1              1.00
52   0.517953        0                 0              0.97
53   0.530613        1                 1              1.00
54   0.547466        2                 2              1.00
55   0.533509        1                 1              1.00
56   0.527725        1                 1              1.00
57   0.549343        2                 2              1.00
58   0.535250        2                 2              0.90
59   0.534621        1                 1              0.99
60   0.533262        1                 1              1.00
61   0.536693        2                 2              1.00
62   0.535556        2                 2              0.96
63   0.538483        2                 2              1.00
64   0.526977        1                 1              1.00
65   0.539025        2                 2              1.00
66   0.525277        1                 1              0.69
67   0.536660        2                 2              1.00
68   0.515279        0                 0              0.97
69   0.531645        1                 1              1.00

Y_Quality  Y_Class  prediction_label  prediction_score
49   0.531993        1                 1               1.0
50   0.531070        1                 1               1.0
51   0.530372        1                 1               1.0
52   0.517953        0                 0               1.0
53   0.530613        1                 1               1.0
54   0.547466        2                 2               1.0
55   0.533509        1                 1               1.0
56   0.527725        1                 1               1.0
57   0.549343        2                 2               1.0
58   0.535250        2                 2               1.0
59   0.534621        1                 1               1.0
60   0.533262        1                 1               1.0
61   0.536693        2                 2               1.0
62   0.535556        2                 2               1.0
63   0.538483        2                 2               1.0
64   0.526977        1                 1               1.0
65   0.539025        2                 2               1.0
66   0.525277        1                 1               1.0
67   0.536660        2                 2               1.0
68   0.515279        0                 0               1.0
69   0.531645        1                 1               1.0

Y_Quality  Y_Class  prediction_label  prediction_score
49   0.531993        1                 1              1.00
50   0.531070        1                 1              1.00
51   0.530372        1                 1              1.00
52   0.517953        0                 0              1.00
53   0.530613        1                 1              1.00
54   0.547466        2                 2              1.00
55   0.533509        1                 1              1.00
56   0.527725        1                 1              1.00
57   0.549343        2                 2              1.00
58   0.535250        2                 2              0.66
59   0.534621        1                 1              1.00
60   0.533262        1                 1              1.00
61   0.536693        2                 2              1.00
62   0.535556        2                 2              1.00
63   0.538483        2                 2              1.00
64   0.526977        1                 1              1.00
65   0.539025        2                 2              1.00
66   0.525277        1                 1              0.62
67   0.536660        2                 2              1.00
68   0.515279        0                 0              1.00
69   0.531645        1                 1              1.00

Y_Quality  Y_Class  prediction_label  prediction_score
49   0.531993        1                 1            0.9985
50   0.531070        1                 1            0.9987
51   0.530372        1                 1            0.9988
52   0.517953        0                 0            0.9928
53   0.530613        1                 1            0.9988
54   0.547466        2                 2            0.9981
55   0.533509        1                 1            0.9975
56   0.527725        1                 1            0.9985
57   0.549343        2                 2            0.9976
58   0.535250        2                 2            0.9783
59   0.534621        1                 1            0.9905
60   0.533262        1                 1            0.9980
61   0.536693        2                 2            0.9968
62   0.535556        2                 2            0.9920
63   0.538483        2                 2            0.9978
64   0.526977        1                 1            0.9981
65   0.539025        2                 2            0.9980
66   0.525277        1                 1            0.9820
67   0.536660        2                 2            0.9968
68   0.515279        0                 0            0.9921
69   0.531645        1                 1            0.9985

Y_Quality  Y_Class  prediction_label  prediction_score
49   0.531993        1                 1            0.9823
50   0.531070        1                 1            0.9909
51   0.530372        1                 1            0.9915
52   0.517953        0                 0            0.8920
53   0.530613        1                 1            0.9915
54   0.547466        2                 2            0.9768
55   0.533509        1                 1            0.9763
56   0.527725        1                 1            0.9915
57   0.549343        2                 2            0.9768
58   0.535250        2                 2            0.9768
59   0.534621        1                 1            0.9693
60   0.533262        1                 1            0.9763
61   0.536693        2                 2            0.9768
62   0.535556        2                 2            0.9768
63   0.538483        2                 2            0.9768
64   0.526977        1                 1            0.9911
65   0.539025        2                 2            0.9768
66   0.525277        1                 1            0.8895
67   0.536660        2                 2            0.9768
68   0.515279        0                 0            0.8920
69   0.531645        1                 1            0.9823

Y_Quality  Y_Class  prediction_label  prediction_score
49   0.531993        1                 1               1.0
50   0.531070        1                 1               1.0
51   0.530372        1                 1               1.0
52   0.517953        0                 0               1.0
53   0.530613        1                 1               1.0
54   0.547466        2                 2               1.0
55   0.533509        1                 1               1.0
56   0.527725        1                 1               1.0
57   0.549343        2                 2               1.0
58   0.535250        2                 2               1.0
59   0.534621        1                 1               1.0
60   0.533262        1                 1               1.0
61   0.536693        2                 2               1.0
62   0.535556        2                 2               1.0
63   0.538483        2                 2               1.0
64   0.526977        1                 1               1.0
65   0.539025        2                 2               1.0
66   0.525277        1                 1               1.0
67   0.536660        2                 2               1.0
68   0.515279        0                 0               1.0
69   0.531645        1                 1               1.0

In [68]:
T0103061_final_classification_model = finalize_model(T01_model_gbc)

T0103061_prediction = predict_model(T0103061_final_classification_model, data=T0103061_datas)

T0103061_prediction = pd.DataFrame(T0103061_prediction, columns = ['prediction_label'])

T0103061_y_class = pd.DataFrame(T0103061_class, columns = ['Y_Class'])
T0103061_idx = T0103061_y_class.index
T0103061_y_class = T0103061_y_class.reset_index()
T0103061_prediction = pd.concat([T0103061_prediction, T0103061_y_class], axis = 1)
T0103061_prediction = T0103061_prediction.set_index('index')
T0103061_prediction.drop(['Y_Class'], axis = 1, inplace = True)

# 5

In [69]:
T1003042_class = T1003042['Y_Class']
T1003042_target = T1003042['Y_Quality']
T1003042_data = T1003042.drop(['Y_Class', 'Y_Quality'], axis = 1)

In [70]:
T1003042c = T1003042_data.columns
T1003042scaler = RobustScaler()
T1003042scaled = T1003042scaler.fit_transform(T1003042_data)
T1003042_data = pd.DataFrame(T1003042scaled, columns = T1003042c)

T1003042_y_class = pd.DataFrame(T1003042_target, columns = ['Y_Quality'])
T1003042_idx = T1003042_y_class.index
T1003042_y_class = T1003042_y_class.reset_index()
T1003042_data = pd.concat([T1003042_data, T1003042_y_class], axis = 1)
T1003042_data = T1003042_data.set_index('index')
T1003042_data.drop(['Y_Quality'], axis = 1, inplace = True)
T1003042_data

PRODUCT_CODE  X_1       X_2  X_5      X_11      X_12      X_13  X_16  \
index                                                                         
22              0.0  0.0  0.666667  0.0  0.365821  0.477327  0.284107   0.0   
23              0.0  0.0  0.666667  0.0  0.376502  0.501193  0.295359   1.0   
25              0.0  0.0 -0.166667  0.0  0.526035  0.663484  0.458509   0.0   
29              0.0  0.0  0.333333  0.0  0.477971  0.663484  0.379747   1.0   
37              0.0  0.0  0.333333  0.0  0.531375  0.696897  0.430380   0.0   
...             ...  ...       ...  ...       ...       ...       ...   ...   
547             0.0  0.0  0.000000 -1.0 -1.182911 -1.021480 -1.263010   0.0   
548             0.0  0.0  0.500000 -1.0 -1.177570 -0.916468 -1.223629   0.0   
558             0.0  0.0  0.500000 -1.0 -0.830441 -0.706444 -0.891702   1.0   
561             0.0  0.0  0.000000  0.0 -0.392523 -0.324582 -0.357243   1.0   
592             0.0  0.0  0.000000 -1.0 -0.109479 -0.071599 -0.109705   0.0   

       X_17  X_18  ...     X_924     X_925     X_926     X_927     X_928  \
index              ...                                                     
22     -0.5  -1.0  ... -0.015873  0.642857  0.770933  0.509091  0.000000   
23      0.0   1.0  ...  0.058758  0.108048 -0.003699 -0.116427 -0.307602   
25     -1.5   0.0  ...  0.825397 -0.714286 -0.023876  0.509091  0.100000   
29      0.0   1.0  ...  0.841270  0.285714  0.470041  0.181818  0.100000   
37      0.0  -1.0  ...  1.619048  0.666667  0.417324  0.054545  0.100000   
...     ...   ...  ...       ...       ...       ...       ...       ...   
547    -0.5   0.0  ... -0.857143 -0.261905  0.121298  0.145455  0.000000   
548     1.0   1.0  ... -0.047619  0.285714 -0.414793 -0.654545  0.100000   
558    -0.5  -1.0  ... -0.349206  0.214286 -0.896517 -1.363636 -0.100000   
561     0.5   1.0  ... -1.349206  0.595238  0.694696  0.545455 -0.900000   
592    -1.0   2.0  ... -0.174603 -0.833333 -0.410738 -0.090909  0.000000   

          X_929     X_930     X_931     X_932     X_933  
index                                                    
22     0.558616  0.435946  1.000000  0.517333  0.000000  
23     0.191278  0.897387  0.444444  0.135883  0.012865  
25     0.778988  3.923518  1.000000  0.660000  0.000000  
29     0.955798  3.923518  1.000000  0.260000  0.000000  
37     0.976297  3.923518  1.000000  0.682667  0.100000  
...         ...       ...       ...       ...       ...  
547    0.617553 -0.435946  1.000000  1.060000  0.100000  
548    0.638053  0.435946  1.000000  1.344000  0.100000  
558   -0.081999  0.000000  1.000000  1.100000  0.100000  
561   -0.253684  0.000000  1.000000  0.848000  0.100000  
592    1.007047  3.923518  0.000000 -0.500000  0.000000  

[172 rows x 548 columns]

In [71]:
from pycaret.regression import *
setup_rgs = setup(data = T1003042_data, target = T1003042_target, session_id = 4)
top5 = compare_models(sort='MSE', n_select=5)

Processing:   0%|          | 0/89 [00:00<?, ?it/s]

In [72]:
T01_total_models = []

T01_model_lightgbm = create_model('lightgbm', fold = 5)
T01_total_models.append(T01_model_lightgbm)

T01_model_rf = create_model('rf', fold = 5)
T01_total_models.append(T01_model_rf)

T01_model_gbr = create_model('gbr', fold = 5)
T01_total_models.append(T01_model_gbr)

T01_model_et = create_model('et', fold = 5)
T01_total_models.append(T01_model_et)

T01_model_catboost = create_model('catboost', fold = 5)
T01_total_models.append(T01_model_catboost)

T01_model_xgb = create_model('xgboost', fold = 5)
T01_total_models.append(T01_model_xgb)

T01_model_ada = create_model('ada', fold = 5)
T01_total_models.append(T01_model_ada)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [73]:
T01_model_lightgbm = tune_model(T01_model_lightgbm, fold=5, choose_better = True)

T01_model_rf = tune_model(T01_model_rf, fold=5, choose_better = True)

T01_model_gbr = tune_model(T01_model_gbr, fold=5, choose_better = True)

T01_model_et = tune_model(T01_model_et, fold=5, choose_better = True)

T01_model_catboost = tune_model(T01_model_catboost, fold=5, choose_better = True)

T01_model_xgb = tune_model(T01_model_xgb, fold=5, choose_better = True)

T01_model_ada = tune_model(T01_model_ada, fold=5, choose_better = True)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

...

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


In [74]:
T01_tuned_models = [T01_model_lightgbm, T01_model_rf, T01_model_gbr, T01_model_et, T01_model_catboost, T01_model_xgb, T01_model_ada]

for model in T01_tuned_models:
    display(predict_model(model))

PRODUCT_CODE  X_1       X_2  X_5      X_11      X_12      X_13  X_16  \
120           0.0  0.0 -0.333333  0.0 -0.013351 -0.023866 -0.008439   0.0   
121           0.0  0.0  0.000000  0.0  0.536716  0.596659  0.526020   0.0   
122           0.0  0.0 -0.666667  0.0 -0.574099 -0.477327 -0.604782   0.0   
123           0.0 -1.0 -0.833333  0.0  0.766355  0.849642  0.734177   1.0   
124           0.0  0.0 -0.666667  0.0 -1.636849 -1.379475 -1.746835   0.0   
125           0.0  0.0  0.666667  0.0 -0.194927 -0.162291 -0.194093   0.0   
126           0.0  0.0 -0.500000  0.0 -1.268358 -1.054893 -1.330520   1.0   
127           0.0 -1.0 -0.833333 -1.0  0.680908  0.792363  0.599156   1.0   
128           0.0  0.0  0.666667  0.0  0.376502  0.501193  0.295359   1.0   
129           0.0  0.0  0.166667 -1.0 -0.686248 -0.610979 -0.711674   1.0   
130           0.0  0.0 -0.500000  0.0 -0.301736 -0.243437 -0.357243   1.0   
131           0.0  0.0 -0.833333  0.0  0.456609  0.510740  0.458509   0.0   
132           0.0  0.0  0.333333  0.0 -0.568758 -0.477327 -0.548523   0.0   
133           0.0  0.0 -0.500000  0.0 -0.355140 -0.300716 -0.413502  -1.0   
134           0.0  0.0  0.333333 -1.0  0.387183  0.429594  0.379747   1.0   
135           0.0  0.0  0.666667  0.0  0.392523  0.386635  0.390999   1.0   
136           0.0  0.0 -0.500000  0.0  0.077437  0.095465  0.059072   1.0   
137           0.0  0.0 -0.833333  0.0 -0.061415 -0.033413 -0.081575   0.0   
138           0.0  0.0  0.000000  0.0 -0.093458 -0.071599 -0.081575   0.0   
139           0.0 -1.0 -0.666667  0.0  0.146862  0.152745  0.143460   0.0   
140           0.0  0.0  0.000000 -1.0 -0.056075 -0.057279 -0.081575   0.0   
141           0.0  0.0 -0.166667  0.0  1.006676  1.140811  0.914205   1.0   
142           0.0  0.0  0.166667  0.0  0.451268  0.606205  0.323488   0.0   
143           0.0  0.0 -0.666667  0.0  0.899866  1.050119  0.790436   1.0   
144           0.0 -1.0 -0.666667  0.0  0.702270  0.782816  0.649789   1.0   
145           0.0  0.0  0.500000  0.0 -0.969292 -0.797136 -0.976090   0.0   
146           0.0  0.0  0.333333  0.0  0.376502  0.429594  0.379747   1.0   
147           0.0  0.0  0.666667  0.0  0.910547  1.026253  0.818565   1.0   
148           0.0  0.0  0.500000  0.0 -0.830441 -0.644391 -0.835443   1.0   
149           0.0  0.0  0.500000  0.0 -1.722296 -1.460621 -1.786217   0.0   
150           0.0  0.0  0.166667 -1.0  0.867824  1.011933  0.790436   1.0   
151           0.0  0.0 -0.833333  0.0  0.349800  0.362769  0.351617   1.0   
152           0.0 -1.0  0.666667  0.0  0.536716  0.687351  0.419128   1.0   
153           0.0  0.0  0.000000  0.0 -1.263017 -1.031026 -1.319269   0.0   
154           0.0  0.0  0.500000 -1.0 -1.230975 -1.054893 -1.279887   0.0   
155           0.0  0.0 -0.166667  0.0  0.526035  0.663485  0.458509   0.0   
156           0.0  0.0  0.666667  0.0  0.013351  0.023866  0.008439   1.0   
157           0.0  0.0  0.500000  0.0 -0.819760 -0.634845 -0.824191   1.0   
158           0.0  0.0 -0.333333  0.0 -1.086782 -0.902148 -1.139241  -1.0   
159           0.0  0.0 -0.166667 -1.0  0.841121  0.978520  0.773558   0.0   
160           0.0  0.0  0.500000 -1.0  0.638184  0.696897  0.610408   0.0   
161           0.0  0.0 -0.166667  0.0  0.461949  0.653938  0.362869   0.0   
162           0.0  0.0  0.666667  0.0  0.210948  0.233890  0.210970   1.0   
163           0.0  0.0  0.333333  0.0 -0.157543 -0.152745 -0.194093   0.0   
164           0.0  0.0  0.500000  0.0 -1.081442 -0.902148 -1.139241   1.0   
165           0.0 -1.0 -0.333333  0.0  0.531375  0.606205  0.447257   0.0   
166           0.0  0.0 -0.500000  0.0  0.248331  0.243437  0.227848   0.0   
167           0.0  0.0  0.500000  0.0 -0.040053 -0.033413 -0.036568   0.0   
168           0.0  0.0 -0.500000  0.0 -1.727637 -1.484487 -1.825598   1.0   
169           0.0  0.0  0.333333  0.0 -0.974633 -0.797136 -1.043601   0.0   
170           0.0  0.0  0.166667  0.0  0.905207  1.050119  0.818565   1.0   
1

PRODUCT_CODE  X_1       X_2  X_5      X_11      X_12      X_13  X_16  \
120           0.0  0.0 -0.333333  0.0 -0.013351 -0.023866 -0.008439   0.0   
121           0.0  0.0  0.000000  0.0  0.536716  0.596659  0.526020   0.0   
122           0.0  0.0 -0.666667  0.0 -0.574099 -0.477327 -0.604782   0.0   
123           0.0 -1.0 -0.833333  0.0  0.766355  0.849642  0.734177   1.0   
124           0.0  0.0 -0.666667  0.0 -1.636849 -1.379475 -1.746835   0.0   
125           0.0  0.0  0.666667  0.0 -0.194927 -0.162291 -0.194093   0.0   
126           0.0  0.0 -0.500000  0.0 -1.268358 -1.054893 -1.330520   1.0   
127           0.0 -1.0 -0.833333 -1.0  0.680908  0.792363  0.599156   1.0   
128           0.0  0.0  0.666667  0.0  0.376502  0.501193  0.295359   1.0   
129           0.0  0.0  0.166667 -1.0 -0.686248 -0.610979 -0.711674   1.0   
130           0.0  0.0 -0.500000  0.0 -0.301736 -0.243437 -0.357243   1.0   
131           0.0  0.0 -0.833333  0.0  0.456609  0.510740  0.458509   0.0   
132           0.0  0.0  0.333333  0.0 -0.568758 -0.477327 -0.548523   0.0   
133           0.0  0.0 -0.500000  0.0 -0.355140 -0.300716 -0.413502  -1.0   
134           0.0  0.0  0.333333 -1.0  0.387183  0.429594  0.379747   1.0   
135           0.0  0.0  0.666667  0.0  0.392523  0.386635  0.390999   1.0   
136           0.0  0.0 -0.500000  0.0  0.077437  0.095465  0.059072   1.0   
137           0.0  0.0 -0.833333  0.0 -0.061415 -0.033413 -0.081575   0.0   
138           0.0  0.0  0.000000  0.0 -0.093458 -0.071599 -0.081575   0.0   
139           0.0 -1.0 -0.666667  0.0  0.146862  0.152745  0.143460   0.0   
140           0.0  0.0  0.000000 -1.0 -0.056075 -0.057279 -0.081575   0.0   
141           0.0  0.0 -0.166667  0.0  1.006676  1.140811  0.914205   1.0   
142           0.0  0.0  0.166667  0.0  0.451268  0.606205  0.323488   0.0   
143           0.0  0.0 -0.666667  0.0  0.899866  1.050119  0.790436   1.0   
144           0.0 -1.0 -0.666667  0.0  0.702270  0.782816  0.649789   1.0   
145           0.0  0.0  0.500000  0.0 -0.969292 -0.797136 -0.976090   0.0   
146           0.0  0.0  0.333333  0.0  0.376502  0.429594  0.379747   1.0   
147           0.0  0.0  0.666667  0.0  0.910547  1.026253  0.818565   1.0   
148           0.0  0.0  0.500000  0.0 -0.830441 -0.644391 -0.835443   1.0   
149           0.0  0.0  0.500000  0.0 -1.722296 -1.460621 -1.786217   0.0   
150           0.0  0.0  0.166667 -1.0  0.867824  1.011933  0.790436   1.0   
151           0.0  0.0 -0.833333  0.0  0.349800  0.362769  0.351617   1.0   
152           0.0 -1.0  0.666667  0.0  0.536716  0.687351  0.419128   1.0   
153           0.0  0.0  0.000000  0.0 -1.263017 -1.031026 -1.319269   0.0   
154           0.0  0.0  0.500000 -1.0 -1.230975 -1.054893 -1.279887   0.0   
155           0.0  0.0 -0.166667  0.0  0.526035  0.663485  0.458509   0.0   
156           0.0  0.0  0.666667  0.0  0.013351  0.023866  0.008439   1.0   
157           0.0  0.0  0.500000  0.0 -0.819760 -0.634845 -0.824191   1.0   
158           0.0  0.0 -0.333333  0.0 -1.086782 -0.902148 -1.139241  -1.0   
159           0.0  0.0 -0.166667 -1.0  0.841121  0.978520  0.773558   0.0   
160           0.0  0.0  0.500000 -1.0  0.638184  0.696897  0.610408   0.0   
161           0.0  0.0 -0.166667  0.0  0.461949  0.653938  0.362869   0.0   
162           0.0  0.0  0.666667  0.0  0.210948  0.233890  0.210970   1.0   
163           0.0  0.0  0.333333  0.0 -0.157543 -0.152745 -0.194093   0.0   
164           0.0  0.0  0.500000  0.0 -1.081442 -0.902148 -1.139241   1.0   
165           0.0 -1.0 -0.333333  0.0  0.531375  0.606205  0.447257   0.0   
166           0.0  0.0 -0.500000  0.0  0.248331  0.243437  0.227848   0.0   
167           0.0  0.0  0.500000  0.0 -0.040053 -0.033413 -0.036568   0.0   
168           0.0  0.0 -0.500000  0.0 -1.727637 -1.484487 -1.825598   1.0   
169           0.0  0.0  0.333333  0.0 -0.974633 -0.797136 -1.043601   0.0   
170           0.0  0.0  0.166667  0.0  0.905207  1.050119  0.818565   1.0   
1

PRODUCT_CODE  X_1       X_2  X_5      X_11      X_12      X_13  X_16  \
120           0.0  0.0 -0.333333  0.0 -0.013351 -0.023866 -0.008439   0.0   
121           0.0  0.0  0.000000  0.0  0.536716  0.596659  0.526020   0.0   
122           0.0  0.0 -0.666667  0.0 -0.574099 -0.477327 -0.604782   0.0   
123           0.0 -1.0 -0.833333  0.0  0.766355  0.849642  0.734177   1.0   
124           0.0  0.0 -0.666667  0.0 -1.636849 -1.379475 -1.746835   0.0   
125           0.0  0.0  0.666667  0.0 -0.194927 -0.162291 -0.194093   0.0   
126           0.0  0.0 -0.500000  0.0 -1.268358 -1.054893 -1.330520   1.0   
127           0.0 -1.0 -0.833333 -1.0  0.680908  0.792363  0.599156   1.0   
128           0.0  0.0  0.666667  0.0  0.376502  0.501193  0.295359   1.0   
129           0.0  0.0  0.166667 -1.0 -0.686248 -0.610979 -0.711674   1.0   
130           0.0  0.0 -0.500000  0.0 -0.301736 -0.243437 -0.357243   1.0   
131           0.0  0.0 -0.833333  0.0  0.456609  0.510740  0.458509   0.0   
132           0.0  0.0  0.333333  0.0 -0.568758 -0.477327 -0.548523   0.0   
133           0.0  0.0 -0.500000  0.0 -0.355140 -0.300716 -0.413502  -1.0   
134           0.0  0.0  0.333333 -1.0  0.387183  0.429594  0.379747   1.0   
135           0.0  0.0  0.666667  0.0  0.392523  0.386635  0.390999   1.0   
136           0.0  0.0 -0.500000  0.0  0.077437  0.095465  0.059072   1.0   
137           0.0  0.0 -0.833333  0.0 -0.061415 -0.033413 -0.081575   0.0   
138           0.0  0.0  0.000000  0.0 -0.093458 -0.071599 -0.081575   0.0   
139           0.0 -1.0 -0.666667  0.0  0.146862  0.152745  0.143460   0.0   
140           0.0  0.0  0.000000 -1.0 -0.056075 -0.057279 -0.081575   0.0   
141           0.0  0.0 -0.166667  0.0  1.006676  1.140811  0.914205   1.0   
142           0.0  0.0  0.166667  0.0  0.451268  0.606205  0.323488   0.0   
143           0.0  0.0 -0.666667  0.0  0.899866  1.050119  0.790436   1.0   
144           0.0 -1.0 -0.666667  0.0  0.702270  0.782816  0.649789   1.0   
145           0.0  0.0  0.500000  0.0 -0.969292 -0.797136 -0.976090   0.0   
146           0.0  0.0  0.333333  0.0  0.376502  0.429594  0.379747   1.0   
147           0.0  0.0  0.666667  0.0  0.910547  1.026253  0.818565   1.0   
148           0.0  0.0  0.500000  0.0 -0.830441 -0.644391 -0.835443   1.0   
149           0.0  0.0  0.500000  0.0 -1.722296 -1.460621 -1.786217   0.0   
150           0.0  0.0  0.166667 -1.0  0.867824  1.011933  0.790436   1.0   
151           0.0  0.0 -0.833333  0.0  0.349800  0.362769  0.351617   1.0   
152           0.0 -1.0  0.666667  0.0  0.536716  0.687351  0.419128   1.0   
153           0.0  0.0  0.000000  0.0 -1.263017 -1.031026 -1.319269   0.0   
154           0.0  0.0  0.500000 -1.0 -1.230975 -1.054893 -1.279887   0.0   
155           0.0  0.0 -0.166667  0.0  0.526035  0.663485  0.458509   0.0   
156           0.0  0.0  0.666667  0.0  0.013351  0.023866  0.008439   1.0   
157           0.0  0.0  0.500000  0.0 -0.819760 -0.634845 -0.824191   1.0   
158           0.0  0.0 -0.333333  0.0 -1.086782 -0.902148 -1.139241  -1.0   
159           0.0  0.0 -0.166667 -1.0  0.841121  0.978520  0.773558   0.0   
160           0.0  0.0  0.500000 -1.0  0.638184  0.696897  0.610408   0.0   
161           0.0  0.0 -0.166667  0.0  0.461949  0.653938  0.362869   0.0   
162           0.0  0.0  0.666667  0.0  0.210948  0.233890  0.210970   1.0   
163           0.0  0.0  0.333333  0.0 -0.157543 -0.152745 -0.194093   0.0   
164           0.0  0.0  0.500000  0.0 -1.081442 -0.902148 -1.139241   1.0   
165           0.0 -1.0 -0.333333  0.0  0.531375  0.606205  0.447257   0.0   
166           0.0  0.0 -0.500000  0.0  0.248331  0.243437  0.227848   0.0   
167           0.0  0.0  0.500000  0.0 -0.040053 -0.033413 -0.036568   0.0   
168           0.0  0.0 -0.500000  0.0 -1.727637 -1.484487 -1.825598   1.0   
169           0.0  0.0  0.333333  0.0 -0.974633 -0.797136 -1.043601   0.0   
170           0.0  0.0  0.166667  0.0  0.905207  1.050119  0.818565   1.0   
1

PRODUCT_CODE  X_1       X_2  X_5      X_11      X_12      X_13  X_16  \
120           0.0  0.0 -0.333333  0.0 -0.013351 -0.023866 -0.008439   0.0   
121           0.0  0.0  0.000000  0.0  0.536716  0.596659  0.526020   0.0   
122           0.0  0.0 -0.666667  0.0 -0.574099 -0.477327 -0.604782   0.0   
123           0.0 -1.0 -0.833333  0.0  0.766355  0.849642  0.734177   1.0   
124           0.0  0.0 -0.666667  0.0 -1.636849 -1.379475 -1.746835   0.0   
125           0.0  0.0  0.666667  0.0 -0.194927 -0.162291 -0.194093   0.0   
126           0.0  0.0 -0.500000  0.0 -1.268358 -1.054893 -1.330520   1.0   
127           0.0 -1.0 -0.833333 -1.0  0.680908  0.792363  0.599156   1.0   
128           0.0  0.0  0.666667  0.0  0.376502  0.501193  0.295359   1.0   
129           0.0  0.0  0.166667 -1.0 -0.686248 -0.610979 -0.711674   1.0   
130           0.0  0.0 -0.500000  0.0 -0.301736 -0.243437 -0.357243   1.0   
131           0.0  0.0 -0.833333  0.0  0.456609  0.510740  0.458509   0.0   
132           0.0  0.0  0.333333  0.0 -0.568758 -0.477327 -0.548523   0.0   
133           0.0  0.0 -0.500000  0.0 -0.355140 -0.300716 -0.413502  -1.0   
134           0.0  0.0  0.333333 -1.0  0.387183  0.429594  0.379747   1.0   
135           0.0  0.0  0.666667  0.0  0.392523  0.386635  0.390999   1.0   
136           0.0  0.0 -0.500000  0.0  0.077437  0.095465  0.059072   1.0   
137           0.0  0.0 -0.833333  0.0 -0.061415 -0.033413 -0.081575   0.0   
138           0.0  0.0  0.000000  0.0 -0.093458 -0.071599 -0.081575   0.0   
139           0.0 -1.0 -0.666667  0.0  0.146862  0.152745  0.143460   0.0   
140           0.0  0.0  0.000000 -1.0 -0.056075 -0.057279 -0.081575   0.0   
141           0.0  0.0 -0.166667  0.0  1.006676  1.140811  0.914205   1.0   
142           0.0  0.0  0.166667  0.0  0.451268  0.606205  0.323488   0.0   
143           0.0  0.0 -0.666667  0.0  0.899866  1.050119  0.790436   1.0   
144           0.0 -1.0 -0.666667  0.0  0.702270  0.782816  0.649789   1.0   
145           0.0  0.0  0.500000  0.0 -0.969292 -0.797136 -0.976090   0.0   
146           0.0  0.0  0.333333  0.0  0.376502  0.429594  0.379747   1.0   
147           0.0  0.0  0.666667  0.0  0.910547  1.026253  0.818565   1.0   
148           0.0  0.0  0.500000  0.0 -0.830441 -0.644391 -0.835443   1.0   
149           0.0  0.0  0.500000  0.0 -1.722296 -1.460621 -1.786217   0.0   
150           0.0  0.0  0.166667 -1.0  0.867824  1.011933  0.790436   1.0   
151           0.0  0.0 -0.833333  0.0  0.349800  0.362769  0.351617   1.0   
152           0.0 -1.0  0.666667  0.0  0.536716  0.687351  0.419128   1.0   
153           0.0  0.0  0.000000  0.0 -1.263017 -1.031026 -1.319269   0.0   
154           0.0  0.0  0.500000 -1.0 -1.230975 -1.054893 -1.279887   0.0   
155           0.0  0.0 -0.166667  0.0  0.526035  0.663485  0.458509   0.0   
156           0.0  0.0  0.666667  0.0  0.013351  0.023866  0.008439   1.0   
157           0.0  0.0  0.500000  0.0 -0.819760 -0.634845 -0.824191   1.0   
158           0.0  0.0 -0.333333  0.0 -1.086782 -0.902148 -1.139241  -1.0   
159           0.0  0.0 -0.166667 -1.0  0.841121  0.978520  0.773558   0.0   
160           0.0  0.0  0.500000 -1.0  0.638184  0.696897  0.610408   0.0   
161           0.0  0.0 -0.166667  0.0  0.461949  0.653938  0.362869   0.0   
162           0.0  0.0  0.666667  0.0  0.210948  0.233890  0.210970   1.0   
163           0.0  0.0  0.333333  0.0 -0.157543 -0.152745 -0.194093   0.0   
164           0.0  0.0  0.500000  0.0 -1.081442 -0.902148 -1.139241   1.0   
165           0.0 -1.0 -0.333333  0.0  0.531375  0.606205  0.447257   0.0   
166           0.0  0.0 -0.500000  0.0  0.248331  0.243437  0.227848   0.0   
167           0.0  0.0  0.500000  0.0 -0.040053 -0.033413 -0.036568   0.0   
168           0.0  0.0 -0.500000  0.0 -1.727637 -1.484487 -1.825598   1.0   
169           0.0  0.0  0.333333  0.0 -0.974633 -0.797136 -1.043601   0.0   
170           0.0  0.0  0.166667  0.0  0.905207  1.050119  0.818565   1.0   
1

PRODUCT_CODE  X_1       X_2  X_5      X_11      X_12      X_13  X_16  \
120           0.0  0.0 -0.333333  0.0 -0.013351 -0.023866 -0.008439   0.0   
121           0.0  0.0  0.000000  0.0  0.536716  0.596659  0.526020   0.0   
122           0.0  0.0 -0.666667  0.0 -0.574099 -0.477327 -0.604782   0.0   
123           0.0 -1.0 -0.833333  0.0  0.766355  0.849642  0.734177   1.0   
124           0.0  0.0 -0.666667  0.0 -1.636849 -1.379475 -1.746835   0.0   
125           0.0  0.0  0.666667  0.0 -0.194927 -0.162291 -0.194093   0.0   
126           0.0  0.0 -0.500000  0.0 -1.268358 -1.054893 -1.330520   1.0   
127           0.0 -1.0 -0.833333 -1.0  0.680908  0.792363  0.599156   1.0   
128           0.0  0.0  0.666667  0.0  0.376502  0.501193  0.295359   1.0   
129           0.0  0.0  0.166667 -1.0 -0.686248 -0.610979 -0.711674   1.0   
130           0.0  0.0 -0.500000  0.0 -0.301736 -0.243437 -0.357243   1.0   
131           0.0  0.0 -0.833333  0.0  0.456609  0.510740  0.458509   0.0   
132           0.0  0.0  0.333333  0.0 -0.568758 -0.477327 -0.548523   0.0   
133           0.0  0.0 -0.500000  0.0 -0.355140 -0.300716 -0.413502  -1.0   
134           0.0  0.0  0.333333 -1.0  0.387183  0.429594  0.379747   1.0   
135           0.0  0.0  0.666667  0.0  0.392523  0.386635  0.390999   1.0   
136           0.0  0.0 -0.500000  0.0  0.077437  0.095465  0.059072   1.0   
137           0.0  0.0 -0.833333  0.0 -0.061415 -0.033413 -0.081575   0.0   
138           0.0  0.0  0.000000  0.0 -0.093458 -0.071599 -0.081575   0.0   
139           0.0 -1.0 -0.666667  0.0  0.146862  0.152745  0.143460   0.0   
140           0.0  0.0  0.000000 -1.0 -0.056075 -0.057279 -0.081575   0.0   
141           0.0  0.0 -0.166667  0.0  1.006676  1.140811  0.914205   1.0   
142           0.0  0.0  0.166667  0.0  0.451268  0.606205  0.323488   0.0   
143           0.0  0.0 -0.666667  0.0  0.899866  1.050119  0.790436   1.0   
144           0.0 -1.0 -0.666667  0.0  0.702270  0.782816  0.649789   1.0   
145           0.0  0.0  0.500000  0.0 -0.969292 -0.797136 -0.976090   0.0   
146           0.0  0.0  0.333333  0.0  0.376502  0.429594  0.379747   1.0   
147           0.0  0.0  0.666667  0.0  0.910547  1.026253  0.818565   1.0   
148           0.0  0.0  0.500000  0.0 -0.830441 -0.644391 -0.835443   1.0   
149           0.0  0.0  0.500000  0.0 -1.722296 -1.460621 -1.786217   0.0   
150           0.0  0.0  0.166667 -1.0  0.867824  1.011933  0.790436   1.0   
151           0.0  0.0 -0.833333  0.0  0.349800  0.362769  0.351617   1.0   
152           0.0 -1.0  0.666667  0.0  0.536716  0.687351  0.419128   1.0   
153           0.0  0.0  0.000000  0.0 -1.263017 -1.031026 -1.319269   0.0   
154           0.0  0.0  0.500000 -1.0 -1.230975 -1.054893 -1.279887   0.0   
155           0.0  0.0 -0.166667  0.0  0.526035  0.663485  0.458509   0.0   
156           0.0  0.0  0.666667  0.0  0.013351  0.023866  0.008439   1.0   
157           0.0  0.0  0.500000  0.0 -0.819760 -0.634845 -0.824191   1.0   
158           0.0  0.0 -0.333333  0.0 -1.086782 -0.902148 -1.139241  -1.0   
159           0.0  0.0 -0.166667 -1.0  0.841121  0.978520  0.773558   0.0   
160           0.0  0.0  0.500000 -1.0  0.638184  0.696897  0.610408   0.0   
161           0.0  0.0 -0.166667  0.0  0.461949  0.653938  0.362869   0.0   
162           0.0  0.0  0.666667  0.0  0.210948  0.233890  0.210970   1.0   
163           0.0  0.0  0.333333  0.0 -0.157543 -0.152745 -0.194093   0.0   
164           0.0  0.0  0.500000  0.0 -1.081442 -0.902148 -1.139241   1.0   
165           0.0 -1.0 -0.333333  0.0  0.531375  0.606205  0.447257   0.0   
166           0.0  0.0 -0.500000  0.0  0.248331  0.243437  0.227848   0.0   
167           0.0  0.0  0.500000  0.0 -0.040053 -0.033413 -0.036568   0.0   
168           0.0  0.0 -0.500000  0.0 -1.727637 -1.484487 -1.825598   1.0   
169           0.0  0.0  0.333333  0.0 -0.974633 -0.797136 -1.043601   0.0   
170           0.0  0.0  0.166667  0.0  0.905207  1.050119  0.818565   1.0   
1

PRODUCT_CODE  X_1       X_2  X_5      X_11      X_12      X_13  X_16  \
120           0.0  0.0 -0.333333  0.0 -0.013351 -0.023866 -0.008439   0.0   
121           0.0  0.0  0.000000  0.0  0.536716  0.596659  0.526020   0.0   
122           0.0  0.0 -0.666667  0.0 -0.574099 -0.477327 -0.604782   0.0   
123           0.0 -1.0 -0.833333  0.0  0.766355  0.849642  0.734177   1.0   
124           0.0  0.0 -0.666667  0.0 -1.636849 -1.379475 -1.746835   0.0   
125           0.0  0.0  0.666667  0.0 -0.194927 -0.162291 -0.194093   0.0   
126           0.0  0.0 -0.500000  0.0 -1.268358 -1.054893 -1.330520   1.0   
127           0.0 -1.0 -0.833333 -1.0  0.680908  0.792363  0.599156   1.0   
128           0.0  0.0  0.666667  0.0  0.376502  0.501193  0.295359   1.0   
129           0.0  0.0  0.166667 -1.0 -0.686248 -0.610979 -0.711674   1.0   
130           0.0  0.0 -0.500000  0.0 -0.301736 -0.243437 -0.357243   1.0   
131           0.0  0.0 -0.833333  0.0  0.456609  0.510740  0.458509   0.0   
132           0.0  0.0  0.333333  0.0 -0.568758 -0.477327 -0.548523   0.0   
133           0.0  0.0 -0.500000  0.0 -0.355140 -0.300716 -0.413502  -1.0   
134           0.0  0.0  0.333333 -1.0  0.387183  0.429594  0.379747   1.0   
135           0.0  0.0  0.666667  0.0  0.392523  0.386635  0.390999   1.0   
136           0.0  0.0 -0.500000  0.0  0.077437  0.095465  0.059072   1.0   
137           0.0  0.0 -0.833333  0.0 -0.061415 -0.033413 -0.081575   0.0   
138           0.0  0.0  0.000000  0.0 -0.093458 -0.071599 -0.081575   0.0   
139           0.0 -1.0 -0.666667  0.0  0.146862  0.152745  0.143460   0.0   
140           0.0  0.0  0.000000 -1.0 -0.056075 -0.057279 -0.081575   0.0   
141           0.0  0.0 -0.166667  0.0  1.006676  1.140811  0.914205   1.0   
142           0.0  0.0  0.166667  0.0  0.451268  0.606205  0.323488   0.0   
143           0.0  0.0 -0.666667  0.0  0.899866  1.050119  0.790436   1.0   
144           0.0 -1.0 -0.666667  0.0  0.702270  0.782816  0.649789   1.0   
145           0.0  0.0  0.500000  0.0 -0.969292 -0.797136 -0.976090   0.0   
146           0.0  0.0  0.333333  0.0  0.376502  0.429594  0.379747   1.0   
147           0.0  0.0  0.666667  0.0  0.910547  1.026253  0.818565   1.0   
148           0.0  0.0  0.500000  0.0 -0.830441 -0.644391 -0.835443   1.0   
149           0.0  0.0  0.500000  0.0 -1.722296 -1.460621 -1.786217   0.0   
150           0.0  0.0  0.166667 -1.0  0.867824  1.011933  0.790436   1.0   
151           0.0  0.0 -0.833333  0.0  0.349800  0.362769  0.351617   1.0   
152           0.0 -1.0  0.666667  0.0  0.536716  0.687351  0.419128   1.0   
153           0.0  0.0  0.000000  0.0 -1.263017 -1.031026 -1.319269   0.0   
154           0.0  0.0  0.500000 -1.0 -1.230975 -1.054893 -1.279887   0.0   
155           0.0  0.0 -0.166667  0.0  0.526035  0.663485  0.458509   0.0   
156           0.0  0.0  0.666667  0.0  0.013351  0.023866  0.008439   1.0   
157           0.0  0.0  0.500000  0.0 -0.819760 -0.634845 -0.824191   1.0   
158           0.0  0.0 -0.333333  0.0 -1.086782 -0.902148 -1.139241  -1.0   
159           0.0  0.0 -0.166667 -1.0  0.841121  0.978520  0.773558   0.0   
160           0.0  0.0  0.500000 -1.0  0.638184  0.696897  0.610408   0.0   
161           0.0  0.0 -0.166667  0.0  0.461949  0.653938  0.362869   0.0   
162           0.0  0.0  0.666667  0.0  0.210948  0.233890  0.210970   1.0   
163           0.0  0.0  0.333333  0.0 -0.157543 -0.152745 -0.194093   0.0   
164           0.0  0.0  0.500000  0.0 -1.081442 -0.902148 -1.139241   1.0   
165           0.0 -1.0 -0.333333  0.0  0.531375  0.606205  0.447257   0.0   
166           0.0  0.0 -0.500000  0.0  0.248331  0.243437  0.227848   0.0   
167           0.0  0.0  0.500000  0.0 -0.040053 -0.033413 -0.036568   0.0   
168           0.0  0.0 -0.500000  0.0 -1.727637 -1.484487 -1.825598   1.0   
169           0.0  0.0  0.333333  0.0 -0.974633 -0.797136 -1.043601   0.0   
170           0.0  0.0  0.166667  0.0  0.905207  1.050119  0.818565   1.0   
1

PRODUCT_CODE  X_1       X_2  X_5      X_11      X_12      X_13  X_16  \
120           0.0  0.0 -0.333333  0.0 -0.013351 -0.023866 -0.008439   0.0   
121           0.0  0.0  0.000000  0.0  0.536716  0.596659  0.526020   0.0   
122           0.0  0.0 -0.666667  0.0 -0.574099 -0.477327 -0.604782   0.0   
123           0.0 -1.0 -0.833333  0.0  0.766355  0.849642  0.734177   1.0   
124           0.0  0.0 -0.666667  0.0 -1.636849 -1.379475 -1.746835   0.0   
125           0.0  0.0  0.666667  0.0 -0.194927 -0.162291 -0.194093   0.0   
126           0.0  0.0 -0.500000  0.0 -1.268358 -1.054893 -1.330520   1.0   
127           0.0 -1.0 -0.833333 -1.0  0.680908  0.792363  0.599156   1.0   
128           0.0  0.0  0.666667  0.0  0.376502  0.501193  0.295359   1.0   
129           0.0  0.0  0.166667 -1.0 -0.686248 -0.610979 -0.711674   1.0   
130           0.0  0.0 -0.500000  0.0 -0.301736 -0.243437 -0.357243   1.0   
131           0.0  0.0 -0.833333  0.0  0.456609  0.510740  0.458509   0.0   
132           0.0  0.0  0.333333  0.0 -0.568758 -0.477327 -0.548523   0.0   
133           0.0  0.0 -0.500000  0.0 -0.355140 -0.300716 -0.413502  -1.0   
134           0.0  0.0  0.333333 -1.0  0.387183  0.429594  0.379747   1.0   
135           0.0  0.0  0.666667  0.0  0.392523  0.386635  0.390999   1.0   
136           0.0  0.0 -0.500000  0.0  0.077437  0.095465  0.059072   1.0   
137           0.0  0.0 -0.833333  0.0 -0.061415 -0.033413 -0.081575   0.0   
138           0.0  0.0  0.000000  0.0 -0.093458 -0.071599 -0.081575   0.0   
139           0.0 -1.0 -0.666667  0.0  0.146862  0.152745  0.143460   0.0   
140           0.0  0.0  0.000000 -1.0 -0.056075 -0.057279 -0.081575   0.0   
141           0.0  0.0 -0.166667  0.0  1.006676  1.140811  0.914205   1.0   
142           0.0  0.0  0.166667  0.0  0.451268  0.606205  0.323488   0.0   
143           0.0  0.0 -0.666667  0.0  0.899866  1.050119  0.790436   1.0   
144           0.0 -1.0 -0.666667  0.0  0.702270  0.782816  0.649789   1.0   
145           0.0  0.0  0.500000  0.0 -0.969292 -0.797136 -0.976090   0.0   
146           0.0  0.0  0.333333  0.0  0.376502  0.429594  0.379747   1.0   
147           0.0  0.0  0.666667  0.0  0.910547  1.026253  0.818565   1.0   
148           0.0  0.0  0.500000  0.0 -0.830441 -0.644391 -0.835443   1.0   
149           0.0  0.0  0.500000  0.0 -1.722296 -1.460621 -1.786217   0.0   
150           0.0  0.0  0.166667 -1.0  0.867824  1.011933  0.790436   1.0   
151           0.0  0.0 -0.833333  0.0  0.349800  0.362769  0.351617   1.0   
152           0.0 -1.0  0.666667  0.0  0.536716  0.687351  0.419128   1.0   
153           0.0  0.0  0.000000  0.0 -1.263017 -1.031026 -1.319269   0.0   
154           0.0  0.0  0.500000 -1.0 -1.230975 -1.054893 -1.279887   0.0   
155           0.0  0.0 -0.166667  0.0  0.526035  0.663485  0.458509   0.0   
156           0.0  0.0  0.666667  0.0  0.013351  0.023866  0.008439   1.0   
157           0.0  0.0  0.500000  0.0 -0.819760 -0.634845 -0.824191   1.0   
158           0.0  0.0 -0.333333  0.0 -1.086782 -0.902148 -1.139241  -1.0   
159           0.0  0.0 -0.166667 -1.0  0.841121  0.978520  0.773558   0.0   
160           0.0  0.0  0.500000 -1.0  0.638184  0.696897  0.610408   0.0   
161           0.0  0.0 -0.166667  0.0  0.461949  0.653938  0.362869   0.0   
162           0.0  0.0  0.666667  0.0  0.210948  0.233890  0.210970   1.0   
163           0.0  0.0  0.333333  0.0 -0.157543 -0.152745 -0.194093   0.0   
164           0.0  0.0  0.500000  0.0 -1.081442 -0.902148 -1.139241   1.0   
165           0.0 -1.0 -0.333333  0.0  0.531375  0.606205  0.447257   0.0   
166           0.0  0.0 -0.500000  0.0  0.248331  0.243437  0.227848   0.0   
167           0.0  0.0  0.500000  0.0 -0.040053 -0.033413 -0.036568   0.0   
168           0.0  0.0 -0.500000  0.0 -1.727637 -1.484487 -1.825598   1.0   
169           0.0  0.0  0.333333  0.0 -0.974633 -0.797136 -1.043601   0.0   
170           0.0  0.0  0.166667  0.0  0.905207  1.050119  0.818565   1.0   
1

In [75]:
T1003042_final_regression_model = finalize_model(T01_model_et)

T1003042_prediction = predict_model(T1003042_final_regression_model, data=T1003042_data)

T1003042_datas = T1003042_prediction['prediction_label']
T1003042_datas = pd.DataFrame(T1003042_datas.values, columns = ['Y_Quality'])

T1003042y_idx= T1003042_class.index
T1003042y_idx = pd.DataFrame(T1003042y_idx, columns = ['index'])
T1003042_datas = pd.concat([T1003042y_idx, T1003042_datas], axis = 1)
T1003042_datas = T1003042_datas.set_index('index')
T1003042_datas

Y_Quality
index           
22      0.517719
23      0.519090
25      0.529362
29      0.532405
37      0.533110
...          ...
547     0.508819
548     0.507571
558     0.532065
561     0.522148
592     0.528349

[172 rows x 1 columns]

In [76]:
from pycaret.classification import *
# 분류 패키지의 모든 모듈을 임포트한다.
exp_clf101 = setup(data=T1003042_datas, 
                   target=T1003042_class, 
                   fold=5,
                   session_id=4)
top5 = compare_models(sort='Accuracy', n_select=5)

Processing:   0%|          | 0/73 [00:00<?, ?it/s]

In [77]:
T01_total_models = []

T01_model_lightgbm = create_model('lightgbm', fold = 5)
T01_total_models.append(T01_model_lightgbm)

T01_model_rf = create_model('rf', fold = 5)
T01_total_models.append(T01_model_rf)

T01_model_gbc = create_model('gbc', fold = 5)
T01_total_models.append(T01_model_gbc)

T01_model_et = create_model('et', fold = 5)
T01_total_models.append(T01_model_et)

T01_model_catboost = create_model('catboost', fold = 5)
T01_total_models.append(T01_model_catboost)

T01_model_xgb = create_model('xgboost', fold = 5)
T01_total_models.append(T01_model_xgb)

T01_model_ada = create_model('ada', fold = 5)
T01_total_models.append(T01_model_ada)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [78]:
T01_model_lightgbm = tune_model(T01_model_lightgbm, fold=5, choose_better = True)

T01_model_rf = tune_model(T01_model_rf, fold=5, choose_better = True)

T01_model_gbc = tune_model(T01_model_gbc, fold=5, choose_better = True)

T01_model_et = tune_model(T01_model_et, fold=5, choose_better = True)

T01_model_catboost = tune_model(T01_model_catboost, fold=5, choose_better = True)

T01_model_xgb = tune_model(T01_model_xgb, fold=5, choose_better = True)

T01_model_ada = tune_model(T01_model_ada, fold=5, choose_better = True)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

...

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


In [79]:
T01_tuned_models = [T01_model_lightgbm, T01_model_rf, T01_model_gbc, T01_model_et, T01_model_catboost, T01_model_xgb, T01_model_ada]

for model in T01_tuned_models:
    display(predict_model(model))

Y_Quality  Y_Class  prediction_label  prediction_score
120   0.529014        1                 1            0.9994
121   0.528038        1                 1            0.9995
122   0.530413        1                 1            0.9994
123   0.533568        1                 1            0.9990
124   0.532359        1                 1            0.9995
125   0.534737        1                 1            0.6514
126   0.538641        2                 2            0.9858
127   0.508819        0                 0            0.9999
128   0.533270        1                 1            0.9990
129   0.528348        1                 1            0.9995
130   0.532954        1                 1            0.9995
131   0.532341        1                 1            0.9995
132   0.520597        0                 0            0.9999
133   0.529641        1                 1            0.9994
134   0.528040        1                 1            0.9995
135   0.534808        1                 1            0.6514
136   0.535076        2                 1            0.6514
137   0.533300        1                 1            0.9990
138   0.528094        1                 1            0.9995
139   0.528506        1                 1            0.9994
140   0.531035        1                 1            0.9994
141   0.529194        1                 1            0.9994
142   0.529257        1                 1            0.9994
143   0.529225        1                 1            0.9994
144   0.526232        1                 1            0.9991
145   0.533625        1                 1            0.9990
146   0.525570        1                 1            0.9990
147   0.525897        1                 1            0.9990
148   0.527843        1                 1            0.9995
149   0.545343        2                 2            0.9858
150   0.532694        1                 1            0.9995
151   0.519090        0                 0            0.9999
152   0.527976        1                 1            0.9995
153   0.530948        1                 1            0.9994
154   0.529456        1                 1            0.9994
155   0.532317        1                 1            0.9995
156   0.532006        1                 1            0.9994
157   0.532676        1                 1            0.9995
158   0.529362        1                 1            0.9994
159   0.534951        2                 1            0.6514
160   0.530125        1                 1            0.9994
161   0.525035        0                 0            0.9999
162   0.530857        1                 1            0.9994
163   0.527714        1                 1            0.9995
164   0.528521        1                 1            0.9994
165   0.523046        0                 0            0.9999
166   0.532065        1                 1            0.9994
167   0.531079        1                 1            0.9994
168   0.534837        1                 1            0.6514
169   0.530413        1                 1            0.9994
170   0.531740        1                 1            0.9994
171   0.527983        1                 1            0.9995

Y_Quality  Y_Class  prediction_label  prediction_score
120   0.529014        1                 1              1.00
121   0.528038        1                 1              1.00
122   0.530413        1                 1              1.00
123   0.533568        1                 1              1.00
124   0.532359        1                 1              1.00
125   0.534737        1                 1              1.00
126   0.538641        2                 2              1.00
127   0.508819        0                 0              1.00
128   0.533270        1                 1              1.00
129   0.528348        1                 1              1.00
130   0.532954        1                 1              1.00
131   0.532341        1                 1              1.00
132   0.520597        0                 0              1.00
133   0.529641        1                 1              1.00
134   0.528040        1                 1              1.00
135   0.534808        1                 1              0.98
136   0.535076        2                 2              0.89
137   0.533300        1                 1              1.00
138   0.528094        1                 1              1.00
139   0.528506        1                 1              1.00
140   0.531035        1                 1              1.00
141   0.529194        1                 1              1.00
142   0.529257        1                 1              1.00
143   0.529225        1                 1              1.00
144   0.526232        1                 1              1.00
145   0.533625        1                 1              1.00
146   0.525570        1                 1              1.00
147   0.525897        1                 1              1.00
148   0.527843        1                 1              1.00
149   0.545343        2                 2              1.00
150   0.532694        1                 1              1.00
151   0.519090        0                 0              1.00
152   0.527976        1                 1              1.00
153   0.530948        1                 1              1.00
154   0.529456        1                 1              1.00
155   0.532317        1                 1              1.00
156   0.532006        1                 1              1.00
157   0.532676        1                 1              1.00
158   0.529362        1                 1              1.00
159   0.534951        2                 1              0.67
160   0.530125        1                 1              1.00
161   0.525035        0                 0              0.89
162   0.530857        1                 1              1.00
163   0.527714        1                 1              1.00
164   0.528521        1                 1              1.00
165   0.523046        0                 0              0.99
166   0.532065        1                 1              1.00
167   0.531079        1                 1              1.00
168   0.534837        1                 1              0.98
169   0.530413        1                 1              1.00
170   0.531740        1                 1              1.00
171   0.527983        1                 1              1.00

Y_Quality  Y_Class  prediction_label  prediction_score
120   0.529014        1                 1               1.0
121   0.528038        1                 1               1.0
122   0.530413        1                 1               1.0
123   0.533568        1                 1               1.0
124   0.532359        1                 1               1.0
125   0.534737        1                 1               1.0
126   0.538641        2                 2               1.0
127   0.508819        0                 0               1.0
128   0.533270        1                 1               1.0
129   0.528348        1                 1               1.0
130   0.532954        1                 1               1.0
131   0.532341        1                 1               1.0
132   0.520597        0                 0               1.0
133   0.529641        1                 1               1.0
134   0.528040        1                 1               1.0
135   0.534808        1                 1               1.0
136   0.535076        2                 2               1.0
137   0.533300        1                 1               1.0
138   0.528094        1                 1               1.0
139   0.528506        1                 1               1.0
140   0.531035        1                 1               1.0
141   0.529194        1                 1               1.0
142   0.529257        1                 1               1.0
143   0.529225        1                 1               1.0
144   0.526232        1                 1               1.0
145   0.533625        1                 1               1.0
146   0.525570        1                 1               1.0
147   0.525897        1                 1               1.0
148   0.527843        1                 1               1.0
149   0.545343        2                 2               1.0
150   0.532694        1                 1               1.0
151   0.519090        0                 0               1.0
152   0.527976        1                 1               1.0
153   0.530948        1                 1               1.0
154   0.529456        1                 1               1.0
155   0.532317        1                 1               1.0
156   0.532006        1                 1               1.0
157   0.532676        1                 1               1.0
158   0.529362        1                 1               1.0
159   0.534951        2                 1               1.0
160   0.530125        1                 1               1.0
161   0.525035        0                 0               1.0
162   0.530857        1                 1               1.0
163   0.527714        1                 1               1.0
164   0.528521        1                 1               1.0
165   0.523046        0                 0               1.0
166   0.532065        1                 1               1.0
167   0.531079        1                 1               1.0
168   0.534837        1                 1               1.0
169   0.530413        1                 1               1.0
170   0.531740        1                 1               1.0
171   0.527983        1                 1               1.0

Y_Quality  Y_Class  prediction_label  prediction_score
120   0.529014        1                 1              1.00
121   0.528038        1                 1              1.00
122   0.530413        1                 1              1.00
123   0.533568        1                 1              1.00
124   0.532359        1                 1              1.00
125   0.534737        1                 1              1.00
126   0.538641        2                 2              1.00
127   0.508819        0                 0              1.00
128   0.533270        1                 1              1.00
129   0.528348        1                 1              1.00
130   0.532954        1                 1              1.00
131   0.532341        1                 1              1.00
132   0.520597        0                 0              1.00
133   0.529641        1                 1              1.00
134   0.528040        1                 1              1.00
135   0.534808        1                 1              1.00
136   0.535076        2                 2              0.69
137   0.533300        1                 1              1.00
138   0.528094        1                 1              1.00
139   0.528506        1                 1              1.00
140   0.531035        1                 1              1.00
141   0.529194        1                 1              1.00
142   0.529257        1                 1              1.00
143   0.529225        1                 1              1.00
144   0.526232        1                 1              1.00
145   0.533625        1                 1              1.00
146   0.525570        1                 1              1.00
147   0.525897        1                 1              1.00
148   0.527843        1                 1              1.00
149   0.545343        2                 2              1.00
150   0.532694        1                 1              1.00
151   0.519090        0                 0              1.00
152   0.527976        1                 1              1.00
153   0.530948        1                 1              1.00
154   0.529456        1                 1              1.00
155   0.532317        1                 1              1.00
156   0.532006        1                 1              1.00
157   0.532676        1                 1              1.00
158   0.529362        1                 1              1.00
159   0.534951        2                 1              0.70
160   0.530125        1                 1              1.00
161   0.525035        0                 0              0.73
162   0.530857        1                 1              1.00
163   0.527714        1                 1              1.00
164   0.528521        1                 1              1.00
165   0.523046        0                 0              1.00
166   0.532065        1                 1              1.00
167   0.531079        1                 1              1.00
168   0.534837        1                 1              0.98
169   0.530413        1                 1              1.00
170   0.531740        1                 1              1.00
171   0.527983        1                 1              1.00

Y_Quality  Y_Class  prediction_label  prediction_score
120   0.529014        1                 1            0.9998
121   0.528038        1                 1            0.9997
122   0.530413        1                 1            0.9998
123   0.533568        1                 1            0.9996
124   0.532359        1                 1            0.9997
125   0.534737        1                 1            0.9781
126   0.538641        2                 2            0.9964
127   0.508819        0                 0            0.9966
128   0.533270        1                 1            0.9997
129   0.528348        1                 1            0.9997
130   0.532954        1                 1            0.9997
131   0.532341        1                 1            0.9997
132   0.520597        0                 0            0.9970
133   0.529641        1                 1            0.9998
134   0.528040        1                 1            0.9997
135   0.534808        1                 1            0.9781
136   0.535076        2                 2            0.9867
137   0.533300        1                 1            0.9996
138   0.528094        1                 1            0.9997
139   0.528506        1                 1            0.9997
140   0.531035        1                 1            0.9998
141   0.529194        1                 1            0.9998
142   0.529257        1                 1            0.9998
143   0.529225        1                 1            0.9998
144   0.526232        1                 1            0.9992
145   0.533625        1                 1            0.9996
146   0.525570        1                 1            0.9908
147   0.525897        1                 1            0.9965
148   0.527843        1                 1            0.9997
149   0.545343        2                 2            0.9964
150   0.532694        1                 1            0.9997
151   0.519090        0                 0            0.9970
152   0.527976        1                 1            0.9997
153   0.530948        1                 1            0.9998
154   0.529456        1                 1            0.9998
155   0.532317        1                 1            0.9997
156   0.532006        1                 1            0.9998
157   0.532676        1                 1            0.9997
158   0.529362        1                 1            0.9998
159   0.534951        2                 1            0.9781
160   0.530125        1                 1            0.9998
161   0.525035        0                 0            0.9839
162   0.530857        1                 1            0.9998
163   0.527714        1                 1            0.9997
164   0.528521        1                 1            0.9997
165   0.523046        0                 0            0.9974
166   0.532065        1                 1            0.9997
167   0.531079        1                 1            0.9998
168   0.534837        1                 1            0.9781
169   0.530413        1                 1            0.9998
170   0.531740        1                 1            0.9998
171   0.527983        1                 1            0.9997

Y_Quality  Y_Class  prediction_label  prediction_score
120   0.529014        1                 1            0.9981
121   0.528038        1                 1            0.9981
122   0.530413        1                 1            0.9981
123   0.533568        1                 1            0.9874
124   0.532359        1                 1            0.9981
125   0.534737        1                 1            0.9646
126   0.538641        2                 2            0.9625
127   0.508819        0                 0            0.9685
128   0.533270        1                 1            0.9896
129   0.528348        1                 1            0.9981
130   0.532954        1                 1            0.9969
131   0.532341        1                 1            0.9981
132   0.520597        0                 0            0.9685
133   0.529641        1                 1            0.9981
134   0.528040        1                 1            0.9981
135   0.534808        1                 1            0.9646
136   0.535076        2                 2            0.9625
137   0.533300        1                 1            0.9888
138   0.528094        1                 1            0.9981
139   0.528506        1                 1            0.9981
140   0.531035        1                 1            0.9981
141   0.529194        1                 1            0.9981
142   0.529257        1                 1            0.9981
143   0.529225        1                 1            0.9981
144   0.526232        1                 1            0.9818
145   0.533625        1                 1            0.9874
146   0.525570        1                 1            0.9783
147   0.525897        1                 1            0.9783
148   0.527843        1                 1            0.9981
149   0.545343        2                 2            0.9625
150   0.532694        1                 1            0.9980
151   0.519090        0                 0            0.9685
152   0.527976        1                 1            0.9981
153   0.530948        1                 1            0.9981
154   0.529456        1                 1            0.9981
155   0.532317        1                 1            0.9981
156   0.532006        1                 1            0.9981
157   0.532676        1                 1            0.9980
158   0.529362        1                 1            0.9981
159   0.534951        2                 1            0.9646
160   0.530125        1                 1            0.9981
161   0.525035        0                 0            0.9685
162   0.530857        1                 1            0.9981
163   0.527714        1                 1            0.9981
164   0.528521        1                 1            0.9981
165   0.523046        0                 0            0.9685
166   0.532065        1                 1            0.9981
167   0.531079        1                 1            0.9981
168   0.534837        1                 1            0.9646
169   0.530413        1                 1            0.9981
170   0.531740        1                 1            0.9981
171   0.527983        1                 1            0.9981

Y_Quality  Y_Class  prediction_label  prediction_score
120   0.529014        1                 1               1.0
121   0.528038        1                 1               1.0
122   0.530413        1                 1               1.0
123   0.533568        1                 1               1.0
124   0.532359        1                 1               1.0
125   0.534737        1                 1               1.0
126   0.538641        2                 2               1.0
127   0.508819        0                 0               1.0
128   0.533270        1                 1               1.0
129   0.528348        1                 1               1.0
130   0.532954        1                 1               1.0
131   0.532341        1                 1               1.0
132   0.520597        0                 0               1.0
133   0.529641        1                 1               1.0
134   0.528040        1                 1               1.0
135   0.534808        1                 1               1.0
136   0.535076        2                 2               1.0
137   0.533300        1                 1               1.0
138   0.528094        1                 1               1.0
139   0.528506        1                 1               1.0
140   0.531035        1                 1               1.0
141   0.529194        1                 1               1.0
142   0.529257        1                 1               1.0
143   0.529225        1                 1               1.0
144   0.526232        1                 1               1.0
145   0.533625        1                 1               1.0
146   0.525570        1                 1               1.0
147   0.525897        1                 1               1.0
148   0.527843        1                 1               1.0
149   0.545343        2                 2               1.0
150   0.532694        1                 1               1.0
151   0.519090        0                 0               1.0
152   0.527976        1                 1               1.0
153   0.530948        1                 1               1.0
154   0.529456        1                 1               1.0
155   0.532317        1                 1               1.0
156   0.532006        1                 1               1.0
157   0.532676        1                 1               1.0
158   0.529362        1                 1               1.0
159   0.534951        2                 1               1.0
160   0.530125        1                 1               1.0
161   0.525035        0                 0               1.0
162   0.530857        1                 1               1.0
163   0.527714        1                 1               1.0
164   0.528521        1                 1               1.0
165   0.523046        0                 0               1.0
166   0.532065        1                 1               1.0
167   0.531079        1                 1               1.0
168   0.534837        1                 1               1.0
169   0.530413        1                 1               1.0
170   0.531740        1                 1               1.0
171   0.527983        1                 1               1.0

In [80]:
T1003042_final_classification_model = finalize_model(T01_model_xgb)

T1003042_prediction = predict_model(T1003042_final_classification_model, data=T1003042_datas)

T10030421_prediction = pd.DataFrame(T1003042_prediction, columns = ['prediction_label'])

T1003042_y_class = pd.DataFrame(T1003042_class, columns = ['Y_Class'])
T1003042_idx = T1003042_y_class.index
T1003042_y_class = T1003042_y_class.reset_index()
T1003042_prediction = pd.concat([T1003042_prediction, T1003042_y_class], axis = 1)
T1003042_prediction = T1003042_prediction.set_index('index')
T1003042_prediction.drop(['Y_Class'], axis = 1, inplace = True)

# 6

In [81]:
T1003043.drop(['index'], inplace = True, axis = 1)

In [82]:
T1003043_class = T1003043['Y_Class']
T1003043_target = T1003043['Y_Quality']
T1003043_data = T1003043.drop(['Y_Class', 'Y_Quality'], axis = 1)

In [83]:
T1003043c = T1003043_data.columns
T1003043scaler = RobustScaler()
T1003043scaled = T1003043scaler.fit_transform(T1003043_data)
T1003043_data = pd.DataFrame(T1003043scaled, columns = T1003043c)

T1003043_y_class = pd.DataFrame(T1003043_target, columns = ['Y_Quality'])
T1003043_idx = T1003043_y_class.index
T1003043_y_class = T1003043_y_class.reset_index()
T1003043_data = pd.concat([T1003043_data, T1003043_y_class], axis = 1)
T1003043_data = T1003043_data.set_index('index')
T1003043_data.drop(['Y_Quality'], axis = 1, inplace = True)
T1003043_data

PRODUCT_CODE  X_1       X_2      X_11      X_12      X_13  X_16  X_17  \
index                                                                          
0               0.0  0.0  0.000000 -0.068966  0.000000  0.000000   1.0  -1.0   
1               0.0  0.0  0.333333  0.000000 -0.081967 -0.170213   0.0   0.0   
2               0.0  1.0 -0.666667  0.931034  0.918033  0.829787   0.0   0.0   
3               0.0  0.0  0.000000 -0.068966  0.000000  0.000000   1.0  -1.0   
4               0.0  0.0  0.333333  0.000000 -0.081967 -0.170213   0.0   0.0   
5               0.0  1.0 -0.666667  0.931034  0.918033  0.829787   0.0   0.0   
6               0.0  0.0  0.000000 -0.068966  0.000000  0.000000   1.0  -1.0   
7               0.0  0.0  0.333333  0.000000 -0.081967 -0.170213   0.0   0.0   
8               0.0  1.0 -0.666667  0.931034  0.918033  0.829787   0.0   0.0   
9               0.0  0.0  0.000000 -0.068966  0.000000  0.000000   1.0  -1.0   
10              0.0  0.0  0.333333  0.000000 -0.081967 -0.170213   0.0   0.0   
11              0.0  1.0 -0.666667  0.931034  0.918033  0.829787   0.0   0.0   
12              0.0  0.0  0.000000 -0.068966  0.000000  0.000000   1.0  -1.0   
13              0.0  0.0  0.333333  0.000000 -0.081967 -0.170213   0.0   0.0   
14              0.0  1.0 -0.666667  0.931034  0.918033  0.829787   0.0   0.0   

       X_18      X_20  ...     X_924     X_925     X_926     X_927     X_928  \
index                  ...                                                     
0       0.5  0.166667  ...  0.000000 -0.292308 -0.244928  0.000000  0.166667   
1       0.0  0.000000  ... -0.456522  0.000000  0.000000 -0.055276  0.000000   
2      -0.5 -0.833333  ...  0.543478  0.707692  0.755072  0.944724 -0.833333   
3       0.5  0.166667  ...  0.000000 -0.292308 -0.244928  0.000000  0.166667   
4       0.0  0.000000  ... -0.456522  0.000000  0.000000 -0.055276  0.000000   
5      -0.5 -0.833333  ...  0.543478  0.707692  0.755072  0.944724 -0.833333   
6       0.5  0.166667  ...  0.000000 -0.292308 -0.244928  0.000000  0.166667   
7       0.0  0.000000  ... -0.456522  0.000000  0.000000 -0.055276  0.000000   
8      -0.5 -0.833333  ...  0.543478  0.707692  0.755072  0.944724 -0.833333   
9       0.5  0.166667  ...  0.000000 -0.292308 -0.244928  0.000000  0.166667   
10      0.0  0.000000  ... -0.456522  0.000000  0.000000 -0.055276  0.000000   
11     -0.5 -0.833333  ...  0.543478  0.707692  0.755072  0.944724 -0.833333   
12      0.5  0.166667  ...  0.000000 -0.292308 -0.244928  0.000000  0.166667   
13      0.0  0.000000  ... -0.456522  0.000000  0.000000 -0.055276  0.000000   
14     -0.5 -0.833333  ...  0.543478  0.707692  0.755072  0.944724 -0.833333   

         X_929  X_930  X_931     X_932  X_933  
index                                          
0      0.02834    0.0    0.0  0.627615    1.0  
1      0.00000    0.0    1.0  0.000000    0.0  
2     -0.97166   -1.0    0.0 -0.372385    0.0  
3      0.02834    0.0    0.0  0.627615    1.0  
4      0.00000    0.0    1.0  0.000000    0.0  
5     -0.97166   -1.0    0.0 -0.372385    0.0  
6      0.02834    0.0    0.0  0.627615    1.0  
7      0.00000    0.0    1.0  0.000000    0.0  
8     -0.97166   -1.0    0.0 -0.372385    0.0  
9      0.02834    0.0    0.0  0.627615    1.0  
10     0.00000    0.0    1.0  0.000000    0.0  
11    -0.97166   -1.0    0.0 -0.372385    0.0  
12     0.02834    0.0    0.0  0.627615    1.0  
13     0.00000    0.0    1.0  0.000000    0.0  
14    -0.97166   -1.0    0.0 -0.372385    0.0  

[15 rows x 453 columns]

In [84]:
from pycaret.regression import *
setup_rgs = setup(data = T1003043_data, target = T1003043_target, session_id = 4)
top5 = compare_models(sort='MSE', n_select=5)

Processing:   0%|          | 0/89 [00:00<?, ?it/s]

In [85]:
T01_total_models = []

T01_model_lightgbm = create_model('lightgbm', fold = 5)
T01_total_models.append(T01_model_lightgbm)

T01_model_rf = create_model('rf', fold = 5)
T01_total_models.append(T01_model_rf)

T01_model_gbr = create_model('gbr', fold = 5)
T01_total_models.append(T01_model_gbr)

T01_model_et = create_model('et', fold = 5)
T01_total_models.append(T01_model_et)

T01_model_catboost = create_model('catboost', fold = 5)
T01_total_models.append(T01_model_catboost)

T01_model_xgb = create_model('xgboost', fold = 5)
T01_total_models.append(T01_model_xgb)

T01_model_ada = create_model('ada', fold = 5)
T01_total_models.append(T01_model_ada)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [86]:
T01_model_lightgbm = tune_model(T01_model_lightgbm, fold=5, choose_better = True)

T01_model_rf = tune_model(T01_model_rf, fold=5, choose_better = True)

T01_model_gbr = tune_model(T01_model_gbr, fold=5, choose_better = True)

T01_model_et = tune_model(T01_model_et, fold=5, choose_better = True)

T01_model_catboost = tune_model(T01_model_catboost, fold=5, choose_better = True)

T01_model_xgb = tune_model(T01_model_xgb, fold=5, choose_better = True)

T01_model_ada = tune_model(T01_model_ada, fold=5, choose_better = True)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

...

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


In [87]:
T01_tuned_models = [T01_model_lightgbm, T01_model_rf, T01_model_gbr, T01_model_et, T01_model_catboost, T01_model_xgb, T01_model_ada]

for model in T01_tuned_models:
    display(predict_model(model))

PRODUCT_CODE  X_1       X_2      X_11      X_12      X_13  X_16  X_17  \
10           0.0  0.0  0.000000 -0.068966  0.000000  0.000000   1.0  -1.0   
11           0.0  0.0  0.000000 -0.068966  0.000000  0.000000   1.0  -1.0   
12           0.0  0.0  0.000000 -0.068966  0.000000  0.000000   1.0  -1.0   
13           0.0  0.0  0.000000 -0.068966  0.000000  0.000000   1.0  -1.0   
14           0.0  0.0  0.333333  0.000000 -0.081967 -0.170213   0.0   0.0   

    X_18      X_20  ...     X_926     X_927     X_928    X_929  X_930  X_931  \
10   0.5  0.166667  ... -0.244928  0.000000  0.166667  0.02834    0.0    0.0   
11   0.5  0.166667  ... -0.244928  0.000000  0.166667  0.02834    0.0    0.0   
12   0.5  0.166667  ... -0.244928  0.000000  0.166667  0.02834    0.0    0.0   
13   0.5  0.166667  ... -0.244928  0.000000  0.166667  0.02834    0.0    0.0   
14   0.0  0.000000  ...  0.000000 -0.055276  0.000000  0.00000    0.0    1.0   

       X_932  X_933  Y_Quality  prediction_label  
10  0.627615    1.0   0.530533          0.529107  
11  0.627615    1.0   0.530533          0.529107  
12  0.627615    1.0   0.530533          0.529107  
13  0.627615    1.0   0.530533          0.529107  
14  0.000000    0.0   0.525916          0.529107  

[5 rows x 455 columns]

PRODUCT_CODE  X_1       X_2      X_11      X_12      X_13  X_16  X_17  \
10           0.0  0.0  0.000000 -0.068966  0.000000  0.000000   1.0  -1.0   
11           0.0  0.0  0.000000 -0.068966  0.000000  0.000000   1.0  -1.0   
12           0.0  0.0  0.000000 -0.068966  0.000000  0.000000   1.0  -1.0   
13           0.0  0.0  0.000000 -0.068966  0.000000  0.000000   1.0  -1.0   
14           0.0  0.0  0.333333  0.000000 -0.081967 -0.170213   0.0   0.0   

    X_18      X_20  ...     X_926     X_927     X_928    X_929  X_930  X_931  \
10   0.5  0.166667  ... -0.244928  0.000000  0.166667  0.02834    0.0    0.0   
11   0.5  0.166667  ... -0.244928  0.000000  0.166667  0.02834    0.0    0.0   
12   0.5  0.166667  ... -0.244928  0.000000  0.166667  0.02834    0.0    0.0   
13   0.5  0.166667  ... -0.244928  0.000000  0.166667  0.02834    0.0    0.0   
14   0.0  0.000000  ...  0.000000 -0.055276  0.000000  0.00000    0.0    1.0   

       X_932  X_933  Y_Quality  prediction_label  
10  0.627615    1.0   0.530533          0.529681  
11  0.627615    1.0   0.530533          0.529681  
12  0.627615    1.0   0.530533          0.529681  
13  0.627615    1.0   0.530533          0.529681  
14  0.000000    0.0   0.525916          0.529681  

[5 rows x 455 columns]

PRODUCT_CODE  X_1       X_2      X_11      X_12      X_13  X_16  X_17  \
10           0.0  0.0  0.000000 -0.068966  0.000000  0.000000   1.0  -1.0   
11           0.0  0.0  0.000000 -0.068966  0.000000  0.000000   1.0  -1.0   
12           0.0  0.0  0.000000 -0.068966  0.000000  0.000000   1.0  -1.0   
13           0.0  0.0  0.000000 -0.068966  0.000000  0.000000   1.0  -1.0   
14           0.0  0.0  0.333333  0.000000 -0.081967 -0.170213   0.0   0.0   

    X_18      X_20  ...     X_926     X_927     X_928    X_929  X_930  X_931  \
10   0.5  0.166667  ... -0.244928  0.000000  0.166667  0.02834    0.0    0.0   
11   0.5  0.166667  ... -0.244928  0.000000  0.166667  0.02834    0.0    0.0   
12   0.5  0.166667  ... -0.244928  0.000000  0.166667  0.02834    0.0    0.0   
13   0.5  0.166667  ... -0.244928  0.000000  0.166667  0.02834    0.0    0.0   
14   0.0  0.000000  ...  0.000000 -0.055276  0.000000  0.00000    0.0    1.0   

       X_932  X_933  Y_Quality  prediction_label  
10  0.627615    1.0   0.530533          0.530533  
11  0.627615    1.0   0.530533          0.530533  
12  0.627615    1.0   0.530533          0.530533  
13  0.627615    1.0   0.530533          0.530533  
14  0.000000    0.0   0.525916          0.525916  

[5 rows x 455 columns]

PRODUCT_CODE  X_1       X_2      X_11      X_12      X_13  X_16  X_17  \
10           0.0  0.0  0.000000 -0.068966  0.000000  0.000000   1.0  -1.0   
11           0.0  0.0  0.000000 -0.068966  0.000000  0.000000   1.0  -1.0   
12           0.0  0.0  0.000000 -0.068966  0.000000  0.000000   1.0  -1.0   
13           0.0  0.0  0.000000 -0.068966  0.000000  0.000000   1.0  -1.0   
14           0.0  0.0  0.333333  0.000000 -0.081967 -0.170213   0.0   0.0   

    X_18      X_20  ...     X_926     X_927     X_928    X_929  X_930  X_931  \
10   0.5  0.166667  ... -0.244928  0.000000  0.166667  0.02834    0.0    0.0   
11   0.5  0.166667  ... -0.244928  0.000000  0.166667  0.02834    0.0    0.0   
12   0.5  0.166667  ... -0.244928  0.000000  0.166667  0.02834    0.0    0.0   
13   0.5  0.166667  ... -0.244928  0.000000  0.166667  0.02834    0.0    0.0   
14   0.0  0.000000  ...  0.000000 -0.055276  0.000000  0.00000    0.0    1.0   

       X_932  X_933  Y_Quality  prediction_label  
10  0.627615    1.0   0.530533          0.529681  
11  0.627615    1.0   0.530533          0.529681  
12  0.627615    1.0   0.530533          0.529681  
13  0.627615    1.0   0.530533          0.529681  
14  0.000000    0.0   0.525916          0.529681  

[5 rows x 455 columns]

PRODUCT_CODE  X_1       X_2      X_11      X_12      X_13  X_16  X_17  \
10           0.0  0.0  0.000000 -0.068966  0.000000  0.000000   1.0  -1.0   
11           0.0  0.0  0.000000 -0.068966  0.000000  0.000000   1.0  -1.0   
12           0.0  0.0  0.000000 -0.068966  0.000000  0.000000   1.0  -1.0   
13           0.0  0.0  0.000000 -0.068966  0.000000  0.000000   1.0  -1.0   
14           0.0  0.0  0.333333  0.000000 -0.081967 -0.170213   0.0   0.0   

    X_18      X_20  ...     X_926     X_927     X_928    X_929  X_930  X_931  \
10   0.5  0.166667  ... -0.244928  0.000000  0.166667  0.02834    0.0    0.0   
11   0.5  0.166667  ... -0.244928  0.000000  0.166667  0.02834    0.0    0.0   
12   0.5  0.166667  ... -0.244928  0.000000  0.166667  0.02834    0.0    0.0   
13   0.5  0.166667  ... -0.244928  0.000000  0.166667  0.02834    0.0    0.0   
14   0.0  0.000000  ...  0.000000 -0.055276  0.000000  0.00000    0.0    1.0   

       X_932  X_933  Y_Quality  prediction_label  
10  0.627615    1.0   0.530533          0.530526  
11  0.627615    1.0   0.530533          0.530526  
12  0.627615    1.0   0.530533          0.530526  
13  0.627615    1.0   0.530533          0.530526  
14  0.000000    0.0   0.525916          0.525917  

[5 rows x 455 columns]

PRODUCT_CODE  X_1       X_2      X_11      X_12      X_13  X_16  X_17  \
10           0.0  0.0  0.000000 -0.068966  0.000000  0.000000   1.0  -1.0   
11           0.0  0.0  0.000000 -0.068966  0.000000  0.000000   1.0  -1.0   
12           0.0  0.0  0.000000 -0.068966  0.000000  0.000000   1.0  -1.0   
13           0.0  0.0  0.000000 -0.068966  0.000000  0.000000   1.0  -1.0   
14           0.0  0.0  0.333333  0.000000 -0.081967 -0.170213   0.0   0.0   

    X_18      X_20  ...     X_926     X_927     X_928    X_929  X_930  X_931  \
10   0.5  0.166667  ... -0.244928  0.000000  0.166667  0.02834    0.0    0.0   
11   0.5  0.166667  ... -0.244928  0.000000  0.166667  0.02834    0.0    0.0   
12   0.5  0.166667  ... -0.244928  0.000000  0.166667  0.02834    0.0    0.0   
13   0.5  0.166667  ... -0.244928  0.000000  0.166667  0.02834    0.0    0.0   
14   0.0  0.000000  ...  0.000000 -0.055276  0.000000  0.00000    0.0    1.0   

       X_932  X_933  Y_Quality  prediction_label  
10  0.627615    1.0   0.530533          0.530804  
11  0.627615    1.0   0.530533          0.530804  
12  0.627615    1.0   0.530533          0.530804  
13  0.627615    1.0   0.530533          0.530804  
14  0.000000    0.0   0.525916          0.526276  

[5 rows x 455 columns]

PRODUCT_CODE  X_1       X_2      X_11      X_12      X_13  X_16  X_17  \
10           0.0  0.0  0.000000 -0.068966  0.000000  0.000000   1.0  -1.0   
11           0.0  0.0  0.000000 -0.068966  0.000000  0.000000   1.0  -1.0   
12           0.0  0.0  0.000000 -0.068966  0.000000  0.000000   1.0  -1.0   
13           0.0  0.0  0.000000 -0.068966  0.000000  0.000000   1.0  -1.0   
14           0.0  0.0  0.333333  0.000000 -0.081967 -0.170213   0.0   0.0   

    X_18      X_20  ...     X_926     X_927     X_928    X_929  X_930  X_931  \
10   0.5  0.166667  ... -0.244928  0.000000  0.166667  0.02834    0.0    0.0   
11   0.5  0.166667  ... -0.244928  0.000000  0.166667  0.02834    0.0    0.0   
12   0.5  0.166667  ... -0.244928  0.000000  0.166667  0.02834    0.0    0.0   
13   0.5  0.166667  ... -0.244928  0.000000  0.166667  0.02834    0.0    0.0   
14   0.0  0.000000  ...  0.000000 -0.055276  0.000000  0.00000    0.0    1.0   

       X_932  X_933  Y_Quality  prediction_label  
10  0.627615    1.0   0.530533          0.525916  
11  0.627615    1.0   0.530533          0.525916  
12  0.627615    1.0   0.530533          0.525916  
13  0.627615    1.0   0.530533          0.525916  
14  0.000000    0.0   0.525916          0.525916  

[5 rows x 455 columns]

In [88]:
T1003043_final_regression_model = finalize_model(T01_model_gbr)

T1003043_prediction = predict_model(T1003043_final_regression_model, data=T1003043_data)

T1003043_datas = T1003043_prediction['prediction_label']
T1003043_datas = pd.DataFrame(T1003043_datas.values, columns = ['Y_Quality'])

T1003043y_idx= T1003043_class.index
T1003043y_idx = pd.DataFrame(T1003043y_idx, columns = ['index'])
T1003043_datas = pd.concat([T1003043y_idx, T1003043_datas], axis = 1)
T1003043_datas = T1003043_datas.set_index('index')
T1003043_datas

Y_Quality
index           
0       0.530533
1       0.525916
2       0.531375
3       0.530533
4       0.525916
5       0.531375
6       0.530533
7       0.525916
8       0.531375
9       0.530533
10      0.525916
11      0.531375
12      0.530533
13      0.525916
14      0.531375

In [89]:
from pycaret.classification import *
# 분류 패키지의 모든 모듈을 임포트한다.
exp_clf101 = setup(data=T1003043_datas, 
                   target=T1003043_class, 
                   fold=5,
                   session_id=4)
top5 = compare_models(sort='Accuracy', n_select=5)

Processing:   0%|          | 0/73 [00:00<?, ?it/s]

In [90]:
T01_total_models = []

T01_model_lightgbm = create_model('lightgbm', fold = 5)
T01_total_models.append(T01_model_lightgbm)

T01_model_rf = create_model('rf', fold = 5)
T01_total_models.append(T01_model_rf)

#T01_model_gbc = create_model('gbc', fold = 5)
#T01_total_models.append(T01_model_gbc)

T01_model_et = create_model('et', fold = 5)
T01_total_models.append(T01_model_et)

#T01_model_catboost = create_model('catboost', fold = 5)
#T01_total_models.append(T01_model_catboost)

T01_model_xgb = create_model('xgboost', fold = 5)
T01_total_models.append(T01_model_xgb)

T01_model_ada = create_model('ada', fold = 5)
T01_total_models.append(T01_model_ada)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [91]:
T01_model_lightgbm = tune_model(T01_model_lightgbm, fold=5, choose_better = True)

T01_model_rf = tune_model(T01_model_rf, fold=5, choose_better = True)

#T01_model_gbc = tune_model(T01_model_gbc, fold=5, choose_better = True)

T01_model_et = tune_model(T01_model_et, fold=5, choose_better = True)

#T01_model_catboost = tune_model(T01_model_catboost, fold=5, choose_better = True)

T01_model_xgb = tune_model(T01_model_xgb, fold=5, choose_better = True)

T01_model_ada = tune_model(T01_model_ada, fold=5, choose_better = True)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


In [92]:
T01_tuned_models = [T01_model_lightgbm, T01_model_rf, T01_model_et, T01_model_xgb, T01_model_ada]

for model in T01_tuned_models:
    display(predict_model(model))

Y_Quality  Y_Class  prediction_label  prediction_score
10   0.525916        1                 1               1.0
11   0.525916        1                 1               1.0
12   0.525916        1                 1               1.0
13   0.531375        1                 1               1.0
14   0.531375        1                 1               1.0

Y_Quality  Y_Class  prediction_label
10   0.525916        1                 1
11   0.525916        1                 1
12   0.525916        1                 1
13   0.531375        1                 1
14   0.531375        1                 1

Y_Quality  Y_Class  prediction_label
10   0.525916        1                 1
11   0.525916        1                 1
12   0.525916        1                 1
13   0.531375        1                 1
14   0.531375        1                 1

Y_Quality  Y_Class  prediction_label  prediction_score
10   0.525916        1                 1            0.8963
11   0.525916        1                 1            0.8963
12   0.525916        1                 1            0.8963
13   0.531375        1                 1            0.8963
14   0.531375        1                 1            0.8963

Y_Quality  Y_Class  prediction_label
10   0.525916        1                 1
11   0.525916        1                 1
12   0.525916        1                 1
13   0.531375        1                 1
14   0.531375        1                 1

In [93]:
T1003043_final_classification_model = finalize_model(T01_model_lightgbm)

T1003043_prediction = predict_model(T1003043_final_classification_model, data=T1003043_datas)

T1003043_prediction = pd.DataFrame(T1003043_prediction, columns = ['prediction_label'])

T1003043_y_class = pd.DataFrame(T1003043_class, columns = ['Y_Class'])
T1003043_idx = T1003043_y_class.index
T1003043_y_class = T1003043_y_class.reset_index()
T1003043_prediction = pd.concat([T1003043_prediction, T1003043_y_class], axis = 1)
T1003043_prediction = T1003043_prediction.set_index('index')
T1003043_prediction.drop(['Y_Class'], axis = 1, inplace = True)

# 7

In [94]:
T1003062_class = T1003062['Y_Class']
T1003062_target = T1003062['Y_Quality']
T1003062_data = T1003062.drop(['Y_Class', 'Y_Quality'], axis = 1)

In [95]:
T1003062c = T1003062_data.columns
T1003062scaler = RobustScaler()
T1003062scaled = T1003062scaler.fit_transform(T1003062_data)
T1003062_data = pd.DataFrame(T1003062scaled, columns = T1003062c)

T1003062_y_class = pd.DataFrame(T1003062_target, columns = ['Y_Quality'])
T1003062_idx = T1003062_y_class.index
T1003062_y_class = T1003062_y_class.reset_index()
T1003062_data = pd.concat([T1003062_data, T1003062_y_class], axis = 1)
T1003062_data = T1003062_data.set_index('index')
T1003062_data.drop(['Y_Quality'], axis = 1, inplace = True)
T1003062_data

PRODUCT_CODE  X_1  X_2   X_7  X_8      X_11      X_12      X_13  X_15  \
index                                                                          
26              0.0  0.0  0.4  0.75  0.0 -0.603524 -0.650602 -0.537859   0.0   
30              0.0  0.0 -1.0  0.00  1.0 -0.647577 -0.686747 -0.574413   0.0   
36              0.0  0.0 -0.4  2.25  1.0 -0.559471 -0.598394 -0.485640   0.0   
42              0.0  0.0  0.4  0.00  0.0 -0.647577 -0.678715 -0.600522   0.0   
43              0.0  0.0  0.4  1.50  0.0 -0.607930 -0.686747 -0.475196   0.0   
...             ...  ...  ...   ...  ...       ...       ...       ...   ...   
588             0.0 -1.0 -0.8 -0.25  0.0 -1.118943 -1.100402 -1.274151   0.0   
589             0.0 -1.0  0.2 -0.25  0.0 -1.127753 -1.140562 -1.274151   0.0   
590             0.0 -1.0 -0.8 -0.25  0.0 -1.105727 -1.128514 -1.174935   0.0   
591             0.0 -1.0 -1.2 -0.25  0.0 -1.110132 -1.128514 -1.237598   0.0   
593             0.0  0.0  0.4 -0.25  0.0 -0.977974 -0.991968 -1.112272   0.0   

       X_16  ...     X_924     X_925     X_926     X_927     X_928     X_929  \
index        ...                                                               
26      0.0  ... -1.158879 -0.333333 -0.860625 -0.068182  0.111111  0.750402   
30      1.0  ...  0.261682  0.208333 -0.046635  0.181818  0.111111  0.687410   
36      0.0  ...  1.158879 -0.500000 -0.599894 -0.159091  0.111111  0.257713   
42      1.0  ...  0.542056  0.041667  0.464229  0.954545  0.111111  0.618673   
43      0.0  ...  1.869159  1.041667  1.768945  1.863636  0.000000 -0.270137   
...     ...  ...       ...       ...       ...       ...       ...       ...   
588     1.0  ...  0.074766  0.812500  0.454690  0.000000  0.111111 -0.104491   
589     0.0  ... -0.560748 -0.041667  0.195019  0.522727  0.000000  0.460188   
590     0.0  ...  0.579439 -0.416667  0.360360  0.727273  0.111111  0.723405   
591     1.0  ...  0.728972 -0.104167  0.348702  0.204545  0.000000  0.732404   
593     0.0  ... -0.056075  0.229167  0.565978  0.500000  0.111111  0.718906   

          X_930  X_931     X_932  X_933  
index                                    
26     1.111111    1.0  1.009251    0.1  
30     0.888889    1.0 -0.314550    0.0  
36     0.333333    1.0  0.908326    0.1  
42     1.000000    1.0  1.666947    0.1  
43    -0.111111    1.0  0.780488    0.0  
...         ...    ...       ...    ...  
588    0.000000    1.0  0.756939    0.0  
589    1.000000    1.0  1.362489    0.1  
590    1.111111    0.0 -0.050462    0.0  
591    1.000000    0.0  0.050463    0.0  
593    1.000000    0.0 -0.706476    0.0  

[171 rows x 548 columns]

In [96]:
#13
from pycaret.regression import *
setup_rgs = setup(data = T1003062_data, target = T1003062_target, session_id = 4)
top5 = compare_models(sort='MSE', n_select=5)

Processing:   0%|          | 0/89 [00:00<?, ?it/s]

In [97]:
T10_total_models = []

T10_model_lightgbm = create_model('lightgbm', fold = 5)
T10_total_models.append(T10_model_lightgbm)

T10_model_rf = create_model('rf', fold = 5)
T10_total_models.append(T10_model_rf)

T10_model_gbr = create_model('gbr', fold = 5)
T10_total_models.append(T10_model_gbr)

T10_model_et = create_model('et', fold = 5)
T10_total_models.append(T10_model_et)

T10_model_catboost = create_model('catboost', fold = 5)
T10_total_models.append(T10_model_catboost)

T10_model_xgb = create_model('xgboost', fold = 5)
T10_total_models.append(T10_model_xgb)

T10_model_ada = create_model('ada', fold = 5)

T10_total_models.append(T10_model_ada)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [98]:
T10_model_lightgbm = tune_model(T10_model_lightgbm, fold=5, choose_better = True)

T10_model_rf = tune_model(T10_model_rf, fold=5, choose_better = True)

T10_model_gbr = tune_model(T10_model_gbr, fold=5, choose_better = True)

T10_model_et = tune_model(T10_model_et, fold=5, choose_better = True)

T10_model_catboost = tune_model(T10_model_catboost, fold=5, choose_better = True)

T10_model_xgb = tune_model(T10_model_xgb, fold=5, choose_better = True)

T10_model_ada = tune_model(T10_model_ada, fold=5, choose_better = True)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

...

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


In [99]:
T10_tuned_models = [T10_model_lightgbm, T10_model_rf, T10_model_gbr, T10_model_et, T10_model_catboost, T10_model_xgb, T10_model_ada]

for model in T10_tuned_models:
    display(predict_model(model))

PRODUCT_CODE  X_1  X_2   X_7  X_8      X_11      X_12      X_13  X_15  \
119           0.0  0.0 -0.8  1.50  0.0 -2.502203 -2.317269 -2.919060   0.0   
120           0.0  0.0 -0.8  1.50  0.0 -1.026432 -1.020080 -1.211488   0.0   
121           0.0  0.0  0.2  0.75  0.0 -0.325991 -0.405622 -0.255875   0.0   
122           0.0  0.0  0.4  1.50  1.0 -0.035242 -0.072289  0.000000   0.0   
123           0.0  0.0 -0.4  0.75  0.0  0.431718  0.365462  0.417755   0.0   
124           0.0  0.0  0.0  0.75  0.0 -0.497797 -0.582329 -0.396867   0.0   
125           0.0 -1.0  0.4  1.50  0.0 -0.942731 -0.951807 -0.971279   0.0   
126           0.0  0.0  0.4  0.00  0.0  0.189427  0.168675  0.214099   0.0   
127           0.0  0.0  0.6  0.00  0.0  0.035242  0.000000  0.052219   0.0   
128           0.0  0.0 -0.4  0.50  0.0  0.392070  0.365462  0.355091   0.0   
129           0.0  0.0  0.4 -0.25  0.0 -0.977974 -0.991968 -1.112272   0.0   
130           0.0  0.0 -0.4  0.00  0.0  0.634361  0.610442  0.673629   0.0   
131           0.0  0.0 -1.0  0.00  0.0 -0.030837 -0.072289 -0.015666   2.0   
132           0.0 -1.0  0.4  0.00  0.0  0.740088  0.726908  0.788512   0.0   
133           0.0  0.0  0.6  0.50  0.0 -1.013216 -1.020080 -1.133159   0.0   
134           0.0  0.0  0.0 -0.25  0.0 -0.651982 -0.698795 -0.548303   0.0   
135           0.0  0.0  0.4  0.00  0.0  0.436123  0.377510  0.433420   0.0   
136           0.0  0.0  0.0  0.75  0.0  0.687225  0.638554  0.762402   0.0   
137           0.0  0.0  0.4 -0.25  0.0 -1.400881 -1.365462 -1.556136   0.0   
138           0.0  0.0 -0.4  0.00  0.0 -0.237885 -0.297189 -0.193211   0.0   
139           0.0  0.0 -0.6 -0.25  0.0 -0.303965 -0.385542 -0.255875   0.0   
140           0.0 -1.0  0.4  0.00  0.0 -0.581498 -0.658635 -0.537859   0.0   
141           0.0  0.0  0.6  0.00  0.0  0.092511  0.060241  0.114883   0.0   
142           0.0 -1.0  0.4  0.75  0.0 -0.964758 -0.983936 -1.033943   0.0   
143           0.0  0.0  0.4  0.00  0.0  0.762115  0.710843  0.814621   0.0   
144           0.0  0.0  0.4  1.25  0.0 -0.458150 -0.542169 -0.360313   0.0   
145           0.0  0.0 -0.4  2.25  1.0 -0.559471 -0.598394 -0.485640   0.0   
146           0.0  0.0  0.0  0.00  0.0  0.321586  0.269076  0.281984   0.0   
147           0.0  0.0 -0.6  0.25  0.0 -0.462555 -0.530120 -0.396867   0.0   
148           0.0  0.0 -0.4  0.50  0.0 -0.365639 -0.413655 -0.292428   0.0   
149           0.0  0.0 -0.8 -0.25  0.0  0.132159  0.092369  0.114883   0.0   
150           0.0  0.0 -0.4  0.75  0.0  0.471366  0.393574  0.548303   0.0   
151           0.0  0.0 -0.8  1.50  0.0 -0.603524 -0.658635 -0.511749   0.0   
152           0.0 -1.0 -1.2  0.75  1.0 -0.308370 -0.353414 -0.203655   0.0   
153           0.0  0.0  0.0  1.75  0.0 -2.519824 -2.345381 -2.934726   0.0   
154           0.0  0.0  0.4  0.00  0.0  0.762115  0.726908  0.814621   0.0   
155           0.0  0.0  0.2  0.00  0.0 -0.577093 -0.650602 -0.485640   0.0   
156           0.0  0.0  0.4  0.75  0.0 -0.268722 -0.337349 -0.193211   0.0   
157           0.0  0.0 -1.2  1.50  1.0  0.920705  0.867470  1.049608   0.0   
158           0.0  0.0  0.0 -0.25  0.0 -1.149780 -1.092369 -1.362924   0.0   
159           0.0  0.0  0.6 -0.25  0.0  0.797357  0.726908  0.866841   0.0   
160           0.0  0.0  0.6  1.50  0.0 -0.176211 -0.208835 -0.104439   0.0   
161           0.0  0.0  0.0 -0.25  0.0  0.136564  0.148594  0.125326   0.0   
162           0.0  0.0  0.0  0.00  0.0  0.784141  0.710843  0.892950   0.0   
163           0.0  0.0 -0.8  0.00  0.0 -0.101322 -0.148594 -0.078329   0.0   
164           0.0  0.0 -0.8  0.00  0.0  0.127753  0.120482  0.114883   0.0   
165           0.0  0.0 -0.4  0.00  1.0  0.242291  0.216867  0.255875   0.0   
166           0.0  0.0 -0.4  0.50  0.0 -0.149780 -0.208835 -0.104439   0.0   
167           0.0  0.0 -0.8 -0.25  0.0  0.700441  0.638554  0.751958   0.0   
168           0.0  0.0 -0.6  0.50  0.0  0.211454  0.216867  0.214099   0.0   
169           0.0  0.0  0.6

PRODUCT_CODE  X_1  X_2   X_7  X_8      X_11      X_12      X_13  X_15  \
119           0.0  0.0 -0.8  1.50  0.0 -2.502203 -2.317269 -2.919060   0.0   
120           0.0  0.0 -0.8  1.50  0.0 -1.026432 -1.020080 -1.211488   0.0   
121           0.0  0.0  0.2  0.75  0.0 -0.325991 -0.405622 -0.255875   0.0   
122           0.0  0.0  0.4  1.50  1.0 -0.035242 -0.072289  0.000000   0.0   
123           0.0  0.0 -0.4  0.75  0.0  0.431718  0.365462  0.417755   0.0   
124           0.0  0.0  0.0  0.75  0.0 -0.497797 -0.582329 -0.396867   0.0   
125           0.0 -1.0  0.4  1.50  0.0 -0.942731 -0.951807 -0.971279   0.0   
126           0.0  0.0  0.4  0.00  0.0  0.189427  0.168675  0.214099   0.0   
127           0.0  0.0  0.6  0.00  0.0  0.035242  0.000000  0.052219   0.0   
128           0.0  0.0 -0.4  0.50  0.0  0.392070  0.365462  0.355091   0.0   
129           0.0  0.0  0.4 -0.25  0.0 -0.977974 -0.991968 -1.112272   0.0   
130           0.0  0.0 -0.4  0.00  0.0  0.634361  0.610442  0.673629   0.0   
131           0.0  0.0 -1.0  0.00  0.0 -0.030837 -0.072289 -0.015666   2.0   
132           0.0 -1.0  0.4  0.00  0.0  0.740088  0.726908  0.788512   0.0   
133           0.0  0.0  0.6  0.50  0.0 -1.013216 -1.020080 -1.133159   0.0   
134           0.0  0.0  0.0 -0.25  0.0 -0.651982 -0.698795 -0.548303   0.0   
135           0.0  0.0  0.4  0.00  0.0  0.436123  0.377510  0.433420   0.0   
136           0.0  0.0  0.0  0.75  0.0  0.687225  0.638554  0.762402   0.0   
137           0.0  0.0  0.4 -0.25  0.0 -1.400881 -1.365462 -1.556136   0.0   
138           0.0  0.0 -0.4  0.00  0.0 -0.237885 -0.297189 -0.193211   0.0   
139           0.0  0.0 -0.6 -0.25  0.0 -0.303965 -0.385542 -0.255875   0.0   
140           0.0 -1.0  0.4  0.00  0.0 -0.581498 -0.658635 -0.537859   0.0   
141           0.0  0.0  0.6  0.00  0.0  0.092511  0.060241  0.114883   0.0   
142           0.0 -1.0  0.4  0.75  0.0 -0.964758 -0.983936 -1.033943   0.0   
143           0.0  0.0  0.4  0.00  0.0  0.762115  0.710843  0.814621   0.0   
144           0.0  0.0  0.4  1.25  0.0 -0.458150 -0.542169 -0.360313   0.0   
145           0.0  0.0 -0.4  2.25  1.0 -0.559471 -0.598394 -0.485640   0.0   
146           0.0  0.0  0.0  0.00  0.0  0.321586  0.269076  0.281984   0.0   
147           0.0  0.0 -0.6  0.25  0.0 -0.462555 -0.530120 -0.396867   0.0   
148           0.0  0.0 -0.4  0.50  0.0 -0.365639 -0.413655 -0.292428   0.0   
149           0.0  0.0 -0.8 -0.25  0.0  0.132159  0.092369  0.114883   0.0   
150           0.0  0.0 -0.4  0.75  0.0  0.471366  0.393574  0.548303   0.0   
151           0.0  0.0 -0.8  1.50  0.0 -0.603524 -0.658635 -0.511749   0.0   
152           0.0 -1.0 -1.2  0.75  1.0 -0.308370 -0.353414 -0.203655   0.0   
153           0.0  0.0  0.0  1.75  0.0 -2.519824 -2.345381 -2.934726   0.0   
154           0.0  0.0  0.4  0.00  0.0  0.762115  0.726908  0.814621   0.0   
155           0.0  0.0  0.2  0.00  0.0 -0.577093 -0.650602 -0.485640   0.0   
156           0.0  0.0  0.4  0.75  0.0 -0.268722 -0.337349 -0.193211   0.0   
157           0.0  0.0 -1.2  1.50  1.0  0.920705  0.867470  1.049608   0.0   
158           0.0  0.0  0.0 -0.25  0.0 -1.149780 -1.092369 -1.362924   0.0   
159           0.0  0.0  0.6 -0.25  0.0  0.797357  0.726908  0.866841   0.0   
160           0.0  0.0  0.6  1.50  0.0 -0.176211 -0.208835 -0.104439   0.0   
161           0.0  0.0  0.0 -0.25  0.0  0.136564  0.148594  0.125326   0.0   
162           0.0  0.0  0.0  0.00  0.0  0.784141  0.710843  0.892950   0.0   
163           0.0  0.0 -0.8  0.00  0.0 -0.101322 -0.148594 -0.078329   0.0   
164           0.0  0.0 -0.8  0.00  0.0  0.127753  0.120482  0.114883   0.0   
165           0.0  0.0 -0.4  0.00  1.0  0.242291  0.216867  0.255875   0.0   
166           0.0  0.0 -0.4  0.50  0.0 -0.149780 -0.208835 -0.104439   0.0   
167           0.0  0.0 -0.8 -0.25  0.0  0.700441  0.638554  0.751958   0.0   
168           0.0  0.0 -0.6  0.50  0.0  0.211454  0.216867  0.214099   0.0   
169           0.0  0.0  0.6

PRODUCT_CODE  X_1  X_2   X_7  X_8      X_11      X_12      X_13  X_15  \
119           0.0  0.0 -0.8  1.50  0.0 -2.502203 -2.317269 -2.919060   0.0   
120           0.0  0.0 -0.8  1.50  0.0 -1.026432 -1.020080 -1.211488   0.0   
121           0.0  0.0  0.2  0.75  0.0 -0.325991 -0.405622 -0.255875   0.0   
122           0.0  0.0  0.4  1.50  1.0 -0.035242 -0.072289  0.000000   0.0   
123           0.0  0.0 -0.4  0.75  0.0  0.431718  0.365462  0.417755   0.0   
124           0.0  0.0  0.0  0.75  0.0 -0.497797 -0.582329 -0.396867   0.0   
125           0.0 -1.0  0.4  1.50  0.0 -0.942731 -0.951807 -0.971279   0.0   
126           0.0  0.0  0.4  0.00  0.0  0.189427  0.168675  0.214099   0.0   
127           0.0  0.0  0.6  0.00  0.0  0.035242  0.000000  0.052219   0.0   
128           0.0  0.0 -0.4  0.50  0.0  0.392070  0.365462  0.355091   0.0   
129           0.0  0.0  0.4 -0.25  0.0 -0.977974 -0.991968 -1.112272   0.0   
130           0.0  0.0 -0.4  0.00  0.0  0.634361  0.610442  0.673629   0.0   
131           0.0  0.0 -1.0  0.00  0.0 -0.030837 -0.072289 -0.015666   2.0   
132           0.0 -1.0  0.4  0.00  0.0  0.740088  0.726908  0.788512   0.0   
133           0.0  0.0  0.6  0.50  0.0 -1.013216 -1.020080 -1.133159   0.0   
134           0.0  0.0  0.0 -0.25  0.0 -0.651982 -0.698795 -0.548303   0.0   
135           0.0  0.0  0.4  0.00  0.0  0.436123  0.377510  0.433420   0.0   
136           0.0  0.0  0.0  0.75  0.0  0.687225  0.638554  0.762402   0.0   
137           0.0  0.0  0.4 -0.25  0.0 -1.400881 -1.365462 -1.556136   0.0   
138           0.0  0.0 -0.4  0.00  0.0 -0.237885 -0.297189 -0.193211   0.0   
139           0.0  0.0 -0.6 -0.25  0.0 -0.303965 -0.385542 -0.255875   0.0   
140           0.0 -1.0  0.4  0.00  0.0 -0.581498 -0.658635 -0.537859   0.0   
141           0.0  0.0  0.6  0.00  0.0  0.092511  0.060241  0.114883   0.0   
142           0.0 -1.0  0.4  0.75  0.0 -0.964758 -0.983936 -1.033943   0.0   
143           0.0  0.0  0.4  0.00  0.0  0.762115  0.710843  0.814621   0.0   
144           0.0  0.0  0.4  1.25  0.0 -0.458150 -0.542169 -0.360313   0.0   
145           0.0  0.0 -0.4  2.25  1.0 -0.559471 -0.598394 -0.485640   0.0   
146           0.0  0.0  0.0  0.00  0.0  0.321586  0.269076  0.281984   0.0   
147           0.0  0.0 -0.6  0.25  0.0 -0.462555 -0.530120 -0.396867   0.0   
148           0.0  0.0 -0.4  0.50  0.0 -0.365639 -0.413655 -0.292428   0.0   
149           0.0  0.0 -0.8 -0.25  0.0  0.132159  0.092369  0.114883   0.0   
150           0.0  0.0 -0.4  0.75  0.0  0.471366  0.393574  0.548303   0.0   
151           0.0  0.0 -0.8  1.50  0.0 -0.603524 -0.658635 -0.511749   0.0   
152           0.0 -1.0 -1.2  0.75  1.0 -0.308370 -0.353414 -0.203655   0.0   
153           0.0  0.0  0.0  1.75  0.0 -2.519824 -2.345381 -2.934726   0.0   
154           0.0  0.0  0.4  0.00  0.0  0.762115  0.726908  0.814621   0.0   
155           0.0  0.0  0.2  0.00  0.0 -0.577093 -0.650602 -0.485640   0.0   
156           0.0  0.0  0.4  0.75  0.0 -0.268722 -0.337349 -0.193211   0.0   
157           0.0  0.0 -1.2  1.50  1.0  0.920705  0.867470  1.049608   0.0   
158           0.0  0.0  0.0 -0.25  0.0 -1.149780 -1.092369 -1.362924   0.0   
159           0.0  0.0  0.6 -0.25  0.0  0.797357  0.726908  0.866841   0.0   
160           0.0  0.0  0.6  1.50  0.0 -0.176211 -0.208835 -0.104439   0.0   
161           0.0  0.0  0.0 -0.25  0.0  0.136564  0.148594  0.125326   0.0   
162           0.0  0.0  0.0  0.00  0.0  0.784141  0.710843  0.892950   0.0   
163           0.0  0.0 -0.8  0.00  0.0 -0.101322 -0.148594 -0.078329   0.0   
164           0.0  0.0 -0.8  0.00  0.0  0.127753  0.120482  0.114883   0.0   
165           0.0  0.0 -0.4  0.00  1.0  0.242291  0.216867  0.255875   0.0   
166           0.0  0.0 -0.4  0.50  0.0 -0.149780 -0.208835 -0.104439   0.0   
167           0.0  0.0 -0.8 -0.25  0.0  0.700441  0.638554  0.751958   0.0   
168           0.0  0.0 -0.6  0.50  0.0  0.211454  0.216867  0.214099   0.0   
169           0.0  0.0  0.6

PRODUCT_CODE  X_1  X_2   X_7  X_8      X_11      X_12      X_13  X_15  \
119           0.0  0.0 -0.8  1.50  0.0 -2.502203 -2.317269 -2.919060   0.0   
120           0.0  0.0 -0.8  1.50  0.0 -1.026432 -1.020080 -1.211488   0.0   
121           0.0  0.0  0.2  0.75  0.0 -0.325991 -0.405622 -0.255875   0.0   
122           0.0  0.0  0.4  1.50  1.0 -0.035242 -0.072289  0.000000   0.0   
123           0.0  0.0 -0.4  0.75  0.0  0.431718  0.365462  0.417755   0.0   
124           0.0  0.0  0.0  0.75  0.0 -0.497797 -0.582329 -0.396867   0.0   
125           0.0 -1.0  0.4  1.50  0.0 -0.942731 -0.951807 -0.971279   0.0   
126           0.0  0.0  0.4  0.00  0.0  0.189427  0.168675  0.214099   0.0   
127           0.0  0.0  0.6  0.00  0.0  0.035242  0.000000  0.052219   0.0   
128           0.0  0.0 -0.4  0.50  0.0  0.392070  0.365462  0.355091   0.0   
129           0.0  0.0  0.4 -0.25  0.0 -0.977974 -0.991968 -1.112272   0.0   
130           0.0  0.0 -0.4  0.00  0.0  0.634361  0.610442  0.673629   0.0   
131           0.0  0.0 -1.0  0.00  0.0 -0.030837 -0.072289 -0.015666   2.0   
132           0.0 -1.0  0.4  0.00  0.0  0.740088  0.726908  0.788512   0.0   
133           0.0  0.0  0.6  0.50  0.0 -1.013216 -1.020080 -1.133159   0.0   
134           0.0  0.0  0.0 -0.25  0.0 -0.651982 -0.698795 -0.548303   0.0   
135           0.0  0.0  0.4  0.00  0.0  0.436123  0.377510  0.433420   0.0   
136           0.0  0.0  0.0  0.75  0.0  0.687225  0.638554  0.762402   0.0   
137           0.0  0.0  0.4 -0.25  0.0 -1.400881 -1.365462 -1.556136   0.0   
138           0.0  0.0 -0.4  0.00  0.0 -0.237885 -0.297189 -0.193211   0.0   
139           0.0  0.0 -0.6 -0.25  0.0 -0.303965 -0.385542 -0.255875   0.0   
140           0.0 -1.0  0.4  0.00  0.0 -0.581498 -0.658635 -0.537859   0.0   
141           0.0  0.0  0.6  0.00  0.0  0.092511  0.060241  0.114883   0.0   
142           0.0 -1.0  0.4  0.75  0.0 -0.964758 -0.983936 -1.033943   0.0   
143           0.0  0.0  0.4  0.00  0.0  0.762115  0.710843  0.814621   0.0   
144           0.0  0.0  0.4  1.25  0.0 -0.458150 -0.542169 -0.360313   0.0   
145           0.0  0.0 -0.4  2.25  1.0 -0.559471 -0.598394 -0.485640   0.0   
146           0.0  0.0  0.0  0.00  0.0  0.321586  0.269076  0.281984   0.0   
147           0.0  0.0 -0.6  0.25  0.0 -0.462555 -0.530120 -0.396867   0.0   
148           0.0  0.0 -0.4  0.50  0.0 -0.365639 -0.413655 -0.292428   0.0   
149           0.0  0.0 -0.8 -0.25  0.0  0.132159  0.092369  0.114883   0.0   
150           0.0  0.0 -0.4  0.75  0.0  0.471366  0.393574  0.548303   0.0   
151           0.0  0.0 -0.8  1.50  0.0 -0.603524 -0.658635 -0.511749   0.0   
152           0.0 -1.0 -1.2  0.75  1.0 -0.308370 -0.353414 -0.203655   0.0   
153           0.0  0.0  0.0  1.75  0.0 -2.519824 -2.345381 -2.934726   0.0   
154           0.0  0.0  0.4  0.00  0.0  0.762115  0.726908  0.814621   0.0   
155           0.0  0.0  0.2  0.00  0.0 -0.577093 -0.650602 -0.485640   0.0   
156           0.0  0.0  0.4  0.75  0.0 -0.268722 -0.337349 -0.193211   0.0   
157           0.0  0.0 -1.2  1.50  1.0  0.920705  0.867470  1.049608   0.0   
158           0.0  0.0  0.0 -0.25  0.0 -1.149780 -1.092369 -1.362924   0.0   
159           0.0  0.0  0.6 -0.25  0.0  0.797357  0.726908  0.866841   0.0   
160           0.0  0.0  0.6  1.50  0.0 -0.176211 -0.208835 -0.104439   0.0   
161           0.0  0.0  0.0 -0.25  0.0  0.136564  0.148594  0.125326   0.0   
162           0.0  0.0  0.0  0.00  0.0  0.784141  0.710843  0.892950   0.0   
163           0.0  0.0 -0.8  0.00  0.0 -0.101322 -0.148594 -0.078329   0.0   
164           0.0  0.0 -0.8  0.00  0.0  0.127753  0.120482  0.114883   0.0   
165           0.0  0.0 -0.4  0.00  1.0  0.242291  0.216867  0.255875   0.0   
166           0.0  0.0 -0.4  0.50  0.0 -0.149780 -0.208835 -0.104439   0.0   
167           0.0  0.0 -0.8 -0.25  0.0  0.700441  0.638554  0.751958   0.0   
168           0.0  0.0 -0.6  0.50  0.0  0.211454  0.216867  0.214099   0.0   
169           0.0  0.0  0.6

PRODUCT_CODE  X_1  X_2   X_7  X_8      X_11      X_12      X_13  X_15  \
119           0.0  0.0 -0.8  1.50  0.0 -2.502203 -2.317269 -2.919060   0.0   
120           0.0  0.0 -0.8  1.50  0.0 -1.026432 -1.020080 -1.211488   0.0   
121           0.0  0.0  0.2  0.75  0.0 -0.325991 -0.405622 -0.255875   0.0   
122           0.0  0.0  0.4  1.50  1.0 -0.035242 -0.072289  0.000000   0.0   
123           0.0  0.0 -0.4  0.75  0.0  0.431718  0.365462  0.417755   0.0   
124           0.0  0.0  0.0  0.75  0.0 -0.497797 -0.582329 -0.396867   0.0   
125           0.0 -1.0  0.4  1.50  0.0 -0.942731 -0.951807 -0.971279   0.0   
126           0.0  0.0  0.4  0.00  0.0  0.189427  0.168675  0.214099   0.0   
127           0.0  0.0  0.6  0.00  0.0  0.035242  0.000000  0.052219   0.0   
128           0.0  0.0 -0.4  0.50  0.0  0.392070  0.365462  0.355091   0.0   
129           0.0  0.0  0.4 -0.25  0.0 -0.977974 -0.991968 -1.112272   0.0   
130           0.0  0.0 -0.4  0.00  0.0  0.634361  0.610442  0.673629   0.0   
131           0.0  0.0 -1.0  0.00  0.0 -0.030837 -0.072289 -0.015666   2.0   
132           0.0 -1.0  0.4  0.00  0.0  0.740088  0.726908  0.788512   0.0   
133           0.0  0.0  0.6  0.50  0.0 -1.013216 -1.020080 -1.133159   0.0   
134           0.0  0.0  0.0 -0.25  0.0 -0.651982 -0.698795 -0.548303   0.0   
135           0.0  0.0  0.4  0.00  0.0  0.436123  0.377510  0.433420   0.0   
136           0.0  0.0  0.0  0.75  0.0  0.687225  0.638554  0.762402   0.0   
137           0.0  0.0  0.4 -0.25  0.0 -1.400881 -1.365462 -1.556136   0.0   
138           0.0  0.0 -0.4  0.00  0.0 -0.237885 -0.297189 -0.193211   0.0   
139           0.0  0.0 -0.6 -0.25  0.0 -0.303965 -0.385542 -0.255875   0.0   
140           0.0 -1.0  0.4  0.00  0.0 -0.581498 -0.658635 -0.537859   0.0   
141           0.0  0.0  0.6  0.00  0.0  0.092511  0.060241  0.114883   0.0   
142           0.0 -1.0  0.4  0.75  0.0 -0.964758 -0.983936 -1.033943   0.0   
143           0.0  0.0  0.4  0.00  0.0  0.762115  0.710843  0.814621   0.0   
144           0.0  0.0  0.4  1.25  0.0 -0.458150 -0.542169 -0.360313   0.0   
145           0.0  0.0 -0.4  2.25  1.0 -0.559471 -0.598394 -0.485640   0.0   
146           0.0  0.0  0.0  0.00  0.0  0.321586  0.269076  0.281984   0.0   
147           0.0  0.0 -0.6  0.25  0.0 -0.462555 -0.530120 -0.396867   0.0   
148           0.0  0.0 -0.4  0.50  0.0 -0.365639 -0.413655 -0.292428   0.0   
149           0.0  0.0 -0.8 -0.25  0.0  0.132159  0.092369  0.114883   0.0   
150           0.0  0.0 -0.4  0.75  0.0  0.471366  0.393574  0.548303   0.0   
151           0.0  0.0 -0.8  1.50  0.0 -0.603524 -0.658635 -0.511749   0.0   
152           0.0 -1.0 -1.2  0.75  1.0 -0.308370 -0.353414 -0.203655   0.0   
153           0.0  0.0  0.0  1.75  0.0 -2.519824 -2.345381 -2.934726   0.0   
154           0.0  0.0  0.4  0.00  0.0  0.762115  0.726908  0.814621   0.0   
155           0.0  0.0  0.2  0.00  0.0 -0.577093 -0.650602 -0.485640   0.0   
156           0.0  0.0  0.4  0.75  0.0 -0.268722 -0.337349 -0.193211   0.0   
157           0.0  0.0 -1.2  1.50  1.0  0.920705  0.867470  1.049608   0.0   
158           0.0  0.0  0.0 -0.25  0.0 -1.149780 -1.092369 -1.362924   0.0   
159           0.0  0.0  0.6 -0.25  0.0  0.797357  0.726908  0.866841   0.0   
160           0.0  0.0  0.6  1.50  0.0 -0.176211 -0.208835 -0.104439   0.0   
161           0.0  0.0  0.0 -0.25  0.0  0.136564  0.148594  0.125326   0.0   
162           0.0  0.0  0.0  0.00  0.0  0.784141  0.710843  0.892950   0.0   
163           0.0  0.0 -0.8  0.00  0.0 -0.101322 -0.148594 -0.078329   0.0   
164           0.0  0.0 -0.8  0.00  0.0  0.127753  0.120482  0.114883   0.0   
165           0.0  0.0 -0.4  0.00  1.0  0.242291  0.216867  0.255875   0.0   
166           0.0  0.0 -0.4  0.50  0.0 -0.149780 -0.208835 -0.104439   0.0   
167           0.0  0.0 -0.8 -0.25  0.0  0.700441  0.638554  0.751958   0.0   
168           0.0  0.0 -0.6  0.50  0.0  0.211454  0.216867  0.214099   0.0   
169           0.0  0.0  0.6

PRODUCT_CODE  X_1  X_2   X_7  X_8      X_11      X_12      X_13  X_15  \
119           0.0  0.0 -0.8  1.50  0.0 -2.502203 -2.317269 -2.919060   0.0   
120           0.0  0.0 -0.8  1.50  0.0 -1.026432 -1.020080 -1.211488   0.0   
121           0.0  0.0  0.2  0.75  0.0 -0.325991 -0.405622 -0.255875   0.0   
122           0.0  0.0  0.4  1.50  1.0 -0.035242 -0.072289  0.000000   0.0   
123           0.0  0.0 -0.4  0.75  0.0  0.431718  0.365462  0.417755   0.0   
124           0.0  0.0  0.0  0.75  0.0 -0.497797 -0.582329 -0.396867   0.0   
125           0.0 -1.0  0.4  1.50  0.0 -0.942731 -0.951807 -0.971279   0.0   
126           0.0  0.0  0.4  0.00  0.0  0.189427  0.168675  0.214099   0.0   
127           0.0  0.0  0.6  0.00  0.0  0.035242  0.000000  0.052219   0.0   
128           0.0  0.0 -0.4  0.50  0.0  0.392070  0.365462  0.355091   0.0   
129           0.0  0.0  0.4 -0.25  0.0 -0.977974 -0.991968 -1.112272   0.0   
130           0.0  0.0 -0.4  0.00  0.0  0.634361  0.610442  0.673629   0.0   
131           0.0  0.0 -1.0  0.00  0.0 -0.030837 -0.072289 -0.015666   2.0   
132           0.0 -1.0  0.4  0.00  0.0  0.740088  0.726908  0.788512   0.0   
133           0.0  0.0  0.6  0.50  0.0 -1.013216 -1.020080 -1.133159   0.0   
134           0.0  0.0  0.0 -0.25  0.0 -0.651982 -0.698795 -0.548303   0.0   
135           0.0  0.0  0.4  0.00  0.0  0.436123  0.377510  0.433420   0.0   
136           0.0  0.0  0.0  0.75  0.0  0.687225  0.638554  0.762402   0.0   
137           0.0  0.0  0.4 -0.25  0.0 -1.400881 -1.365462 -1.556136   0.0   
138           0.0  0.0 -0.4  0.00  0.0 -0.237885 -0.297189 -0.193211   0.0   
139           0.0  0.0 -0.6 -0.25  0.0 -0.303965 -0.385542 -0.255875   0.0   
140           0.0 -1.0  0.4  0.00  0.0 -0.581498 -0.658635 -0.537859   0.0   
141           0.0  0.0  0.6  0.00  0.0  0.092511  0.060241  0.114883   0.0   
142           0.0 -1.0  0.4  0.75  0.0 -0.964758 -0.983936 -1.033943   0.0   
143           0.0  0.0  0.4  0.00  0.0  0.762115  0.710843  0.814621   0.0   
144           0.0  0.0  0.4  1.25  0.0 -0.458150 -0.542169 -0.360313   0.0   
145           0.0  0.0 -0.4  2.25  1.0 -0.559471 -0.598394 -0.485640   0.0   
146           0.0  0.0  0.0  0.00  0.0  0.321586  0.269076  0.281984   0.0   
147           0.0  0.0 -0.6  0.25  0.0 -0.462555 -0.530120 -0.396867   0.0   
148           0.0  0.0 -0.4  0.50  0.0 -0.365639 -0.413655 -0.292428   0.0   
149           0.0  0.0 -0.8 -0.25  0.0  0.132159  0.092369  0.114883   0.0   
150           0.0  0.0 -0.4  0.75  0.0  0.471366  0.393574  0.548303   0.0   
151           0.0  0.0 -0.8  1.50  0.0 -0.603524 -0.658635 -0.511749   0.0   
152           0.0 -1.0 -1.2  0.75  1.0 -0.308370 -0.353414 -0.203655   0.0   
153           0.0  0.0  0.0  1.75  0.0 -2.519824 -2.345381 -2.934726   0.0   
154           0.0  0.0  0.4  0.00  0.0  0.762115  0.726908  0.814621   0.0   
155           0.0  0.0  0.2  0.00  0.0 -0.577093 -0.650602 -0.485640   0.0   
156           0.0  0.0  0.4  0.75  0.0 -0.268722 -0.337349 -0.193211   0.0   
157           0.0  0.0 -1.2  1.50  1.0  0.920705  0.867470  1.049608   0.0   
158           0.0  0.0  0.0 -0.25  0.0 -1.149780 -1.092369 -1.362924   0.0   
159           0.0  0.0  0.6 -0.25  0.0  0.797357  0.726908  0.866841   0.0   
160           0.0  0.0  0.6  1.50  0.0 -0.176211 -0.208835 -0.104439   0.0   
161           0.0  0.0  0.0 -0.25  0.0  0.136564  0.148594  0.125326   0.0   
162           0.0  0.0  0.0  0.00  0.0  0.784141  0.710843  0.892950   0.0   
163           0.0  0.0 -0.8  0.00  0.0 -0.101322 -0.148594 -0.078329   0.0   
164           0.0  0.0 -0.8  0.00  0.0  0.127753  0.120482  0.114883   0.0   
165           0.0  0.0 -0.4  0.00  1.0  0.242291  0.216867  0.255875   0.0   
166           0.0  0.0 -0.4  0.50  0.0 -0.149780 -0.208835 -0.104439   0.0   
167           0.0  0.0 -0.8 -0.25  0.0  0.700441  0.638554  0.751958   0.0   
168           0.0  0.0 -0.6  0.50  0.0  0.211454  0.216867  0.214099   0.0   
169           0.0  0.0  0.6

PRODUCT_CODE  X_1  X_2   X_7  X_8      X_11      X_12      X_13  X_15  \
119           0.0  0.0 -0.8  1.50  0.0 -2.502203 -2.317269 -2.919060   0.0   
120           0.0  0.0 -0.8  1.50  0.0 -1.026432 -1.020080 -1.211488   0.0   
121           0.0  0.0  0.2  0.75  0.0 -0.325991 -0.405622 -0.255875   0.0   
122           0.0  0.0  0.4  1.50  1.0 -0.035242 -0.072289  0.000000   0.0   
123           0.0  0.0 -0.4  0.75  0.0  0.431718  0.365462  0.417755   0.0   
124           0.0  0.0  0.0  0.75  0.0 -0.497797 -0.582329 -0.396867   0.0   
125           0.0 -1.0  0.4  1.50  0.0 -0.942731 -0.951807 -0.971279   0.0   
126           0.0  0.0  0.4  0.00  0.0  0.189427  0.168675  0.214099   0.0   
127           0.0  0.0  0.6  0.00  0.0  0.035242  0.000000  0.052219   0.0   
128           0.0  0.0 -0.4  0.50  0.0  0.392070  0.365462  0.355091   0.0   
129           0.0  0.0  0.4 -0.25  0.0 -0.977974 -0.991968 -1.112272   0.0   
130           0.0  0.0 -0.4  0.00  0.0  0.634361  0.610442  0.673629   0.0   
131           0.0  0.0 -1.0  0.00  0.0 -0.030837 -0.072289 -0.015666   2.0   
132           0.0 -1.0  0.4  0.00  0.0  0.740088  0.726908  0.788512   0.0   
133           0.0  0.0  0.6  0.50  0.0 -1.013216 -1.020080 -1.133159   0.0   
134           0.0  0.0  0.0 -0.25  0.0 -0.651982 -0.698795 -0.548303   0.0   
135           0.0  0.0  0.4  0.00  0.0  0.436123  0.377510  0.433420   0.0   
136           0.0  0.0  0.0  0.75  0.0  0.687225  0.638554  0.762402   0.0   
137           0.0  0.0  0.4 -0.25  0.0 -1.400881 -1.365462 -1.556136   0.0   
138           0.0  0.0 -0.4  0.00  0.0 -0.237885 -0.297189 -0.193211   0.0   
139           0.0  0.0 -0.6 -0.25  0.0 -0.303965 -0.385542 -0.255875   0.0   
140           0.0 -1.0  0.4  0.00  0.0 -0.581498 -0.658635 -0.537859   0.0   
141           0.0  0.0  0.6  0.00  0.0  0.092511  0.060241  0.114883   0.0   
142           0.0 -1.0  0.4  0.75  0.0 -0.964758 -0.983936 -1.033943   0.0   
143           0.0  0.0  0.4  0.00  0.0  0.762115  0.710843  0.814621   0.0   
144           0.0  0.0  0.4  1.25  0.0 -0.458150 -0.542169 -0.360313   0.0   
145           0.0  0.0 -0.4  2.25  1.0 -0.559471 -0.598394 -0.485640   0.0   
146           0.0  0.0  0.0  0.00  0.0  0.321586  0.269076  0.281984   0.0   
147           0.0  0.0 -0.6  0.25  0.0 -0.462555 -0.530120 -0.396867   0.0   
148           0.0  0.0 -0.4  0.50  0.0 -0.365639 -0.413655 -0.292428   0.0   
149           0.0  0.0 -0.8 -0.25  0.0  0.132159  0.092369  0.114883   0.0   
150           0.0  0.0 -0.4  0.75  0.0  0.471366  0.393574  0.548303   0.0   
151           0.0  0.0 -0.8  1.50  0.0 -0.603524 -0.658635 -0.511749   0.0   
152           0.0 -1.0 -1.2  0.75  1.0 -0.308370 -0.353414 -0.203655   0.0   
153           0.0  0.0  0.0  1.75  0.0 -2.519824 -2.345381 -2.934726   0.0   
154           0.0  0.0  0.4  0.00  0.0  0.762115  0.726908  0.814621   0.0   
155           0.0  0.0  0.2  0.00  0.0 -0.577093 -0.650602 -0.485640   0.0   
156           0.0  0.0  0.4  0.75  0.0 -0.268722 -0.337349 -0.193211   0.0   
157           0.0  0.0 -1.2  1.50  1.0  0.920705  0.867470  1.049608   0.0   
158           0.0  0.0  0.0 -0.25  0.0 -1.149780 -1.092369 -1.362924   0.0   
159           0.0  0.0  0.6 -0.25  0.0  0.797357  0.726908  0.866841   0.0   
160           0.0  0.0  0.6  1.50  0.0 -0.176211 -0.208835 -0.104439   0.0   
161           0.0  0.0  0.0 -0.25  0.0  0.136564  0.148594  0.125326   0.0   
162           0.0  0.0  0.0  0.00  0.0  0.784141  0.710843  0.892950   0.0   
163           0.0  0.0 -0.8  0.00  0.0 -0.101322 -0.148594 -0.078329   0.0   
164           0.0  0.0 -0.8  0.00  0.0  0.127753  0.120482  0.114883   0.0   
165           0.0  0.0 -0.4  0.00  1.0  0.242291  0.216867  0.255875   0.0   
166           0.0  0.0 -0.4  0.50  0.0 -0.149780 -0.208835 -0.104439   0.0   
167           0.0  0.0 -0.8 -0.25  0.0  0.700441  0.638554  0.751958   0.0   
168           0.0  0.0 -0.6  0.50  0.0  0.211454  0.216867  0.214099   0.0   
169           0.0  0.0  0.6

In [100]:
T1003062_final_regression_model = finalize_model(T10_model_et)

T1003062_prediction = predict_model(T1003062_final_regression_model, data=T1003062_data)
T1003062_prediction

T1003062_datas = T1003062_prediction['prediction_label']
T1003062_datas = pd.DataFrame(T1003062_datas.values, columns = ['Y_Quality'])

T1003062y_idx= T1003062_class.index
T1003062y_idx = pd.DataFrame(T1003062y_idx, columns = ['index'])
T1003062_datas = pd.concat([T1003062y_idx, T1003062_datas], axis = 1)
T1003062_datas = T1003062_datas.set_index('index')
T1003062_datas

Y_Quality
index           
26      0.531992
30      0.528646
36      0.529633
42      0.530965
43      0.529498
...          ...
588     0.530121
589     0.529510
590     0.529948
591     0.529308
593     0.526546

[171 rows x 1 columns]

In [101]:
from pycaret.classification import *
# 분류 패키지의 모든 모듈을 임포트한다.
exp_clf101 = setup(data=T1003062_datas, 
                   target=T1003062_class, 
                   fold=5,
                   session_id=4)
top5 = compare_models(sort='Accuracy', n_select=5)

Processing:   0%|          | 0/73 [00:00<?, ?it/s]

In [102]:
T10_total_models = []

T10_model_lightgbm = create_model('lightgbm', fold = 5)
T10_total_models.append(T10_model_lightgbm)

T10_model_rf = create_model('rf', fold = 5)
T10_total_models.append(T10_model_rf)

T10_model_gbc = create_model('gbc', fold = 5)
T10_total_models.append(T10_model_gbc)

T10_model_et = create_model('et', fold = 5)
T10_total_models.append(T10_model_et)

T10_model_catboost = create_model('catboost', fold = 5)
T10_total_models.append(T10_model_catboost)

T10_model_xgb = create_model('xgboost', fold = 5)
T10_total_models.append(T10_model_xgb)

T10_model_ada = create_model('ada', fold = 5)

T10_total_models.append(T10_model_ada)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [103]:
T10_model_lightgbm = tune_model(T10_model_lightgbm, fold=5, choose_better = True)

T10_model_rf = tune_model(T10_model_rf, fold=5, choose_better = True)

T10_model_gbc = tune_model(T10_model_gbc, fold=5, choose_better = True)

T10_model_et = tune_model(T10_model_et, fold=5, choose_better = True)

T10_model_catboost = tune_model(T10_model_catboost, fold=5, choose_better = True)

T10_model_xgb = tune_model(T10_model_xgb, fold=5, choose_better = True)

T10_model_ada = tune_model(T10_model_ada, fold=5, choose_better = True)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

...

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


In [104]:
T10_tuned_models = [T10_model_lightgbm, T10_model_rf, T10_model_gbc, T10_model_et, T10_model_catboost, T10_model_xgb, T10_model_ada]

for model in T10_tuned_models:
    display(predict_model(model))

Y_Quality  Y_Class  prediction_label  prediction_score
119   0.536183        2                 2            0.9999
120   0.528917        1                 1            0.9994
121   0.532144        1                 1            0.9994
122   0.535622        2                 2            0.9999
123   0.530411        1                 1            0.9994
124   0.531835        1                 1            0.9994
125   0.528822        1                 1            0.9994
126   0.531992        1                 1            0.9994
127   0.532191        1                 1            0.9994
128   0.527929        1                 1            0.9994
129   0.529013        1                 1            0.9994
130   0.527629        1                 1            0.9983
131   0.529746        1                 1            0.9994
132   0.526810        1                 1            0.9983
133   0.523386        0                 0            0.9883
134   0.529308        1                 1            0.9994
135   0.533017        1                 1            0.9994
136   0.527414        1                 1            0.9983
137   0.525498        1                 1            0.9978
138   0.529567        1                 1            0.9994
139   0.528889        1                 1            0.9994
140   0.532827        1                 1            0.9994
141   0.530800        1                 1            0.9994
142   0.527343        1                 1            0.9983
143   0.537283        2                 2            0.9999
144   0.528617        1                 1            0.9994
145   0.531930        1                 1            0.9994
146   0.502517        0                 0            0.9883
147   0.530121        1                 1            0.9994
148   0.535905        2                 2            0.9999
149   0.528370        1                 1            0.9994
150   0.529217        1                 1            0.9994
151   0.527594        1                 1            0.9983
152   0.532506        1                 1            0.9994
153   0.529622        1                 1            0.9994
154   0.532289        1                 1            0.9994
155   0.529803        1                 1            0.9994
156   0.525067        0                 0            0.6650
157   0.529581        1                 1            0.9994
158   0.530965        1                 1            0.9994
159   0.532740        1                 1            0.9994
160   0.533887        1                 1            0.9992
161   0.526127        1                 1            0.9978
162   0.529075        1                 1            0.9994
163   0.528344        1                 1            0.9994
164   0.529673        1                 1            0.9994
165   0.533894        1                 1            0.9992
166   0.533430        1                 1            0.9994
167   0.527238        1                 1            0.9983
168   0.537060        2                 2            0.9999
169   0.527879        1                 1            0.9994
170   0.528494        1                 1            0.9994

Y_Quality  Y_Class  prediction_label  prediction_score
119   0.536183        2                 2            1.0000
120   0.528917        1                 1            1.0000
121   0.532144        1                 1            1.0000
122   0.535622        2                 2            0.9667
123   0.530411        1                 1            1.0000
124   0.531835        1                 1            1.0000
125   0.528822        1                 1            1.0000
126   0.531992        1                 1            1.0000
127   0.532191        1                 1            1.0000
128   0.527929        1                 1            1.0000
129   0.529013        1                 1            1.0000
130   0.527629        1                 1            1.0000
131   0.529746        1                 1            1.0000
132   0.526810        1                 1            1.0000
133   0.523386        0                 0            0.9968
134   0.529308        1                 1            1.0000
135   0.533017        1                 1            1.0000
136   0.527414        1                 1            1.0000
137   0.525498        1                 1            0.8692
138   0.529567        1                 1            1.0000
139   0.528889        1                 1            1.0000
140   0.532827        1                 1            1.0000
141   0.530800        1                 1            1.0000
142   0.527343        1                 1            1.0000
143   0.537283        2                 2            1.0000
144   0.528617        1                 1            1.0000
145   0.531930        1                 1            1.0000
146   0.502517        0                 0            0.9968
147   0.530121        1                 1            1.0000
148   0.535905        2                 2            1.0000
149   0.528370        1                 1            1.0000
150   0.529217        1                 1            1.0000
151   0.527594        1                 1            1.0000
152   0.532506        1                 1            1.0000
153   0.529622        1                 1            1.0000
154   0.532289        1                 1            1.0000
155   0.529803        1                 1            1.0000
156   0.525067        0                 0            0.7635
157   0.529581        1                 1            1.0000
158   0.530965        1                 1            1.0000
159   0.532740        1                 1            1.0000
160   0.533887        1                 1            1.0000
161   0.526127        1                 1            1.0000
162   0.529075        1                 1            1.0000
163   0.528344        1                 1            1.0000
164   0.529673        1                 1            1.0000
165   0.533894        1                 1            1.0000
166   0.533430        1                 1            1.0000
167   0.527238        1                 1            1.0000
168   0.537060        2                 2            1.0000
169   0.527879        1                 1            1.0000
170   0.528494        1                 1            1.0000

Y_Quality  Y_Class  prediction_label  prediction_score
119   0.536183        2                 2               1.0
120   0.528917        1                 1               1.0
121   0.532144        1                 1               1.0
122   0.535622        2                 2               1.0
123   0.530411        1                 1               1.0
124   0.531835        1                 1               1.0
125   0.528822        1                 1               1.0
126   0.531992        1                 1               1.0
127   0.532191        1                 1               1.0
128   0.527929        1                 1               1.0
129   0.529013        1                 1               1.0
130   0.527629        1                 1               1.0
131   0.529746        1                 1               1.0
132   0.526810        1                 1               1.0
133   0.523386        0                 0               1.0
134   0.529308        1                 1               1.0
135   0.533017        1                 1               1.0
136   0.527414        1                 1               1.0
137   0.525498        1                 1               1.0
138   0.529567        1                 1               1.0
139   0.528889        1                 1               1.0
140   0.532827        1                 1               1.0
141   0.530800        1                 1               1.0
142   0.527343        1                 1               1.0
143   0.537283        2                 2               1.0
144   0.528617        1                 1               1.0
145   0.531930        1                 1               1.0
146   0.502517        0                 0               1.0
147   0.530121        1                 1               1.0
148   0.535905        2                 2               1.0
149   0.528370        1                 1               1.0
150   0.529217        1                 1               1.0
151   0.527594        1                 1               1.0
152   0.532506        1                 1               1.0
153   0.529622        1                 1               1.0
154   0.532289        1                 1               1.0
155   0.529803        1                 1               1.0
156   0.525067        0                 0               1.0
157   0.529581        1                 1               1.0
158   0.530965        1                 1               1.0
159   0.532740        1                 1               1.0
160   0.533887        1                 1               1.0
161   0.526127        1                 1               1.0
162   0.529075        1                 1               1.0
163   0.528344        1                 1               1.0
164   0.529673        1                 1               1.0
165   0.533894        1                 1               1.0
166   0.533430        1                 1               1.0
167   0.527238        1                 1               1.0
168   0.537060        2                 2               1.0
169   0.527879        1                 1               1.0
170   0.528494        1                 1               1.0

Y_Quality  Y_Class  prediction_label  prediction_score
119   0.536183        2                 2              1.00
120   0.528917        1                 1              1.00
121   0.532144        1                 1              1.00
122   0.535622        2                 2              1.00
123   0.530411        1                 1              1.00
124   0.531835        1                 1              1.00
125   0.528822        1                 1              1.00
126   0.531992        1                 1              1.00
127   0.532191        1                 1              1.00
128   0.527929        1                 1              1.00
129   0.529013        1                 1              1.00
130   0.527629        1                 1              1.00
131   0.529746        1                 1              1.00
132   0.526810        1                 1              1.00
133   0.523386        0                 0              1.00
134   0.529308        1                 1              1.00
135   0.533017        1                 1              1.00
136   0.527414        1                 1              1.00
137   0.525498        1                 1              1.00
138   0.529567        1                 1              1.00
139   0.528889        1                 1              1.00
140   0.532827        1                 1              1.00
141   0.530800        1                 1              1.00
142   0.527343        1                 1              1.00
143   0.537283        2                 2              1.00
144   0.528617        1                 1              1.00
145   0.531930        1                 1              1.00
146   0.502517        0                 0              1.00
147   0.530121        1                 1              1.00
148   0.535905        2                 2              1.00
149   0.528370        1                 1              1.00
150   0.529217        1                 1              1.00
151   0.527594        1                 1              1.00
152   0.532506        1                 1              1.00
153   0.529622        1                 1              1.00
154   0.532289        1                 1              1.00
155   0.529803        1                 1              1.00
156   0.525067        0                 0              0.63
157   0.529581        1                 1              1.00
158   0.530965        1                 1              1.00
159   0.532740        1                 1              1.00
160   0.533887        1                 1              1.00
161   0.526127        1                 1              1.00
162   0.529075        1                 1              1.00
163   0.528344        1                 1              1.00
164   0.529673        1                 1              1.00
165   0.533894        1                 1              1.00
166   0.533430        1                 1              1.00
167   0.527238        1                 1              1.00
168   0.537060        2                 2              1.00
169   0.527879        1                 1              1.00
170   0.528494        1                 1              1.00

Y_Quality  Y_Class  prediction_label  prediction_score
119   0.536183        2                 2            0.9969
120   0.528917        1                 1            0.9998
121   0.532144        1                 1            0.9998
122   0.535622        2                 2            0.9935
123   0.530411        1                 1            0.9998
124   0.531835        1                 1            0.9998
125   0.528822        1                 1            0.9998
126   0.531992        1                 1            0.9998
127   0.532191        1                 1            0.9998
128   0.527929        1                 1            0.9997
129   0.529013        1                 1            0.9998
130   0.527629        1                 1            0.9997
131   0.529746        1                 1            0.9998
132   0.526810        1                 1            0.9994
133   0.523386        0                 0            0.9956
134   0.529308        1                 1            0.9998
135   0.533017        1                 1            0.9997
136   0.527414        1                 1            0.9997
137   0.525498        1                 1            0.9962
138   0.529567        1                 1            0.9998
139   0.528889        1                 1            0.9998
140   0.532827        1                 1            0.9998
141   0.530800        1                 1            0.9998
142   0.527343        1                 1            0.9997
143   0.537283        2                 2            0.9972
144   0.528617        1                 1            0.9998
145   0.531930        1                 1            0.9998
146   0.502517        0                 0            0.9949
147   0.530121        1                 1            0.9998
148   0.535905        2                 2            0.9969
149   0.528370        1                 1            0.9997
150   0.529217        1                 1            0.9998
151   0.527594        1                 1            0.9997
152   0.532506        1                 1            0.9998
153   0.529622        1                 1            0.9998
154   0.532289        1                 1            0.9998
155   0.529803        1                 1            0.9998
156   0.525067        0                 0            0.9813
157   0.529581        1                 1            0.9998
158   0.530965        1                 1            0.9998
159   0.532740        1                 1            0.9998
160   0.533887        1                 1            0.9995
161   0.526127        1                 1            0.9989
162   0.529075        1                 1            0.9998
163   0.528344        1                 1            0.9997
164   0.529673        1                 1            0.9998
165   0.533894        1                 1            0.9995
166   0.533430        1                 1            0.9996
167   0.527238        1                 1            0.9997
168   0.537060        2                 2            0.9972
169   0.527879        1                 1            0.9997
170   0.528494        1                 1            0.9998

Y_Quality  Y_Class  prediction_label  prediction_score
119   0.536183        2                 2            0.9664
120   0.528917        1                 1            0.9982
121   0.532144        1                 1            0.9982
122   0.535622        2                 2            0.9664
123   0.530411        1                 1            0.9982
124   0.531835        1                 1            0.9982
125   0.528822        1                 1            0.9982
126   0.531992        1                 1            0.9982
127   0.532191        1                 1            0.9982
128   0.527929        1                 1            0.9982
129   0.529013        1                 1            0.9982
130   0.527629        1                 1            0.9961
131   0.529746        1                 1            0.9982
132   0.526810        1                 1            0.9825
133   0.523386        0                 0            0.9534
134   0.529308        1                 1            0.9982
135   0.533017        1                 1            0.9963
136   0.527414        1                 1            0.9921
137   0.525498        1                 1            0.9635
138   0.529567        1                 1            0.9982
139   0.528889        1                 1            0.9982
140   0.532827        1                 1            0.9981
141   0.530800        1                 1            0.9982
142   0.527343        1                 1            0.9921
143   0.537283        2                 2            0.9664
144   0.528617        1                 1            0.9982
145   0.531930        1                 1            0.9982
146   0.502517        0                 0            0.9534
147   0.530121        1                 1            0.9982
148   0.535905        2                 2            0.9664
149   0.528370        1                 1            0.9982
150   0.529217        1                 1            0.9982
151   0.527594        1                 1            0.9961
152   0.532506        1                 1            0.9982
153   0.529622        1                 1            0.9982
154   0.532289        1                 1            0.9982
155   0.529803        1                 1            0.9982
156   0.525067        0                 0            0.9534
157   0.529581        1                 1            0.9982
158   0.530965        1                 1            0.9982
159   0.532740        1                 1            0.9982
160   0.533887        1                 1            0.9877
161   0.526127        1                 1            0.9731
162   0.529075        1                 1            0.9982
163   0.528344        1                 1            0.9982
164   0.529673        1                 1            0.9982
165   0.533894        1                 1            0.9877
166   0.533430        1                 1            0.9899
167   0.527238        1                 1            0.9890
168   0.537060        2                 2            0.9664
169   0.527879        1                 1            0.9982
170   0.528494        1                 1            0.9982

Y_Quality  Y_Class  prediction_label  prediction_score
119   0.536183        2                 2               1.0
120   0.528917        1                 1               1.0
121   0.532144        1                 1               1.0
122   0.535622        2                 2               1.0
123   0.530411        1                 1               1.0
124   0.531835        1                 1               1.0
125   0.528822        1                 1               1.0
126   0.531992        1                 1               1.0
127   0.532191        1                 1               1.0
128   0.527929        1                 1               1.0
129   0.529013        1                 1               1.0
130   0.527629        1                 1               1.0
131   0.529746        1                 1               1.0
132   0.526810        1                 1               1.0
133   0.523386        0                 0               1.0
134   0.529308        1                 1               1.0
135   0.533017        1                 1               1.0
136   0.527414        1                 1               1.0
137   0.525498        1                 1               1.0
138   0.529567        1                 1               1.0
139   0.528889        1                 1               1.0
140   0.532827        1                 1               1.0
141   0.530800        1                 1               1.0
142   0.527343        1                 1               1.0
143   0.537283        2                 2               1.0
144   0.528617        1                 1               1.0
145   0.531930        1                 1               1.0
146   0.502517        0                 0               1.0
147   0.530121        1                 1               1.0
148   0.535905        2                 2               1.0
149   0.528370        1                 1               1.0
150   0.529217        1                 1               1.0
151   0.527594        1                 1               1.0
152   0.532506        1                 1               1.0
153   0.529622        1                 1               1.0
154   0.532289        1                 1               1.0
155   0.529803        1                 1               1.0
156   0.525067        0                 0               1.0
157   0.529581        1                 1               1.0
158   0.530965        1                 1               1.0
159   0.532740        1                 1               1.0
160   0.533887        1                 1               1.0
161   0.526127        1                 1               1.0
162   0.529075        1                 1               1.0
163   0.528344        1                 1               1.0
164   0.529673        1                 1               1.0
165   0.533894        1                 1               1.0
166   0.533430        1                 1               1.0
167   0.527238        1                 1               1.0
168   0.537060        2                 2               1.0
169   0.527879        1                 1               1.0
170   0.528494        1                 1               1.0

In [105]:
T1003062_final_classification_model = finalize_model(T01_model_gbc)

T1003062_prediction = predict_model(T1003062_final_classification_model, data=T1003062_datas)

T1003062_prediction = pd.DataFrame(T1003062_prediction, columns = ['prediction_label'])

T1003062_y_class = pd.DataFrame(T1003062_class, columns = ['Y_Class'])
T1003062_idx = T1003062_y_class.index
T1003062_y_class = T1003062_y_class.reset_index()
T1003062_prediction = pd.concat([T1003062_prediction, T1003062_y_class], axis = 1)
T1003062_prediction = T1003062_prediction.set_index('index')
T1003062_prediction.drop(['Y_Class'], axis = 1, inplace = True)

# 8

In [106]:
T1003063.drop(['index'], inplace = True, axis = 1)

In [107]:
T1003063_class = T1003063['Y_Class']
T1003063_target = T1003063['Y_Quality']
T1003063_data = T1003063.drop(['Y_Class', 'Y_Quality'], axis = 1)

In [108]:
T1003063c = T1003063_data.columns
T1003063scaler = RobustScaler()
T1003063scaled = T1003063scaler.fit_transform(T1003063_data)
T1003063_data = pd.DataFrame(T1003063scaled, columns = T1003063c)

T1003063_y_class = pd.DataFrame(T1003063_target, columns = ['Y_Quality'])
T1003063_idx = T1003063_y_class.index
T1003063_y_class = T1003063_y_class.reset_index()
T1003063_data = pd.concat([T1003063_data, T1003063_y_class], axis = 1)
T1003063_data = T1003063_data.set_index('index')
T1003063_data.drop(['Y_Quality'], axis = 1, inplace = True)
T1003063_data

PRODUCT_CODE  X_1       X_2  X_7      X_11  X_12      X_13  X_16  X_17  \
index                                                                           
0               0.0  0.0  0.333333  0.0  0.000000   0.0 -0.050847   1.0   1.0   
1               0.0  0.0  0.000000  0.0 -0.042553   0.0  0.000000   0.0   0.0   
2               0.0  1.0 -0.666667  1.0  0.957447   1.0  0.949153   0.0   0.0   
3               0.0  0.0  0.333333  0.0  0.000000   0.0 -0.050847   1.0   1.0   
4               0.0  0.0  0.000000  0.0 -0.042553   0.0  0.000000   0.0   0.0   
5               0.0  1.0 -0.666667  1.0  0.957447   1.0  0.949153   0.0   0.0   
6               0.0  0.0  0.333333  0.0  0.000000   0.0 -0.050847   1.0   1.0   
7               0.0  0.0  0.000000  0.0 -0.042553   0.0  0.000000   0.0   0.0   
8               0.0  1.0 -0.666667  1.0  0.957447   1.0  0.949153   0.0   0.0   
9               0.0  0.0  0.333333  0.0  0.000000   0.0 -0.050847   1.0   1.0   
10              0.0  0.0  0.000000  0.0 -0.042553   0.0  0.000000   0.0   0.0   
11              0.0  1.0 -0.666667  1.0  0.957447   1.0  0.949153   0.0   0.0   
12              0.0  0.0  0.333333  0.0  0.000000   0.0 -0.050847   1.0   1.0   
13              0.0  0.0  0.000000  0.0 -0.042553   0.0  0.000000   0.0   0.0   
14              0.0  1.0 -0.666667  1.0  0.957447   1.0  0.949153   0.0   0.0   

       X_18  ...     X_924     X_925     X_926     X_927  X_928     X_929  \
index        ...                                                            
0       0.0  ...  0.000000 -0.372727 -0.372265  0.000000    1.0  0.000000   
1       0.0  ... -0.447964  0.000000  0.000000 -0.326531    0.0  0.010687   
2       0.0  ...  0.552036  0.627273  0.627735  0.673469    0.0 -0.989313   
3       0.0  ...  0.000000 -0.372727 -0.372265  0.000000    1.0  0.000000   
4       0.0  ... -0.447964  0.000000  0.000000 -0.326531    0.0  0.010687   
5       0.0  ...  0.552036  0.627273  0.627735  0.673469    0.0 -0.989313   
6       0.0  ...  0.000000 -0.372727 -0.372265  0.000000    1.0  0.000000   
7       0.0  ... -0.447964  0.000000  0.000000 -0.326531    0.0  0.010687   
8       0.0  ...  0.552036  0.627273  0.627735  0.673469    0.0 -0.989313   
9       0.0  ...  0.000000 -0.372727 -0.372265  0.000000    1.0  0.000000   
10      0.0  ... -0.447964  0.000000  0.000000 -0.326531    0.0  0.010687   
11      0.0  ...  0.552036  0.627273  0.627735  0.673469    0.0 -0.989313   
12      0.0  ...  0.000000 -0.372727 -0.372265  0.000000    1.0  0.000000   
13      0.0  ... -0.447964  0.000000  0.000000 -0.326531    0.0  0.010687   
14      0.0  ...  0.552036  0.627273  0.627735  0.673469    0.0 -0.989313   

       X_930  X_931     X_932  X_933  
index                                 
0        0.0    0.0  0.198276    1.0  
1        0.0    0.0  0.000000    0.0  
2       -1.0   -1.0 -0.801724    0.0  
3        0.0    0.0  0.198276    1.0  
4        0.0    0.0  0.000000    0.0  
5       -1.0   -1.0 -0.801724    0.0  
6        0.0    0.0  0.198276    1.0  
7        0.0    0.0  0.000000    0.0  
8       -1.0   -1.0 -0.801724    0.0  
9        0.0    0.0  0.198276    1.0  
10       0.0    0.0  0.000000    0.0  
11      -1.0   -1.0 -0.801724    0.0  
12       0.0    0.0  0.198276    1.0  
13       0.0    0.0  0.000000    0.0  
14      -1.0   -1.0 -0.801724    0.0  

[15 rows x 445 columns]

In [109]:
#13
from pycaret.regression import *
setup_rgs = setup(data = T1003063_data, target = T1003063_target, session_id = 4)
top5 = compare_models(sort='MSE', n_select=5)

Processing:   0%|          | 0/89 [00:00<?, ?it/s]

In [110]:
T10_total_models = []

T10_model_lightgbm = create_model('lightgbm', fold = 5)
T10_total_models.append(T10_model_lightgbm)

T10_model_rf = create_model('rf', fold = 5)
T10_total_models.append(T10_model_rf)

T10_model_gbr = create_model('gbr', fold = 5)
T10_total_models.append(T10_model_gbr)

T10_model_et = create_model('et', fold = 5)
T10_total_models.append(T10_model_et)

T10_model_catboost = create_model('catboost', fold = 5)
T10_total_models.append(T10_model_catboost)

T10_model_xgb = create_model('xgboost', fold = 5)
T10_total_models.append(T10_model_xgb)

T10_model_ada = create_model('ada', fold = 5)

T10_total_models.append(T10_model_ada)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [111]:
T10_model_lightgbm = tune_model(T10_model_lightgbm, fold=5, choose_better = True)

T10_model_rf = tune_model(T10_model_rf, fold=5, choose_better = True)

T10_model_gbr = tune_model(T10_model_gbr, fold=5, choose_better = True)

T10_model_et = tune_model(T10_model_et, fold=5, choose_better = True)

T10_model_catboost = tune_model(T10_model_catboost, fold=5, choose_better = True)

T10_model_xgb = tune_model(T10_model_xgb, fold=5, choose_better = True)

T10_model_ada = tune_model(T10_model_ada, fold=5, choose_better = True)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

...

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


In [112]:
T10_tuned_models = [T10_model_lightgbm, T10_model_rf, T10_model_gbr, T10_model_et, T10_model_catboost, T10_model_xgb, T10_model_ada]

for model in T10_tuned_models:
    display(predict_model(model))

PRODUCT_CODE  X_1       X_2  X_7      X_11  X_12      X_13  X_16  X_17  \
10           0.0  0.0  0.333333  0.0  0.000000   0.0 -0.050847   1.0   1.0   
11           0.0  0.0  0.333333  0.0  0.000000   0.0 -0.050847   1.0   1.0   
12           0.0  0.0  0.333333  0.0  0.000000   0.0 -0.050847   1.0   1.0   
13           0.0  0.0  0.333333  0.0  0.000000   0.0 -0.050847   1.0   1.0   
14           0.0  0.0  0.000000  0.0 -0.042553   0.0  0.000000   0.0   0.0   

    X_18  ...     X_926     X_927  X_928     X_929  X_930  X_931     X_932  \
10   0.0  ... -0.372265  0.000000    1.0  0.000000    0.0    0.0  0.198276   
11   0.0  ... -0.372265  0.000000    1.0  0.000000    0.0    0.0  0.198276   
12   0.0  ... -0.372265  0.000000    1.0  0.000000    0.0    0.0  0.198276   
13   0.0  ... -0.372265  0.000000    1.0  0.000000    0.0    0.0  0.198276   
14   0.0  ...  0.000000 -0.326531    0.0  0.010687    0.0    0.0  0.000000   

    X_933  Y_Quality  prediction_label  
10    1.0   0.534951          0.534428  
11    1.0   0.534951          0.534428  
12    1.0   0.534951          0.534428  
13    1.0   0.534951          0.534428  
14    0.0   0.535205          0.534428  

[5 rows x 447 columns]

PRODUCT_CODE  X_1       X_2  X_7      X_11  X_12      X_13  X_16  X_17  \
10           0.0  0.0  0.333333  0.0  0.000000   0.0 -0.050847   1.0   1.0   
11           0.0  0.0  0.333333  0.0  0.000000   0.0 -0.050847   1.0   1.0   
12           0.0  0.0  0.333333  0.0  0.000000   0.0 -0.050847   1.0   1.0   
13           0.0  0.0  0.333333  0.0  0.000000   0.0 -0.050847   1.0   1.0   
14           0.0  0.0  0.000000  0.0 -0.042553   0.0  0.000000   0.0   0.0   

    X_18  ...     X_926     X_927  X_928     X_929  X_930  X_931     X_932  \
10   0.0  ... -0.372265  0.000000    1.0  0.000000    0.0    0.0  0.198276   
11   0.0  ... -0.372265  0.000000    1.0  0.000000    0.0    0.0  0.198276   
12   0.0  ... -0.372265  0.000000    1.0  0.000000    0.0    0.0  0.198276   
13   0.0  ... -0.372265  0.000000    1.0  0.000000    0.0    0.0  0.198276   
14   0.0  ...  0.000000 -0.326531    0.0  0.010687    0.0    0.0  0.000000   

    X_933  Y_Quality  prediction_label  
10    1.0   0.534951          0.534985  
11    1.0   0.534951          0.534985  
12    1.0   0.534951          0.534985  
13    1.0   0.534951          0.534985  
14    0.0   0.535205          0.535190  

[5 rows x 447 columns]

PRODUCT_CODE  X_1       X_2  X_7      X_11  X_12      X_13  X_16  X_17  \
10           0.0  0.0  0.333333  0.0  0.000000   0.0 -0.050847   1.0   1.0   
11           0.0  0.0  0.333333  0.0  0.000000   0.0 -0.050847   1.0   1.0   
12           0.0  0.0  0.333333  0.0  0.000000   0.0 -0.050847   1.0   1.0   
13           0.0  0.0  0.333333  0.0  0.000000   0.0 -0.050847   1.0   1.0   
14           0.0  0.0  0.000000  0.0 -0.042553   0.0  0.000000   0.0   0.0   

    X_18  ...     X_926     X_927  X_928     X_929  X_930  X_931     X_932  \
10   0.0  ... -0.372265  0.000000    1.0  0.000000    0.0    0.0  0.198276   
11   0.0  ... -0.372265  0.000000    1.0  0.000000    0.0    0.0  0.198276   
12   0.0  ... -0.372265  0.000000    1.0  0.000000    0.0    0.0  0.198276   
13   0.0  ... -0.372265  0.000000    1.0  0.000000    0.0    0.0  0.198276   
14   0.0  ...  0.000000 -0.326531    0.0  0.010687    0.0    0.0  0.000000   

    X_933  Y_Quality  prediction_label  
10    1.0   0.534951          0.534951  
11    1.0   0.534951          0.534951  
12    1.0   0.534951          0.534951  
13    1.0   0.534951          0.534951  
14    0.0   0.535205          0.535205  

[5 rows x 447 columns]

PRODUCT_CODE  X_1       X_2  X_7      X_11  X_12      X_13  X_16  X_17  \
10           0.0  0.0  0.333333  0.0  0.000000   0.0 -0.050847   1.0   1.0   
11           0.0  0.0  0.333333  0.0  0.000000   0.0 -0.050847   1.0   1.0   
12           0.0  0.0  0.333333  0.0  0.000000   0.0 -0.050847   1.0   1.0   
13           0.0  0.0  0.333333  0.0  0.000000   0.0 -0.050847   1.0   1.0   
14           0.0  0.0  0.000000  0.0 -0.042553   0.0  0.000000   0.0   0.0   

    X_18  ...     X_926     X_927  X_928     X_929  X_930  X_931     X_932  \
10   0.0  ... -0.372265  0.000000    1.0  0.000000    0.0    0.0  0.198276   
11   0.0  ... -0.372265  0.000000    1.0  0.000000    0.0    0.0  0.198276   
12   0.0  ... -0.372265  0.000000    1.0  0.000000    0.0    0.0  0.198276   
13   0.0  ... -0.372265  0.000000    1.0  0.000000    0.0    0.0  0.198276   
14   0.0  ...  0.000000 -0.326531    0.0  0.010687    0.0    0.0  0.000000   

    X_933  Y_Quality  prediction_label  
10    1.0   0.534951          0.534951  
11    1.0   0.534951          0.534951  
12    1.0   0.534951          0.534951  
13    1.0   0.534951          0.534951  
14    0.0   0.535205          0.535205  

[5 rows x 447 columns]

PRODUCT_CODE  X_1       X_2  X_7      X_11  X_12      X_13  X_16  X_17  \
10           0.0  0.0  0.333333  0.0  0.000000   0.0 -0.050847   1.0   1.0   
11           0.0  0.0  0.333333  0.0  0.000000   0.0 -0.050847   1.0   1.0   
12           0.0  0.0  0.333333  0.0  0.000000   0.0 -0.050847   1.0   1.0   
13           0.0  0.0  0.333333  0.0  0.000000   0.0 -0.050847   1.0   1.0   
14           0.0  0.0  0.000000  0.0 -0.042553   0.0  0.000000   0.0   0.0   

    X_18  ...     X_926     X_927  X_928     X_929  X_930  X_931     X_932  \
10   0.0  ... -0.372265  0.000000    1.0  0.000000    0.0    0.0  0.198276   
11   0.0  ... -0.372265  0.000000    1.0  0.000000    0.0    0.0  0.198276   
12   0.0  ... -0.372265  0.000000    1.0  0.000000    0.0    0.0  0.198276   
13   0.0  ... -0.372265  0.000000    1.0  0.000000    0.0    0.0  0.198276   
14   0.0  ...  0.000000 -0.326531    0.0  0.010687    0.0    0.0  0.000000   

    X_933  Y_Quality  prediction_label  
10    1.0   0.534951          0.534951  
11    1.0   0.534951          0.534951  
12    1.0   0.534951          0.534951  
13    1.0   0.534951          0.534951  
14    0.0   0.535205          0.535205  

[5 rows x 447 columns]

PRODUCT_CODE  X_1       X_2  X_7      X_11  X_12      X_13  X_16  X_17  \
10           0.0  0.0  0.333333  0.0  0.000000   0.0 -0.050847   1.0   1.0   
11           0.0  0.0  0.333333  0.0  0.000000   0.0 -0.050847   1.0   1.0   
12           0.0  0.0  0.333333  0.0  0.000000   0.0 -0.050847   1.0   1.0   
13           0.0  0.0  0.333333  0.0  0.000000   0.0 -0.050847   1.0   1.0   
14           0.0  0.0  0.000000  0.0 -0.042553   0.0  0.000000   0.0   0.0   

    X_18  ...     X_926     X_927  X_928     X_929  X_930  X_931     X_932  \
10   0.0  ... -0.372265  0.000000    1.0  0.000000    0.0    0.0  0.198276   
11   0.0  ... -0.372265  0.000000    1.0  0.000000    0.0    0.0  0.198276   
12   0.0  ... -0.372265  0.000000    1.0  0.000000    0.0    0.0  0.198276   
13   0.0  ... -0.372265  0.000000    1.0  0.000000    0.0    0.0  0.198276   
14   0.0  ...  0.000000 -0.326531    0.0  0.010687    0.0    0.0  0.000000   

    X_933  Y_Quality  prediction_label  
10    1.0   0.534951          0.534848  
11    1.0   0.534951          0.534848  
12    1.0   0.534951          0.534848  
13    1.0   0.534951          0.534848  
14    0.0   0.535205          0.534848  

[5 rows x 447 columns]

PRODUCT_CODE  X_1       X_2  X_7      X_11  X_12      X_13  X_16  X_17  \
10           0.0  0.0  0.333333  0.0  0.000000   0.0 -0.050847   1.0   1.0   
11           0.0  0.0  0.333333  0.0  0.000000   0.0 -0.050847   1.0   1.0   
12           0.0  0.0  0.333333  0.0  0.000000   0.0 -0.050847   1.0   1.0   
13           0.0  0.0  0.333333  0.0  0.000000   0.0 -0.050847   1.0   1.0   
14           0.0  0.0  0.000000  0.0 -0.042553   0.0  0.000000   0.0   0.0   

    X_18  ...     X_926     X_927  X_928     X_929  X_930  X_931     X_932  \
10   0.0  ... -0.372265  0.000000    1.0  0.000000    0.0    0.0  0.198276   
11   0.0  ... -0.372265  0.000000    1.0  0.000000    0.0    0.0  0.198276   
12   0.0  ... -0.372265  0.000000    1.0  0.000000    0.0    0.0  0.198276   
13   0.0  ... -0.372265  0.000000    1.0  0.000000    0.0    0.0  0.198276   
14   0.0  ...  0.000000 -0.326531    0.0  0.010687    0.0    0.0  0.000000   

    X_933  Y_Quality  prediction_label  
10    1.0   0.534951          0.533702  
11    1.0   0.534951          0.533702  
12    1.0   0.534951          0.533702  
13    1.0   0.534951          0.533702  
14    0.0   0.535205          0.535205  

[5 rows x 447 columns]

In [113]:
T1003063_final_regression_model = finalize_model(T10_model_gbr)

T1003063_prediction = predict_model(T1003063_final_regression_model, data=T1003063_data)
T1003063_prediction

T1003063_datas = T1003063_prediction['prediction_label']
T1003063_datas = pd.DataFrame(T1003063_datas.values, columns = ['Y_Quality'])

T1003063y_idx= T1003063_class.index
T1003063y_idx = pd.DataFrame(T1003063y_idx, columns = ['index'])
T1003063_datas = pd.concat([T1003063y_idx, T1003063_datas], axis = 1)
T1003063_datas = T1003063_datas.set_index('index')
T1003063_datas

Y_Quality
index           
0       0.534951
1       0.535205
2       0.533702
3       0.534951
4       0.535205
5       0.533702
6       0.534951
7       0.535205
8       0.533702
9       0.534951
10      0.535205
11      0.533702
12      0.534951
13      0.535205
14      0.533702

In [114]:
from pycaret.classification import *
# 분류 패키지의 모든 모듈을 임포트한다.
exp_clf101 = setup(data=T1003063_datas, 
                   target=T1003063_class, 
                   fold=5,
                   session_id=4)
top5 = compare_models(sort='Accuracy', n_select=5)

Processing:   0%|          | 0/73 [00:00<?, ?it/s]

In [115]:
T10_total_models = []

T10_model_lightgbm = create_model('lightgbm', fold = 5)
T10_total_models.append(T10_model_lightgbm)

T10_model_rf = create_model('rf', fold = 5)
T10_total_models.append(T10_model_rf)

T10_model_gbc = create_model('gbc', fold = 5)
T10_total_models.append(T10_model_gbc)

T10_model_et = create_model('et', fold = 5)
T10_total_models.append(T10_model_et)

T10_model_catboost = create_model('catboost', fold = 5)
T10_total_models.append(T10_model_catboost)

T10_model_xgb = create_model('xgboost', fold = 5)
T10_total_models.append(T10_model_xgb)

T10_model_ada = create_model('ada', fold = 5)

T10_total_models.append(T10_model_ada)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [116]:
T10_model_lightgbm = tune_model(T10_model_lightgbm, fold=5, choose_better = True)

T10_model_rf = tune_model(T10_model_rf, fold=5, choose_better = True)

T10_model_gbc = tune_model(T10_model_gbc, fold=5, choose_better = True)

T10_model_et = tune_model(T10_model_et, fold=5, choose_better = True)

T10_model_catboost = tune_model(T10_model_catboost, fold=5, choose_better = True)

T10_model_xgb = tune_model(T10_model_xgb, fold=5, choose_better = True)

T10_model_ada = tune_model(T10_model_ada, fold=5, choose_better = True)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

...

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


In [117]:
T10_tuned_models = [T10_model_lightgbm, T10_model_rf, T10_model_gbc, T10_model_et, T10_model_catboost, T10_model_xgb, T10_model_ada]

for model in T10_tuned_models:
    display(predict_model(model))

Y_Quality  Y_Class  prediction_label  prediction_score
10   0.534951        2                 2               0.7
11   0.533702        1                 2               0.7
12   0.535205        2                 2               0.7
13   0.533702        1                 2               0.7
14   0.534951        2                 2               0.7

Y_Quality  Y_Class  prediction_label  prediction_score
10   0.534951        2                 2              1.00
11   0.533702        1                 1              0.96
12   0.535205        2                 2              1.00
13   0.533702        1                 1              0.96
14   0.534951        2                 2              1.00

Y_Quality  Y_Class  prediction_label  prediction_score
10   0.534951        2                 2               1.0
11   0.533702        1                 1               1.0
12   0.535205        2                 2               1.0
13   0.533702        1                 1               1.0
14   0.534951        2                 2               1.0

Y_Quality  Y_Class  prediction_label  prediction_score
10   0.534951        2                 2               1.0
11   0.533702        1                 1               1.0
12   0.535205        2                 2               1.0
13   0.533702        1                 1               1.0
14   0.534951        2                 2               1.0

Y_Quality  Y_Class  prediction_label  prediction_score
10   0.534951        2                 2            0.8940
11   0.533702        1                 1            0.8683
12   0.535205        2                 2            0.9089
13   0.533702        1                 1            0.8683
14   0.534951        2                 2            0.8940

Y_Quality  Y_Class  prediction_label  prediction_score
10   0.534951        2                 2            0.6752
11   0.533702        1                 2            0.6752
12   0.535205        2                 2            0.7372
13   0.533702        1                 2            0.6752
14   0.534951        2                 2            0.6752

Y_Quality  Y_Class  prediction_label  prediction_score
10   0.534951        2                 2               1.0
11   0.533702        1                 1               1.0
12   0.535205        2                 2               1.0
13   0.533702        1                 1               1.0
14   0.534951        2                 2               1.0

In [118]:
T1003063_final_classification_model = finalize_model(T10_model_gbc)

T1003063_prediction = predict_model(T1003063_final_classification_model, data=T1003063_datas)

T1003063_prediction = pd.DataFrame(T1003063_prediction, columns = ['prediction_label'])

T1003063_y_class = pd.DataFrame(T1003063_class, columns = ['Y_Class'])
T1003063_idx = T1003063_y_class.index
T1003063_y_class = T1003063_y_class.reset_index()
T1003063_prediction = pd.concat([T1003063_prediction, T1003063_y_class], axis = 1)
T1003063_prediction = T1003063_prediction.set_index('index')
T1003063_prediction.drop(['Y_Class'], axis = 1, inplace = True)

# Test

In [155]:
test_data = pd.read_csv("./test.csv")
test_data

PRODUCT_ID         TIMESTAMP     LINE PRODUCT_CODE  X_1   X_2  X_3   X_4  \
0     TEST_000   2022-09-09 2:01  T100306         T_31  2.0  94.0  0.0  45.0   
1     TEST_001   2022-09-09 2:09  T100304         T_31  2.0  93.0  0.0  45.0   
2     TEST_002   2022-09-09 8:42  T100304         T_31  2.0  95.0  0.0  45.0   
3     TEST_003  2022-09-09 10:56  T010305         A_31  NaN   NaN  NaN   NaN   
4     TEST_004  2022-09-09 11:04  T010306         A_31  NaN   NaN  NaN   NaN   
..         ...               ...      ...          ...  ...   ...  ...   ...   
305   TEST_305  2022-11-05 11:18  T100306         T_31  2.0  91.0  0.0  45.0   
306   TEST_306  2022-11-05 16:39  T100304         T_31  2.0  96.0  0.0  45.0   
307   TEST_307  2022-11-05 16:47  T100306         T_31  2.0  91.0  0.0  45.0   
308   TEST_308  2022-11-05 20:53  T100306         T_31  2.0  95.0  0.0  45.0   
309   TEST_309  2022-11-05 21:01  T100306         T_31  2.0  87.0  0.0  45.0   

      X_5  X_6  ...  X_2866  X_2867  X_2868  X_2869  X_2870  X_2871  X_2872  \
0    10.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
1    11.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
2    11.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
3     NaN  NaN  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
4     NaN  NaN  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
..    ...  ...  ...     ...     ...     ...     ...     ...     ...     ...   
305  10.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
306  11.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
307  10.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
308  10.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
309  10.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   

     X_2873  X_2874  X_2875  
0       NaN     NaN     NaN  
1       NaN     NaN     NaN  
2       NaN     NaN     NaN  
3       NaN     NaN     NaN  
4       NaN     NaN     NaN  
..      ...     ...     ...  
305     NaN     NaN     NaN  
306     NaN     NaN     NaN  
307     NaN     NaN     NaN  
308     NaN     NaN     NaN  
309     NaN     NaN     NaN  

[310 rows x 2879 columns]

In [156]:
test_data['YEAR'] =  pd.to_datetime(test_data['TIMESTAMP']).dt.year
test_data['MONTH'] =  pd.to_datetime(test_data['TIMESTAMP']).dt.month
test_data['DAY'] =  pd.to_datetime(test_data['TIMESTAMP']).dt.day
test_data['HOUR'] =  pd.to_datetime(test_data['TIMESTAMP']).dt.hour
test_data['MINUTE'] =  pd.to_datetime(test_data['TIMESTAMP']).dt.minute
test_data['DAY_OF_WEEK'] =  pd.to_datetime(test_data['TIMESTAMP']).dt.day_name()

In [157]:
test_data = test_data.drop(['MONTH', 'DAY', 'YEAR', 'MINUTE', 'HOUR', 'DAY_OF_WEEK'], axis = 1)

In [158]:
test_data.drop(colls, inplace = True, axis = 1)

In [159]:
#test_data.loc[test_data.DAY_OF_WEEK == 'Monday','DAY_OF_WEEK'] = 1
#test_data.loc[test_data.DAY_OF_WEEK == 'Tuesday','DAY_OF_WEEK'] = 2
#test_data.loc[test_data.DAY_OF_WEEK == 'Wednesday','DAY_OF_WEEK'] = 3
#test_data.loc[test_data.DAY_OF_WEEK == 'Thursday','DAY_OF_WEEK'] = 4
#test_data.loc[test_data.DAY_OF_WEEK == 'Friday','DAY_OF_WEEK'] = 5
#test_data.loc[test_data.DAY_OF_WEEK == 'Saturday','DAY_OF_WEEK'] = 6
#test_data.loc[test_data.DAY_OF_WEEK == 'Sunday','DAY_OF_WEEK'] = 7

test_data.loc[test_data.PRODUCT_CODE == 'A_31','PRODUCT_CODE'] = 1
test_data.loc[test_data.PRODUCT_CODE == 'T_31','PRODUCT_CODE'] = 2
test_data.loc[test_data.PRODUCT_CODE == 'O_31','PRODUCT_CODE'] = 3

test_data.drop(['PRODUCT_ID', 'TIMESTAMP'], axis = 1, inplace = True)
test_data

LINE PRODUCT_CODE  X_1   X_2  X_3   X_4   X_5  X_6   X_7   X_8  ...  \
0    T100306            2  2.0  94.0  0.0  45.0  10.0  0.0  51.0  10.0  ...   
1    T100304            2  2.0  93.0  0.0  45.0  11.0  0.0  45.0  10.0  ...   
2    T100304            2  2.0  95.0  0.0  45.0  11.0  0.0  45.0  10.0  ...   
3    T010305            1  NaN   NaN  NaN   NaN   NaN  NaN   NaN   NaN  ...   
4    T010306            1  NaN   NaN  NaN   NaN   NaN  NaN   NaN   NaN  ...   
..       ...          ...  ...   ...  ...   ...   ...  ...   ...   ...  ...   
305  T100306            2  2.0  91.0  0.0  45.0  10.0  0.0  51.0  10.0  ...   
306  T100304            2  2.0  96.0  0.0  45.0  11.0  0.0  45.0  10.0  ...   
307  T100306            2  2.0  91.0  0.0  45.0  10.0  0.0  50.0  10.0  ...   
308  T100306            2  2.0  95.0  0.0  45.0  10.0  0.0  51.0  10.0  ...   
309  T100306            2  2.0  87.0  0.0  45.0  10.0  0.0  51.0  10.0  ...   

     X_2862  X_2863      X_2864  X_2865  X_2866  X_2867  X_2868  X_2869  \
0       NaN     NaN         NaN     NaN     NaN     NaN     NaN     NaN   
1       NaN     NaN         NaN     NaN     NaN     NaN     NaN     NaN   
2       NaN     NaN         NaN     NaN     NaN     NaN     NaN     NaN   
3     183.8   467.0  444.192308   423.0     NaN     NaN     NaN     NaN   
4     179.7   465.0  443.211539   423.0     NaN     NaN     NaN     NaN   
..      ...     ...         ...     ...     ...     ...     ...     ...   
305     NaN     NaN         NaN     NaN     NaN     NaN     NaN     NaN   
306     NaN     NaN         NaN     NaN     NaN     NaN     NaN     NaN   
307     NaN     NaN         NaN     NaN     NaN     NaN     NaN     NaN   
308     NaN     NaN         NaN     NaN     NaN     NaN     NaN     NaN   
309     NaN     NaN         NaN     NaN     NaN     NaN     NaN     NaN   

     X_2870  X_2871  
0       NaN     NaN  
1       NaN     NaN  
2       NaN     NaN  
3       NaN     NaN  
4       NaN     NaN  
..      ...     ...  
305     NaN     NaN  
306     NaN     NaN  
307     NaN     NaN  
308     NaN     NaN  
309     NaN     NaN  

[310 rows x 2795 columns]

In [160]:
TT0503041 = test_data[(test_data['LINE'] == 'T050304') & (test_data['PRODUCT_CODE'] == 1)]
TT0503042 = test_data[(test_data['LINE'] == 'T050304') & (test_data['PRODUCT_CODE'] == 2)]
TT0503043 = test_data[(test_data['LINE'] == 'T050304') & (test_data['PRODUCT_CODE'] == 3)]

TT0503071 = test_data[(test_data['LINE'] == 'T050307') & (test_data['PRODUCT_CODE'] == 1)]
TT0503072 = test_data[(test_data['LINE'] == 'T050307') & (test_data['PRODUCT_CODE'] == 2)]
TT0503073 = test_data[(test_data['LINE'] == 'T050307') & (test_data['PRODUCT_CODE'] == 3)]

TT0103051 = test_data[(test_data['LINE'] == 'T010305') & (test_data['PRODUCT_CODE'] == 1)]
TT0103052 = test_data[(test_data['LINE'] == 'T010305') & (test_data['PRODUCT_CODE'] == 2)]
TT0103053 = test_data[(test_data['LINE'] == 'T010305') & (test_data['PRODUCT_CODE'] == 3)]

TT0103061 = test_data[(test_data['LINE'] == 'T010306') & (test_data['PRODUCT_CODE'] == 1)]
TT0103062 = test_data[(test_data['LINE'] == 'T010306') & (test_data['PRODUCT_CODE'] == 2)]
TT0103063 = test_data[(test_data['LINE'] == 'T010306') & (test_data['PRODUCT_CODE'] == 3)]

TT1003041 = test_data[(test_data['LINE'] == 'T100304') & (test_data['PRODUCT_CODE'] == 1)]
TT1003042 = test_data[(test_data['LINE'] == 'T100304') & (test_data['PRODUCT_CODE'] == 2)]
TT1003043 = test_data[(test_data['LINE'] == 'T100304') & (test_data['PRODUCT_CODE'] == 3)]

TT1003061 = test_data[(test_data['LINE'] == 'T100306') & (test_data['PRODUCT_CODE'] == 1)]
TT1003062 = test_data[(test_data['LINE'] == 'T100306') & (test_data['PRODUCT_CODE'] == 2)]
TT1003063 = test_data[(test_data['LINE'] == 'T100306') & (test_data['PRODUCT_CODE'] == 3)]

In [161]:
TT0503041.drop(T0503041_col, inplace = True, axis = 1)
TT0503071.drop(T0503071_col, inplace = True, axis = 1)
TT0103051.drop(T0103051_col, inplace = True, axis = 1)
TT0103061.drop(T0103061_col, inplace = True, axis = 1)
TT1003042.drop(T1003042_col, inplace = True, axis = 1)
TT1003043.drop(T1003043_col, inplace = True, axis = 1)
TT1003062.drop(T1003062_col, inplace = True, axis = 1)
TT1003063.drop(T1003063_col, inplace = True, axis = 1)

In [162]:
#여기
TT0503041.drop(T0503041x_col, inplace = True, axis = 1)
TT0503071.drop(T0503071x_col, inplace = True, axis = 1)
TT0103051.drop(T0103051x_col, inplace = True, axis = 1)
TT0103061.drop(T0103061x_col, inplace = True, axis = 1)
TT1003042.drop(T1003042x_col, inplace = True, axis = 1)
TT1003043.drop(T1003043x_col, inplace = True, axis = 1)
TT1003062.drop(T1003062x_col, inplace = True, axis = 1)
TT1003063.drop(T1003063x_col, inplace = True, axis = 1)

In [163]:
#TT0503041 = TT0503041.fillna(0)
#TT0503071 = TT0503071.fillna(0)
#TT0103051 = TT0103051.fillna(0)
#TT0103061 = TT0103061.fillna(0)
#TT1003042 = TT1003042.fillna(0)
#TT1003043 = TT1003043.fillna(0)
#TT1003062 = TT1003062.fillna(0)
#TT1003063 = TT1003063.fillna(0)

TT0503041 = TT0503041.fillna(TT0503041.mean())
TT0503071 = TT0503071.fillna(TT0503071.mean())
TT0103051 = TT0103051.fillna(TT0103051.mean())
TT0103061 = TT0103061.fillna(TT0103061.mean())
TT1003042 = TT1003042.fillna(TT1003042.mean())
TT1003043 = TT1003043.fillna(TT1003043.mean())
TT1003062 = TT1003062.fillna(TT1003062.mean())
TT1003063 = TT1003063.fillna(TT1003063.mean())

In [147]:
#여기2
TT0503041.drop(T0503041x_col, inplace = True, axis = 1)
TT0503071.drop(T0503071x_col, inplace = True, axis = 1)
TT0103051.drop(T0103051x_col, inplace = True, axis = 1)
TT0103061.drop(T0103061x_col, inplace = True, axis = 1)
TT1003042.drop(T1003042x_col, inplace = True, axis = 1)
TT1003043.drop(T1003043x_col, inplace = True, axis = 1)
TT1003062.drop(T1003062x_col, inplace = True, axis = 1)
TT1003063.drop(T1003063x_col, inplace = True, axis = 1)

In [164]:
TT0503041.drop(['LINE'], axis = 1, inplace = True)
TT0503071.drop(['LINE'], axis = 1, inplace = True)
TT0103051.drop(['LINE'], axis = 1, inplace = True)
TT0103061.drop(['LINE'], axis = 1, inplace = True)
TT1003042.drop(['LINE'], axis = 1, inplace = True)
TT1003043.drop(['LINE'], axis = 1, inplace = True)
TT1003062.drop(['LINE'], axis = 1, inplace = True)
TT1003063.drop(['LINE'], axis = 1, inplace = True)

In [165]:
TT0503041_idx = TT0503041['PRODUCT_CODE'].index
TT0503041_idx = pd.DataFrame(TT0503041_idx, columns = ['index'])

TT0503041c = TT0503041.columns
TT0503041scaled = T0503041scaler.transform(TT0503041)

TT0503041 = pd.DataFrame(TT0503041scaled, columns = TT0503041c)

TT0503041 = pd.concat([TT0503041_idx, TT0503041], axis = 1)
TT0503041 = TT0503041.set_index('index')

In [166]:
TT0503071_idx = TT0503071['PRODUCT_CODE'].index
TT0503071_idx = pd.DataFrame(TT0503071_idx, columns = ['index'])

TT0503071c = TT0503071.columns
TT0503071scaled = T0503071scaler.transform(TT0503071)

TT0503071 = pd.DataFrame(TT0503071scaled, columns = TT0503071c)

TT0503071 = pd.concat([TT0503071_idx, TT0503071], axis = 1)
TT0503071 = TT0503071.set_index('index')

In [167]:
TT0103051_idx = TT0103051['PRODUCT_CODE'].index
TT0103051_idx = pd.DataFrame(TT0103051_idx, columns = ['index'])

TT0103051c = TT0103051.columns
TT0103051scaled = T0103051scaler.transform(TT0103051)
TT0103051 = pd.DataFrame(TT0103051scaled, columns = TT0103051c)

TT0103051 = pd.concat([TT0103051_idx, TT0103051], axis = 1)
TT0103051 = TT0103051.set_index('index')

In [168]:
TT0103061_idx = TT0103061['PRODUCT_CODE'].index
TT0103061_idx = pd.DataFrame(TT0103061_idx, columns = ['index'])

TT0103061c = TT0103061.columns
TT0103061scaled = T0103061scaler.transform(TT0103061)
TT0103061 = pd.DataFrame(TT0103061scaled, columns = TT0103061c)

TT0103061 = pd.concat([TT0103061_idx, TT0103061], axis = 1)
TT0103061 = TT0103061.set_index('index')

In [169]:
TT1003042_idx = TT1003042['PRODUCT_CODE'].index
TT1003042_idx = pd.DataFrame(TT1003042_idx, columns = ['index'])

TT1003042c = TT1003042.columns
TT1003042scaled = T1003042scaler.transform(TT1003042)
TT1003042 = pd.DataFrame(TT1003042scaled, columns = TT1003042c)

TT1003042 = pd.concat([TT1003042_idx, TT1003042], axis = 1)
TT1003042 = TT1003042.set_index('index')

In [170]:
TT1003043_idx = TT1003043['PRODUCT_CODE'].index
TT1003043_idx = pd.DataFrame(TT1003043_idx, columns = ['index'])

TT1003043c = TT1003043.columns
TT1003043scaled = T1003043scaler.transform(TT1003043)
TT1003043 = pd.DataFrame(TT1003043scaled, columns = TT1003043c)

TT1003043 = pd.concat([TT1003043_idx, TT1003043], axis = 1)
TT1003043 = TT1003043.set_index('index')

In [171]:
TT1003062_idx = TT1003062['PRODUCT_CODE'].index
TT1003062_idx = pd.DataFrame(TT1003062_idx, columns = ['index'])

TT1003062c = TT1003062.columns
TT1003062scaled = T1003062scaler.transform(TT1003062)
TT1003062 = pd.DataFrame(TT1003062scaled, columns = TT1003062c)

TT1003062 = pd.concat([TT1003062_idx, TT1003062], axis = 1)
TT1003062 = TT1003062.set_index('index')

In [172]:
TT1003063_idx = TT1003063['PRODUCT_CODE'].index
TT1003063_idx = pd.DataFrame(TT1003063_idx, columns = ['index'])

TT1003063c = TT1003063.columns
TT1003063scaled = T1003063scaler.transform(TT1003063)
TT1003063 = pd.DataFrame(TT1003063scaled, columns = TT1003063c)

TT1003063 = pd.concat([TT1003063_idx, TT1003063], axis = 1)
TT1003063 = TT1003063.set_index('index')

In [173]:
from pycaret.regression import *
TT0503041_prediction = predict_model(T0503041_final_regression_model, data=TT0503041)
TT0503071_prediction = predict_model(T0503071_final_regression_model, data=TT0503071)
TT0103051_prediction = predict_model(T0103051_final_regression_model, data=TT0103051)
TT0103061_prediction = predict_model(T0103061_final_regression_model, data=TT0103061)
TT1003042_prediction = predict_model(T1003042_final_regression_model, data=TT1003042)
TT1003043_prediction = predict_model(T1003043_final_regression_model, data=TT1003043)
TT1003062_prediction = predict_model(T1003062_final_regression_model, data=TT1003062)
TT1003063_prediction = predict_model(T1003063_final_regression_model, data=TT1003063)

TT0503041_prediction = pd.DataFrame(TT0503041_prediction, columns = ['prediction_label'])
TT0503071_prediction = pd.DataFrame(TT0503071_prediction, columns = ['prediction_label'])
TT0103051_prediction = pd.DataFrame(TT0103051_prediction, columns = ['prediction_label'])
TT0103061_prediction = pd.DataFrame(TT0103061_prediction, columns = ['prediction_label'])
TT1003042_prediction = pd.DataFrame(TT1003042_prediction, columns = ['prediction_label'])
TT1003043_prediction = pd.DataFrame(TT1003043_prediction, columns = ['prediction_label'])
TT1003062_prediction = pd.DataFrame(TT1003062_prediction, columns = ['prediction_label'])
TT1003063_prediction = pd.DataFrame(TT1003063_prediction, columns = ['prediction_label'])

In [174]:
TT0503041_y_class = pd.DataFrame(TT0503041, columns = ['PRODUCT_CODE'])
TT0503041_idx = TT0503041_y_class.index
TT0503041_y_class = TT0503041_y_class.reset_index()
TT0503041_prediction = pd.concat([TT0503041_prediction, TT0503041_y_class], axis = 1)
TT0503041_prediction = TT0503041_prediction.set_index('index')
TT0503041_prediction.drop(['PRODUCT_CODE'], axis = 1, inplace = True)

TT0503071_y_class = pd.DataFrame(TT0503071, columns = ['PRODUCT_CODE'])
TT0503071_idx = TT0503071_y_class.index
TT0503071_y_class = TT0503071_y_class.reset_index()
TT0503071_prediction = pd.concat([TT0503071_prediction, TT0503071_y_class], axis = 1)
TT0503071_prediction = TT0503071_prediction.set_index('index')
TT0503071_prediction.drop(['PRODUCT_CODE'], axis = 1, inplace = True)

TT0103051_y_class = pd.DataFrame(TT0103051, columns = ['PRODUCT_CODE'])
TT0103051_idx = TT0103051_y_class.index
TT0103051_y_class = TT0103051_y_class.reset_index()
TT0103051_prediction = pd.concat([TT0103051_prediction, TT0103051_y_class], axis = 1)
TT0103051_prediction = TT0103051_prediction.set_index('index')
TT0103051_prediction.drop(['PRODUCT_CODE'], axis = 1, inplace = True)

TT0103061_y_class = pd.DataFrame(TT0103061, columns = ['PRODUCT_CODE'])
TT0103061_idx = TT0103061_y_class.index
TT0103061_y_class = TT0103061_y_class.reset_index()
TT0103061_prediction = pd.concat([TT0103061_prediction, TT0103061_y_class], axis = 1)
TT0103061_prediction = TT0103061_prediction.set_index('index')
TT0103061_prediction.drop(['PRODUCT_CODE'], axis = 1, inplace = True)

TT1003042_y_class = pd.DataFrame(TT1003042, columns = ['PRODUCT_CODE'])
TT1003042_idx = TT1003042_y_class.index
TT1003042_y_class = TT1003042_y_class.reset_index()
TT1003042_prediction = pd.concat([TT1003042_prediction, TT1003042_y_class], axis = 1)
TT1003042_prediction = TT1003042_prediction.set_index('index')
TT1003042_prediction.drop(['PRODUCT_CODE'], axis = 1, inplace = True)

TT1003043_y_class = pd.DataFrame(TT1003043, columns = ['PRODUCT_CODE'])
TT1003043_idx = TT1003043_y_class.index
TT1003043_y_class = TT1003043_y_class.reset_index()
TT1003043_prediction = pd.concat([TT1003043_prediction, TT1003043_y_class], axis = 1)
TT1003043_prediction = TT1003043_prediction.set_index('index')
TT1003043_prediction.drop(['PRODUCT_CODE'], axis = 1, inplace = True)

TT1003062_y_class = pd.DataFrame(TT1003062, columns = ['PRODUCT_CODE'])
TT1003062_idx = TT1003062_y_class.index
TT1003062_y_class = TT1003062_y_class.reset_index()
TT1003062_prediction = pd.concat([TT1003062_prediction, TT1003062_y_class], axis = 1)
TT1003062_prediction = TT1003062_prediction.set_index('index')
TT1003062_prediction.drop(['PRODUCT_CODE'], axis = 1, inplace = True)

TT1003063_y_class = pd.DataFrame(TT1003063, columns = ['PRODUCT_CODE'])
TT1003063_idx = TT1003063_y_class.index
TT1003063_y_class = TT1003063_y_class.reset_index()
TT1003063_prediction = pd.concat([TT1003063_prediction, TT1003063_y_class], axis = 1)
TT1003063_prediction = TT1003063_prediction.set_index('index')
TT1003063_prediction.drop(['PRODUCT_CODE'], axis = 1, inplace = True)

In [175]:
TT0503041_datas = TT0503041_prediction['prediction_label']
TT0503041_datas = pd.DataFrame(TT0503041_datas.values, columns = ['Y_Quality'])

TT0503041y_idx= TT0503041_prediction.index
TT0503041y_idx = pd.DataFrame(TT0503041y_idx, columns = ['index'])
TT0503041_datas = pd.concat([TT0503041y_idx, TT0503041_datas], axis = 1)
TT0503041_datas = TT0503041_datas.set_index('index') #1

TT0503071_datas = TT0503071_prediction['prediction_label']
TT0503071_datas = pd.DataFrame(TT0503071_datas.values, columns = ['Y_Quality'])

TT0503071y_idx= TT0503071_prediction.index
TT0503071y_idx = pd.DataFrame(TT0503071y_idx, columns = ['index'])
TT0503071_datas = pd.concat([TT0503071y_idx, TT0503071_datas], axis = 1)
TT0503071_datas = TT0503071_datas.set_index('index') #2

TT0103051_datas = TT0103051_prediction['prediction_label']
TT0103051_datas = pd.DataFrame(TT0103051_datas.values, columns = ['Y_Quality'])

TT0103051y_idx= TT0103051_prediction.index
TT0103051y_idx = pd.DataFrame(TT0103051y_idx, columns = ['index'])
TT0103051_datas = pd.concat([TT0103051y_idx, TT0103051_datas], axis = 1)
TT0103051_datas = TT0103051_datas.set_index('index') #3

TT0103061_datas = TT0103061_prediction['prediction_label']
TT0103061_datas = pd.DataFrame(TT0103061_datas.values, columns = ['Y_Quality'])

TT0103061y_idx= TT0103061_prediction.index
TT0103061y_idx = pd.DataFrame(TT0103061y_idx, columns = ['index'])
TT0103061_datas = pd.concat([TT0103061y_idx, TT0103061_datas], axis = 1)
TT0103061_datas = TT0103061_datas.set_index('index') #4

TT1003042_datas = TT1003042_prediction['prediction_label']
TT1003042_datas = pd.DataFrame(TT1003042_datas.values, columns = ['Y_Quality'])

TT1003042y_idx= TT1003042_prediction.index
TT1003042y_idx = pd.DataFrame(TT1003042y_idx, columns = ['index'])
TT1003042_datas = pd.concat([TT1003042y_idx, TT1003042_datas], axis = 1)
TT1003042_datas = TT1003042_datas.set_index('index') #5

TT1003043_datas = TT1003043_prediction['prediction_label']
TT1003043_datas = pd.DataFrame(TT1003043_datas.values, columns = ['Y_Quality'])

TT1003043y_idx= TT1003043_prediction.index
TT1003043y_idx = pd.DataFrame(TT1003043y_idx, columns = ['index'])
TT1003043_datas = pd.concat([TT1003043y_idx, TT1003043_datas], axis = 1)
TT1003043_datas = TT1003043_datas.set_index('index') #6

TT1003062_datas = TT1003062_prediction['prediction_label']
TT1003062_datas = pd.DataFrame(TT1003062_datas.values, columns = ['Y_Quality'])

TT1003062y_idx= TT1003062_prediction.index
TT1003062y_idx = pd.DataFrame(TT1003062y_idx, columns = ['index'])
TT1003062_datas = pd.concat([TT1003062y_idx, TT1003062_datas], axis = 1)
TT1003062_datas = TT1003062_datas.set_index('index') #7

TT1003063_datas = TT1003063_prediction['prediction_label']
TT1003063_datas = pd.DataFrame(TT1003063_datas.values, columns = ['Y_Quality'])

TT1003063y_idx= TT1003063_prediction.index
TT1003063y_idx = pd.DataFrame(TT1003063y_idx, columns = ['index'])
TT1003063_datas = pd.concat([TT1003063y_idx, TT1003063_datas], axis = 1)
TT1003063_datas = TT1003063_datas.set_index('index') #8

In [176]:
from pycaret.classification import *

TT0503041_predictions = predict_model(T0503041_final_classification_model, data=TT0503041_datas)
TT0503071_predictions = predict_model(T0503071_final_classification_model, data=TT0503071_datas)
TT0103051_predictions = predict_model(T0103051_final_classification_model, data=TT0103051_datas)
TT0103061_predictions = predict_model(T0103061_final_classification_model, data=TT0103061_datas)
TT1003042_predictions = predict_model(T1003042_final_classification_model, data=TT1003042_datas)
TT1003043_predictions = predict_model(T1003043_final_classification_model, data=TT1003043_datas)
TT1003062_predictions = predict_model(T1003062_final_classification_model, data=TT1003062_datas)
TT1003063_predictions = predict_model(T1003063_final_classification_model, data=TT1003063_datas)

TT0503041_predictions = pd.DataFrame(TT0503041_predictions, columns = ['prediction_label'])
TT0503071_predictions = pd.DataFrame(TT0503071_predictions, columns = ['prediction_label'])
TT0103051_predictions = pd.DataFrame(TT0103051_predictions, columns = ['prediction_label'])
TT0103061_predictions = pd.DataFrame(TT0103061_predictions, columns = ['prediction_label'])
TT1003042_predictions = pd.DataFrame(TT1003042_predictions, columns = ['prediction_label'])
TT1003043_predictions = pd.DataFrame(TT1003043_predictions, columns = ['prediction_label'])
TT1003062_predictions = pd.DataFrame(TT1003062_predictions, columns = ['prediction_label'])
TT1003063_predictions = pd.DataFrame(TT1003063_predictions, columns = ['prediction_label'])

In [177]:
TT0503041_idxf = TT0503041_datas.index
TT0503041_p = pd.DataFrame(TT0503041_idxf, columns = ['index'])
TT0503041_predictions = pd.concat([TT0503041_p, TT0503041_predictions], axis = 1)
TT0503041_predictions = TT0503041_predictions.set_index('index')

TT0503071_idxf = TT0503071_datas.index
TT0503071_p = pd.DataFrame(TT0503071_idxf, columns = ['index'])
TT0503071_predictions = pd.concat([TT0503071_p, TT0503071_predictions], axis = 1)
TT0503071_predictions = TT0503071_predictions.set_index('index')

TT0103051_idxf = TT0103051_datas.index
TT0103051_p = pd.DataFrame(TT0103051_idxf, columns = ['index'])
TT0103051_predictions = pd.concat([TT0103051_p, TT0103051_predictions], axis = 1)
TT0103051_predictions = TT0103051_predictions.set_index('index')

TT0103061_idxf = TT0103061_datas.index
TT0103061_p = pd.DataFrame(TT0103061_idxf, columns = ['index'])
TT0103061_predictions = pd.concat([TT0103061_p, TT0103061_predictions], axis = 1)
TT0103061_predictions = TT0103061_predictions.set_index('index')

TT1003042_idxf = TT1003042_datas.index
TT1003042_p = pd.DataFrame(TT1003042_idxf, columns = ['index'])
TT1003042_predictions = pd.concat([TT1003042_p, TT1003042_predictions], axis = 1)
TT1003042_predictions = TT1003042_predictions.set_index('index')

TT1003043_idxf = TT1003043_datas.index
TT1003043_p = pd.DataFrame(TT1003043_idxf, columns = ['index'])
TT1003043_predictions = pd.concat([TT1003043_p, TT1003043_predictions], axis = 1)
TT1003043_predictions = TT1003043_predictions.set_index('index')

TT1003062_idxf = TT1003062_datas.index
TT1003062_p = pd.DataFrame(TT1003062_idxf, columns = ['index'])
TT1003062_predictions = pd.concat([TT1003062_p, TT1003062_predictions], axis = 1)
TT1003062_predictions = TT1003062_predictions.set_index('index')

TT1003063_idxf = TT1003063_datas.index
TT1003063_p = pd.DataFrame(TT1003063_idxf, columns = ['index'])
TT1003063_predictions = pd.concat([TT1003063_p, TT1003063_predictions], axis = 1)
TT1003063_predictions = TT1003063_predictions.set_index('index')

In [178]:
final_test = pd.concat([TT0503041_predictions, TT0503071_predictions, TT0103051_predictions, TT0103061_predictions, TT1003042_predictions, TT1003043_predictions, TT1003062_predictions, TT1003063_predictions])
final_test

prediction_label
index                  
7                     0
8                     0
14                    0
35                    0
41                    0
...                 ...
305                   1
307                   1
308                   1
309                   1
257                   1

[310 rows x 1 columns]

In [179]:
final_test = final_test.sort_index(ascending=True)
final_test['prediction_label']

index
0      1
1      1
2      1
3      0
4      1
      ..
305    1
306    1
307    1
308    1
309    1
Name: prediction_label, Length: 310, dtype: int32

In [180]:
#52
sample_submission = pd.read_csv('sample_submission.csv')
sample_submission['Y_Class'] = final_test['prediction_label']
display(sample_submission.head())
sample_submission.to_csv('codeline_robust_regpyc_classpyc_fillmean_submission.csv',index=False)

PRODUCT_ID  Y_Class
0   TEST_000        1
1   TEST_001        1
2   TEST_002        1
3   TEST_003        0
4   TEST_004        1

In [181]:
np.array(final_test['prediction_label'])

array([1, 1, 1, 0, 1, 2, 1, 0, 0, 2, 0, 1, 1, 1, 0, 1, 2, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 0, 1, 0, 2, 1, 1, 0, 0, 1,
       1, 1, 1, 0, 1, 0, 1, 0, 0, 1, 1, 0, 1, 1, 0, 0, 0, 1, 1, 1, 0, 0,
       0, 1, 0, 0, 0, 0, 1, 1, 1, 1, 2, 1, 2, 1, 1, 1, 1, 1, 1, 1, 0, 1,
       0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 1, 2, 1, 1, 1, 1, 2, 1,
       1, 1, 1, 2, 1, 2, 0, 0, 1, 2, 1, 1, 2, 2, 1, 1, 2, 1, 1, 1, 1, 1,
       1, 1, 2, 2, 2, 2, 1, 1, 1, 0, 0, 2, 2, 1, 1, 2, 1, 1, 1, 2, 1, 1,
       1, 1, 1, 1, 1, 1, 2, 2, 1, 2, 1, 1, 1, 1, 1, 2, 1, 1, 2, 1, 1, 1,
       1, 1, 1, 2, 2, 1, 1, 2, 1, 1, 1, 2, 1, 2, 1, 2, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 2, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,

In [182]:
final_test['prediction_label'].value_counts()

1    242
2     37
0     31
Name: prediction_label, dtype: int64